In [1]:
import pandas as pd
import numpy as np
import os
import re
import requests
from bs4 import BeautifulSoup

import os
os.environ["PGDATABASE"] = 'crsp'
os.environ['PGUSER'] = 'bdcallen'
os.environ['PGPASSWORD'] = 'temp_20180308'
os.getenv("PGHOST", "localhost")

dbname = os.getenv("PGDATABASE")
host = os.getenv("PGHOST", "localhost")
conn_string = "postgresql://" + host + "/" + dbname

from sqlalchemy import create_engine, inspect, types as st
from asxlisting import get_soup, is_valid_issuer_id, make_valid_id_df
from asxlisting_db import make_sql_table_comment, set_table_ownership_access
from asxlisting_db import conn_string

In [2]:
engine = create_engine(conn_string)

In [4]:
indexes_df = pd.read_sql("SELECT * FROM edgar.sc13dg_indexes", engine)

In [5]:
indexes_df

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2        edgar/data/1163453/0001019687-04-000771.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
9        edgar/data/1163453/0001019687-04-001131.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
12       edgar/data/1279095/0001144204-04-004297.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
16       edgar/data/1135338/0000919574-04-001356.txt   
17        edgar/data/923877/0000807249-04-000123.txt   
18       edgar/data/1135338/0000919574-04-001735.txt   
19       edgar/data/1279095/0001144204-04-007831.txt   
20       edgar/data/1135338/0000919574-04-001367.txt   
21       edgar/data/1135338/0000919574-04-001873.txt   
22       edgar/data/1135338/0000919574-04-001745.txt   
23       edgar/data/1135338/0000919574-04-001385.txt   
24        edgar/data/925765/0000926274-04-000155.txt   
25       edgar/data/1135338/0000919574-04-001749.txt   
26       edgar/data/1135338/0000919574-04-001895.txt   
27       edgar/data/1135338/0000919574-04-001407.txt   
28        edgar/data/927752/0000950142-04-002200.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
...                                              ...   
1112480  edgar/data/1489218/0001144204-12-009088.txt   
1112481   edgar/data/905448/0000950123-10-088156.txt   
1112482   edgar/data/872573/0000872573-10-000005.txt   
1112483  edgar/data/1043325/0000950123-10-094394.txt   
1112484   edgar/data/354204/0001047469-02-001657.txt   
1112485  edgar/data/1100682/0000902664-10-003436.txt   
1112486   edgar/data/354204/0001047469-02-001844.txt   
1112487  edgar/data/1291361/0001193125-12-052496.txt   
1112488  edgar/data/1375686/0001204459-12-000006.txt   
1112489   edgar/data/887793/0000930413-12-000848.txt   
1112490   edgar/data/879764/0001193125-12-058927.txt   
1112491   edgar/data/357301/0000932471-12-002808.txt   
1112492  edgar/data/1036250/0000950159-12-000075.txt   
1112493  edgar/data/1121884/0000897423-02-000040.txt   
1112494  edgar/data/1364742/0001086364-10-009847.txt   
1112495   edgar/data/763744/0001005477-02-001266.txt   
1112496   edgar/data/840886/0000914317-02-000096.txt   
1112497   edgar/data/315066/0000315066-02-000607.txt   
1112498  edgar/data/1512920/0001512920-12-000014.txt   
1112499   edgar/data/315066/0000315066-10-003507.txt   
1112500  edgar/data/1090159/0000910662-10-000472.txt   
1112501   edgar/data/912593/0000315066-12-000160.txt   
1112502  edgar/data/1446847/0000766524-10-000033.txt   
1112503  edgar/data/1011064/0000315066-12-003052.txt   
1112504  edgar/data/1389234/0000919574-12-001395.txt   
1112505   edgar/data/354204/0001047469-02-002192.txt   
1112506   edgar/data/354204/0001047469-02-002213.txt   
1112507  edgar/data/1506481/0001144204-12-005365.txt   
1112508  edgar/data/1120970/0001214305-10-000022.txt   
1112509   edgar/data/923204/0001193125-12-048752.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001019687-04-000771.txt    SC 13D                           1   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G  

In [ ]:
sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
         INNER JOIN edgar.filings AS b
         USING(file_name)
         WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
         AND a.downloaded
         AND a.file_name ~ a.document
      """

downloaded_df = pd.read_sql(sql, engine)
downloaded_df

In [861]:
sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
         INNER JOIN edgar.filings AS b
         USING(file_name)
         LEFT JOIN edgar.sc13dg_indexes_old AS c
         USING(file_name, document)
         WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
         AND a.downloaded
         AND a.file_name ~ a.document
         AND c.file_name IS NULL
      """

smaller_df = pd.read_sql(sql, engine)
smaller_df 

file_name  \
0        edgar/data/1000014/0000930661-97-000604.txt   
1        edgar/data/1000015/0000080255-02-000148.txt   
2        edgar/data/1000015/0000080255-03-000161.txt   
3        edgar/data/1000015/0000080255-04-000151.txt   
4        edgar/data/1000015/0000080255-05-000266.txt   
5        edgar/data/1000015/0000080255-97-000155.txt   
6        edgar/data/1000015/0000080255-98-000237.txt   
7        edgar/data/1000015/0000080255-99-000474.txt   
8        edgar/data/1000015/0000315066-01-000534.txt   
9        edgar/data/1000015/0000315066-98-000797.txt   
10       edgar/data/1000015/0000818063-98-000009.txt   
11       edgar/data/1000015/0000912057-01-004618.txt   
12       edgar/data/1000015/0000912057-01-004619.txt   
13       edgar/data/1000015/0000912057-01-521036.txt   
14       edgar/data/1000015/0000912057-01-521089.txt   
15       edgar/data/1000015/0000912057-01-521099.txt   
16       edgar/data/1000015/0000912057-01-522809.txt   
17       edgar/data/1000015/0000912057-01-523726.txt   
18       edgar/data/1000015/0000912057-02-008136.txt   
19       edgar/data/1000015/0000912938-01-000126.txt   
20       edgar/data/1000015/0000912938-98-000100.txt   
21       edgar/data/1000015/0000912938-99-000265.txt   
22       edgar/data/1000015/0000919574-00-000839.txt   
23       edgar/data/1000015/0000919574-01-000205.txt   
24       edgar/data/1000015/0000919574-02-000367.txt   
25       edgar/data/1000015/0000919574-03-000244.txt   
26       edgar/data/1000015/0000919574-04-000455.txt   
27       edgar/data/1000015/0000919574-05-000482.txt   
28       edgar/data/1000015/0000919574-05-000485.txt   
29       edgar/data/1000015/0000929638-04-000166.txt   
...                                              ...   
1081664     edgar/data/9984/0001193125-08-014537.txt   
1081665     edgar/data/9984/0001193125-08-027233.txt   
1081666     edgar/data/9984/0001193125-08-082037.txt   
1081667     edgar/data/9984/0001193125-09-017486.txt   
1081668     edgar/data/9984/0001193125-09-030677.txt   
1081669     edgar/data/9984/0001193125-10-282462.txt   
1081670     edgar/data/9984/0001193125-14-030644.txt   
1081671     edgar/data/9984/0001206774-17-002753.txt   
1081672     edgar/data/9984/0001258897-16-002624.txt   
1081673     edgar/data/9984/0001258897-17-001162.txt   
1081674     edgar/data/9984/0001258897-18-001042.txt   
1081675     edgar/data/9984/0001258897-19-001052.txt   
1081676     edgar/data/9984/0001445305-14-000365.txt   
1081677     edgar/data/9984/0001567619-19-003559.txt   
1081678    edgar/data/99974/0000945621-00-000175.txt   
1081679    edgar/data/99974/0000945621-97-000069.txt   
1081680    edgar/data/99974/0000945621-98-000047.txt   
1081681    edgar/data/99982/0000950110-00-000133.txt   
1081682    edgar/data/99982/0000950110-01-000153.txt   
1081683    edgar/data/99982/0000950110-01-000154.txt   
1081684    edgar/data/99982/0000950110-01-000155.txt   
1081685    edgar/data/99982/0000950110-01-000156.txt   
1081686    edgar/data/99982/0000950110-02-000014.txt   
1081687    edgar/data/99982/0000950110-02-000075.txt   
1081688    edgar/data/99982/0000950110-02-000077.txt   
1081689    edgar/data/99982/0000950110-02-000079.txt   
1081690    edgar/data/99982/0000950110-98-000230.txt   
1081691    edgar/data/99982/0000950110-98-000231.txt   
1081692    edgar/data/99982/0000950110-99-000794.txt   
1081693    edgar/data/99982/0000950123-01-504715.txt   

                         document  downloaded            company_name  \
0        0000930661-97-000604.txt        True    RICE PARTNERS II L P   
1        0000080255-02-000148.txt        True          META GROUP INC   
2        0000080255-03-000161.txt        True          META GROUP INC   
3        0000080255-04-000151.txt        True          META GROUP INC   
4        0000080255-05-000266.txt        True          META GROUP INC   
5        0000080255-97-000155.txt        True          META GROUP INC   
6        0000080255-98-000237.txt        True          META

In [856]:
indexes_df.shape[0]

286013

In [857]:
smaller_df.shape[0]

1081694

In [858]:
downloaded_df.shape[0]

1367618

In [860]:
downloaded_df.shape[0] - smaller_df.shape[0] 

285924

In [5]:
indexes_df[indexes_df['success'] == False]

file_name                  document  \
1       edgar/data/1364742/0001086364-12-002106.txt  0001086364-12-002106.txt   
2        edgar/data/872448/0001086364-11-002317.txt  0001086364-11-002317.txt   
3       edgar/data/1329919/0001140361-13-004557.txt  0001140361-13-004557.txt   
4       edgar/data/1552797/0000357235-13-000062.txt  0000357235-13-000062.txt   
5       edgar/data/1334933/0001086364-11-000247.txt  0001086364-11-000247.txt   
7        edgar/data/902219/0000902219-12-000427.txt  0000902219-12-000427.txt   
9       edgar/data/1306923/0001306923-06-000020.txt  0001306923-06-000020.txt   
10      edgar/data/1329919/0001172661-13-000444.txt  0001172661-13-000444.txt   
11      edgar/data/1334933/0001183740-11-000126.txt  0001183740-11-000126.txt   
13      edgar/data/1127439/0000948046-07-000041.txt  0000948046-07-000041.txt   
22       edgar/data/864047/0000950144-00-001286.txt  0000950144-00-001286.txt   
23       edgar/data/945914/0000950172-96-000047.txt  0000950172-96-000047.txt   
31      edgar/data/1086434/0001178913-10-000354.txt  0001178913-10-000354.txt   
45       edgar/data/888002/0000888002-10-000383.txt  0000888002-10-000383.txt   
136     edgar/data/1348456/0001193125-06-129897.txt  0001193125-06-129897.txt   
151      edgar/data/866609/0001085146-07-000211.txt  0001085146-07-000211.txt   
152      edgar/data/866609/0001085146-07-000234.txt  0001085146-07-000234.txt   
154      edgar/data/938506/0000935836-07-000006.txt  0000935836-07-000006.txt   
175      edgar/data/802724/0000935836-07-000157.txt  0000935836-07-000157.txt   
184     edgar/data/1174172/0000950005-07-000176.txt  0000950005-07-000176.txt   
192      edgar/data/812900/0000947871-10-000302.txt  0000947871-10-000302.txt   
196      edgar/data/888002/0000888002-10-000385.txt  0000888002-10-000385.txt   
203      edgar/data/888002/0000888002-10-000390.txt  0000888002-10-000390.txt   
208      edgar/data/888002/0000888002-10-000394.txt  0000888002-10-000394.txt   
209      edgar/data/888002/0000888002-10-000397.txt  0000888002-10-000397.txt   
211      edgar/data/888002/0000888002-10-000402.txt  0000888002-10-000402.txt   
212      edgar/data/888002/0000888002-10-000404.txt  0000888002-10-000404.txt   
213      edgar/data/888002/0000888002-10-000408.txt  0000888002-10-000408.txt   
214      edgar/data/888002/0000888002-10-000413.txt  0000888002-10-000413.txt   
218      edgar/data/888002/0000888002-10-000414.txt  0000888002-10-000414.txt   
...                                             ...                       ...   
280637   edgar/data/820289/0000820289-07-000015.txt  0000820289-07-000015.txt   
280638   edgar/data/820289/0000820289-07-000016.txt  0000820289-07-000016.txt   
280654  edgar/data/1023313/0000950123-07-002193.txt  0000950123-07-002193.txt   
280750   edgar/data/925261/0000021344-14-000031.txt  0000021344-14-000031.txt   
280767   edgar/data/820289/0000820289-07-000002.txt  0000820289-07-000002.txt   
280768   edgar/data/820289/0000820289-07-000004.txt  0000820289-07-000004.txt   
280769   edgar/data/820289/0000820289-07-000005.txt  0000820289-07-000005.txt   
280776  edgar/data/1283157/0001085146-07-000423.txt  0001085146-07-000423.txt   
280783   edgar/data/710846/0001144204-07-014027.txt  0001144204-07-014027.txt   
280819  edgar/data/1331875/0001264128-07-000047.txt  0001264128-07-000047.txt   
280826  edgar/data/1351950/0000894579-07-000002.txt  0000894579-07-000002.txt   
280921  edgar/data/1299901/0001085146-07-000163.txt  0001085146-07-000163.txt   
280927  edgar/data/1321850/0001193125-07-024590.txt  0001193125-07-024590.txt   
281206   edgar/data/884731/0000899140-14-000598.txt  0000899140-14-000598.txt   
281245  edgar/data/1380393/0001085146-07-000423.txt  0001085146-07-000423.txt   
281257   edgar/data/921671/0001074683-07-000080.txt  0001074683-07-000080.txt   
281285   edgar/data/932267/0001144204-14-043077.txt  0001144204-14-043077.txt   
281287   edgar/data/932267/0001144204-14-055626.txt  0001144204-14-055626

In [12]:
get_index_url('edgar/data/1329919/0001140361-13-004557.txt')

'https://www.sec.gov/Archives/edgar/data/1329919/000114036113004557/0001140361-13-004557-index.htm'

In [6]:
def get_file_text_from_directory(file_name, document, directory):
    
    path = directory + '/' + get_file_path(file_name, document)
    f = open(path, 'r')
    txt = f.read()
    f.close()
    return(txt)

In [7]:
def get_file_path(file_name, document):
    
    url = re.sub("(\\d{10})-(\\d{2})-(\\d{6})\\.txt", "\\1\\2\\3", file_name)
    
    path = url + '/' + document
    
    return(path)

In [8]:
def get_index_url(file_name): 
    
    # This is a Python version of the function of the same name in scrape_filing_doc_functions.R
    
    regex = "/(\\d+)/(\\d{10}-\\d{2}-\\d{6})"
    matches = re.findall(regex, file_name)[0]
    
    cik = matches[0]
    acc_no = matches[1]
    
    path = re.sub("[^\\d]", "", acc_no)
    
    url = "https://www.sec.gov/Archives/edgar/data/" + cik + "/" + path + "/" + acc_no + "-index.htm"
    
    return(url)

In [569]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['amendment_statement_start'] = find_amendment_statement_start(text, form_type, \
                    lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

In [202]:
def write_indexes_to_table(file_name, document, form_type, directory, engine):
    
    try:
        
        df = get_key_indices(file_name, document, form_type, directory)
        df['success'] = True
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)
        
    except:
        
        df = pd.DataFrame({'file_name': [file_name], 'document': [document], 'form_type': [form_type], \
              'title_page_end_lower_bound': [-2], 'cover_page_q1_start': [-2], 'is_rep_q_as_items': [-2],\
              'num_cusip_sedol_b_q1': [-2], 'cover_page_start': [-2], 'item_section_start': [-2], \
              'cover_page_last_q_end': [-2], 'cover_page_end': [-2], 'num_cusip_b_items': [-2],\
              'signature_start': [-2], 'amendment_statement_start': [-2], 'success': [False]})
        
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)    

In [151]:
def is_rep_q_as_items(text, q1_start = None):
    
    # this function works on the basis that the the actual "items" in the real item section does not go beyond
    # Item 10. So by searching for Item 12 or 14 (in SC 13G and SC 13D respectively), we can detect whether
    # a filer has erroneously labelled the questions in the reporting pages as items
    
    if(q1_start is None):
      
        q1_start = find_orthodox_cover_page_q1_start(text)
    
    if(q1_start == -1):
    
        text_raised = text.upper()
        
        regex = '\n\s*ITEM\s*(\.)?\s*[\(]?\s*1[24]\s*[\)]?(\.)?'
        
        search = re.search(regex, text_raised)
        
        if(search):
            return(True)
        else:
            return(False)
            
    else:
      
        return(False)

In [70]:
def find_last_search_start(regex, text):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return(None)
    
    else:
        
        end = 0
        
        while(search is not None):
            
            start = end + search.start()
            end = end + search.end()
            search = re.search(regex, text[end:])
        
    return(start)
    
    


def find_last_search_end(regex, text):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return(None)
    
    else:
        
        end = 0
        
        while(search is not None):
            
            end = end + search.end()
            search = re.search(regex, text[end:])
        
    return(end)


In [16]:
def get_title_page_end_lower_bound(text, upper_bound = None):
    
    rep_q_as_items = is_rep_q_as_items(text)
    
    if(upper_bound is None):
        upper_bound = get_title_page_end_upper_bound(text)
    
    text_raised = text.upper()[:upper_bound]
    
    if(not rep_q_as_items):
        
        last_search = find_last_search_end('\((?:NAME|CUSIP|SEDOL|DATE|TITLE|AMENDMENT)(.*?\s)*?' + \
                     '(?:ISSUER|SECURITIES|NUMBER|STATEMENT|SCHEDULE|NO\.?|#)\)', text_raised)
        
        if(last_search):
            
            return(last_search)
        
        else:
            return(0)
        
    else:
        
        return(0)

        
        
def get_title_page_end_upper_bound(text, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        rep_q_as_items = is_rep_q_as_items(text)

    text_raised = text.upper()

    if(rep_q_as_items):

        end = re.search('ITEM\s*[#\.\:]?\s*[\(]?\s*1[24]\s*[\)]?[\.\:]?', text_raised).start()

        regex = 'ITEM\s*[#\.\:]?\s*[\(]?\s*1\s*[\)]?[\.\:]?'

        search = re.search(regex, text_raised[:end])

        return(search.start())

    else:

        regex = '[\(]?\s*1\s*[\)]?\s*[:\.]{0,1}\s*NAME[S]?\s+(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?' + \
                '(\s*/\s*)?(S\.S\.\s+)?(\s+(?:OR|AND))\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[S]?\.\s+' + \
                '(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?'     

        search = re.search(regex, text_raised)

        if(search):

            return(search.start())

        else:
            regex = '(?<!DESCRIBED\sIN)\s*ITEM\s*[#\.\:]?\s*[\(]?\s*[0-9]{1,2}\s*' + \
                    '[\)]?[\.\:]?'
            search = re.search(regex, text_raised)

            return(search.start())

In [159]:
def find_title_page_end(text):
    
    rep_q_as_items = is_rep_q_as_items(text)
    
    upper_bound = get_title_page_end_upper_bound(text, rep_q_as_items)
    
    text_raised = text.upper()[:upper_bound]
    
    regex1_end = find_regex1_end(text)
    
    num_cusip_lines = len(re.findall('(?:CUSIP|SEDOL)', text_raised))
    
    if(regex1_end != -1):
        
        return(regex1_end)
    
    elif(num_cusip_lines < 2):
        
        return(upper_bound)
        
    else:
            
        
        rep_start_re = ['(?:CUSIP|SEDOL)', 'SCHEDULE\s+13[DG](/A)?', 'SC\s+13[DG](/A)?', \
                        'PAGE', '13[DG](/A)?']

        pot_results = []

        for regex in rep_start_re:

            start = find_last_search_start(regex, text_raised)

            if(start):
                pot_results.append(start)
                
        result = min(pot_results)
        
        return(result)
    

In [194]:
def find_orthodox_cover_page_q1_start(text):

    text_raised = text.upper()

    regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?'

    regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
    
    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
             'PERSON[\(]?[S]?[\)]?'
    
    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
             'ABOVE\s+PERSON[\(]?[S]?[\)]?'
    
    regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'
    
    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
             '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
             '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'
    
    
    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'
    
    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'
    
    regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
              'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
    start = None
    
    for i in range(len(regex_list)):
        
        search = re.search(regex_list[i], text_raised)
        
        if(search):
            
            if(start is None):
                
                start = search.start()
                
            else:
                
                new = search.start()
                
                if(new < start):
                    
                    start = new            

    if(start):
        
        return(start)
    
    else:
        
        return(-1)   

In [201]:
def cover_page_start(text, form_type, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_cover_page_q1_start(text, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)\s*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)


In [200]:
def find_cover_pages_last_question(text, rep_q_as_items = None,  lower_bound = None, upper_bound = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(lower_bound is not None and lower_bound > 0):
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[lower_bound:upper_bound]
            
        else:
            
            text_raised = text.upper()[lower_bound:]
            
    else:
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[:upper_bound]
            
        else:
            
            text_raised = text.upper() 
    
    if(rep_q_as_items):
        
        regex = 'ITEM\s*[\(]?\s*1[24]\s*[\)]?\s*[\:\.]?'
        
    else:
    
        regex = '[\(]?\s*1[24][\)]?\s*[\:\.]?\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?[\*]?\s*(\(SEE\s+INSTRUCTIONS\))?'

    search = re.search(regex, text_raised)

    if(search is None):
        return(None)
    
    end = 0

    while(search is not None):
        
        end = end + search.end()
        search = re.search(regex, text_raised[end:])

    if(lower_bound is not None and lower_bound > 0):
        
        end = end + lower_bound
        
    return(end)       
        

    
    
def find_cover_pages_end(text, rep_q_as_items = None, lower_bound = None, upper_bound = None):
    
    
    end = find_cover_pages_last_question(text, rep_q_as_items, lower_bound, upper_bound)
        
    answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'
    
    if(upper_bound is not None):
    
        last_answer = re.search(answer_regex, text[end:upper_bound])
        
    else:
        
        last_answer = re.search(answer_regex, text[end:])
    
    if(last_answer is not None):
    
        return(end + last_answer.end())
    
    else:
        
        return(-1)
        
 

def num_cusip_sedol_before_index(text, index = None):

    try:
        if(index):
            text_lowered = text.lower()[:index]
        else:
            text_lowered = text.lower()
        
        num_cusip_sedol = len(re.findall('(cusip|sedol)', text_lowered))
        
        return(num_cusip_sedol)

    except Exception as e:
        print(e)
        return(None)

    
def find_explanatory_statement_start(text, lower_bound = None, upper_bound = None):
    
    # This function is designed to get the start of the explanatory/amendment statement 
    # that is sometimes found between the end of the cover pages and the start of the item section 
    
    

    regex_list = ['\n\s*explanatory\s+note', '\n\s*amendment\s+(number|no)(\.)?\s*[0-9]+\s*\n',\
                  '\n\s*schedule\s+13[dg]\s+amendment\s+(number|no)(\.)?\s*[0-9]+\s*\n',\
                  '\n\s*this\s+amendment\s+(number|no)(\.)?\s*[0-9]+\s+', \
                    '\n\s*pursuant\s+to\s+rule\s+13d-', '\n\s*this\s+amended\s+schedule\s+13[dg]', \
'\n\s*the\s+undersigned(\s+reporting\s+person(s)?)?\s+hereby\s+amend\s+(the|their)\s+schedule\s+13[dg]',\
                  '\n\s*the\s+schedule\s+13[dg]\s+was\s+initially\s+filed',\
                 '\n(.)+hereby\s+amends\s+the\s+schedule\s+13[dg]',\
                  '\n\s*the\s+filing\s+of\s+this\s+schedule\s+13[dg]',\
                 '\n\s*the\s+filing\s+of\s+this\s+statement\s+on\s+schedule\s+13[dg]',\
                 '\n\s*the\s+reporting\s+person(s)?\s+listed\s+']

    if(lower_bound):

        if(upper_bound):

            text_lowered = text.lower()[lower_bound:upper_bound]

        else:

            text_lowered = text.lower()[lower_bound:]

    else:

        if(upper_bound):

            text_lowered = text.lower()[:upper_bound]

        else:

            text_lowered = text.lower()

    search_starts = []

    for pattern in regex_list:

        search = re.search(pattern, text_lowered)

        if(search):

            search_starts.append(search.start())

    if(len(search_starts)):

        if(lower_bound):

            return(min(search_starts) + lower_bound)

        else:

            return(min(search_starts))

    else:

        return(-1)
        
    

In [842]:
i = 2000
get_key_indices(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], \
                sc_13d_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1056947/0001140361-13-024732.txt  0001140361-13-024732.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        1940                 1940   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     1              1940   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                6012                   5715            5780   

   num_cusip_b_items  signature_start  exhibit_start  main_text_length  \
0                  3            23819          24639             28555   

   amendment_statement_start  has_jumbled_order  has_exhibit_break  
0                         -1              False               True

In [635]:
find_orthodox_cover_page_q1_start(t)

1871

In [689]:
find_all_orthodox_q1_starts(t)

[1669, 5796]

In [840]:
t[100:-1]

'.C. 20549\n\nSCHEDULE 13G\n\nUnder the Securities Exchange Act of 1934\n\n(Amendment No:  1)\n\nJACOBS ENGINEERING GROUP INC\n--------------------------------------------------------\n(Name of Issuer)\n\nCommon Stock\n--------------------------------------------------------\n(Title of Class of Securities)\n\n469814107\n--------------------------------------------------------\n(CUSIP Number)\n\nDecember 30, 2011\n--------------------------------------------------------\n(Date of Event Which Requires Filing of this Statement)\n\nCheck the appropriate box to designate the rule pursuant to\nwhich this Schedule is filed:\n\n[X] Rule 13d-1(b)\n[ ] Rule 13d-1(c)\n[ ] Rule 13d-1(d)\n\n\n*The remainder of this cover page shall be filled out\nfor a reporting person\'s initial filing on this form with\nrespect to the subject class of securities, and for any\nsubsequent amendment containing information which\nwould alter the disclosures provided in a prior cover page.\n\nThe information required 

In [841]:
t[100:]

'.C. 20549\n\nSCHEDULE 13G\n\nUnder the Securities Exchange Act of 1934\n\n(Amendment No:  1)\n\nJACOBS ENGINEERING GROUP INC\n--------------------------------------------------------\n(Name of Issuer)\n\nCommon Stock\n--------------------------------------------------------\n(Title of Class of Securities)\n\n469814107\n--------------------------------------------------------\n(CUSIP Number)\n\nDecember 30, 2011\n--------------------------------------------------------\n(Date of Event Which Requires Filing of this Statement)\n\nCheck the appropriate box to designate the rule pursuant to\nwhich this Schedule is filed:\n\n[X] Rule 13d-1(b)\n[ ] Rule 13d-1(c)\n[ ] Rule 13d-1(d)\n\n\n*The remainder of this cover page shall be filled out\nfor a reporting person\'s initial filing on this form with\nrespect to the subject class of securities, and for any\nsubsequent amendment containing information which\nwould alter the disclosures provided in a prior cover page.\n\nThe information required 

In [653]:
indexes_df.loc[indexes_df['file_name'] == 'edgar/data/1106939/0000892303-00-000015.txt']

file_name                  document  \
9168  edgar/data/1106939/0000892303-00-000015.txt  0000892303-00-000015.txt   

     form_type  title_page_end_lower_bound  cover_page_q1_start  \
9168    SC 13G                      1666.0               1666.0   

     is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
9168             False                   1.0            1666.0   

      item_section_start  cover_page_last_q_end  cover_page_end  \
9168              6671.0                 6669.0            -1.0   

      num_cusip_b_items  signature_start  amendment_statement_start  success  
9168                2.0           5403.0                       -1.0     True

In [844]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    
    key_info['is_schedule_to'] = [is_schedule_to(text)]
    key_info['has_table_of_contents'] = [has_table_of_contents(text)]
    
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text, key_info['item_section_start'][0])]
    key_info['exhibit_start'] = [get_exhibit_sec_start(text, key_info['signature_start'][0])]
    key_info['main_text_length'] = [len(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['amendment_statement_start'] = find_amendment_statement_start(text, form_type, \
                    lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    key_info['has_jumbled_order'] = [has_jumbled_order(text, form_type, key_info['exhibit_start'][0])]
    
    key_info['has_exhibit_break'] = [has_exhibit_break(text, key_info['cover_page_start'][0],\
                                                       key_info['signature_start'][0])]
    

    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)
    
    

In [ ]:
has_table_of_contents(text)

In [831]:
indexes_df[indexes_df['document'] == '0000928464-12-000024.txt']

file_name                  document  \
22849  edgar/data/1376139/0000928464-12-000024.txt  0000928464-12-000024.txt   
42119   edgar/data/921669/0000928464-12-000024.txt  0000928464-12-000024.txt   

      form_type  title_page_end_lower_bound  cover_page_q1_start  \
22849  SC 13D/A                      7459.0                 -1.0   
42119  SC 13D/A                      7459.0                 -1.0   

      is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
22849              True                   1.0              -1.0   
42119              True                   1.0              -1.0   

       item_section_start  cover_page_last_q_end  cover_page_end  \
22849                 NaN                10241.0         10427.0   
42119                 NaN                10241.0         10427.0   

       num_cusip_b_items  signature_start  amendment_statement_start  success  
22849                1.0          10378.0                     3358.0     True  
42119                1.0          10378.0                     3358.0     True

In [836]:
def is_schedule_to(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*(?:SCHEDULE|SC)\s+TO(/A)?\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)

In [839]:
def has_table_of_contents(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*TABLE\s+OF\s+CONTENTS\s*\n')):
        
        return(True)
    
    else:
        
        return(False)

In [837]:
i = 22849
is_schedule_to(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory))

True

In [838]:
i = 9168
is_schedule_to(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory))

False

In [ ]:
has_table_of_contents(text)

In [845]:
i = 9168
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

TypeError: search() missing 1 required positional argument: 'string'

In [825]:
i = 1
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1364742/0001086364-12-002106.txt  0001086364-12-002106.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1355                 1382   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1355   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                2039                   2031            2039   

   num_cusip_b_items  signature_start  exhibit_start  main_text_length  \
0                  2             7294           8390             11545   

   amendment_statement_start  has_jumbled_order  has_exhibit_break  
0                         -1              False              False

In [821]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/872448/000031506611002274/0000315066-11-002274-index.htm'

In [827]:
print(t[8390:])




Exhibit A




Subsidiary

BlackRock Japan Co. Ltd.
BlackRock Advisors (UK) Limited
BlackRock Institutional Trust Company, N.A.
BlackRock Fund Advisors
BlackRock Asset Management Canada Limited
BlackRock Asset Management Australia Limited
BlackRock Advisors, LLC
BlackRock Investment Management, LLC
BlackRock Investment Management (Australia) Limited
BlackRock (Luxembourg) S.A.
BlackRock (Netherlands) B.V.
BlackRock Fund Managers Limited
BlackRock Asset Management Ireland Limited
BlackRock International Limited
BlackRock Investment Management (UK) Limited



*Entity beneficially owns 5% or greater of the outstanding
shares of the security class being reported on this
Schedule 13G.
Exhibit B


POWER OF ATTORNEY

The undersigned, BLACKROCK, INC., a corporation duly organized
under the laws of the State of Delaware, United States (the
"Company"), does hereby make, constitute and appoint each of Robert
Connolly, Howard Surloff, Edward Baer, Bartholomew Battista,
Daniel Waltcher, Karen Cla

In [820]:
print(t[588:3433])

Item 1(a).	Name of Issuer:

		Atmel Corporation

Item 1(b).	Name of Issuer's Principal Executive Offices:

		2325 Orchard Parkway
		San Jose, CA  95131


Item 2(a).	Name of Person Filing:

		FMR LLC

Item 2(b).	Address or Principal Business Office or, if None,
Residence:

		82 Devonshire Street, Boston,
Massachusetts  02109

Item 2(c).	Citizenship:

		Not applicable

Item 2(d).	Title of Class of Securities:

		Common Stock

Item 2(e).	CUSIP Number:

		049513104

Item 3.	This statement is filed pursuant to Rule 13d-1(b) or 13d-2(b)
and the person filing, FMR LLC, is a parent holding company
in accordance with Section 240.13d-1(b)(ii)(G).  (Note:  See
Item 7).

Item 4.	Ownership

	(a)	Amount Beneficially Owned:	23,492,785

	(b)	Percent of Class:	5.126%

	(c)	Number of shares as to which such
person has:

	(i)	sole power to vote or to direct
the vote:	1,749,751

	(ii)	shared power to vote or to
direct the vote:	0

	(iii)	sole power to dispose or to
direct the disposition of:	23,492,785

	

In [826]:
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

In [781]:
get_index_url('edgar/data/814133/0000814133-13-000028.txt')

'https://www.sec.gov/Archives/edgar/data/814133/000081413313000028/0000814133-13-000028-index.htm'

In [848]:
def is_schedule_to(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*(?:SCHEDULE|SC)\s+TO(/A)?\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)
        
        
        
def has_table_of_contents(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*TABLE\s+OF\s+CONTENTS\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)

In [853]:
i = 100000
eg = get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

eg

file_name                  document  \
0  edgar/data/1184765/0001445546-13-003273.txt  0001445546-13-003273.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1824                 1891   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1869                3965   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   3770            3830                  2            11106   

   exhibit_start  main_text_length  amendment_statement_start  \
0             -1             12207                         -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [851]:
eg.columns

Index(['file_name', 'document', 'form_type', 'title_page_end_lower_bound',
       'cover_page_q1_start', 'is_rep_q_as_items', 'is_schedule_to',
       'has_table_of_contents', 'num_cusip_sedol_b_q1', 'cover_page_start',
       'item_section_start', 'cover_page_last_q_end', 'cover_page_end',
       'num_cusip_b_items', 'signature_start', 'exhibit_start',
       'main_text_length', 'amendment_statement_start', 'has_jumbled_order',
       'has_exhibit_break'],
      dtype='object')

In [852]:
def write_indexes_to_table(file_name, document, form_type, directory, engine):
    
    try:
        
        df = get_key_indices(file_name, document, form_type, directory)
        df['success'] = True
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)
        
    except:
        
        df = pd.DataFrame({'file_name': [file_name], 'document': [document], 'form_type': [form_type], \
              'title_page_end_lower_bound': [-2], 'cover_page_q1_start': [-2], 'is_rep_q_as_items': [-2],\
              'is_schedule_to': [-2],  'has_table_of_contents': [-2], 'num_cusip_sedol_b_q1': [-2],\
              'cover_page_start': [-2], 'item_section_start': [-2], 'cover_page_last_q_end': [-2],\
              'cover_page_end': [-2], 'num_cusip_b_items': [-2], 'signature_start': [-2], \
              'exhibit_start': [-2], 'main_text_length': [-2], 'amendment_statement_start': [-2],\
              'has_jumbled_order': [-2], 'has_exhibit_break': [-2], 'success': [False]})
        
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)    

In [815]:
print(re.sub('\n\s+\n', '\n', t[25875:]))


SIGNATURES
     After reasonable inquiry and to the best of my knowledge and belief, I certify that the
information set forth in this statement is true, complete and correct.
     Dated: August 15, 2011
STRATFORD CAPITAL PARTNERS, L.P.
By:
Stratford Capital GP Associates, L.P., its general partner
By:
Stratford Capital Corporation, its general partner
By:
/s/ David W. Knickel
David W. Knickel, Vice President
STRATFORD CAPITAL GP ASSOCIATES, L.P.
By:
Stratford Capital Corporation, its general partner
By:
/s/ David W. Knickel
David W. Knickel, Vice President
STRATFORD CAPITAL CORPORATION
By:
/s/ David W. Knickel
David W. Knickel, Vice President
RETAIL & RESTAURANT GROWTH CAPITAL, L.P.
By:
Retail & Restaurant Growth Partners, L.P., its general partner
By: Retail & Restaurant Growth Management, Inc., its general partner
By:
/s/ Raymond C. Hemmig
Raymond C. Hemmig, Chairman and CEO
RETAIL & RESTAURANT GROWTH PARTNERS, L.P.
By: Retail & Restaurant Growth Management, Inc., its general partne

In [790]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1742550/000121390018012112/0001213900-18-012112-index.htm'

In [804]:
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

In [736]:
find_orthodox_cover_page_q1_start_end(t)

(-1, -1)

In [793]:
t[15471:16200]

'AMENDMENT NO. 3 TO SCHEDULE 13D\n\n\n\n\n\n\n\xa0\xa0\xa0\xa0\xa0This Amendment No.\xa03 to Schedule\xa013D (this “\nThird Amendment\n”) amends and supplements the\nSchedule\xa013D originally filed on August\xa021, 2006, as amended by Amendment No.\xa01 on August\xa028, 2006,\nand by Amendment No.\xa02 on September\xa024, 2010 (the “\nSecond Amendment\n”) (collectively, the “\nSchedule\n13D\n”), which related to the common stock, par value $0.001 per share (“\nCommon Stock\n”), of Teletouch\nCommunications, Inc., a Delaware corporation (the “\nIssuer\n”). Capitalized terms used herein and not\notherwise defined have the meaning assigned to such terms in the Second Amendment. All items or\nresponses not described herein remain as previously reported in the Second Amendment.\n\n\n\n\n\n\n\n'

In [776]:
t[1922:7212]

'\n\n\n\n\n\n\n\n    CUSIP NO. 91529Y106           13G                        Page 2 of 10 Pages\n\n  1. NAME OF REPORTING PERSON\n     S.S. OR I.R.S. IDENTIFICATION NO. OF ABOVE PERSON\n\n        AXA Assurances I.A.R.D. Mutuelle\n\n  2. CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP *                (A) [ ]\n                                                                       (B) [ ]\n\n  3. SEC USE ONLY\n\n  4. CITIZENSHIP OR PLACE OF ORGANIZATION\n     France\n\n\n           NUMBER OF SHARES   5. SOLE VOTING POWER                           0\n               BENEFICIALLY\n                OWNED AS OF   6. SHARED VOTING POWER                    38,369\n          December 31, 2010\n                    BY EACH   7. SOLE DISPOSITIVE POWER                      0\n                  REPORTING\n               PERSON WITH:   8. SHARED DISPOSITIVE POWER               56,017\n\n\n  9. AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH                        56,017\n     REPORTING PERSON\n     (Not 

In [733]:
get_index_url('edgar/data/888002/0000888002-11-000169.txt')

'https://www.sec.gov/Archives/edgar/data/888002/000088800211000169/0000888002-11-000169-index.htm'

In [699]:
get_exhibit_sec_start(text, lower_bound = 1669, upper_bound = 6676)

-1

In [795]:
def get_exhibit_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_upper = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    regex0 = '\n\s*EXHIBIT\s+INDEX\s*\n'
    
    regex1 = '\n\s*EXHIBIT\s+[0-9A-Z](:)?\s*\n'
    
    regex2 = '\n\s*APPENDIX\s+[0-9A-Z](:)?\s*\n'
    
    regex_list = [regex0, regex1, regex2]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_upper)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
        return(-1)

In [ ]:
find_all_orthodox_q1_starts(text, exhibit_start)

In [734]:
regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
         'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'

In [737]:
re.search(regex0, t)

In [741]:
t[1000:]

"------------------\n            (Date of event which requires filing of this Statement)\n\n  Check the appropriate box to designate the rule pursuant to which\n  this Schedule is filed:\n\n    X  Rule 13d-1(b)\n       Rule 13d-1(c)\n       Rule 13d-1(d)\n\n  * The remainder of this cover page shall be filled out for a reporting\n  person's initial filing on this form with respect to the subject class\n  of securities, and for any subsequent amendment containing information\n  which would alter the disclosures provided in a prior cover page.\n\n  The information required in the remainder of this cover page shall not\n  be deemed to be 'filed' for the purpose of Section 18 of the Securities\n  Exchange Act of 1934 ('Act') or otherwise subject to the liabilities\n  of that section of the Act but shall be subject to all other provisions\n  of the Act (however, see the Notes).\n\n                       (CONTINUED ON FOLLOWING PAGE(S))\n\n\n\n\n\n\n\n                                   13G  

In [742]:
page = requests.get('https://www.sec.gov/Archives/edgar/data/5513/000088800211000169/0000888002-11-000169.txt')
page

<Response [200]>

In [743]:
page.content

b"-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n F9OBTNxQEgyxwS0QYqvNcTdxBQbMQ9JPA9jDfjshs7957Aj1yE03B4Q7pk1W+ijm\n 1aZtYaIYyQYFVRn/Y7N2Gg==\n\n<SEC-DOCUMENT>0000888002-11-000169.txt : 20110209\n<SEC-HEADER>0000888002-11-000169.hdr.sgml : 20110209\n<ACCEPTANCE-DATETIME>20110209083424\nACCESSION NUMBER:\t\t0000888002-11-000169\nCONFORMED SUBMISSION TYPE:\tSC 13G/A\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20110209\nDATE AS OF CHANGE:\t\t20110209\nGROUP MEMBERS:\t\tAXA\nGROUP MEMBERS:\t\tAXA ASSURANCES I.A.R.D. MUTUELLE\nGROUP MEMBERS:\t\tAXA ASSURANCES VIE MUTUELLE\nGROUP MEMBERS:\t\tAXA-EQUITABLE LIFE INSURANCE COMPANY\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tUnum Group\n\t\tCENTRAL INDEX KEY:\t\t\t000000

In [748]:
re.search(b'<[a-zA-Z0-9\-]+\s+', page.content)

<re.Match object; span=(4397, 4408), match=b'<PAGE\n\n    '>

In [753]:
re.search(b'<PAGE\s+', page.content)

<re.Match object; span=(4397, 4408), match=b'<PAGE\n\n    '>

In [757]:
re.search(b'>', page.content[4408:])

<re.Match object; span=(6287, 6288), match=b'>'>

In [764]:
6288 + 4408

10696

In [765]:
page.content[4397:10696]

b"<PAGE\n\n    CUSIP NO. 91529Y106           13G                        Page 2 of 10 Pages\n\n  1. NAME OF REPORTING PERSON\n     S.S. OR I.R.S. IDENTIFICATION NO. OF ABOVE PERSON\n\n        AXA Assurances I.A.R.D. Mutuelle\n\n  2. CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP *                (A) [ ]\n                                                                       (B) [ ]\n\n  3. SEC USE ONLY\n\n  4. CITIZENSHIP OR PLACE OF ORGANIZATION\n     France\n\n\n           NUMBER OF SHARES   5. SOLE VOTING POWER                           0\n               BENEFICIALLY\n                OWNED AS OF   6. SHARED VOTING POWER                    38,369\n          December 31, 2010\n                    BY EACH   7. SOLE DISPOSITIVE POWER                      0\n                  REPORTING\n               PERSON WITH:   8. SHARED DISPOSITIVE POWER               56,017\n\n\n  9. AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH                        56,017\n     REPORTING PERSON\n     (Not to be 

In [754]:
re.findall(b'<PAGE\s+', page.content)

[b'<PAGE\n\n    ', b'<PAGE\n\n', b'<PAGE\n\n', b'<PAGE\n\n', b'<PAGE\n']

In [755]:
re.findall(b'</PAGE\s+', page.content)

[]

In [768]:
re.findall(b'<PAGE[^>]', page.content)

[b'<PAGE\n', b'<PAGE\n', b'<PAGE\n', b'<PAGE\n', b'<PAGE\n']

In [756]:
'page'.encode('utf-8')

b'page'

In [772]:
print(fix_unmatched_page_tags(page.content))

b"-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n F9OBTNxQEgyxwS0QYqvNcTdxBQbMQ9JPA9jDfjshs7957Aj1yE03B4Q7pk1W+ijm\n 1aZtYaIYyQYFVRn/Y7N2Gg==\n\n<SEC-DOCUMENT>0000888002-11-000169.txt : 20110209\n<SEC-HEADER>0000888002-11-000169.hdr.sgml : 20110209\n<ACCEPTANCE-DATETIME>20110209083424\nACCESSION NUMBER:\t\t0000888002-11-000169\nCONFORMED SUBMISSION TYPE:\tSC 13G/A\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20110209\nDATE AS OF CHANGE:\t\t20110209\nGROUP MEMBERS:\t\tAXA\nGROUP MEMBERS:\t\tAXA ASSURANCES I.A.R.D. MUTUELLE\nGROUP MEMBERS:\t\tAXA ASSURANCES VIE MUTUELLE\nGROUP MEMBERS:\t\tAXA-EQUITABLE LIFE INSURANCE COMPANY\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tUnum Group\n\t\tCENTRAL INDEX KEY:\t\t\t000000

In [766]:
re.search('A[^B]', 'ACD')

<re.Match object; span=(0, 2), match='AC'>

In [767]:
re.search('A[^B]', 'ABCD')

In [773]:
def fix_unmatched_page_tags(text):
    
    # First fix missing right dels
    
    start_tag_r_regex = '<PAGE[^>]' 
    end_tag_r_regex = '</PAGE[^>]'
    
    corrected_r_start = '<PAGE>\n' # Introduce newline in case newline replace by right del
    corrected_r_end = '</PAGE>\n'
    
    fixed_content = re.sub(start_tag_r_regex, corrected_r_start, text)
    fixed_content = re.sub(end_tag_r_regex, corrected_r_end, fixed_content)
    
    # Now fix missing left dels
    
    start_tag_l_regex = '[^<]PAGE>' 
    end_tag_l_regex = '[^<]/PAGE>'
    
    corrected_l_start = '\n<PAGE>' # Introduce newline in case newline replace by left del
    corrected_l_end = '\n</PAGE>'
    
    fixed_content = re.sub(start_tag_l_regex, corrected_l_start, fixed_content)
    fixed_content = re.sub(end_tag_l_regex, corrected_l_end, fixed_content)
    
    return(fixed_content)


def clean_text(text):
    
    # this function gets rid of unwanted characters and spaces
    
    result = fix_unmatched_page_tags(text) # First fix tags which are missing delimeters
    
    char_list = ['\xa0', '&#160;', '&#\n160;']
    
    for c in char_list:
        
        result = re.sub(c, ' ', result) 
        
    return(result)

In [769]:
def fix_unmatched_page_tags(page_content):
    
    # First fix missing right dels
    
    start_tag_r_regex = '<PAGE[^>]' 
    end_tag_r_regex = '</PAGE[^>]'
    
    corrected_r_start = '<PAGE>\n' # Introduce newline in case newline replace by right del
    corrected_r_end = '</PAGE>\n'
    
    fixed_content = re.sub(start_tag_r_regex.encode('utf-8'), corrected_r_start.encode('utf-8'), page.content)
    fixed_content = re.sub(end_tag_r_regex.encode('utf-8'), corrected_r_end.encode('utf-8'), fixed_content)
    
    # Now fix missing left dels
    
    start_tag_l_regex = '[^<]PAGE>' 
    end_tag_l_regex = '[^<]/PAGE>'
    
    corrected_l_start = '\n<PAGE>' # Introduce newline in case newline replace by left del
    corrected_l_end = '\n</PAGE>'
    
    fixed_content = re.sub(start_tag_l_regex.encode('utf-8'), corrected_r_start.encode('utf-8'), fixed_content)
    fixed_content = re.sub(end_tag_l_regex.encode('utf-8'), corrected_r_end.encode('utf-8'), fixed_content)
    
    return(fixed_content)

In [751]:
re.search(b'<[a-zA-Z0-9\-\/]+\s+', page.content).group(0)

b'<PAGE\n\n    '

In [744]:
soup = BeautifulSoup(page.content, 'html.parser')

In [749]:
soup.find('PAGE')

In [700]:
def has_exhibit_break(text, cover_page_start, signature_start):
    
    exhibit_st = get_exhibit_sec_start(text, cover_page_start, signature_start)
    
    if(exhibit_st != -1):
        
        return(True)
    
    else:
        
        return(False)

In [ ]:
def has_jumbled_order(text, form_type, has_table_of_contents = None, exhibit_start):
    
    # This function is defined to be true if there are item sections or signature sections in the parts of the
    # text which are before the last instance of an orthodox q1 of a cover page (hence "jumbled")
    # this can include cases where for instance, an order goes cover_page -> items -> signatures -> 
    # cover_page -> items -> signatures 
    
    
    result = False # Assume false till proven otherwise
    
    q1_starts = find_all_orthodox_q1_starts(text, exhibit_start)

    for i in range(len(q1_starts)):

        if(i == 0):
            
            if(has_table_of_contents is None):
                
                has_table_of_contents = has_table_of_contents(text, 0, q1_starts[i])
            

            segment = get_bounded_text(text, 0, q1_starts[i])
            
            if(has_table_of_contents):
                
                table_of_conts_index
            
            has_items = (get_item_section_start(segment, form_type) != -1)
            has_signatures = (get_signatures_sec_start(segment) != -1)

        else:

            segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

            has_items = (get_item_section_start(segment, form_type) != -1)
            has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

    return(result)

In [655]:
get_index_url('edgar/data/1106939/0000892303-00-000015.txt')

'https://www.sec.gov/Archives/edgar/data/1106939/000089230300000015/0000892303-00-000015-index.htm'

In [709]:
def find_all_orthodox_q1_starts(text, exhibit_start = None):
    
    # Finds all orthodox q1s BEFORE the exhibit section if it exists in the main text
    # (we do not want cover pages from exhibit parts)
    
    lst = []
    
    start, end = find_orthodox_cover_page_q1_start_end(text)
    
    while(start != -1):
        
        lst.append(start)
        p_start, p_end = find_orthodox_cover_page_q1_start_end(text, end)
        
        if(p_start != -1):
            
            start = end + p_start
            end = end + p_end
            
        else:
            
            start = -1
            
    if(exhibit_start is not None and exhibit_start != -1):
        
        result = [i for i in lst if i < exhibit_start]
        return(result)

    else:
        
        return(lst)
        

In [720]:
def get_item_section_start(text, form_type):    
    
    
    if(re.search('SC\s+13D', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?\s*security\s+and\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?\s*identity\s+and\s+background',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*source\s+and\s+amount\s+of\s+funds',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*purpose\s+of\s+transaction',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*interest\s+in\s+securities\s+of\s+the\s+issuer',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*contracts,\s+arrangements,\s+understandings',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*material\s+to\s+be\s+filed\s+as\s+exhibits'
                  ]
                       
        
    elif(re.search('SC\s+13G', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name[s]?\s+of\s+person[s]?\s+filing',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+principle',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*c[\)]?[#\.\;\:]?\s*citizenship',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*d[\)]?[#\.\;\:]?\s*title\s+of\s+class',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*e[\)]?[#\.\;\:]?\s*cusip\s+number',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*if\s+this\s+statement\s+is\s+filed\s+pursuant',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*ownership',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*ownership\s+of\s+five',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*ownership\s+of\s+more',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*8[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*9[#\.\;\:]?\s*notice\s+of\s+dissolution',
                   '\n\s*[#\.\;\:]?\s*10[#\.\;\:]?\s*certification'
                  ]
        
    else:
        
        # Not a Schedule 13D(/A) or 13G(/A)
        return(None)
   
    cover_pages_end = find_cover_pages_last_question(text)
    
    if(cover_pages_end):

        text_lowered = text[cover_pages_end:].lower()

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*(?:[0-9])[#\.\;\:]?', text_lowered)
        
        if(search):
            
            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(cover_pages_end + search.start() + num_to_item)  
        
        else:
            return(-1) # ie. assume no Item section (this probably happens with 13D/A and 13G/A)
    
    else:
        
        text_lowered = text.lower() # Assume NO REPORTING PAGES (this happens, especially with 13D/A and 13G/A)

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*[0-9][#\.\;\:]?', text_lowered)

        if(search):

            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(search.start() + num_to_item)  
        
        else: 
             
            result = -1 # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    search_str = search.group(0)
            
                    num_to_item = re.search('item', search_str).start()
                    
                    result = search.start() + num_to_item
                    break
            
            
            return(result)     

In [717]:
def get_signatures_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_lowered = get_bounded_text(text, lower_bound, upper_bound).lower()
    
    regex1 = '\n\s*(signature|signatures)\s*(\.)?\n'
    
    regex2 = 'the\s+following\s+certification\s+shall\s+be\s+included\s+if\s+the\s+statement\s+is\s+filed\s+' + \
             'pursuant to rule 13d-1\(b\)'
    
    regex3 = 'by\s+signing\s+below\s+i\s+certify\s+that,\s+to\s+the\s+best\s+of\s+my\s+knowledge'

    regex4 = 'after\s+reasonable\s+inquiry\s+'
    
    regex_list = [regex1, regex2, regex3, regex4]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_lowered)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
      
        return(-1)

In [710]:
def has_jumbled_order(text, form_type, exhibit_start):
    
    # This function is defined to be true if there are item sections or signature sections in the parts of the
    # text which are before the last instance of an orthodox q1 of a cover page (hence "jumbled")
    # this can include cases where for instance, an order goes cover_page -> items -> signatures -> 
    # cover_page -> items -> signatures 
    
    result = False # Assume false till proven otherwise
    
    q1_starts = find_all_orthodox_q1_starts(text, exhibit_start)

    for i in range(len(q1_starts)):

        if(i == 0):

            segment = get_bounded_text(text, 0, q1_starts[i])

        else:

            segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

        has_items = (get_item_section_start(segment, form_type) != -1)
        has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

    return(result)

In [711]:
has_jumbled_order(t, 'SC 13G', -1)

True

In [706]:
m = 0
for i in range(m):
    
    print('Hello')

In [ ]:
get_exhibit_sec_start(text, lower_bound = None, upper_bound = None)

In [675]:
def cover_page_start(text, lower_bound = None, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text, cover_page_q1)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_orthodox_cover_page_q1_start(text, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)\s*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)

In [687]:
def cover_page_start_is_rep_as_q(text, form_type, lower_bound = None, upper_bound = None, rep_q_as_items = None):
    # this function is for cases where is_rep_q_as_items is True
    
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
        
    search = None
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)

    if(re.search('SC 13D', form_type)):
        
        if(rep_q_as_items):
            
            search = re.search('\n\s*ITEM\s+[\(\|]?\s?1\s?[\)\|]?\s*[:\.]{0,1}(.)+?' + \
                  '\n\s*ITEM\s+[\(\|]?\s?14\s?[\)\|]?\s*[:\.]{0,1}', text_raised, flags = re.DOTALL)
            
        else:
            return(-1)
        
    if(re.search('SC 13G', form_type)):
        
        if(rep_q_as_items):
            
            search = re.search('\n\s*ITEM\s+[\(\|]?\s?1\s?[\)\|]?\s*[:\.]{0,1}(.)+?' + \
                  '\n\s*ITEM\s+[\(\|]?\s?12\s?[\)\|]?\s*[:\.]{0,1}', text_raised, flags = re.DOTALL)
            
        else:
            return(-1)
            
    if(search):
        
        return(search.start() + lower_bound)
    
    else:
        
        return(-1)

In [676]:
q1_starts = find_all_orthodox_q1_starts(t)
q1_starts

[1669, 5796]

In [697]:
get_exhibit_sec_start(t, lower_bound = 5796, upper_bound = None)

-1

In [694]:
get_cover_page_starts(t, 'SC 13G', q1_starts)

[1669, 5796]

In [693]:
t

'\n\nSC 13G\n\n1\n\n\n\n\n\n               SECURITIES AND EXCHANGE COMMISSION\n                      WASHINGTON, D.C 20549\n\n                          SCHEDULE 13G\n\n            Under the Securities Exchange Act of 1934\n                      (Amendment No.     )*\n                                     ----\n\n\n                   THERMOVIEW INDUSTRIES, INC.\n     -------------------------------------------------------\n                        (Name of Issuer)\n\n                          COMMON STOCK\n     -------------------------------------------------------\n                 (Title of Class of Securities)\n\n                           883671 50 5\n     -------------------------------------------------------\n                         (CUSIP Number)\n\n                           12/31/1999\n     -------------------------------------------------------\n     (Date of Event Which Requires Filing of this Statement)\n\n     Check the appropriate box to designate the rule pursuant to\nwh

In [688]:
def find_cover_page_q1_start(text, form_type, lower_bound = None, upper_bound = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
         rep_q_as_items = is_rep_q_as_items(get_bounded_text(text, lower_bound, upper_bound))
            
    if(rep_q_as_items):
        
        result = cover_page_start_is_rep_as_q(text, form_type, lower_bound, upper_bound, rep_q_as_items)
        
    else:
        
        result = find_orthodox_cover_page_q1_start(text, lower_bound, upper_bound)
        
    return(result)

In [692]:
def get_cover_page_starts(text, form_type, q1_starts = None):
    
    cover_page_starts = []
    
    if(q1_starts is not None and len(q1_starts) > 0):
        
        for i in range(len(q1_starts)):
            
            if(i == 0):
                
                start = cover_page_start(text, form_type, lower_bound = 0, cover_page_q1 = q1_starts[i],\
                                         rep_q_as_items = False)
                                                                
                cover_page_starts.append(start)
                
            else:
                
                start = cover_page_start(text, form_type, lower_bound = q1_starts[i-1], \
                                         cover_page_q1 = q1_starts[i], rep_q_as_items = False)
                                                                
                cover_page_starts.append(start)
        
        return(cover_page_starts)
    
    else:
        
        return(None)
      

In [ ]:
get_cover_page_starts(text, form_type, q1_starts = None)

In [690]:
def find_cover_page_q1_start(text, form_type, lower_bound = None, upper_bound = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
         rep_q_as_items = is_rep_q_as_items(get_bounded_text(text, lower_bound, upper_bound))
            
    if(rep_q_as_items):
        
        result = cover_page_start_is_rep_as_q(text, form_type, lower_bound, upper_bound, rep_q_as_items)
        
    else:
        
        result = find_orthodox_cover_page_q1_start(text, lower_bound, upper_bound)
        
    return(result)

    
        
def cover_page_start(text, form_type, lower_bound = None, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text, cover_page_q1)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_cover_page_q1_start(text, form_type, lower_bound, cover_page_q1, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)\s*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)

In [685]:
get_index_url('edgar/data/911631/0001193125-07-031855.txt')

'https://www.sec.gov/Archives/edgar/data/911631/000119312507031855/0001193125-07-031855-index.htm'

In [678]:
t[:1669]

'\n\nSC 13G\n\n1\n\n\n\n\n\n               SECURITIES AND EXCHANGE COMMISSION\n                      WASHINGTON, D.C 20549\n\n                          SCHEDULE 13G\n\n            Under the Securities Exchange Act of 1934\n                      (Amendment No.     )*\n                                     ----\n\n\n                   THERMOVIEW INDUSTRIES, INC.\n     -------------------------------------------------------\n                        (Name of Issuer)\n\n                          COMMON STOCK\n     -------------------------------------------------------\n                 (Title of Class of Securities)\n\n                           883671 50 5\n     -------------------------------------------------------\n                         (CUSIP Number)\n\n                           12/31/1999\n     -------------------------------------------------------\n     (Date of Event Which Requires Filing of this Statement)\n\n     Check the appropriate box to designate the rule pursuant to\nwh

In [679]:
t[1669:5796]

"\n\n\n\n1.   NAME OF REPORTING PERSONS I.R.S. IDENTIFICATION NO. OF ABOVE\n     PERSONS (ENTITIES ONLY)\n          Robert E. Anderson\n\n2.   CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP.\n          (a) [x]\n          (b) [ ]\n\n3.   SEC USE ONLY\n\n4.   CITIZENSHIP OR PLACE OF ORGANIZATION\n\n          U.S.A.\n\n\nNUMBER OF                5.   SOLE VOTING POWER: 1,667\n SHARES\nBENEFICIALLY             6.   SHARED VOTING POWER:  0\n OWNED BY\nEACH REPORTING           7.   SOLE DISPOSITIVE POWER: 1,667\n PERSON WITH\n                         8.   SHARED DISPOSITIVE POWER: 0\n\n9.   AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON\n\n          1,667 Shares\n\n\n10.  CHECK IF THE AGGREGATE AMOUNT IN ROW (9) EXCLUDES CERTAIN\n     SHARES\n     [x] Excludes 455,215 held by the Robert E. Anderson Trust\n     dtd 4/15/98\n\n\n11.  PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (9)\n\n          .02\n\n12.  TYPE OF REPORTING PERSON\n\n          IN\n\n\nItem 1(a) Name of Issuer:

In [ ]:
def find_all_cover_page_starts(text, q1_starts = None, )

In [ ]:
def is_rep_q_as_items(text, q1_start = None):
    
    # this function works on the basis that the the actual "items" in the real item section does not go beyond
    # Item 10. So by searching for Item 12 or 14 (in SC 13G and SC 13D respectively), we can detect whether
    # a filer has erroneously labelled the questions in the reporting pages as items
    
    if(q1_start is None):
      
        q1_start = find_orthodox_cover_page_q1_start(text)
    
    if(q1_start == -1):
    
        text_raised = text.upper()
        
        regex = '\n\s*ITEM\s*(\.)?\s*[\(]?\s*1[24]\s*[\)]?(\.)?'
        
        search = re.search(regex, text_raised)
        
        if(search):
            return(True)
        else:
            return(False)
            
    else:
      
        return(False)

In [674]:
t[1669:5796]

"\n\n\n\n1.   NAME OF REPORTING PERSONS I.R.S. IDENTIFICATION NO. OF ABOVE\n     PERSONS (ENTITIES ONLY)\n          Robert E. Anderson\n\n2.   CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP.\n          (a) [x]\n          (b) [ ]\n\n3.   SEC USE ONLY\n\n4.   CITIZENSHIP OR PLACE OF ORGANIZATION\n\n          U.S.A.\n\n\nNUMBER OF                5.   SOLE VOTING POWER: 1,667\n SHARES\nBENEFICIALLY             6.   SHARED VOTING POWER:  0\n OWNED BY\nEACH REPORTING           7.   SOLE DISPOSITIVE POWER: 1,667\n PERSON WITH\n                         8.   SHARED DISPOSITIVE POWER: 0\n\n9.   AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON\n\n          1,667 Shares\n\n\n10.  CHECK IF THE AGGREGATE AMOUNT IN ROW (9) EXCLUDES CERTAIN\n     SHARES\n     [x] Excludes 455,215 held by the Robert E. Anderson Trust\n     dtd 4/15/98\n\n\n11.  PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (9)\n\n          .02\n\n12.  TYPE OF REPORTING PERSON\n\n          IN\n\n\nItem 1(a) Name of Issuer:

In [667]:
start, end = find_orthodox_cover_page_q1_start_end(t)

In [668]:
end

1695

In [671]:
find_orthodox_cover_page_q1_start_end(text, 1695)

(805, 854)

In [662]:
def find_orthodox_cover_page_q1_start_end(text, lower_bound = None, upper_bound = None):

    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()

    regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?'

    regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
    
    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
             'PERSON[\(]?[S]?[\)]?'
    
    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
             'ABOVE\s+PERSON[\(]?[S]?[\)]?'
    
    regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'
    
    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
             '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
             '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'
    
    
    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'
    
    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'
    
    regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
              'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
    
    for i in range(len(regex_list)):
        
        search = re.search(regex_list[i], text_raised)
        
        if(search):
            
            break

    if(search):
        
        return(search.start(), search.end())
    
    else:
        
        return(-1, -1)   

In [656]:
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

In [657]:
t[1669:6676]

"\n\n\n\n1.   NAME OF REPORTING PERSONS I.R.S. IDENTIFICATION NO. OF ABOVE\n     PERSONS (ENTITIES ONLY)\n          Robert E. Anderson\n\n2.   CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP.\n          (a) [x]\n          (b) [ ]\n\n3.   SEC USE ONLY\n\n4.   CITIZENSHIP OR PLACE OF ORGANIZATION\n\n          U.S.A.\n\n\nNUMBER OF                5.   SOLE VOTING POWER: 1,667\n SHARES\nBENEFICIALLY             6.   SHARED VOTING POWER:  0\n OWNED BY\nEACH REPORTING           7.   SOLE DISPOSITIVE POWER: 1,667\n PERSON WITH\n                         8.   SHARED DISPOSITIVE POWER: 0\n\n9.   AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON\n\n          1,667 Shares\n\n\n10.  CHECK IF THE AGGREGATE AMOUNT IN ROW (9) EXCLUDES CERTAIN\n     SHARES\n     [x] Excludes 455,215 held by the Robert E. Anderson Trust\n     dtd 4/15/98\n\n\n11.  PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (9)\n\n          .02\n\n12.  TYPE OF REPORTING PERSON\n\n          IN\n\n\nItem 1(a) Name of Issuer:

In [632]:
def get_main_doc_text(file_name, document, directory):
  
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    soup = BeautifulSoup(full_text, 'html5lib')
    main_doc_text = soup.find(["document", "DOCUMENT"]).get_text('\n')
    
    return(main_doc_text)

In [633]:
get_index_url(sc_13d_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/317540/000002134413000014/0000021344-13-000014-index.htm'

In [646]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [625]:
t[22955:]

'\n\n\n\n\n \n\nAPPENDIX A\n\n \n\nName, business address, present principal occupation or employment and place of citizenship of the directors and executive officers of\n\n \n\nFONDS STRATÉGIQUE D’INVESTISSEMENT\n\n \n\nThe name, business address and present principal occupation or employment of each of the directors and executive officers of Fonds Stratégique d’Investissement are set forth below. The business address of each director and executive officer is Fonds Stratégique d’Investissement c/o 56, rue de Lille, 75007 Paris, France. Unless otherwise indicated, each director and executive officer is a citizen of France.\n\n \n\nDIRECTORS\n\n \n\n\n\n\nName\n\n\nPresent Principal Occupation or Employment\n\n\n\n\n \n\n\n\n\n\nJEAN-PIERRE JOUYET\n\n\nChairman of the Board of Directors\n\n\n\n\n \n\n\n\n\n\nJEAN-YVES GILET\n\n\nChief Executive Officer\n\n\n\n\n \n\n\n\n\n\nPHILIPPE BRAIDY\n\n\nSenior Vice President\n\n\n\n\n \n\n\n\n\n\nDAVID AZEMA\n\n\nDirector\n\n\n\n\n \n\n\n\n\n\nF

In [620]:
t[11654:]

'\n\xa0\n\n\n\n\n\n\n\n Exhibit\n\xa0\xa0\n Description of Exhibit\n\n\n\n\n99.1\n\xa0\xa0\nJoint Filing Agreement.\n\n\n\n\n99.2\n\xa0\xa0\nPower of Attorney.\n \xa0 Page 9 of 30\n\n\n\n\n\n\n SCHEDULE I  EXECUTIVE OFFICERS AND DIRECTORS OF  REPORTING PERSONS \nThe following sets forth the name and present principal occupation of each executive officer and director of Bank of America Corporation\nand Bank of America, N.A. The business address of each of the executive officers and directors of Bank of America Corporation is Bank of America Corporate Center, 100 North Tryon Street, Charlotte, North Carolina 28255. The business address of each\nof the executive officers and directors of Bank of America, N.A. is 101 South Tryon Street, Charlotte, North Carolina 28255.  \xa0\n\n\n\n\n\n\n\n\n\n Name\n\xa0\xa0\n Position with Bank of\nAmerica Corporation\n\xa0\xa0\n Principal Occupation\n\nBrian T. Moynihan\n\xa0\xa0\nChief Executive Officer, President and Director\n\xa0\xa0\nChief Executiv

In [616]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text, key_info['item_section_start'][0])]
    key_info['exhibit_start'] = [get_exhibit_sec_start(text, key_info['signature_start'][0])]
    key_info['main_text_length'] = [len(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['amendment_statement_start'] = find_amendment_statement_start(text, form_type, \
                    lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])

    
    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

In [576]:
get_index_url(sc_13d_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1363679/000126645406000277/0001266454-06-000277-index.htm'

In [582]:
find_title_page_end(t)

KeyboardInterrupt: 

In [577]:
sc_13d_df.loc[i, 'document']

'0001266454-06-000277.txt'

In [586]:
text_raised = t.upper()

regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
         'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'

regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
         'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?'

regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
         'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'

regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
         'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
         'PERSON[\(]?[S]?[\)]?'

regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
         'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
         'ABOVE\s+PERSON[\(]?[S]?[\)]?'

regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
         'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'

regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
         '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
         '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'


regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
         '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
         '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'

regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'

regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'

regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
          'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'

In [587]:
re.search(regex0, text_raised)

<re.Match object; span=(4920, 5198), match='\n            \n          \n\n      \n    \n    \>

In [588]:
regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
start = None

for i in range(len(regex_list)):

    search = re.search(regex_list[i], text_raised)

    if(search):

        if(start is None):

            start = search.start()

        else:

            new = search.start()

            if(new < start):

                start = new            

KeyboardInterrupt: 

In [589]:
def find_orthodox_cover_page_q1_start(text):

    text_raised = text.upper()

    regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?'

    regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
    
    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
             'PERSON[\(]?[S]?[\)]?'
    
    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
             'ABOVE\s+PERSON[\(]?[S]?[\)]?'
    
    regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'
    
    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
             '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
             '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'
    
    
    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'
    
    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'
    
    regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
              'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
    
    for i in range(len(regex_list)):
        
        search = re.search(regex_list[i], text_raised)
        
        if(search):
            
            break

    if(search):
        
        return(search.start())
    
    else:
        
        return(-1)   

In [585]:
find_orthodox_cover_page_q1_start(t)

KeyboardInterrupt: 

In [578]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [580]:
print(t)


SC 13D
1
broadcaster_sc13d-061206.htm
SCHEDULE 13-D


  
    
      Schedule 13-D






  
    
      

          
            
              UNITED
                STATES
              SECURITIES
                AND EXCHANGE COMMISSION
              Washington,
                D.C. 20549
            
          

      
    
    
    SCHEDULE
      13D
    
    Under
      the Securities Exchange Act of 1934
    (Amendment
      No. _____)*
     
     
    
      

          
            
              BROADCASTER,
                INC.
              (formerly
                International Microcomputer Software, Inc.)
            
          
          
            
              (Name
                of Issuer)
            
          
          
             
          
          
            
              Common
                Stock, no par value
            
          
          
            
              (Title
                of Class of Securities)
            
          
    

In [573]:
t[4169:4402]

'____________________________________________________________________________\n\n\n\n------------------------------------------------------------------------\n\n\nCUSIP NO.  20037A201                                             Page 2 of 4\n\n'

In [547]:
t[34441:]

'\n\n\xa0\n\n\xa0\n\nExhibit\n  A\n\nJOINT FILING UNDERTAKING\n\n\xa0\n\nThe\n  undersigned, being duly authorized thereunto, hereby execute this agreement\n  as an exhibit to this Schedule 13D to evidence the agreement of the below-named\n  parties, in accordance with the rules promulgated pursuant to the Securities\n  Exchange Act of 1934, to file this Schedule jointly on behalf of each such party.\n\n\xa0\n\nDated:  May 19, 2006\n\n\xa0\n\nPrides Capital Partners, L.L.C.\n\n\xa0\n\n\n\n    \n        \n            By: \n        \n            /s/ Murray A. Indick  \n\n------------------------ \n\nMurray A. Indick\n\nManaging Member\n\n\xa0\n\n\xa0\n\n\n\n    \n        \n            Kevin A. Richardson, II  \n\n\xa0\n\n\n\n    \n        \n            /s/ Murray A. Indick   \n        \n            By: \n        \n            /s/ Murray A. Indick \n        \n            \xa0 \n    \n        \n            ------------------------   \n        \n            ------------------------  \n    \

In [558]:
def find_cover_pages_last_question(text, rep_q_as_items = None,  lower_bound = None, upper_bound = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(lower_bound is not None and lower_bound > 0):
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[lower_bound:upper_bound]
            
        else:
            
            text_raised = text.upper()[lower_bound:]
            
    else:
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[:upper_bound]
            
        else:
            
            text_raised = text.upper() 
    
    if(rep_q_as_items):
        
        regex = 'ITEM\s*[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?'
        
    else:
    
        regex = '[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?[\*]?\s*(\(SEE\s+INSTRUCTIONS\))?'

    search = re.search(regex, text_raised)

    if(search is None):
        return(None)
    
    end = 0

    while(search is not None):
        
        end = end + search.end()
        search = re.search(regex, text_raised[end:])

    if(lower_bound is not None and lower_bound > 0):
        
        end = end + lower_bound
        
    return(end)       

In [509]:
indexes

NameError: name 'indexes' is not defined

In [554]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [534]:
print(t[3514:])



       Signature

       After reasonable inquiry and to the best of my knowledge and
       belief, I certify that the information set forth in this
       statement is true, complete and correct.

                 02/15/2010
                 Date

                 /s/ Dale M. Brown
                 Signature

                 Dale M. Brown, President
                 Name/Title






In [196]:
i = 1112
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/101507/0001051042-11-000006.txt  0001051042-11-000006.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                        1598                 1716   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1660   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                2576                   2516            2525   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  3             5727                         -1

In [195]:
indexes_df[indexes_df['file_name'] == 'edgar/data/101507/0001051042-11-000006.txt']

file_name                  document  \
1112  edgar/data/101507/0001051042-11-000006.txt  0001051042-11-000006.txt   

     form_type  title_page_end_lower_bound  cover_page_q1_start  \
1112    SC 13G                      1598.0                 -1.0   

     is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
1112             False                   5.0              -1.0   

      item_section_start  cover_page_last_q_end  cover_page_end  \
1112              2576.0                 2516.0          2529.0   

      num_cusip_b_items  signature_start  amendment_statement_start  success  
1112                3.0           5727.0                       -1.0     True

In [197]:
no_cover_start = pd.read_sql("SELECT * FROM edgar.sc13dg_indexes WHERE cover_page_q1_start = -1 AND cover_page_start = -1", engine)
no_cover_start

file_name                  document  \
0     edgar/data/101507/0001051042-11-000006.txt  0001051042-11-000006.txt   
1     edgar/data/741561/0000741561-00-000002.txt  0000741561-00-000002.txt   
2    edgar/data/1051042/0001051042-13-000001.txt  0001051042-13-000001.txt   
3    edgar/data/1051042/0001051042-13-000004.txt  0001051042-13-000004.txt   
4    edgar/data/1051042/0001051042-13-000006.txt  0001051042-13-000006.txt   
5    edgar/data/1051042/0001051042-13-000007.txt  0001051042-13-000007.txt   
6    edgar/data/1051042/0001051042-13-000008.txt  0001051042-13-000008.txt   
7    edgar/data/1051042/0001051042-13-000009.txt  0001051042-13-000009.txt   
8    edgar/data/1051042/0001051042-13-000010.txt  0001051042-13-000010.txt   
9    edgar/data/1051042/0001051042-13-000011.txt  0001051042-13-000011.txt   
10   edgar/data/1051042/0001051042-13-000012.txt  0001051042-13-000012.txt   
11   edgar/data/1051042/0001051042-13-000013.txt  0001051042-13-000013.txt   
12   edgar/data/1051042/0001051042-13-000014.txt  0001051042-13-000014.txt   
13   edgar/data/1051042/0001051042-13-000015.txt  0001051042-13-000015.txt   
14   edgar/data/1051042/0001051042-13-000016.txt  0001051042-13-000016.txt   
15   edgar/data/1051042/0001051042-13-000017.txt  0001051042-13-000017.txt   
16   edgar/data/1051042/0001051042-13-000018.txt  0001051042-13-000018.txt   
17   edgar/data/1051042/0001051042-13-000002.txt  0001051042-13-000002.txt   
18   edgar/data/1051042/0001051042-13-000003.txt  0001051042-13-000003.txt   
19   edgar/data/1438715/0001179591-12-000015.txt  0001179591-12-000015.txt   
20   edgar/data/1117119/0001051042-07-000006.txt  0001051042-07-000006.txt   
21    edgar/data/814427/0000889297-98-000036.txt  0000889297-98-000036.txt   
22    edgar/data/814427/0000889297-98-000045.txt  0000889297-98-000045.txt   
23    edgar/data/806085/0001051042-07-000007.txt  0001051042-07-000007.txt   
24   edgar/data/1311735/0000909143-06-000105.txt  0000909143-06-000105.txt   
25   edgar/data/1311735/0000909143-06-000106.txt  0000909143-06-000106.txt   
26   edgar/data/1376139/0000928464-12-000009.txt  0000928464-12-000009.txt   
27   edgar/data/1376139/0000928464-12-000024.txt  0000928464-12-000024.txt   
28   edgar/data/1128227/0001051042-13-000012.txt  0001051042-13-000012.txt   
29   edgar/data/1051042/0001051042-12-000022.txt  0001051042-12-000022.txt   
..                                           ...                       ...   
414   edgar/data/101507/0001051042-12-000038.txt  0001051042-12-000038.txt   
415    edgar/data/18061/0001193125-13-022562.txt  0001193125-13-022562.txt   
416    edgar/data/18061/0001193125-13-085302.txt  0001193125-13-085302.txt   
417    edgar/data/18061/0001193125-13-022562.txt  0001193125-13-022562.txt   
418    edgar/data/18061/0001193125-13-085302.txt  0001193125-13-085302.txt   
419  edgar/data/1157758/0001051042-07-000003.txt  0001051042-07-000003.txt   
420   edgar/data/750443/0001051042-12-000035.txt  0001051042-12-000035.txt   
421   edgar/data/750443/0001051042-12-000040.txt  0001051042-12-000040.txt   
422   edgar/data/750443/0001051042-12-000044.txt  0001051042-12-000044.txt   
423   edgar/data/754811/0001051042-14-000026.txt  0001051042-14-000026.txt   
424   edgar/data/754811/0001051042-14-000028.txt  0001051042-14-000028.txt   
425   edgar/data/719264/0001138560-07-000016.txt  0001138560-07-000016.txt   
426  edgar/data/1051042/0001051042-07-000002.txt  0001051042-07-000002.txt   
427  edgar/data/1051042/0001051042-07-000003.txt  0001051042-07-000003.txt   
428  edgar/data/1051042/0001051042-07-000004.txt  0001051042-07-000004.txt   
429  edgar/data/1051042/0001051042-07-000005.txt  0001051042-07-000005.txt   
430  edgar/data/1051042/0001051042-07-000006.txt  0001051042-07-000006.txt   
431  edgar/data/1051042/0001051042-07-000007.txt  0001051042-07-000007.txt   
432  edgar/data/1051042/0001051042-07-000008.txt  0001051042-07-000008.txt   
433  edgar/data/1051042/0001051042-07-000009.txt  0001051042-

In [510]:
indexes_df[indexes_df['document'] == '0000950123-10-013272.txt']

file_name                  document  \
488  edgar/data/1201633/0000950123-10-013272.txt  0000950123-10-013272.txt   

    form_type  title_page_end_lower_bound  cover_page_q1_start  \
488  SC 13G/A                      1230.0               1476.0   

    is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
488             False                   2.0            1400.0   

     item_section_start  cover_page_last_q_end  cover_page_end  \
488              9937.0                 8653.0          8683.0   

     num_cusip_b_items  signature_start  amendment_statement_start  success  
488                7.0           1368.0                       -1.0     True

In [521]:
indexes_df[indexes_df['document'] == '0000892303-00-000015.txt']

file_name                  document  \
9168  edgar/data/1106939/0000892303-00-000015.txt  0000892303-00-000015.txt   

     form_type  title_page_end_lower_bound  cover_page_q1_start  \
9168    SC 13G                      1666.0               1666.0   

     is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
9168             False                   1.0            1666.0   

      item_section_start  cover_page_last_q_end  cover_page_end  \
9168              6671.0                 6669.0            -1.0   

      num_cusip_b_items  signature_start  amendment_statement_start  success  
9168                2.0           5403.0                       -1.0     True

In [512]:
i = 488
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1201633/0000950123-10-013272.txt  0000950123-10-013272.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1344                 1625   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1542   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0               10555                   9190            9241   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  7             1510                         -1

In [513]:
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

In [516]:
t[:1542]

'\nSC 13G/A\n1\na55129sc13gza.htm\nSC 13G/A\n\n\n\nsc13gza\n\n\n\nTable of Contents\n\n\n\n\xa0\n\xa0\n\n\n\n\nUNITED STATES\nSECURITIES AND EXCHANGE COMMISSION\n\n\nWashington, D.C. 20549\n\n\nSCHEDULE 13G/A\n\n\nUnder\nthe Securities Exchange Act of 1934\n\xa0\n(Amendment No.\xa06)*\n\nBROADCOM CORPORATION\n\xa0\n\n\n(Name of Issuer)\n\n\nClass\xa0A common stock, par value $0.0001\n\xa0\n(Title of Class of Securities)\n\n111320107\n\xa0\n(CUSIP Number)\n\nDecember\xa031, 2009\n\xa0\n(Date of Event Which Requires Filing of this Statement)\n\nCheck the appropriate box to designate the rule pursuant to which this Schedule is filed:\n\n\n\n\n\n\n\n    \xa0\n\n    o\n    \xa0\n    Rule\xa013d-1 (b)\n\n\n\n    \xa0\n\n    \xa0\n\n    o\n    \xa0\n    Rule\xa013d-1 (c)\n\n\n\n    \xa0\n\n    \xa0\n\n    þ\n    \xa0\n    Rule\xa013d-1 (d)\n\n\n\n\n\n\n\n\n\n    \n    \n    \n\n\n\n    \xa0\n\n\n    *\n    \xa0\n    The remainder of this cover page shall be filled out for a reporting person’s

In [519]:
get_index_url('edgar/data/1429074/0000950123-11-006511.txt')

'https://www.sec.gov/Archives/edgar/data/1429074/000095012311006511/0000950123-11-006511-index.htm'

In [520]:
get_index_url('edgar/data/926660/0000950134-07-014185.txt')

'https://www.sec.gov/Archives/edgar/data/926660/000095013407014185/0000950134-07-014185-index.htm'

In [515]:
print(t[1542:9241])







 
 
 
 
 
 
 
 
 
 
 










CUSIP No.
 
111320107 
 
Page
 
2 
 
of 
 
12 






 



 
 
 
 
 
 





1
 
NAME OF REPORTING PERSON:
I.R.S. Identification Nos. of above persons(entities only):HENRY SAMUELI, PH.D.


 
 
 



 
 
 




2
 
CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP:



 
(a)   o



 
(b)   o



 
 
 



3
 
SEC USE ONLY:


 
 


 
 



 
 
 



4
 
CITIZENSHIP OR PLACE OF ORGANIZATION:


 
 


 
United States



 
 
 
 



 
5
 
SOLE VOTING POWER:


 
 
 


NUMBER OF
 
30,556,607



 
 
 
 



SHARES
6
 
SHARED VOTING POWER:


BENEFICIALLY
 
 


OWNED BY
 
-0-



 
 
 
 



EACH
7
 
SOLE DISPOSITIVE POWER:


REPORTING
 
 


PERSON
 
30,556,607



 
 
 
 



WITH:
8
 
SHARED DISPOSITIVE POWER:


 
 
 


 
 
-0-



 
 
 



9
 
AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON:


 
 


 
30,556,607



 
 
 



10
 
CHECK IF THE AGGREGATE AMOUNT IN ROW (9) EXCLUDES CERTAIN SHARES:


 
 


 
o



 
 
 



11
 
PERCENT OF CLASS REPRESENTED BY AMOUNT

In [511]:
i = 488
get_key_indices(no_cover_start.loc[i, 'file_name'], no_cover_start.loc[i, 'document'], \
                no_cover_start.loc[i, 'form_type'], directory)

KeyError: 'the label [488] is not in the [index]'

In [199]:
get_index_url('edgar/data/741561/0000741561-00-000002.txt')

'https://www.sec.gov/Archives/edgar/data/741561/000074156100000002/0000741561-00-000002-index.htm'

In [180]:
t = get_main_doc_text(sc_13d_df.loc[0, 'file_name'], sc_13d_df.loc[0, 'document'], directory)
t[2657:2700]

'CUSIP No. 233916-20-4\n13D\nPage 3 of 6 Pages'

In [173]:
answer_regex = '\s+([A-Z0]{1}[;,\.]?[A-Z0]{1}[;,\.]?)*([A-Z0]{1}[;,\.]?[A-Z0]{1}[;,\.]?)\s*\n?'

In [174]:
re.search(answer_regex, t[2600:2700])

<re.Match object; span=(17, 23), match='\nTYPE '>

In [157]:
def find_regex1_end(text):
    
    text_lowered = text.lower()

    regex1 = 'but\s+shall\s+be\s+subject\s+to\s+all\s+other\s+provisions\s+of\s+the\s+act\s*' + \
              '(\(however,\s+see\s+the\s+notes\s*\))?(\.)?'

    end = find_last_search_end(regex1, text_lowered)
    
    if(end is not None):
        
        return(end)
    
    else:
        # Use -1 to distinguish cases where regex was not found from other failures
        return(-1)


In [165]:
def get_item_section_start(text, form_type):    
    
    
    if(re.search('SC\s+13D', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?\s*security\s+and\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?\s*identity\s+and\s+background',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*source\s+and\s+amount\s+of\s+funds',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*purpose\s+of\s+transaction',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*interest\s+in\s+securities\s+of\s+the\s+issuer',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*contracts,\s+arrangements,\s+understandings',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*material\s+to\s+be\s+filed\s+as\s+exhibits'
                  ]
                       
        
    elif(re.search('SC\s+13G', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name[s]?\s+of\s+person[s]?\s+filing',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+principle',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*c[\)]?[#\.\;\:]?\s*citizenship',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*d[\)]?[#\.\;\:]?\s*title\s+of\s+class',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*e[\)]?[#\.\;\:]?\s*cusip\s+number',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*if\s+this\s+statement\s+is\s+filed\s+pursuant',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*ownership',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*ownership\s+of\s+five',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*ownership\s+of\s+more',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*8[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*9[#\.\;\:]?\s*notice\s+of\s+dissolution',
                   '\n\s*[#\.\;\:]?\s*10[#\.\;\:]?\s*certification'
                  ]
        
    else:
        
        # Not a Schedule 13D(/A) or 13G(/A)
        return(None)
   
    cover_pages_end = find_cover_pages_last_question(text)
    
    if(cover_pages_end):

        text_lowered = text[cover_pages_end:].lower()

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*(?:[0-9])[#\.\;\:]?', text_lowered)
        
        if(search):

            return(cover_pages_end + search.start())  
        
        else:
            return(None) # ie. assume no Item section (this probably happens with 13D/A and 13G/A)
    
    else:
        
        text_lowered = text.lower() # Assume NO REPORTING PAGES (this happens, especially with 13D/A and 13G/A)

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*[0-9][#\.\;\:]?', text_lowered)

        if(search):

            return(search.start())  
        
        else: 
             
            result = None # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    result = search.start()
                    break
            
            
            return(result) 

In [531]:
def get_signatures_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_lowered = get_bounded_text(text, lower_bound, upper_bound).lower()
    
    regex1 = '\n\s*(signature|signatures)\s*(\.)?\n'
    
    regex2 = 'the\s+following\s+certification\s+shall\s+be\s+included\s+if\s+the\s+statement\s+is\s+filed\s+' + \
             'pursuant to rule 13d-1\(b\)'
    
    regex3 = 'by\s+signing\s+below\s+i\s+certify\s+that,\s+to\s+the\s+best\s+of\s+my\s+knowledge'

    regex4 = 'after\s+reasonable\s+inquiry\s+'
    
    regex_list = [regex1, regex2, regex3, regex4]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_lowered)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
        return(None)

In [529]:
def get_exhibit_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_upper = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    regex0 = '\n\s*EXHIBIT\s+INDEX'
    
    regex1 = '\n\s*EXHIBIT\s+[0-9A-Z](:)?'
    
    regex2 = '\n\s*APPENDIX\s+[0-9A-Z](:)?'
    
    regex_list = [regex0, regex1, regex2]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_upper)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
        return(-1)

In [537]:
get_exhibit_sec_start(t, lower_bound = 3514, upper_bound = None)

-1

In [535]:
t[3514:]

'\n\n       Signature\n\n       After reasonable inquiry and to the best of my knowledge and\n       belief, I certify that the information set forth in this\n       statement is true, complete and correct.\n\n                 02/15/2010\n                 Date\n\n                 /s/ Dale M. Brown\n                 Signature\n\n                 Dale M. Brown, President\n                 Name/Title\n\n\n\n'

In [594]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text, key_info['item_section_start'][0])]
    key_info['exhibit_start'] = [get_exhibit_sec_start(text, key_info['signature_start'][0])]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['amendment_statement_start'] = find_amendment_statement_start(text, form_type, \
                    lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

In [21]:
sc_13d_df = indexes_df[indexes_df['form_type'] == 'SC 13D'].copy().reset_index(drop = True)

In [22]:
sc_13d_df

file_name                  document  \
0      edgar/data/1360823/0001116502-06-000894.txt  0001116502-06-000894.txt   
1      edgar/data/1295315/0001123292-06-000307.txt  0001123292-06-000307.txt   
2      edgar/data/1327670/0000921895-06-001277.txt  0000921895-06-001277.txt   
3       edgar/data/884423/0000884423-10-000004.txt  0000884423-10-000004.txt   
4      edgar/data/1358905/0001005477-06-002180.txt  0001005477-06-002180.txt   
5      edgar/data/1301030/0000950005-06-000298.txt  0000950005-06-000298.txt   
6      edgar/data/1337851/0001337851-06-000014.txt  0001337851-06-000014.txt   
7      edgar/data/1326150/0000902664-06-001334.txt  0000902664-06-001334.txt   
8       edgar/data/709878/0000950103-11-000069.txt  0000950103-11-000069.txt   
9      edgar/data/1326150/0000902664-06-001658.txt  0000902664-06-001658.txt   
10     edgar/data/1349469/0001332277-06-000332.txt  0001332277-06-000332.txt   
11     edgar/data/1362393/0001023175-06-000193.txt  0001023175-06-000193.txt   
12     edgar/data/1363679/0001266454-06-000285.txt  0001266454-06-000285.txt   
13     edgar/data/1363667/0001144204-06-022409.txt  0001144204-06-022409.txt   
14     edgar/data/1363679/0001266454-06-000277.txt  0001266454-06-000277.txt   
15     edgar/data/1362518/0000902561-06-000065.txt  0000902561-06-000065.txt   
16     edgar/data/1295249/0000930413-06-004746.txt  0000930413-06-004746.txt   
17     edgar/data/1095691/0001170918-06-000641.txt  0001170918-06-000641.txt   
18     edgar/data/1363482/0001144204-06-021717.txt  0001144204-06-021717.txt   
19     edgar/data/1125766/0001085037-10-000047.txt  0001085037-10-000047.txt   
20     edgar/data/1040762/0001193125-10-006146.txt  0001193125-10-006146.txt   
21     edgar/data/1040762/0001193125-10-006155.txt  0001193125-10-006155.txt   
22     edgar/data/1040762/0001193125-10-011029.txt  0001193125-10-011029.txt   
23     edgar/data/1040762/0001193125-10-036504.txt  0001193125-10-036504.txt   
24      edgar/data/316888/0000919574-11-001613.txt  0000919574-11-001613.txt   
25     edgar/data/1520637/0001521536-12-000171.txt  0001521536-12-000171.txt   
26     edgar/data/1449359/0001140361-12-010942.txt  0001140361-12-010942.txt   
27     edgar/data/1322747/0001144204-12-013559.txt  0001144204-12-013559.txt   
28     edgar/data/1010917/0000950157-97-000351.txt  0000950157-97-000351.txt   
29     edgar/data/1296621/0001085037-06-001142.txt  0001085037-06-001142.txt   
...                                            ...                       ...   
17474  edgar/data/1295557/0001193125-10-008187.txt  0001193125-10-008187.txt   
17475  edgar/data/1295557/0000807249-10-000029.txt  0000807249-10-000029.txt   
17476  edgar/data/1295557/0000947871-10-000328.txt  0000947871-10-000328.txt   
17477  edgar/data/1473770/0001065949-10-000012.txt  0001065949-10-000012.txt   
17478  edgar/data/1119603/0001104659-10-005141.txt  0001104659-10-005141.txt   
17479  edgar/data/1119603/0000950123-10-015091.txt  0000950123-10-015091.txt   
17480  edgar/data/1119603/0001104659-10-008780.txt  0001104659-10-008780.txt   
17481  edgar/data/1209361/0000891092-10-000499.txt  0000891092-10-000499.txt   
17482  edgar/data/1000194/0000930413-10-000583.txt  0000930413-10-000583.txt   
17483  edgar/data/1411963/0001144204-10-016178.txt  0001144204-10-016178.txt   
17484   edgar/data/946552/0001144204-10-001288.txt  0001144204-10-001288.txt   
17485  edgar/data/1282393/0001193125-10-004473.txt  0001193125-10-004473.txt   
17486  edgar/data/1282393/0001132413-10-000002.txt  0001132413-10-000002.txt   
17487  edgar/data/1318482/0001337851-10-000002.txt  0001337851-10-000002.txt   
17488  edgar/data/1318482/0001337851-10-000004.txt  0001337851-10-000004.txt   
17489  edgar/data/1318482/0001337851-10-000006.txt  0001337851-10-000006.txt   
17490  edgar/data/1069736/0001193125-10-007383.txt  0001193125-10-007383.txt   
17491   edgar/data/826773/0000909518-10-000072.txt  0000909518-10-000072.txt   
17492   edgar/data/918923/0000921895-10-0

In [23]:
max(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'])

87277.0

In [24]:
min(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'])

0.0

In [25]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 20).sum()

12689

In [26]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 40).sum()

11579

In [27]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 60).sum()

10391

In [28]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 80).sum()

9968

In [29]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 100).sum()

9526

In [30]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 150).sum()

8457

In [31]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 200).sum()

7830

In [32]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 250).sum()

7255

In [33]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 300).sum()

6775

In [34]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 500).sum()

5724

In [35]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 750).sum()

4883

In [36]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 1000).sum()

4298

In [37]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 2000).sum()

3175

In [205]:
filt = np.logical_and(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 1000, \
                      sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] < 2000)

sc_13d_df.loc[filt]

file_name                  document  \
7      edgar/data/1326150/0000902664-06-001334.txt  0000902664-06-001334.txt   
8       edgar/data/709878/0000950103-11-000069.txt  0000950103-11-000069.txt   
79      edgar/data/947116/0000950144-97-013146.txt  0000950144-97-013146.txt   
81      edgar/data/915912/0000898822-98-000328.txt  0000898822-98-000328.txt   
88       edgar/data/51103/0000909518-07-000044.txt  0000909518-07-000044.txt   
126    edgar/data/1470423/0000950123-11-012934.txt  0000950123-11-012934.txt   
144    edgar/data/1017475/0001193125-12-006480.txt  0001193125-12-006480.txt   
157    edgar/data/1462180/0001462180-12-000001.txt  0001462180-12-000001.txt   
158    edgar/data/1462180/0001462180-12-000020.txt  0001462180-12-000020.txt   
159    edgar/data/1462180/0001462180-12-000023.txt  0001462180-12-000023.txt   
160    edgar/data/1497246/0001062993-12-000595.txt  0001062993-12-000595.txt   
176    edgar/data/1174893/0001144204-07-012426.txt  0001144204-07-012426.txt   
221     edgar/data/814549/0001193125-13-067504.txt  0001193125-13-067504.txt   
244    edgar/data/1282648/0000909334-06-000190.txt  0000909334-06-000190.txt   
245    edgar/data/1282648/0000909334-06-000192.txt  0000909334-06-000192.txt   
254    edgar/data/1278038/0001364773-06-000001.txt  0001364773-06-000001.txt   
260    edgar/data/1361872/0001144204-12-015596.txt  0001144204-12-015596.txt   
336    edgar/data/1106607/0001144204-07-010764.txt  0001144204-07-010764.txt   
418    edgar/data/1075103/0000950136-00-000243.txt  0000950136-00-000243.txt   
422    edgar/data/1071341/0000894579-06-000231.txt  0000894579-06-000231.txt   
459    edgar/data/1093580/0000891618-00-000922.txt  0000891618-00-000922.txt   
467    edgar/data/1449527/0001521536-12-000023.txt  0001521536-12-000023.txt   
503     edgar/data/912145/0000950124-06-007592.txt  0000950124-06-007592.txt   
519    edgar/data/1571189/0001193125-13-092940.txt  0001193125-13-092940.txt   
555    edgar/data/1159038/0000894189-11-000658.txt  0000894189-11-000658.txt   
573    edgar/data/1159040/0000894189-11-000657.txt  0000894189-11-000657.txt   
630    edgar/data/1390818/0000904454-07-000121.txt  0000904454-07-000121.txt   
637    edgar/data/1571188/0001193125-13-092942.txt  0001193125-13-092942.txt   
646    edgar/data/1056285/0000905718-07-000005.txt  0000905718-07-000005.txt   
697    edgar/data/1508554/0001193125-10-291892.txt  0001193125-10-291892.txt   
...                                            ...                       ...   
17153  edgar/data/1091983/0001023175-07-000027.txt  0001023175-07-000027.txt   
17182  edgar/data/1442596/0001104659-14-042395.txt  0001104659-14-042395.txt   
17185  edgar/data/1500308/0001193125-14-150502.txt  0001193125-14-150502.txt   
17197  edgar/data/1540531/0000905718-14-000499.txt  0000905718-14-000499.txt   
17220   edgar/data/841692/0001365417-07-000013.txt  0001365417-07-000013.txt   
17227  edgar/data/1389613/0001193125-07-036155.txt  0001193125-07-036155.txt   
17238  edgar/data/1343925/0001144204-07-009491.txt  0001144204-07-009491.txt   
17261  edgar/data/1182129/0001104659-14-050284.txt  0001104659-14-050284.txt   
17277  edgar/data/1408193/0001462180-09-000076.txt  0001462180-09-000076.txt   
17297  edgar/data/1122081/0001199835-09-000641.txt  0001199835-09-000641.txt   
17310  edgar/data/1414565/0001104659-16-095621.txt  0001104659-16-095621.txt   
17328  edgar/data/1542093/0001571049-16-011378.txt  0001571049-16-011378.txt   
17334  edgar/data/1417754/0001144204-10-007174.txt  0001144204-10-007174.txt   
17342  edgar/data/1425849/0000903423-16-000932.txt  0000903423-16-000932.txt   
17345  edgar/data/1059272/0001144204-16-085954.txt  0001144204-16-085954.txt   
17360  edgar/data/1437106/0000950123-10-015091.txt  0000950123-10-015091.txt   
17365  edgar/data/1600527/0001193125-16-427911.txt  0001193125-16-427911.txt   
17366  edgar/data/1600527/0001193125-16-433025.txt  0001193125-16-433025.txt   
17369  edgar/data/1386509/0001104659-16-1

In [211]:
i = 637
get_key_indices(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], sc_13d_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1571188/0001193125-13-092942.txt  0001193125-13-092942.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        1240                 1349   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1296   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                3486                   2415            2426   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  3             9611                         -1

In [348]:
i = 17185
idx = get_key_indices(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], sc_13d_df.loc[i, 'form_type'], directory)
idx

file_name                  document  \
0  edgar/data/1500308/0001193125-14-150502.txt  0001193125-14-150502.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        2225                 2288   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     3              2230   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0               40565                  38472           39708   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                 19            85585                         -1

In [349]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [350]:
t[idx.loc[0, 'cover_page_end']:idx.loc[0, 'item_section_start']]

'This Schedule 13D (i)\xa0represents the initial statement on Schedule 13D jointly filed by Tianwen Liu, Yong Feng, Xiaosong Zhang, Junhe Che, Ying Huang, Qiang Peng, Li Wang, Xiaohui Zhu, Yen-wen Kang, Li Huang, Miao Du, Yan Zhou,\nBenson Tam, Jiadong Qu, BENO Group Limited, Jinyuan Development (Hong Kong) Company Limited and Wuxi Jinyuan Industry Investment\xa0& Development Co. Ltd. (collectively, the “Reporting Persons”) with respect to iSoftStone Holdings\nLimited (the “Company” or the “Issuer”), and (ii)\xa0amends and supplements the statement on Schedule 13D filed on July\xa026, 2013, by Mr.\xa0Tianwen Liu with respect to the Issuer with the United States Securities and\nExchange Commission (the “SEC”), as amended and/or supplemented by Amendment No.1 to the Schedule 13D filed on November\xa04, 2013 and Amendment No.2 to the Schedule 13D filed on March\xa03, 2014.'

In [351]:
t[idx.loc[0, 'cover_page_last_q_end']:idx.loc[0, 'cover_page_end']]

'OO\n \xa0\n\n\n(1)\nIncludes Ordinary Shares (as defined below), including Ordinary Shares represented by the ADS (as defined below), indirectly held by Wuxi Jinyuan Industry Investment\n& Development Co. Ltd. through Jinyuan Development (Hong Kong) Company Limited. See Item 5. \n\n\n(2)\nWuxi Jinyuan Industry Investment & Development Co. Ltd. and Jinyuan Development (Hong Kong) Company Limited may also be deemed to beneficially own (i) 103,151,758\nOrdinary Shares held by the other Reporting Persons and (ii) 36,731,389 Ordinary Shares of the Issuer beneficially owned by the Everbright 13D Reporting Persons (as defined below) by reason of the agreements described in Item 4, which are excluded\nfrom the above share amounts and percentages.\xa0See Items 2, 4 and 6. \n\n\n(3)\nBased on a total of 598,049,084 Ordinary Shares, including (i) 582,504,751 Ordinary Shares outstanding as of September 30, 2013, as reported in Exhibit 99.1 to the\nIssuer’s Form 6-K filed with the SEC (as defined 

In [322]:
find_last_footnote_index_end(t, lower_bound = 21481, upper_bound = 22878)

21508

In [354]:
get_index_url('edgar/data/1004039/0000899140-97-000151.txt')

'https://www.sec.gov/Archives/edgar/data/1004039/000089914097000151/0000899140-97-000151-index.htm'

In [346]:
t[21481:22877]

'IN       \n\n\n\n\n\n\n    \n\n\xa0\n\n* Based on an aggregate of 3,746,890,087 Ordinary Shares (comprised of (i)\xa02,380,077,324 Class\xa0A Shares and 659,561,893 Class\xa0B Shares issued and outstanding as of April\xa028, 2014 as disclosed in the Investment Agreement and (ii)\xa0707,250,870 Class\xa0A Shares newly issued by the Issuer to Ali YK under the Investment Agreement).  Each Class\xa0B Share is convertible at the option of the holder into one Class\xa0A Share, and Class\xa0A Shares are not convertible into Class\xa0B Shares.  Based on the foregoing, and pursuant to the SPSA Closing, the percentage of the Ordinary Shares beneficially owned by Yu Feng will equal 2.1%.  Yu Feng is reporting his beneficial ownership of 77,959,008 Class\xa0A Shares as a result of a veto right to be held by YF Venus following the SPSA Closing with respect to any transfer by Ali YK of such 77,959,008 Class\xa0A Shares (subject to certain exceptions).  Yu Feng does not and, following the SPSA Closi

In [347]:
t[22877:]

'9\n\n\n\n\n\n\n\n\xa0\nItem 1.                     Security and Issuer\n\xa0\nThis statement on Schedule 13D (this “Schedule 13D”) relates to the Class\xa0A ordinary shares, par value US$0.00001 per share (the “Class\xa0A Shares”), of Youku Tudou Inc., an exempted company with limited liability incorporated under the laws of the Cayman Islands (the “Issuer”).  The Issuer’s principal place of business is 11/F SinoSteel Plaza, 8 Haidian Street Beijing 100080, People’s Republic of China.\n\xa0\nItem 2.                     Identity and Background\n\xa0\nThis Schedule 13D is being filed jointly, pursuant to Rule\xa013d-1 under the Securities Exchange Act of 1934, as amended (the “Exchange Act”), by (a)\xa0Ali YK Investment Holding Limited, an exempted company with limited liability incorporated under the laws of the Cayman Islands (“Ali YK”), (b)\xa0Alibaba Investment Limited, a company organized under the laws of the British Virgin Islands (“AIL”), (c)\xa0Alibaba Group Holding Limited, an

In [307]:
re.search('\n\s*\n', t[21508:])

<re.Match object; span=(1366, 1369), match='\n\xa0\n'>

In [315]:
text = t
end = find_cover_pages_last_question(text, False)

answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'

if(upper_bound is not None):

    last_answer = re.search(answer_regex, text[end:upper_bound])

else:

    last_answer = re.search(answer_regex, text[end:])

if(last_answer is not None):

    end = end + last_answer.end()

# Now check for footnotes

last_footnote_start = find_last_footnote_index_end(text, lower_bound = end, upper_bound = upper_bound)

if(last_footnote_start is not None):

    end = last_footnote_start

# Now, check for first multi-newlines

search = re.search('\n\s*\n', text[end:])

if(search is not None):

    end = end + search.end()

    

   

In [327]:
text = t
end = find_cover_pages_last_question(text, False)

answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'

if(upper_bound is not None):

    last_answer = re.search(answer_regex, text[end:upper_bound])

else:

    last_answer = re.search(answer_regex, text[end:])

if(last_answer is not None):

    end = end + last_answer.end()

In [328]:
end

21506

In [317]:
find_cover_pages_last_question(text, False)

21481

In [323]:
t == text

True

In [451]:
def get_item_section_start(text, form_type):    
    
    
    if(re.search('SC\s+13D', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?\s*security\s+and\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?\s*identity\s+and\s+background',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*source\s+and\s+amount\s+of\s+funds',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*purpose\s+of\s+transaction',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*interest\s+in\s+securities\s+of\s+the\s+issuer',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*contracts,\s+arrangements,\s+understandings',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*material\s+to\s+be\s+filed\s+as\s+exhibits'
                  ]
                       
        
    elif(re.search('SC\s+13G', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name[s]?\s+of\s+person[s]?\s+filing',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+principle',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*c[\)]?[#\.\;\:]?\s*citizenship',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*d[\)]?[#\.\;\:]?\s*title\s+of\s+class',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*e[\)]?[#\.\;\:]?\s*cusip\s+number',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*if\s+this\s+statement\s+is\s+filed\s+pursuant',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*ownership',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*ownership\s+of\s+five',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*ownership\s+of\s+more',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*8[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*9[#\.\;\:]?\s*notice\s+of\s+dissolution',
                   '\n\s*[#\.\;\:]?\s*10[#\.\;\:]?\s*certification'
                  ]
        
    else:
        
        # Not a Schedule 13D(/A) or 13G(/A)
        return(None)
   
    cover_pages_end = find_cover_pages_last_question(text)
    
    if(cover_pages_end):

        text_lowered = text[cover_pages_end:].lower()

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*(?:[0-9])[#\.\;\:]?', text_lowered)
        
        if(search):
            
            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(cover_pages_end + search.start() + num_to_item)  
        
        else:
            return(None) # ie. assume no Item section (this probably happens with 13D/A and 13G/A)
    
    else:
        
        text_lowered = text.lower() # Assume NO REPORTING PAGES (this happens, especially with 13D/A and 13G/A)

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*[0-9][#\.\;\:]?', text_lowered)

        if(search):

            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(search.start() + num_to_item)  
        
        else: 
             
            result = None # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    search_str = search.group(0)
            
                    num_to_item = re.search('item', search_str).start()
                    
                    result = search.start() + num_to_item
                    break
            
            
            return(result)     

In [325]:
last_answer

<re.Match object; span=(0, 25), match='IN       \n\n\n\n\n\n\n    \n\n\xa0\n\n'>

In [326]:
end

-1

In [330]:
t[21506:22878]

'* Based on an aggregate of 3,746,890,087 Ordinary Shares (comprised of (i)\xa02,380,077,324 Class\xa0A Shares and 659,561,893 Class\xa0B Shares issued and outstanding as of April\xa028, 2014 as disclosed in the Investment Agreement and (ii)\xa0707,250,870 Class\xa0A Shares newly issued by the Issuer to Ali YK under the Investment Agreement).  Each Class\xa0B Share is convertible at the option of the holder into one Class\xa0A Share, and Class\xa0A Shares are not convertible into Class\xa0B Shares.  Based on the foregoing, and pursuant to the SPSA Closing, the percentage of the Ordinary Shares beneficially owned by Yu Feng will equal 2.1%.  Yu Feng is reporting his beneficial ownership of 77,959,008 Class\xa0A Shares as a result of a veto right to be held by YF Venus following the SPSA Closing with respect to any transfer by Ali YK of such 77,959,008 Class\xa0A Shares (subject to certain exceptions).  Yu Feng does not and, following the SPSA Closing, will not have shared dispositive po

In [329]:
find_last_footnote_index_end(text,21506,  22878)

-1

In [314]:
last_answer

<re.Match object; span=(0, 4), match='\nSC '>

In [316]:
end

-1

In [295]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [297]:
t[idx.loc[0, 'cover_page_end']:idx.loc[0, 'item_section_start']]

'* Based on an aggregate of 3,746,890,087 Ordinary Shares (comprised of (i)\xa02,380,077,324 Class\xa0A Shares and 659,561,893 Class\xa0B Shares issued and outstanding as of April\xa028, 2014 as disclosed in the Investment Agreement and (ii)\xa0707,250,870 Class\xa0A Shares newly issued by the Issuer to Ali YK under the Investment Agreement).  Each Class\xa0B Share is convertible at the option of the holder into one Class\xa0A Share, and Class\xa0A Shares are not convertible into Class\xa0B Shares.  Based on the foregoing, and pursuant to the SPSA Closing, the percentage of the Ordinary Shares beneficially owned by Yu Feng will equal 2.1%.  Yu Feng is reporting his beneficial ownership of 77,959,008 Class\xa0A Shares as a result of a veto right to be held by YF Venus following the SPSA Closing with respect to any transfer by Ali YK of such 77,959,008 Class\xa0A Shares (subject to certain exceptions).  Yu Feng does not and, following the SPSA Closing, will not have shared dispositive po

In [299]:
find_last_footnote_start(t, lower_bound = idx.loc[0, 'cover_page_last_q_end'],\
                         upper_bound = idx.loc[0, 'item_section_start'])

21490

In [298]:
t[idx.loc[0, 'cover_page_last_q_end']:idx.loc[0, 'cover_page_end']]

'IN       \n\n\n\n\n\n\n    \n\n\xa0\n\n'

In [300]:
t[21490:]

'\n\n\n\n\n\n\n    \n\n\xa0\n\n* Based on an aggregate of 3,746,890,087 Ordinary Shares (comprised of (i)\xa02,380,077,324 Class\xa0A Shares and 659,561,893 Class\xa0B Shares issued and outstanding as of April\xa028, 2014 as disclosed in the Investment Agreement and (ii)\xa0707,250,870 Class\xa0A Shares newly issued by the Issuer to Ali YK under the Investment Agreement).  Each Class\xa0B Share is convertible at the option of the holder into one Class\xa0A Share, and Class\xa0A Shares are not convertible into Class\xa0B Shares.  Based on the foregoing, and pursuant to the SPSA Closing, the percentage of the Ordinary Shares beneficially owned by Yu Feng will equal 2.1%.  Yu Feng is reporting his beneficial ownership of 77,959,008 Class\xa0A Shares as a result of a veto right to be held by YF Venus following the SPSA Closing with respect to any transfer by Ali YK of such 77,959,008 Class\xa0A Shares (subject to certain exceptions).  Yu Feng does not and, following the SPSA Closing, will 

In [478]:
i = 925
idx = get_key_indices(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], sc_13d_df.loc[i, 'form_type'], directory)
idx

file_name                  document  \
0  edgar/data/1546758/0001193125-12-158467.txt  0001193125-12-158467.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        1458                 1511   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1459   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                2496                   2461            2485   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  2             6002                         -1

In [439]:
find_last_footnote_index_end(t, lower_bound = 4548, upper_bound = 4898)

4812

In [400]:
find_cover_pages_end(t, 'SC 13D', False, 13160, 13336)

-1

In [462]:
get_index_url(sc_13d_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1546758/000119312512158467/0001193125-12-158467-index.htm'

In [479]:
t[2461:2485]

'IN\n \xa0\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\xa0\n\n '

In [480]:
t[2485:2496]

'3\n of 5 \xa0\n '

In [481]:
t[2496:2600]

'Item\xa01. Security and Issuer.  The class of equity securities to which this Schedule 13D relates is the c'

In [455]:
t[5112:5118]

'      '

In [453]:
t[5118:]

'Item\n        1. Security and Issuer\n       \n      This\n        statement relates to the common stock $0.001 par value, of Best Care Inc.,\n        a\n        Nevada Corporation (the “Issuer"). The principal offices of the Issuer are\n        located at 811 Chicago Avenue, Suite 803, Evanston, Illinois 60022.\n      \n      Item\n        2. Identity and Background\n       \n      (a)\n        The\n        name of the person filing this statement: Chaim Limor (the "Reporting\n        Person").\n      \n      (b)\n        The\n        business address of the Reporting Person is: 811 Chicago Avenue, Suite 803,\n        Evanston, Illinois 60022.\n      \n      (c)\n        The\n        present principal occupation of the Reporting Person is serving as secretary\n        and\n        director of the Issuer. The name, principal business, and address of the\n        organization in which such employment is conducted are as follows: Best Care,\n        Inc. 811 Chicago Avenue, Suite 803, E

In [463]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [475]:
find_last_footnote_index_end(t, 2458, 2496)

In [474]:
re.search('Type of reporting\nperson', t)

<re.Match object; span=(2434, 2458), match='Type of reporting\nperson'>

In [467]:
t[:5362]

'\nSC 13D\n1\nd333556dsc13d.htm\nSCHEDULE 13D\n\n\nSchedule 13D\n\n \n\n \xa0\n\xa0 SECURITIES AND EXCHANGE\nCOMMISSION  Washington, D.C. 20549 \n\xa0 \xa0\nSCHEDULE 13D  Under the Securities Exchange Act of 1934  \xa0\n\xa0 Community\nShores Bank Corporation  (Name of Issuer) \n\xa0 \xa0\nCommon Stock \n(Title of Class of Securities)  204046 10 6  (CUSIP Number) \nJerome M. Schwartz  Dickinson Wright PLLC  2600 West Big Beaver Road, Suite 300\n Troy, Michigan 48084-3312  313-223-3628  (Name, Address and Telephone Number of Person Authorized to\nReceive Notices and Communications)  December\xa030, 2011 \n(Date of Event which Requires Filing of this Statement) \n\xa0 \xa0 If the filing person has previously filed a statement on Schedule 13G to report the acquisition which is the subject of this Schedule 13D, and is filing this schedule because of Rule 13d-1(e), 13d-1(f) or\n13d-1(g), check the following box\xa0\xa0¨.  The remainder of this cover page shall be\nfilled out for a reporting

In [458]:
t[idx.loc[0, 'cover_page_last_q_end']:idx.loc[0, 'cover_page_end']]

'IN\n- -------- -----------------------------------------------------------------------\n\n*    Includes 6,000 shares owned by spouse and 1,335,550 shares held by the John\n     A. & Alexandra McMillan Living Trust.\n\n**   The calculation of the foregoing percentage is based on 38,624,272 shares\n     of common stock outstanding as of December 31, 2006, and includes shares\n     underlying options to purchase 125,000 shares of common stock which are\n     exercisable within 60 days of the filing of this Schedule 13D.\n\n\n'

In [459]:
t[idx.loc[0, 'cover_page_end']:idx.loc[0, 'item_section_start']]

'                               Page 2 of 6 Pages\n\n\n\n\n'

In [435]:
t[4600:5200]

'*The\n      Reporting Person received 800,000 shares of the Issuer’s common stock in\n      consideration for services previously rendered to the Issued in the amount\n      of\n      $800. \n    \n    **Based\n      on 4,250,000 shares of the Issuer’s common stock outstanding as of January 9,\n      2007\n    \n      \n        \n      \n      \n        \n          \n          \n        \n        \n          \n          \n          \n            \n          \n        \n        \n          \n          \n        \n      \n    \n     \n    \n      Item\n        1. Security and Issuer\n       \n      This\n        statement relates t'

In [420]:
get_index_url('edgar/data/941179/0000930413-07-001364.txt')

'https://www.sec.gov/Archives/edgar/data/941179/000093041307001364/0000930413-07-001364-index.htm'

In [401]:
find_last_footnote_index_end(t, 13160, 13336)

13197

In [409]:
t[13186:]

'9\n\n\n\n\n\n\n\n\xa0\nResponses to each item of this Statement on Schedule 13D are incorporated by reference into the response to each other item, as applicable.\n\xa0\n\n\n\nItem 1.    \n\nSecurity and Issuer         \n\xa0\nThis Statement on Schedule 13D relates to the shares of common stock, par value $0.01 (the “Common Stock”), of Great Wolf Resorts,\xa0Inc. (the “Issuer”).  The principal executive offices of the Issuer are located at 525 Junction Road, Suite\xa06000 South, Madison, Wisconsin 53717.\n\xa0\n\n\n\nItem 2.    \n\nIdentity and Background         \n\xa0\nThis Statement on Schedule 13D is filed jointly by (i)\xa0K-9 Holdings,\xa0Inc., a Delaware corporation (“K-9 Holdings”), (ii)\xa0K-9 Investors, L.P., a Delaware limited partnership (“K-9 Investors”), (iii)\xa0Apollo Management VII, L.P., a Delaware limited partnership (“Management\xa0VII”), (iv)\xa0AIF VII Management LLC, a Delaware limited liability company (“AIF VII Management”), (v)\xa0Apollo Management, L.P., a D

In [402]:
t[13197:13336]

'Responses to each item of this Statement on Schedule 13D are incorporated by reference into the response to each other item, as applicable.'

In [391]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [406]:
def find_cover_pages_end(text, form_type, rep_q_as_items = None, lower_bound = None, upper_bound = None):
    
    if(upper_bound is None):
        
        upper_bound = get_item_section_start(text, form_type)
    
    if(lower_bound is None):
        
        lower_bound = find_cover_pages_last_question(text, rep_q_as_items, None, upper_bound)
    
    end = None
        
    # First check for footnotes
    
    last_footnote_start = find_last_footnote_index_end(text, lower_bound, upper_bound)
    
    if(last_footnote_start != -1):
        
        end = last_footnote_start
        
        search = re.search('\n\s*\n', text[end:upper_bound])

        if(search is not None):

            end = end + search.end()

            return(end)
        
 
    answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'

    last_answer = re.search(answer_regex, text[lower_bound:upper_bound])

    if(last_answer is not None):

        end = lower_bound + last_answer.end()
        return(end)

    # Finally, try finding a key stopword in all caps, such as SCHEDULE 13D, CUSIP, etc...

    end = first_header_word_after_cover_page(text, form_type, lower_bound, \
                                       upper_bound, rep_q_as_items)

    if(end != -1):

        return(end)

    else:

        return(-1)

            

    

In [395]:
t[13330:]

'cable.\n\xa0\n\n\n\nItem 1.    \n\nSecurity and Issuer         \n\xa0\nThis Statement on Schedule 13D relates to the shares of common stock, par value $0.01 (the “Common Stock”), of Great Wolf Resorts,\xa0Inc. (the “Issuer”).  The principal executive offices of the Issuer are located at 525 Junction Road, Suite\xa06000 South, Madison, Wisconsin 53717.\n\xa0\n\n\n\nItem 2.    \n\nIdentity and Background         \n\xa0\nThis Statement on Schedule 13D is filed jointly by (i)\xa0K-9 Holdings,\xa0Inc., a Delaware corporation (“K-9 Holdings”), (ii)\xa0K-9 Investors, L.P., a Delaware limited partnership (“K-9 Investors”), (iii)\xa0Apollo Management VII, L.P., a Delaware limited partnership (“Management\xa0VII”), (iv)\xa0AIF VII Management LLC, a Delaware limited liability company (“AIF VII Management”), (v)\xa0Apollo Management, L.P., a Delaware limited partnership (“Apollo Management”), (vi)\xa0Apollo Management GP, LLC, a Delaware limited liability company (“Management GP”), (vii)\xa0Apoll

In [ ]:
find_last_search_start(regex, text)

In [215]:
def get_bounded_text(text, lower_bound = None, upper_bound = None):
    
    if(lower_bound is not None):
        
        if(upper_bound is not None):
            
            if(lower_bound >= upper_bound):
                
                raise ValueError("upper_bound not more than lower_bound")
                
            else:
                
                return(text[lower_bound:upper_bound])
            
        else:
            
            return(text[lower_bound:])
        
    else:
        
        if(upper_bound is not None):
            
            return(text[lower_bound:upper_bound])
        
        else:
            
            return(text)
    

In [433]:
def find_last_footnote_index_end(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    
    last_footnote_ind_end = find_last_search_end('\n\s*[\(\|]?\s*([*]+|[0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]?\s*[a-zA-Z]',\
                                                 bounded_text)
    
    if(last_footnote_ind_end is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_ind_end + lower_bound
            
        else: 
            
            result = last_footnote_ind_end
            
        return(result)
            
    else:
        
        return(-1)
    

In [476]:
def find_last_footnote_index_end(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   
    
    # first try regex1
    
    last_footnote_ind_end  = find_last_search_end(regex1, bounded_text)
    
    if(last_footnote_ind_end is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_ind_end + lower_bound
            
        else: 
            
            result = last_footnote_ind_end
            
        return(result)
            
    else:
        
        # Try regex2
        
        last_footnote_ind_end = find_last_search_end(regex2, bounded_text)
    
        if(last_footnote_ind_end is not None):

            if(lower_bound is not None):

                result = last_footnote_ind_end + lower_bound

            else: 

                result = last_footnote_ind_end

            return(result)
        
        else:
            
            return(-1)

In [477]:
def find_last_footnote_start(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   
    
    # first try regex1
    
    last_footnote_start = find_last_search_start(regex1, bounded_text)
    
    if(last_footnote_start is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_start + lower_bound
            
        else: 
            
            result = last_footnote_start
            
        return(result)
            
    else:
        
        # Try regex2
        
        last_footnote_start = find_last_search_start(regex2, bounded_text)
    
        if(last_footnote_start is not None):

            if(lower_bound is not None):

                result = last_footnote_start + lower_bound

            else: 

                result = last_footnote_start

            return(result)
        
        else:
            
            return(-1)

In [275]:
def first_header_word_after_cover_page(text, form_type, cover_page_last_q = None, upper_bound = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(cover_page_last_q is None):
        
        cover_page_last_q = find_cover_pages_last_question(text, rep_q_as_items,  lower_bound, upper_bound)
        
    if(cover_page_last_q == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
    
    else:
        
        text_to_search = get_bounded_text(text, cover_page_last_q, upper_bound)
        
        text_raised = text_to_search.upper()

        regex = '\n\s*(CUSIP|SEDOL|SCHEDULE\s+13[DG]|PAGE|13[DG])'

        search = re.search(regex, text_raised)

        if(search):

            num_forward = search.start()
            
            start = cover_page_last_q + num_forward

            return(start)

        else:

            return(-1)

In [246]:
first_header_word_after_cover_page(t, sc_13d_df.loc[i, 'form_type'], \
                                   cover_page_last_q = 2415, upper_bound = 3486, rep_q_as_items = False)

3433

In [247]:
t[3433:3486]

'\n\n\n\n\n\n\n\n\n\n\n\n\n\nCUSIP No. Q62163110\n\xa0\xa0\n Page\n 3\n of 5 \xa0'

In [290]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)

In [254]:
find_last_footnote_start(t, lower_bound = 2415, upper_bound = 3433)

2942

In [376]:
def find_cover_pages_end(text, form_type, rep_q_as_items = None, lower_bound = None, upper_bound = None):
    
    if(upper_bound is None):
        
        upper_bound = get_item_section_start(text, form_type)
    
    if(lower_bound is None):
        
        lower_bound = find_cover_pages_last_question(text, rep_q_as_items, None, upper_bound)
    
    end = None
        
    # First check for footnotes
    
    last_footnote_start = find_last_footnote_index_end(text, lower_bound, upper_bound)
    
    if(last_footnote_start != -1):
        
        end = last_footnote_start
        
        search = re.search('\n\s*\n', text[end:])

        if(search is not None):

            end = end + search.end()

            return(end)


        else:

            return(-1)
        
    else:
        
        answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'
    
        last_answer = re.search(answer_regex, text[lower_bound:upper_bound])

        if(last_answer is not None):

            end = lower_bound + last_answer.end()
            return(end)
            
        else:

            # Finally, try finding a key stopword in all caps, such as SCHEDULE 13D, CUSIP, etc...

            end = first_header_word_after_cover_page(text, form_type, lower_bound, \
                                               upper_bound, rep_q_as_items)
            
            if(end != -1):
                
                return(end)
            
            else:
                
                return(-1)
            
            

    

In [383]:
find_last_footnote_index_end(t, lower_bound = 2516, upper_bound = 2576)

-1

In [374]:
answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'
    
last_answer = re.search(answer_regex, t[2516:2576])

In [375]:
last_answer

<re.Match object; span=(0, 9), match='IA\n\n\n\n   '>

In [378]:
last_answer.end()

9

In [387]:
find_cover_pages_end(t, 'SC 13G', rep_q_as_items = False, lower_bound = 2516, upper_bound = 2576)

2525

In [379]:
t[2525:2576]

'CUSIP  902952100    SCHEDULE 13G        PAGE 3 OF 4'

In [389]:
get_key_indices('edgar/data/101507/0001051042-11-000006.txt', '0001051042-11-000006.txt', 'SC 13G', directory)

file_name                  document  \
0  edgar/data/101507/0001051042-11-000006.txt  0001051042-11-000006.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                        1598                 1716   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1660   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                2576                   2516            2525   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  3             5727                         -1

In [388]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['amendment_statement_start'] = find_amendment_statement_start(text, form_type, \
                    lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

In [360]:
answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'
    
last_answer = re.search(answer_regex, t[2516:2576])


In [361]:
last_answer

<re.Match object; span=(0, 9), match='IA\n\n\n\n   '>

In [358]:
t = get_main_doc_text('edgar/data/101507/0001051042-11-000006.txt', '0001051042-11-000006.txt', directory)

In [341]:
get_index_url('edgar/data/902219/0000902219-13-000427.txt')

'https://www.sec.gov/Archives/edgar/data/902219/000090221913000427/0000902219-13-000427-index.htm'

In [359]:
t[2501:]

'               IA\n\n\n\n   CUSIP  902952100    SCHEDULE 13G        PAGE 3 OF 4\n\n   ITEM 1 (A)    NAME OF ISSUER\n\n\t         U.S. GLOBAL INVESTORS FUND\n\n   ITEM 1 (B)    ADDRESS OF ISSUER\n\n \t         7900 CALLAGHAN RD.\n\t\t PO BOX 781234\n\t\t SAN ANTONIO, TX  78229\n\n\n   ITEM 2 (A)    NAME OF PERSON FILING\n\n                 FINANCIAL & INVESTMENT MANAGEMENT GROUP, LTD\n\n   ITEM 2 (B)    ADDRESS OF PERSON FILING\n\n                 111 CASS ST.\n                 TRAVERSE CITY, MI 49684\n\n   ITEM 2 (C)    CITIZENSHIP\n\n                 MICHIGAN\n\n   ITEM 2 (D)    TITLE OF CLASS OF SECURITIES\n\n                 CLASS A COMMON STOCK\n\n   ITEM 2 (E)    CUSIP NO.\n\n\t\t 902952100\n\n   ITEM 3        THIS STATEMENT IS BEING FILED BY AN INVESTMENT ADVISOR IN\n                 ACCORDANCE WITH RULE 13D-1(B)(1)(ii)(E).\n\n   CUSIP 902952100     SCHEDULE 13G           PAGE 4 OF 4\n\n   OWNERSHIP\n   ITEM 4 (A)    AMOUNT BENEFICIALLY OWNED\n\n                 881,700   * SEE 

In [282]:
t[2516:2525]

'IA\n\n\n\n   '

In [283]:
t[2525:]

'CUSIP  902952100    SCHEDULE 13G        PAGE 3 OF 4\n\n   ITEM 1 (A)    NAME OF ISSUER\n\n\t         U.S. GLOBAL INVESTORS FUND\n\n   ITEM 1 (B)    ADDRESS OF ISSUER\n\n \t         7900 CALLAGHAN RD.\n\t\t PO BOX 781234\n\t\t SAN ANTONIO, TX  78229\n\n\n   ITEM 2 (A)    NAME OF PERSON FILING\n\n                 FINANCIAL & INVESTMENT MANAGEMENT GROUP, LTD\n\n   ITEM 2 (B)    ADDRESS OF PERSON FILING\n\n                 111 CASS ST.\n                 TRAVERSE CITY, MI 49684\n\n   ITEM 2 (C)    CITIZENSHIP\n\n                 MICHIGAN\n\n   ITEM 2 (D)    TITLE OF CLASS OF SECURITIES\n\n                 CLASS A COMMON STOCK\n\n   ITEM 2 (E)    CUSIP NO.\n\n\t\t 902952100\n\n   ITEM 3        THIS STATEMENT IS BEING FILED BY AN INVESTMENT ADVISOR IN\n                 ACCORDANCE WITH RULE 13D-1(B)(1)(ii)(E).\n\n   CUSIP 902952100     SCHEDULE 13G           PAGE 4 OF 4\n\n   OWNERSHIP\n   ITEM 4 (A)    AMOUNT BENEFICIALLY OWNED\n\n                 881,700   * SEE NOTE 1 *\n\n   ITEM 4 (B)   

In [276]:
get_index_url('edgar/data/101507/0001051042-11-000006.txt')

'https://www.sec.gov/Archives/edgar/data/101507/000105104211000006/0001051042-11-000006-index.htm'

In [278]:
get_index_url(' edgar/data/1379593/0000909143-06-000105.txt')

'https://www.sec.gov/Archives/edgar/data/1379593/000090914306000105/0000909143-06-000105-index.htm'

In [255]:
t[2942:]

'\n\n\n**\nWestcliff Trust may be deemed to beneficially own 71.6% of the Issuer’s issued and outstanding Ordinary Shares, based upon 38,252,399 Ordinary Shares outstanding,\nwhich is the sum of (i) 10,870,275 Ordinary Shares issued and outstanding as reported by the Issuer on its Form 6-K, filed with the US Securities Exchange Commission (the “SEC”) on November 26, 2012, plus (ii) the 27,382,054 Ordinary\nShares that would be issuable to Westcliff Trust upon conversion of the Series\xa03 Notes. \n\n\n\n\n\n\n\n\n\n\n\n\n\nCUSIP No. Q62163110\n\xa0\xa0\n Page\n 3\n of 5 \xa0\n ITEM\xa01. SECURITY AND ISSUER. \nThis Statement of Beneficial Ownership on Schedule 13D (this “Statement”) relates to the Ordinary Shares of Mission NewEnergy\nLimited, an Australian corporation (the “Issuer”) and is being filed pursuant to Rule 13d-2 under the Securities Exchange Act of 1934, as amended (the “Exchange Act”). The address of the principal executive offices of the Issuer\nis Unit 2B, 431 Roberts R

In [235]:
t[3433:3486]

'\n\n\n\n\n\n\n\n\n\n\n\n\n\nCUSIP No. Q62163110\n\xa0\xa0\n Page\n 3\n of 5 \xa0'

In [220]:
re.search('\n\s*[\(\|]?\s*[*0-9a-z]+\s*[\)\|]?', t[2426:3486])

<re.Match object; span=(7, 15), match='\n \xa0\n\n\n*\n'>

In [210]:
get_index_url('edgar/data/1508554/0001193125-10-291892.txt')

'https://www.sec.gov/Archives/edgar/data/1508554/000119312510291892/0001193125-10-291892-index.htm'

In [38]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 4000).sum()

1672

In [39]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 10000).sum()

302

In [71]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 10000]

file_name                  document  \
35      edgar/data/911092/0000898431-06-000059.txt  0000898431-06-000059.txt   
71      edgar/data/882289/0000950148-97-002504.txt  0000950148-97-002504.txt   
141    edgar/data/1504459/0001144204-12-003504.txt  0001144204-12-003504.txt   
216     edgar/data/831529/0000914248-98-000092.txt  0000914248-98-000092.txt   
397      edgar/data/89041/0001019056-06-000408.txt  0001019056-06-000408.txt   
398      edgar/data/89041/0001019056-06-000414.txt  0001019056-06-000414.txt   
407    edgar/data/1140474/0001013594-06-000383.txt  0001013594-06-000383.txt   
423    edgar/data/1000742/0000921530-06-000260.txt  0000921530-06-000260.txt   
491    edgar/data/1008598/0001024739-98-000078.txt  0001024739-98-000078.txt   
495    edgar/data/1283843/0001193125-13-087742.txt  0001193125-13-087742.txt   
496     edgar/data/945532/0001024739-98-000243.txt  0001024739-98-000243.txt   
631      edgar/data/54883/0000903423-07-000209.txt  0000903423-07-000209.txt   
665    edgar/data/1467859/0001193125-13-087742.txt  0001193125-13-087742.txt   
711     edgar/data/901832/0001104659-12-031365.txt  0001104659-12-031365.txt   
730    edgar/data/1385075/0000950127-07-000020.txt  0000950127-07-000020.txt   
896    edgar/data/1362468/0000911420-06-000782.txt  0000911420-06-000782.txt   
904     edgar/data/835540/0000835540-06-000039.txt  0000835540-06-000039.txt   
918      edgar/data/70858/0000070858-06-000204.txt  0000070858-06-000204.txt   
923    edgar/data/1449433/0001104659-12-036479.txt  0001104659-12-036479.txt   
958    edgar/data/1103390/0001104659-12-031365.txt  0001104659-12-031365.txt   
1124   edgar/data/1569578/0001193125-13-098465.txt  0001193125-13-098465.txt   
1252   edgar/data/1445229/0001193125-13-098465.txt  0001193125-13-098465.txt   
1440   edgar/data/1100969/0001193125-13-219579.txt  0001193125-13-219579.txt   
1493   edgar/data/1449433/0001104659-13-048106.txt  0001104659-13-048106.txt   
1550   edgar/data/1427002/0000950123-11-019892.txt  0000950123-11-019892.txt   
1565   edgar/data/1104400/0000902561-06-000188.txt  0000902561-06-000188.txt   
1723    edgar/data/701347/0000950123-11-019892.txt  0000950123-11-019892.txt   
1748    edgar/data/814008/0000897204-00-000042.txt  0000897204-00-000042.txt   
1800   edgar/data/1479426/0001011438-11-000148.txt  0001011438-11-000148.txt   
1818   edgar/data/1534992/0000899681-12-000223.txt  0000899681-12-000223.txt   
...                                            ...                       ...   
16897  edgar/data/1176314/0000922423-07-000324.txt  0000922423-07-000324.txt   
16898   edgar/data/917857/0000950142-07-000063.txt  0000950142-07-000063.txt   
16911  edgar/data/1079482/0001079482-07-000004.txt  0001079482-07-000004.txt   
16936  edgar/data/1338289/0001338289-07-000003.txt  0001338289-07-000003.txt   
16955  edgar/data/1088787/0001140361-13-011683.txt  0001140361-13-011683.txt   
16968  edgar/data/1379378/0001061219-07-000005.txt  0001061219-07-000005.txt   
16969  edgar/data/1379378/0001079482-07-000004.txt  0001079482-07-000004.txt   
16970  edgar/data/1379378/0001228965-07-000001.txt  0001228965-07-000001.txt   
16971  edgar/data/1379378/0001324592-07-000004.txt  0001324592-07-000004.txt   
16972  edgar/data/1379378/0001324593-07-000001.txt  0001324593-07-000001.txt   
16973  edgar/data/1379378/0001338289-07-000003.txt  0001338289-07-000003.txt   
16974  edgar/data/1379378/0001390206-07-000001.txt  0001390206-07-000001.txt   
16975  edgar/data/1379378/0001102995-07-000001.txt  0001102995-07-000001.txt   
16998  edgar/data/1206133/0001493152-13-000486.txt  0001493152-13-000486.txt   
17013  edgar/data/1102995/0001102995-07-000001.txt  0001102995-07-000001.txt   
17014  edgar/data/1061219/0001061219-07-000005.txt  0001061219-07-000005.txt   
17018  edgar/data/1228965/0001228965-07-000001.txt  0001228965-07-000001.txt   
17019  edgar/data/1324593/0001324593-07-000001.txt  0001324593-07-000001.txt   
17039  edgar/data/1122860/0000950127-07-0

In [263]:
get_index_url('edgar/data/33619/0001167674-13-000101.txt')

'https://www.sec.gov/Archives/edgar/data/33619/000116767413000101/0001167674-13-000101-index.htm'

In [284]:

get_key_indices('edgar/data/33619/0001167674-13-000101.txt', '0001167674-13-000101.txt', \
                'SC 13G/A', directory)

file_name                  document  \
0  edgar/data/33619/0001167674-13-000101.txt  0001167674-13-000101.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1268                 1324   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1269   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0                2974                   2937            2974   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  2             9354                         -1

In [285]:
get_key_indices('edgar/data/1042441/0001104659-12-009966.txt', '0001104659-12-009966.txt', 'SC 13D/A', directory)

file_name                  document  \
0  edgar/data/1042441/0001104659-12-009966.txt  0001104659-12-009966.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13D/A                        1706                 1741   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              1706   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0               32151                  32095           32122   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                 21            36167                         -1

In [266]:
get_index_url('edgar/data/1042441/0001104659-12-009966.txt')

'https://www.sec.gov/Archives/edgar/data/1042441/000110465912009966/0001104659-12-009966-index.htm'

In [286]:
t = get_main_doc_text('edgar/data/1042441/0001104659-12-009966.txt', '0001104659-12-009966.txt', directory)

In [288]:
t[32095:32122]

'   IN       \n\n\n\n\n\n\n    \n\n\xa0\n'

In [74]:
get_index_url('edgar/data/1051470/0001193125-06-207740.txt')

'https://www.sec.gov/Archives/edgar/data/1051470/000119312506207740/0001193125-06-207740-index.htm'

In [75]:
get_index_url('edgar/data/1173514/0001193125-12-418696.txt')

'https://www.sec.gov/Archives/edgar/data/1173514/000119312512418696/0001193125-12-418696-index.htm'

In [271]:
def get_signatures_sec_start(text):
    
    text_lowered = text.lower()
    
    
    regex1 = 'the\s+following\s+certification\s+shall\s+be\s+included\s+if\s+the\s+statement\s+is\s+filed\s+' + \
             'pursuant to rule 13d-1\(b\)'
    
    regex2 = 'by\s+signing\s+below\s+i\s+certify\s+that,\s+to\s+the\s+best\s+of\s+my\s+knowledge'
    
    regex3 = '\n\s*(signature|signatures)\s*(\.)?\n'

    regex4 = 'after\s+reasonable\s+inquiry\s+'
    
    regex5 = '\n\s*each\s+of\s+the\s+undersigned\s+'
    
    regex6 = '\n\s*(date|dated)\:\s*'
    
    regex_list = [regex1, regex2, regex3, regex4, regex5, regex6]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_lowered)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        return(regex_search.start())
    
    else:
        return(None)

In [ ]:
Each of the undersigned hereby certifies after reasonable inquiry, that to the best of his/her knowledge and belief, the information set forth in this statement is true, complete and correct

In [79]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 1000).sum()

1757

In [80]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 500).sum()

3577

In [81]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 250).sum()

5923

In [82]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 100).sum()

8992

In [83]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 50).sum()

11590

In [84]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 20).sum()

13339

In [85]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 10).sum()

14245

In [86]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 5).sum()

14909

In [87]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 1).sum()

16318

In [88]:
sc_13d_df.shape[0]

17504

In [ ]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 100).sum()

In [90]:
sc_13d_df['cover_page_max_f_end'] = sc_13d_df.apply(lambda x: max(x['cover_page_last_q_end'], \
                                                                 x['cover_page_end']), axis = 1)

In [91]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 5000]

file_name                  document  \
725    edgar/data/1384652/0001384652-07-000005.txt  0001384652-07-000005.txt   
906    edgar/data/1142512/0001193125-13-129336.txt  0001193125-13-129336.txt   
952    edgar/data/1464420/0001019687-13-000810.txt  0001019687-13-000810.txt   
1359   edgar/data/1003565/0001193125-06-241009.txt  0001193125-06-241009.txt   
1440   edgar/data/1100969/0001193125-13-219579.txt  0001193125-13-219579.txt   
1454   edgar/data/1490054/0001078782-13-001074.txt  0001078782-13-001074.txt   
1538    edgar/data/823277/0000950137-06-014005.txt  0000950137-06-014005.txt   
1705    edgar/data/865911/0001193125-11-024491.txt  0001193125-11-024491.txt   
1747   edgar/data/1475233/0001086380-11-000001.txt  0001086380-11-000001.txt   
1848   edgar/data/1051470/0001193125-06-207740.txt  0001193125-06-207740.txt   
1922    edgar/data/932699/0001193125-12-225741.txt  0001193125-12-225741.txt   
1977   edgar/data/1568233/0001193125-13-153036.txt  0001193125-13-153036.txt   
2012   edgar/data/1071993/0001193125-13-210743.txt  0001193125-13-210743.txt   
2224   edgar/data/1357475/0001085037-06-002066.txt  0001085037-06-002066.txt   
2283    edgar/data/813779/0001193125-13-210743.txt  0001193125-13-210743.txt   
2322   edgar/data/1349532/0001085037-06-002471.txt  0001085037-06-002471.txt   
2359   edgar/data/1381239/0001085037-06-002259.txt  0001085037-06-002259.txt   
2561   edgar/data/1278382/0001193125-06-207740.txt  0001193125-06-207740.txt   
2614   edgar/data/1381863/0001193125-06-241009.txt  0001193125-06-241009.txt   
2857   edgar/data/1444275/0001554795-13-000108.txt  0001554795-13-000108.txt   
2858   edgar/data/1444275/0001554795-13-000110.txt  0001554795-13-000110.txt   
2904    edgar/data/922011/0001019687-13-000810.txt  0001019687-13-000810.txt   
2997   edgar/data/1315373/0001085037-06-002066.txt  0001085037-06-002066.txt   
3233   edgar/data/1364139/0001085037-07-000588.txt  0001085037-07-000588.txt   
3403    edgar/data/916076/0001193125-06-250398.txt  0001193125-06-250398.txt   
3664    edgar/data/797564/0001376189-07-000002.txt  0001376189-07-000002.txt   
3679   edgar/data/1134725/0001193125-13-219579.txt  0001193125-13-219579.txt   
3765   edgar/data/1337013/0001193125-11-332064.txt  0001193125-11-332064.txt   
3796     edgar/data/67347/0001193125-06-228844.txt  0001193125-06-228844.txt   
3818   edgar/data/1577554/0001078782-13-001074.txt  0001078782-13-001074.txt   
...                                            ...                       ...   
14753  edgar/data/1173514/0001193125-12-418701.txt  0001193125-12-418701.txt   
14773  edgar/data/1403853/0001193125-12-497096.txt  0001193125-12-497096.txt   
14780  edgar/data/1565239/0001193125-12-516456.txt  0001193125-12-516456.txt   
14808  edgar/data/1563359/0001193125-12-497096.txt  0001193125-12-497096.txt   
15052  edgar/data/1558768/0001004878-12-000336.txt  0001004878-12-000336.txt   
15071   edgar/data/904532/0001193125-12-418696.txt  0001193125-12-418696.txt   
15072   edgar/data/904532/0001193125-12-418698.txt  0001193125-12-418698.txt   
15073   edgar/data/904532/0001193125-12-418701.txt  0001193125-12-418701.txt   
15270  edgar/data/1529938/0001193125-11-258712.txt  0001193125-11-258712.txt   
15476  edgar/data/1535880/0001193125-11-332064.txt  0001193125-11-332064.txt   
15503  edgar/data/1508348/0001004878-14-000166.txt  0001004878-14-000166.txt   
15565   edgar/data/874841/0001193125-11-344093.txt  0001193125-11-344093.txt   
15615  edgar/data/1537371/0001193125-11-344093.txt  0001193125-11-344093.txt   
15820  edgar/data/1524064/0001193125-12-422065.txt  0001193125-12-422065.txt   
16540  edgar/data/1620928/0001193125-14-452955.txt  0001193125-14-452955.txt   
16606  edgar/data/1599921/0001004878-14-000166.txt  0001004878-14-000166.txt   
16782  edgar/data/1393405/0001085037-07-000588.txt  0001085037-07-000588.txt   
16802  edgar/data/1397107/0001085037-07-000885.txt  0001085037-07-000885.txt   
16896  edgar/data/1167025/0001085037-07-0

In [92]:
(sc_13d_df['cover_page_max_f_end'] == -1).sum()

0

In [ ]:
process_batch_alt(df, directory, engine, num_cores = 12)

In [93]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_max_f_end'] > 5000]

file_name                  document  \
725    edgar/data/1384652/0001384652-07-000005.txt  0001384652-07-000005.txt   
906    edgar/data/1142512/0001193125-13-129336.txt  0001193125-13-129336.txt   
952    edgar/data/1464420/0001019687-13-000810.txt  0001019687-13-000810.txt   
1359   edgar/data/1003565/0001193125-06-241009.txt  0001193125-06-241009.txt   
1440   edgar/data/1100969/0001193125-13-219579.txt  0001193125-13-219579.txt   
1454   edgar/data/1490054/0001078782-13-001074.txt  0001078782-13-001074.txt   
1538    edgar/data/823277/0000950137-06-014005.txt  0000950137-06-014005.txt   
1705    edgar/data/865911/0001193125-11-024491.txt  0001193125-11-024491.txt   
1747   edgar/data/1475233/0001086380-11-000001.txt  0001086380-11-000001.txt   
1848   edgar/data/1051470/0001193125-06-207740.txt  0001193125-06-207740.txt   
1977   edgar/data/1568233/0001193125-13-153036.txt  0001193125-13-153036.txt   
2012   edgar/data/1071993/0001193125-13-210743.txt  0001193125-13-210743.txt   
2224   edgar/data/1357475/0001085037-06-002066.txt  0001085037-06-002066.txt   
2283    edgar/data/813779/0001193125-13-210743.txt  0001193125-13-210743.txt   
2322   edgar/data/1349532/0001085037-06-002471.txt  0001085037-06-002471.txt   
2359   edgar/data/1381239/0001085037-06-002259.txt  0001085037-06-002259.txt   
2561   edgar/data/1278382/0001193125-06-207740.txt  0001193125-06-207740.txt   
2614   edgar/data/1381863/0001193125-06-241009.txt  0001193125-06-241009.txt   
2857   edgar/data/1444275/0001554795-13-000108.txt  0001554795-13-000108.txt   
2858   edgar/data/1444275/0001554795-13-000110.txt  0001554795-13-000110.txt   
2904    edgar/data/922011/0001019687-13-000810.txt  0001019687-13-000810.txt   
2997   edgar/data/1315373/0001085037-06-002066.txt  0001085037-06-002066.txt   
3233   edgar/data/1364139/0001085037-07-000588.txt  0001085037-07-000588.txt   
3403    edgar/data/916076/0001193125-06-250398.txt  0001193125-06-250398.txt   
3664    edgar/data/797564/0001376189-07-000002.txt  0001376189-07-000002.txt   
3679   edgar/data/1134725/0001193125-13-219579.txt  0001193125-13-219579.txt   
3765   edgar/data/1337013/0001193125-11-332064.txt  0001193125-11-332064.txt   
3796     edgar/data/67347/0001193125-06-228844.txt  0001193125-06-228844.txt   
3818   edgar/data/1577554/0001078782-13-001074.txt  0001078782-13-001074.txt   
3916    edgar/data/722051/0000722051-06-000202.txt  0000722051-06-000202.txt   
...                                            ...                       ...   
14750  edgar/data/1173514/0001193125-12-418696.txt  0001193125-12-418696.txt   
14752  edgar/data/1173514/0001193125-12-418698.txt  0001193125-12-418698.txt   
14753  edgar/data/1173514/0001193125-12-418701.txt  0001193125-12-418701.txt   
14773  edgar/data/1403853/0001193125-12-497096.txt  0001193125-12-497096.txt   
14780  edgar/data/1565239/0001193125-12-516456.txt  0001193125-12-516456.txt   
14808  edgar/data/1563359/0001193125-12-497096.txt  0001193125-12-497096.txt   
15052  edgar/data/1558768/0001004878-12-000336.txt  0001004878-12-000336.txt   
15071   edgar/data/904532/0001193125-12-418696.txt  0001193125-12-418696.txt   
15072   edgar/data/904532/0001193125-12-418698.txt  0001193125-12-418698.txt   
15073   edgar/data/904532/0001193125-12-418701.txt  0001193125-12-418701.txt   
15270  edgar/data/1529938/0001193125-11-258712.txt  0001193125-11-258712.txt   
15476  edgar/data/1535880/0001193125-11-332064.txt  0001193125-11-332064.txt   
15503  edgar/data/1508348/0001004878-14-000166.txt  0001004878-14-000166.txt   
15820  edgar/data/1524064/0001193125-12-422065.txt  0001193125-12-422065.txt   
16540  edgar/data/1620928/0001193125-14-452955.txt  0001193125-14-452955.txt   
16606  edgar/data/1599921/0001004878-14-000166.txt  0001004878-14-000166.txt   
16782  edgar/data/1393405/0001085037-07-000588.txt  0001085037-07-000588.txt   
16802  edgar/data/1397107/0001085037-07-000885.txt  0001085037-07-000885.txt   
16896  edgar/data/1167025/0001085037-07-0

In [96]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_max_f_end'] > 15000]

file_name                  document  \
3916    edgar/data/722051/0000722051-06-000202.txt  0000722051-06-000202.txt   
4193    edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   
4625   edgar/data/1041450/0000722051-06-000202.txt  0000722051-06-000202.txt   
4685   edgar/data/1064122/0000950133-06-005429.txt  0000950133-06-005429.txt   
5161    edgar/data/709878/0000950157-06-001062.txt  0000950157-06-001062.txt   
5333   edgar/data/1185854/0000950133-06-005429.txt  0000950133-06-005429.txt   
14750  edgar/data/1173514/0001193125-12-418696.txt  0001193125-12-418696.txt   
14773  edgar/data/1403853/0001193125-12-497096.txt  0001193125-12-497096.txt   
14808  edgar/data/1563359/0001193125-12-497096.txt  0001193125-12-497096.txt   
15071   edgar/data/904532/0001193125-12-418696.txt  0001193125-12-418696.txt   

      form_type  title_page_end_lower_bound  cover_page_q1_start  \
3916     SC 13D                      2484.0               2556.0   
4193     SC 13D                      2466.0               2806.0   
4625     SC 13D                      2484.0               2556.0   
4685     SC 13D                      1862.0               2169.0   
5161     SC 13D                      2466.0               2806.0   
5333     SC 13D                      1862.0               2169.0   
14750    SC 13D                      1758.0               1866.0   
14773    SC 13D                      1716.0               1751.0   
14808    SC 13D                      1716.0               1751.0   
15071    SC 13D                      1758.0               1866.0   

      is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
3916              False                   2.0            2534.0   
4193              False                   2.0            2466.0   
4625              False                   2.0            2534.0   
4685              False                   2.0            2078.0   
5161              False                   2.0            2466.0   
5333              False                   2.0            2078.0   
14750             False                   3.0            1793.0   
14773             False                   2.0            1719.0   
14808             False                   2.0            1719.0   
15071             False                   3.0            1793.0   

       item_section_start  cover_page_last_q_end  cover_page_end  \
3916              26547.0                 4749.0          4758.0   
4193              65952.0                 4295.0          4320.0   
4625              26547.0                 4749.0          4758.0   
4685              22240.0                 6493.0          6534.0   
5161              65952.0                 4295.0          4320.0   
5333              22240.0                 6493.0          6534.0   
14750             96214.0                75978.0         75998.0   
14773             18808.0                 2739.0          3181.0   
14808             18808.0                 2739.0          3181.0   
15071             96214.0                75978.0         75998.0   

       num_cusip_b_items  signature_start  amendment_statement_start  success  \
3916                 9.0          38103.0                       -1.0     True   
4193                 8.0          75126.0                       -1.0     True   
4625                 9.0          38103.0                       -1.0     True   
4685                 6.0          52561.0                       -1.0     True   
5161                 8.0          75126.0                       -1.0     True   
5333                 6.0          52561.0                       -1.0     True   
14750               81.0         136777.0                       -1.0     True   
14773                3.0          23179.0                       -1.0     True   
14808                3.0          23179.0                       -1.0     True   
15071               81.0         136777.0                       -1.0     True   

       cover_page_max_f_end  
39

In [95]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_max_f_end'] > 25000]

file_name                  document  \
4193  edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   
5161  edgar/data/709878/0000950157-06-001062.txt  0000950157-06-001062.txt   

     form_type  title_page_end_lower_bound  cover_page_q1_start  \
4193    SC 13D                      2466.0               2806.0   
5161    SC 13D                      2466.0               2806.0   

     is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
4193             False                   2.0            2466.0   
5161             False                   2.0            2466.0   

      item_section_start  cover_page_last_q_end  cover_page_end  \
4193             65952.0                 4295.0          4320.0   
5161             65952.0                 4295.0          4320.0   

      num_cusip_b_items  signature_start  amendment_statement_start  success  \
4193                8.0          75126.0                       -1.0     True   
5161                8.0          75126.0                       -1.0     True   

      cover_page_max_f_end  
4193                4320.0  
5161                4320.0

In [94]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_max_f_end'] > 50000]

file_name                  document  \
4193  edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   
5161  edgar/data/709878/0000950157-06-001062.txt  0000950157-06-001062.txt   

     form_type  title_page_end_lower_bound  cover_page_q1_start  \
4193    SC 13D                      2466.0               2806.0   
5161    SC 13D                      2466.0               2806.0   

     is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
4193             False                   2.0            2466.0   
5161             False                   2.0            2466.0   

      item_section_start  cover_page_last_q_end  cover_page_end  \
4193             65952.0                 4295.0          4320.0   
5161             65952.0                 4295.0          4320.0   

      num_cusip_b_items  signature_start  amendment_statement_start  success  \
4193                8.0          75126.0                       -1.0     True   
5161                8.0          75126.0                       -1.0     True   

      cover_page_max_f_end  
4193                4320.0  
5161                4320.0

In [182]:
i = 4193
get_key_indices(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], \
                sc_13d_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        3729                 4228   

   is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
0              False                     2              3729   

   item_section_start  cover_page_last_q_end  cover_page_end  \
0               12195                  11648           11699   

   num_cusip_b_items  signature_start  amendment_statement_start  
0                  4            34410                         -1

In [185]:
t = get_main_doc_text(sc_13d_df.loc[i, 'file_name'], sc_13d_df.loc[i, 'document'], directory)
t[11648:34410]

'\n               \n              IN,\n                HC\n            \n          \n\n      \n    \n    \n    \n      \n        \n        \n      \n      \n        \n        \n        \n          \n        \n      \n      \n        \n        \n        CUSIP\n          No.\n          913377107                                                                                                                                                                                                                                                             Page 4\n          of 20 Pages\n      \n    \n    ITEM\n      1.    SECURITY\n      AND ISSUER\n     \n    The\n      title\n      of the class of equity security to which this statement on Schedule 13D relates\n      is the common stock, par value $.01 per share (the “Shares”), of Universal\n      American Financial Corp., a New York corporation (the “Issuer”). The address of\n      the Issuer’s principal executive offices is Six International Drive

In [187]:
t[12195:34410]

'\n      \n    \n    ITEM\n      1.    SECURITY\n      AND ISSUER\n     \n    The\n      title\n      of the class of equity security to which this statement on Schedule 13D relates\n      is the common stock, par value $.01 per share (the “Shares”), of Universal\n      American Financial Corp., a New York corporation (the “Issuer”). The address of\n      the Issuer’s principal executive offices is Six International Drive, Suite 190,\n      Rye Brook, NY 10573.\n     \n    The\n      Reporting Persons may no longer be deemed to hold the Shares in the ordinary\n      course of business and not with the purpose or with the effect of changing\n      or\n      influencing the control of the Issuer, or in connection with or as a participant\n      in any transaction having such purpose or effect. Prior to the event date,\n      the\n      Reporting Persons relied on Rule 13d-1(b)(1) under the Act with respect to\n      the\n      reporting of their ownership of the Shares.\n     \n    ITEM\

In [193]:
get_index_url('edgar/data/101507/0001051042-11-000006.txt')

'https://www.sec.gov/Archives/edgar/data/101507/000105104211000006/0001051042-11-000006-index.htm'

In [188]:
t[34410:]

'\n      \n    \n     \n     \n    SIGNATURE\n     \n    After\n      reasonable inquiry and to the best of my knowledge and belief, the undersigned\n      certifies that the information set forth in this statement is true, complete\n      and\n      correct.\n     \n    \n      \n\n          \n             \n             \n             \n          \n          \n             Dated: \n              October 25, 2006\n            PERRY\n              CORP.\n          \n          \n              \n             \n             \n          \n          \n             \n            By:  \n            /s/ \n              Richard C. Perry\n          \n          \n             \n            \n              Name:\n              Richard C. Perry\n          \n          \n             \n            Title:   \n              President\n          \n\n      \n    \n     \n    \n      \n        \n\n            \n               \n               \n               \n            \n            \n               D

In [186]:
t[3729:12195]

'\n            \n          \n\n      \n    \n    \n    \n    \n    \n    \n      \n        \n        \n      \n      \n        \n        \n        \n          \n        \n      \n      \n        \n        \n        CUSIP\n          No.\n          913377107                                                                                                                                                                                                                                                           \n Page 2 of 20 Pages\n      \n    \n    \n      \n        \n\n            \n              \n                1.\n              \n              \n                Names\n                  of Reporting Persons.\n                I.R.S.\n                  Identification Nos. of above persons (entities only).\n                 \n                Perry\n                  Corp.\n              \n            \n            \n              \n                2.\n              \n              \n        

In [108]:
get_main_doc_text(sc_13d_df.loc[4193, 'file_name'], sc_13d_df.loc[4193, 'document'], directory)

'\nSC 13D\n1\nsc13d.htm\nSCHEDULE 13D\n\n\n  \n    \n      Schedule 13D\n\n\n\n\n\n\n  \n    \n    \n      \n        \n      \n    \n    \n      \n\n          \n            \n              UNITED\n                STATES\n              SECURITIES\n                AND EXCHANGE COMMISSION\n              Washington,\n                D.C. 20549\n              \n            \n          \n          \n            \n              SCHEDULE\n                13D\n            \n          \n          \n            \n              Under\n                the Securities Exchange Act of 1934\n            \n          \n          \n            \n          \n          \n            \n              UNIVERSAL\n                AMERICAN FINANCIAL CORP.\n            \n          \n          \n            \n              (Name\n                of Issuer)\n              \n            \n          \n          \n            \n              Common\n                Stock (par value $.01 per share)\n            \n      

In [100]:
get_file_text_from_directory(sc_13d_df.loc[4193, 'file_name'], sc_13d_df.loc[4193, 'document'], directory)

'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n Qur5OiBiKW8t3RxGQ8jEryljWwQOFRjbs5OuzYL4Qz7hw5aGWnGh+hsLHPoeBT5/\n DCam4jVdwJxkvHIma4vAgA==\n\n<SEC-DOCUMENT>0000950157-06-001062.txt : 20061025\n<SEC-HEADER>0000950157-06-001062.hdr.sgml : 20061025\n<ACCEPTANCE-DATETIME>20061025143729\nACCESSION NUMBER:\t\t0000950157-06-001062\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20061025\nDATE AS OF CHANGE:\t\t20061025\nGROUP MEMBERS:\t\tRICHARD C. PERRY\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tUNIVERSAL AMERICAN FINANCIAL CORP\n\t\tCENTRAL INDEX KEY:\t\t\t0000709878\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tLIFE INSURANCE [6311]\n\t\tIRS NUMBER:\t\t\t\t112580136\n\t\tSTATE OF INCOR

In [73]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_last_q_end'] > 10000]

file_name                  document  \
1440   edgar/data/1100969/0001193125-13-219579.txt  0001193125-13-219579.txt   
1848   edgar/data/1051470/0001193125-06-207740.txt  0001193125-06-207740.txt   
2561   edgar/data/1278382/0001193125-06-207740.txt  0001193125-06-207740.txt   
3679   edgar/data/1134725/0001193125-13-219579.txt  0001193125-13-219579.txt   
3916    edgar/data/722051/0000722051-06-000202.txt  0000722051-06-000202.txt   
4193    edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   
4625   edgar/data/1041450/0000722051-06-000202.txt  0000722051-06-000202.txt   
4685   edgar/data/1064122/0000950133-06-005429.txt  0000950133-06-005429.txt   
5161    edgar/data/709878/0000950157-06-001062.txt  0000950157-06-001062.txt   
5333   edgar/data/1185854/0000950133-06-005429.txt  0000950133-06-005429.txt   
14750  edgar/data/1173514/0001193125-12-418696.txt  0001193125-12-418696.txt   
14773  edgar/data/1403853/0001193125-12-497096.txt  0001193125-12-497096.txt   
14808  edgar/data/1563359/0001193125-12-497096.txt  0001193125-12-497096.txt   
15071   edgar/data/904532/0001193125-12-418696.txt  0001193125-12-418696.txt   

      form_type  title_page_end_lower_bound  cover_page_q1_start  \
1440     SC 13D                      2374.0               2419.0   
1848     SC 13D                      1698.0               1761.0   
2561     SC 13D                      1698.0               1761.0   
3679     SC 13D                      2374.0               2419.0   
3916     SC 13D                      2484.0               2556.0   
4193     SC 13D                      2466.0               2806.0   
4625     SC 13D                      2484.0               2556.0   
4685     SC 13D                      1862.0               2169.0   
5161     SC 13D                      2466.0               2806.0   
5333     SC 13D                      1862.0               2169.0   
14750    SC 13D                      1758.0               1866.0   
14773    SC 13D                      1716.0               1751.0   
14808    SC 13D                      1716.0               1751.0   
15071    SC 13D                      1758.0               1866.0   

      is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
1440              False                   2.0            2396.0   
1848              False                   2.0            1716.0   
2561              False                   2.0            1716.0   
3679              False                   2.0            2396.0   
3916              False                   2.0            2534.0   
4193              False                   2.0            2466.0   
4625              False                   2.0            2534.0   
4685              False                   2.0            2078.0   
5161              False                   2.0            2466.0   
5333              False                   2.0            2078.0   
14750             False                   3.0            1793.0   
14773             False                   2.0            1719.0   
14808             False                   2.0            1719.0   
15071             False                   3.0            1793.0   

       item_section_start  cover_page_last_q_end  cover_page_end  \
1440              27349.0                15618.0         15629.0   
1848              14003.0                 2942.0          6692.0   
2561              14003.0                 2942.0          6692.0   
3679              27349.0                15618.0         15629.0   
3916              26547.0                 4749.0          4758.0   
4193              65952.0                 4295.0          4320.0   
4625              26547.0                 4749.0          4758.0   
4685              22240.0                 6493.0          6534.0   
5161              65952.0                 4295.0          4320.0   
5333              22240.0                 6493.0          6534.0   
14750             96214.0                75978.0         75998.0 

In [72]:
t = get_main_doc_text('edgar/data/1100969/0001193125-13-219579.txt', '0001193125-13-219579.txt', directory)
t[15629:27349]

'(1)\nIncludes 104,904 shares of Common Stock of the Company and 131,250 shares issuable upon the exercise of vested options. \n\n\n(2)\nMr.\xa0Zhang is a party to certain agreements described in Item\xa03 and Item\xa04 below, which agreements contain, among other things, voting agreements and\nlimitations on the sale of Common Stock of the Company owned by the Reporting Persons and the Other Voting Shareholders. As a result, Mr.\xa0Zhang may be deemed to be a member of a “group,” within the meaning of Section\xa013(d)(3)\nof the Act. Shares of Common Stock listed as beneficially owned by Mr.\xa0Zhang exclude those held by the Other Voting Shareholders and the Reporting Persons other than Mr.\xa0Zhang, in each case as to which Mr.\xa0Zhang expressly disclaims\nbeneficial ownership. \n\n\n(3)\nPercentage calculated based on 72,925,679 shares of Common Stock, including 72,794,429 shares outstanding as of May\xa09, 2013 (as provided by the Company) and\n131,250 shares issuable upon the ex

In [40]:
(sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 50000).sum()

5

In [41]:
sc_13d_df.loc[sc_13d_df['item_section_start'] - sc_13d_df['cover_page_end'] > 50000]

file_name                  document  \
2891   edgar/data/1179822/0001144204-06-053486.txt  0001144204-06-053486.txt   
3625    edgar/data/745448/0001144204-06-053486.txt  0001144204-06-053486.txt   
4193    edgar/data/919085/0000950157-06-001062.txt  0000950157-06-001062.txt   
5161    edgar/data/709878/0000950157-06-001062.txt  0000950157-06-001062.txt   
16998  edgar/data/1206133/0001493152-13-000486.txt  0001493152-13-000486.txt   

      form_type  title_page_end_lower_bound  cover_page_q1_start  \
2891     SC 13D                      2105.0               2388.0   
3625     SC 13D                      2105.0               2388.0   
4193     SC 13D                      2466.0               2806.0   
5161     SC 13D                      2466.0               2806.0   
16998    SC 13D                      1654.0               1654.0   

      is_rep_q_as_items  num_cusip_sedol_b_q1  cover_page_start  \
2891              False                   2.0            2282.0   
3625              False                   2.0            2282.0   
4193              False                   2.0            2466.0   
5161              False                   2.0            2466.0   
16998             False                   1.0            1654.0   

       item_section_start  cover_page_last_q_end  cover_page_end  \
2891              87276.0                86217.0            -1.0   
3625              87276.0                86217.0            -1.0   
4193              65952.0                 4295.0          4320.0   
5161              65952.0                 4295.0          4320.0   
16998             53439.0                53437.0            -1.0   

       num_cusip_b_items  signature_start  amendment_statement_start  success  
2891                23.0         126668.0                       -1.0     True  
3625                23.0         126668.0                       -1.0     True  
4193                 8.0          75126.0                       -1.0     True  
5161                 8.0          75126.0                       -1.0     True  
16998                1.0          61678.0                       -1.0     True

In [42]:
get_index_url('edgar/data/919085/0000950157-06-001062.txt')

'https://www.sec.gov/Archives/edgar/data/919085/000095015706001062/0000950157-06-001062-index.htm'

In [43]:
directory = '/media/igow/6TB/data/edgar'

In [54]:
full_text = get_file_text_from_directory('edgar/data/709878/0000950157-06-001062.txt', '0000950157-06-001062.txt', directory)

In [67]:
soup = BeautifulSoup(full_text, 'html5lib')

In [68]:
soup.find(["document", "DOCUMENT"])

<document>
<type>SC 13D
<sequence>1
<filename>sc13d.htm
<description>SCHEDULE 13D
<text>

  
    <title>
      Schedule 13D
</title>
<!-- Licensed to: Cravath Swaine & Moore LLP-->
<!-- Document Created using EDGARizer HTML 3.0.4.0 -->
<!-- Copyright 2006 EDGARfilings, Ltd., an IEC company.-->
<!-- All rights reserved EDGARfilings.com -->

  
    <div> </div>
    <div>
      <div>
        <hr align="left" noshade="" size="2" style="COLOR: black" width="100%"/>
      </div>
    </div>
    <div>
      <table cellpadding="0" cellspacing="0" width="100%">

          <tbody><tr>
            <td colspan="3" valign="top" width="77%">
              <div align="center" style="DISPLAY: block; MARGIN-LEFT: 0pt; TEXT-INDENT: 0pt; LINE-HEIGHT: 1.25; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-WEIGHT: bold; FONT-SIZE: 12pt; COLOR: #000000; FONT-FAMILY: Times New Roman"><strong>UNITED
                STATES</strong></font></div>
              <div align="center" style="DISPLAY: block; MARGI

In [69]:
print(soup.find(["document", "DOCUMENT"]).get_text())


SC 13D
1
sc13d.htm
SCHEDULE 13D


  
    
      Schedule 13D






  
     
    
      
        
      
    
    
      

          
            
              UNITED
                STATES
              SECURITIES
                AND EXCHANGE COMMISSION
              Washington,
                D.C. 20549
               
            
          
          
            
              SCHEDULE
                13D
            
          
          
            
              Under
                the Securities Exchange Act of 1934
            
          
          
             
          
          
            
              UNIVERSAL
                AMERICAN FINANCIAL CORP.
            
          
          
            
              (Name
                of Issuer)
               
            
          
          
            
              Common
                Stock (par value $.01 per share)
            
             
            
              913377107
            
         

In [63]:
soup

<html><body><p>-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 Qur5OiBiKW8t3RxGQ8jEryljWwQOFRjbs5OuzYL4Qz7hw5aGWnGh+hsLHPoeBT5/
 DCam4jVdwJxkvHIma4vAgA==

<sec-document>0000950157-06-001062.txt : 20061025
<sec-header>0000950157-06-001062.hdr.sgml : 20061025
<acceptance-datetime>20061025143729
ACCESSION NUMBER:		0000950157-06-001062
CONFORMED SUBMISSION TYPE:	SC 13D
PUBLIC DOCUMENT COUNT:		2
FILED AS OF DATE:		20061025
DATE AS OF CHANGE:		20061025
GROUP MEMBERS:		RICHARD C. PERRY

SUBJECT COMPANY:	

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			UNIVERSAL AMERICAN FINANCIAL CORP
		CENTRAL INDEX KEY:			0000709878
		STANDARD INDUSTRIAL CLASSIFICATION:	LIFE INSURANCE [6311]
		IRS NUMBER:				112580136
		STATE OF INCORPORATION:			NY
		FISCAL YEAR END:			1231

	FILIN

In [57]:
soup.find(["document", "DOCUMENT"])

<document>
<type>SC 13D
<sequence>1
<filename>sc13d.htm
<description>SCHEDULE 13D
<text>
<html>
<head>
<title>
      Schedule 13D
</title>
<!-- Licensed to: Cravath Swaine & Moore LLP-->
<!-- Document Created using EDGARizer HTML 3.0.4.0 -->
<!-- Copyright 2006 EDGARfilings, Ltd., an IEC company.-->
<!-- All rights reserved EDGARfilings.com -->
</head>
<body bgcolor="#ffffff">
<div> </div>
<div>
<div>
<hr align="left" noshade="" size="2" style="COLOR: black" width="100%"/>
</div>
</div>
<div>
<table cellpadding="0" cellspacing="0" width="100%">
<tr>
<td colspan="3" valign="top" width="77%">
<div align="center" style="DISPLAY: block; MARGIN-LEFT: 0pt; TEXT-INDENT: 0pt; LINE-HEIGHT: 1.25; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-WEIGHT: bold; FONT-SIZE: 12pt; COLOR: #000000; FONT-FAMILY: Times New Roman"><strong>UNITED
                STATES</strong></font></div>
<div align="center" style="DISPLAY: block; MARGIN-LEFT: 0pt; TEXT-INDENT: 0pt; LINE-HEIGHT: 1.25; MARGIN-RIGHT: 0

In [59]:
soup.get_text()

'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n Qur5OiBiKW8t3RxGQ8jEryljWwQOFRjbs5OuzYL4Qz7hw5aGWnGh+hsLHPoeBT5/\n DCam4jVdwJxkvHIma4vAgA==\n\n0000950157-06-001062.txt : 20061025\n0000950157-06-001062.hdr.sgml : 20061025\n20061025143729\nACCESSION NUMBER:\t\t0000950157-06-001062\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20061025\nDATE AS OF CHANGE:\t\t20061025\nGROUP MEMBERS:\t\tRICHARD C. PERRY\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tUNIVERSAL AMERICAN FINANCIAL CORP\n\t\tCENTRAL INDEX KEY:\t\t\t0000709878\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tLIFE INSURANCE [6311]\n\t\tIRS NUMBER:\t\t\t\t112580136\n\t\tSTATE OF INCORPORATION:\t\t\tNY\n\t\tFISCAL YEAR END:\t\t\t12

In [46]:
t = get_main_doc_text('edgar/data/709878/0000950157-06-001062.txt', '0000950157-06-001062.txt', directory)
t[4320:65952]

'CO\n\n\n\n\n\n\xa0\n\xa0\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nCUSIP\n          No.\n          913377107\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0&#\n160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#160;&#16

In [107]:
def get_main_doc_text(file_name, document, directory):
  
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    soup = BeautifulSoup(full_text, 'html5lib')
    main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
    
    return(main_doc_text)

In [148]:
def clean_text(text):
    
    # this function gets rid of unwanted characters and spaces
    
    result = text
    
    char_list = ['\xa0', '&#160;', '&#\n160;']
    
    for c in char_list:
        
        result = re.sub(c, ' ', result) 
        
    return(result)

In [149]:
get_main_doc_text(sc_13d_df.loc[4193, 'file_name'], sc_13d_df.loc[4193, 'document'], directory)

'\nSC 13D\n1\nsc13d.htm\nSCHEDULE 13D\n\n\n  \n    \n      Schedule 13D\n\n\n\n\n\n\n  \n     \n    \n      \n        \n      \n    \n    \n      \n\n          \n            \n              UNITED\n                STATES\n              SECURITIES\n                AND EXCHANGE COMMISSION\n              Washington,\n                D.C. 20549\n               \n            \n          \n          \n            \n              SCHEDULE\n                13D\n            \n          \n          \n            \n              Under\n                the Securities Exchange Act of 1934\n            \n          \n          \n             \n          \n          \n            \n              UNIVERSAL\n                AMERICAN FINANCIAL CORP.\n            \n          \n          \n            \n              (Name\n                of Issuer)\n               \n            \n          \n          \n            \n              Common\n                Stock (par value $.01 per share)\n            \n  

In [150]:
print(get_main_doc_text(sc_13d_df.loc[4193, 'file_name'], sc_13d_df.loc[4193, 'document'], directory))


SC 13D
1
sc13d.htm
SCHEDULE 13D


  
    
      Schedule 13D






  
     
    
      
        
      
    
    
      

          
            
              UNITED
                STATES
              SECURITIES
                AND EXCHANGE COMMISSION
              Washington,
                D.C. 20549
               
            
          
          
            
              SCHEDULE
                13D
            
          
          
            
              Under
                the Securities Exchange Act of 1934
            
          
          
             
          
          
            
              UNIVERSAL
                AMERICAN FINANCIAL CORP.
            
          
          
            
              (Name
                of Issuer)
               
            
          
          
            
              Common
                Stock (par value $.01 per share)
            
             
            
              913377107
            
         

In [127]:
re.sub('\n{1}')

'a\nc'

In [47]:
t

'\nSC 13D\n1\nsc13d.htm\nSCHEDULE 13D\n\n\n\n\n      Schedule 13D\n\n\n\n\n\n\n\n\xa0\n\n\n\n\n\n\n\n\n\nUNITED\n                STATES\nSECURITIES\n                AND EXCHANGE COMMISSION\nWashington,\n                D.C. 20549\n\xa0\n\n\n\n\nSCHEDULE\n                13D\n\n\n\n\nUnder\n                the Securities Exchange Act of 1934\n\n\n\n\xa0\n\n\n\nUNIVERSAL\n                AMERICAN FINANCIAL CORP.\n\n\n\n\n(Name\n                of Issuer)\n\xa0\n\n\n\n\nCommon\n                Stock (par value $.01 per share)\n\n\xa0\n\n913377107\n\n\n\n\n(Title\n                of class of securities)\n\n\xa0\n\n(CUSIP\n                number)\n\n\n\n\nMichael\n                C. Neus\nPerry\n                Corp.\n767\n                Fifth Avenue\n19th\n                Floor\nNew\n                York, NY 10153\nTelephone:\n                (212)\n                583-4000\n\n\n\n\n(Name,\n                address and telephone number of person authorized to receive notices\n             

In [51]:
print(t)


SC 13D
1
sc13d.htm
SCHEDULE 13D




      Schedule 13D







 









UNITED
                STATES
SECURITIES
                AND EXCHANGE COMMISSION
Washington,
                D.C. 20549
 




SCHEDULE
                13D




Under
                the Securities Exchange Act of 1934



 



UNIVERSAL
                AMERICAN FINANCIAL CORP.




(Name
                of Issuer)
 




Common
                Stock (par value $.01 per share)

 

913377107




(Title
                of class of securities)

 

(CUSIP
                number)




Michael
                C. Neus
Perry
                Corp.
767
                Fifth Avenue
19th
                Floor
New
                York, NY 10153
Telephone:
                (212)
                583-4000




(Name,
                address and telephone number of person authorized to receive notices
                and
                communications)




 
October
                24, 2006




(Date
                of event which requir

In [48]:
soup = BeautifulSoup(t, 'html.parser')

In [50]:
soup.get_text()

'\nSC 13D\n1\nsc13d.htm\nSCHEDULE 13D\n\n\n\n\n      Schedule 13D\n\n\n\n\n\n\n\n\xa0\n\n\n\n\n\n\n\n\n\nUNITED\n                STATES\nSECURITIES\n                AND EXCHANGE COMMISSION\nWashington,\n                D.C. 20549\n\xa0\n\n\n\n\nSCHEDULE\n                13D\n\n\n\n\nUnder\n                the Securities Exchange Act of 1934\n\n\n\n\xa0\n\n\n\nUNIVERSAL\n                AMERICAN FINANCIAL CORP.\n\n\n\n\n(Name\n                of Issuer)\n\xa0\n\n\n\n\nCommon\n                Stock (par value $.01 per share)\n\n\xa0\n\n913377107\n\n\n\n\n(Title\n                of class of securities)\n\n\xa0\n\n(CUSIP\n                number)\n\n\n\n\nMichael\n                C. Neus\nPerry\n                Corp.\n767\n                Fifth Avenue\n19th\n                Floor\nNew\n                York, NY 10153\nTelephone:\n                (212)\n                583-4000\n\n\n\n\n(Name,\n                address and telephone number of person authorized to receive notices\n             

In [58]:
full_text

'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n Qur5OiBiKW8t3RxGQ8jEryljWwQOFRjbs5OuzYL4Qz7hw5aGWnGh+hsLHPoeBT5/\n DCam4jVdwJxkvHIma4vAgA==\n\n<SEC-DOCUMENT>0000950157-06-001062.txt : 20061025\n<SEC-HEADER>0000950157-06-001062.hdr.sgml : 20061025\n<ACCEPTANCE-DATETIME>20061025143729\nACCESSION NUMBER:\t\t0000950157-06-001062\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20061025\nDATE AS OF CHANGE:\t\t20061025\nGROUP MEMBERS:\t\tRICHARD C. PERRY\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tUNIVERSAL AMERICAN FINANCIAL CORP\n\t\tCENTRAL INDEX KEY:\t\t\t0000709878\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tLIFE INSURANCE [6311]\n\t\tIRS NUMBER:\t\t\t\t112580136\n\t\tSTATE OF INCOR

In [203]:
from multiprocess import Pool

In [ ]:
p = Pool(12)

In [5]:
def get_file_list_df(engine, num_files = None):

    inspector = inspect(engine)
    
    if('sc13dg_indexes' in inspector.get_table_names(schema='edgar')):
        
        sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
                 INNER JOIN edgar.filings AS b
                 USING(file_name)
                 LEFT JOIN edgar.sc13dg_indexes AS c
                 USING(file_name, document)
                 WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
                 AND a.downloaded
                 AND right(a.file_name, 24) = a.document
                 AND c.file_name IS NULL
              """
        
    else:
        
        sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
                 INNER JOIN edgar.filings AS b
                 USING(file_name)
                 WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
                 AND a.downloaded
                 AND right(a.file_name, 24) = a.document
              """
              
    if(num_files is not None):
      
        sql = sql + " LIMIT " + str(num_files)
        
    df = pd.read_sql(sql, engine)
    
    return(df)

In [15]:
def process_batch_alt(df, directory, engine, num_cores = 12):
  
    p = Pool(num_cores)
  
   
    success = pd.Series(p.map(lambda i: write_indexes_to_table(df.loc[i, 'file_name'], df.loc[i, 'document'],\
                                df.loc[i, 'form_type'], directory, engine),\
                              range(df.shape[0])), ignore_index = True)
    p.close()

    num_success = success.sum()
    return(num_success)


In [10]:
directory = '/media/igow/6TB/data/edgar'

In [16]:
process_batch_alt(get_file_list_df(engine, num_files = 20), directory, engine, num_cores = 12)

TypeError: can't pickle _thread._local objects

Process ForkPoolWorker-32:
Process ForkPoolWorker-36:
Process ForkPoolWorker-28:
Process ForkPoolWorker-27:
Process ForkPoolWorker-35:
Process ForkPoolWorker-30:
Process ForkPoolWorker-31:
Process ForkPoolWorker-29:
Process ForkPoolWorker-25:
Process ForkPoolWorker-34:
Process ForkPoolWorker-26:
Traceback (most recent call last):
Process ForkPoolWorker-33:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/bdcallen/anaconda3/lib/py

  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/synchronize.py", line 102, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
KeyboardInterrupt
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/synchronize.py", line 102, in __enter__
    return self._semlock.__enter__()
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/synchronize.py", line 102, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/synchronize.py", line 102, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
  File "/home/bdcallen/anaconda3/lib/python3.7/site-packages/multiprocess/connection.py", line 410, in _recv_bytes
    buf = self._recv(4)
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
  File "/home/bdcallen/anaconda3/lib/python3.7/site-package

In [7]:
get_file_list_df(engine, num_files = 20)

file_name                  document  \
0    edgar/data/831001/0001047469-05-024286.txt  0001047469-05-024286.txt   
1    edgar/data/908733/0000891804-05-003032.txt  0000891804-05-003032.txt   
2   edgar/data/1018138/0001072613-05-002324.txt  0001072613-05-002324.txt   
3   edgar/data/1018138/0001072613-05-002399.txt  0001072613-05-002399.txt   
4   edgar/data/1167456/0001085146-05-000456.txt  0001085146-05-000456.txt   
5    edgar/data/908733/0000891804-05-003034.txt  0000891804-05-003034.txt   
6    edgar/data/908733/0000891804-05-003639.txt  0000891804-05-003639.txt   
7   edgar/data/1167456/0001085146-05-000584.txt  0001085146-05-000584.txt   
8   edgar/data/1167456/0001085146-05-000588.txt  0001085146-05-000588.txt   
9   edgar/data/1018138/0001072613-05-002460.txt  0001072613-05-002460.txt   
10   edgar/data/908733/0000891804-05-003640.txt  0000891804-05-003640.txt   
11  edgar/data/1018138/0001072613-05-002461.txt  0001072613-05-002461.txt   
12  edgar/data/1005229/0000315066-05-002760.txt  0000315066-05-002760.txt   
13  edgar/data/1018138/0001072613-05-002843.txt  0001072613-05-002843.txt   
14  edgar/data/1109120/0001193125-05-240064.txt  0001193125-05-240064.txt   
15  edgar/data/1167456/0001085146-05-000589.txt  0001085146-05-000589.txt   
16  edgar/data/1167456/0001085146-05-000592.txt  0001085146-05-000592.txt   
17  edgar/data/1167456/0001085146-05-000595.txt  0001085146-05-000595.txt   
18    edgar/data/22252/0001013594-05-000454.txt  0001013594-05-000454.txt   
19    edgar/data/22252/0001105806-05-000016.txt  0001105806-05-000016.txt   

   form_type  
0   SC 13G/A  
1   SC 13G/A  
2   SC 13D/A  
3   SC 13D/A  
4     SC 13G  
5   SC 13G/A  
6   SC 13G/A  
7     SC 13G  
8     SC 13G  
9   SC 13D/A  
10  SC 13G/A  
11  SC 13D/A  
12  SC 13G/A  
13  SC 13D/A  
14  SC 13D/A  
15    SC 13G  
16    SC 13G  
17    SC 13G  
18    SC 13D  
19  SC 13G/A

In [ ]:
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    
    key_info['is_schedule_to'] = [is_schedule_to(text)]
    key_info['has_table_of_contents'] = [has_table_of_contents(text)]
    
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text, key_info['item_section_start'][0])]
    key_info['exhibit_start'] = [get_exhibit_sec_start(text, key_info['signature_start'][0])]
    key_info['main_text_length'] = [len(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['explanatory_statement_start'] = find_explanatory_statement_start(text, lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    key_info['has_jumbled_order'] = [has_jumbled_order(text, form_type, key_info['exhibit_start'][0])]
    
    key_info['has_exhibit_break'] = [has_exhibit_break(text, key_info['cover_page_start'][0],\
                                                       key_info['signature_start'][0])]
    

    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

In [18]:
eg = get_file_list_df(engine, num_files = 60)
eg

file_name                  document  \
0   edgar/data/1274150/0000950159-05-001445.txt  0000950159-05-001445.txt   
1    edgar/data/880115/0000880115-05-000006.txt  0000880115-05-000006.txt   
2   edgar/data/1262276/0000872573-05-000044.txt  0000872573-05-000044.txt   
3   edgar/data/1343063/0000905148-05-005415.txt  0000905148-05-005415.txt   
4   edgar/data/1288633/0000902664-05-002036.txt  0000902664-05-002036.txt   
5   edgar/data/1120830/0001013762-05-001921.txt  0001013762-05-001921.txt   
6   edgar/data/1120830/0001013762-05-001923.txt  0001013762-05-001923.txt   
7   edgar/data/1120830/0001013762-05-001943.txt  0001013762-05-001943.txt   
8   edgar/data/1339851/0000905718-05-000249.txt  0000905718-05-000249.txt   
9   edgar/data/1291075/0001144204-05-038956.txt  0001144204-05-038956.txt   
10  edgar/data/1344765/0001104659-05-056563.txt  0001104659-05-056563.txt   
11  edgar/data/1104252/0000919574-05-003399.txt  0000919574-05-003399.txt   
12  edgar/data/1319959/0001019056-05-001062.txt  0001019056-05-001062.txt   
13  edgar/data/1319959/0001019056-05-001162.txt  0001019056-05-001162.txt   
14  edgar/data/1319959/0001019056-05-001351.txt  0001019056-05-001351.txt   
15  edgar/data/1120830/0001013762-05-001945.txt  0001013762-05-001945.txt   
16  edgar/data/1345837/0001193125-05-236845.txt  0001193125-05-236845.txt   
17  edgar/data/1104252/0001193125-05-195426.txt  0001193125-05-195426.txt   
18  edgar/data/1334978/0000950129-05-011723.txt  0000950129-05-011723.txt   
19  edgar/data/1345826/0000950133-05-005452.txt  0000950133-05-005452.txt   
20  edgar/data/1104252/0000315066-05-002586.txt  0000315066-05-002586.txt   
21  edgar/data/1341697/0000892917-05-000248.txt  0000892917-05-000248.txt   
22  edgar/data/1334978/0000315066-05-003034.txt  0000315066-05-003034.txt   
23  edgar/data/1010422/0001010422-05-000015.txt  0001010422-05-000015.txt   
24  edgar/data/1300073/0001108017-05-000590.txt  0001108017-05-000590.txt   
25  edgar/data/1341274/0001341274-05-000001.txt  0001341274-05-000001.txt   
26  edgar/data/1010422/0001193125-05-241253.txt  0001193125-05-241253.txt   
27  edgar/data/1166414/0001105833-05-000016.txt  0001105833-05-000016.txt   
28  edgar/data/1010422/0001010422-05-000024.txt  0001010422-05-000024.txt   
29  edgar/data/1166414/0001317688-05-000095.txt  0001317688-05-000095.txt   
30  edgar/data/1166414/0001317688-05-000121.txt  0001317688-05-000121.txt   
31  edgar/data/1324348/0001125282-05-005065.txt  0001125282-05-005065.txt   
32  edgar/data/1324348/0001125282-05-005248.txt  0001125282-05-005248.txt   
33  edgar/data/1001462/0001156973-05-001605.txt  0001156973-05-001605.txt   
34  edgar/data/1294704/0001125282-05-005104.txt  0001125282-05-005104.txt   
35  edgar/data/1294704/0001125282-05-006423.txt  0001125282-05-006423.txt   
36  edgar/data/1243310/0000902664-05-002327.txt  0000902664-05-002327.txt   
37  edgar/data/1166414/0001317688-05-000122.txt  0001317688-05-000122.txt   
38  edgar/data/1166414/0001317688-05-000123.txt  0001317688-05-000123.txt   
39  edgar/data/1166414/0001317688-05-000124.txt  0001317688-05-000124.txt   
40  edgar/data/1166414/0001317688-05-000125.txt  0001317688-05-000125.txt   
41  edgar/data/1001462/0001156973-05-001684.txt  0001156973-05-001684.txt   
42  edgar/data/1316738/0001161697-05-001182.txt  0001161697-05-001182.txt   
43   edgar/data/939295/0001104659-05-058333.txt  0001104659-05-058333.txt   
44  edgar/data/1263972/0000899140-05-000957.txt  0000899140-05-000957.txt   
45  edgar/data/1102181/0001140377-05-000304.txt  0001140377-05-000304.txt   
46  edgar/data/1333568/0001144204-05-033064.txt  0001144204-05-033064.txt   
47  edgar/data/1103130/0000915656-05-000141.txt  0000915656-05-000141.txt   
48  edgar/data/1333568/0001144204-05-033161.txt  0001144204-05-033161.txt   
49  edgar/data/1333568/0001144204-05-039108.txt  0001144204-05-039108.txt   
50  edgar/data/1072783/0000950123-05-014728.txt  0000950123-05-014728.txt   
51  edgar/data/1072783/0000950123-

In [83]:
i=0
get_key_indices(eg.loc[i, 'file_name'], eg.loc[i, 'document'], eg.loc[i, 'form_type'], directory)

KeyboardInterrupt: 

In [86]:
t = get_main_doc_text(eg.loc[i, 'file_name'], eg.loc[i, 'document'], directory)

In [87]:
t

'\nSC 13G\n1\ncommenergy13g.htm\nCOMMERCE ENERGY 13G\n\n\n  \n    \n      Commerce Energy 13G\n\n\n\n\n\n\n  \n    SECURITIES\n      AND EXCHANGE COMMISSION\n    WASHINGTON,\n      DC 20549\n    _________________________\n     \n    SCHEDULE\n      13G\n    (Rule\n      13d-102)\n     \n    INFORMATION\n      TO BE INCLUDED IN STATEMENTS\n    FILED\n      PURSUANT TO RULES 13d-1(b), (c) AND (d)\n    AND\n      AMENDMENTS THERETO FILED PURSUANT TO 13d-2(b)\n    (Amendment\n      No. ____________)1 \n     \n    Commerce\n      Energy Group, Inc. \n     \n    (Name\n      of\n      Issuer)\n     \n    Common\n      Stock, $0.001 par value\n    (Title\n      of\n      Class of Securities)\n     \n    20061Q106 \n    \n      \n    \n     \n    (CUSIP\n      NUMBER)\n    \n    December\n      8, 2005\n     \n    (Date\n      of\n      Event Which Requires Filing of this Statement)\n     \n    Check\n      the\n      appropriate box to designate the rule pursuant to which this Schedule is\n  

In [89]:
re.search('The\s+remainder\s+of\s+this\s+cover\s+page\s+shall\s+be\s+filled\s+out\s+for\s+a\s+reporting', t)

<re.Match object; span=(1603, 1693), match='The\n                      remainder of this cove>

In [88]:
find_title_page_end(t)

KeyboardInterrupt: 

In [20]:
t1 = dt.datetime.now()
eg.apply(lambda x: get_key_indices(x['file_name'], x['document'], x['form_type'], directory), axis = 1)
t2 = dt.datetime.now()

KeyboardInterrupt: 

In [90]:
get_title_page_end_upper_bound(t, rep_q_as_items = None)

KeyboardInterrupt: 

In [91]:
find_orthodox_cover_page_q1_start(t)

KeyboardInterrupt: 

In [92]:
t

'\nSC 13G\n1\ncommenergy13g.htm\nCOMMERCE ENERGY 13G\n\n\n  \n    \n      Commerce Energy 13G\n\n\n\n\n\n\n  \n    SECURITIES\n      AND EXCHANGE COMMISSION\n    WASHINGTON,\n      DC 20549\n    _________________________\n     \n    SCHEDULE\n      13G\n    (Rule\n      13d-102)\n     \n    INFORMATION\n      TO BE INCLUDED IN STATEMENTS\n    FILED\n      PURSUANT TO RULES 13d-1(b), (c) AND (d)\n    AND\n      AMENDMENTS THERETO FILED PURSUANT TO 13d-2(b)\n    (Amendment\n      No. ____________)1 \n     \n    Commerce\n      Energy Group, Inc. \n     \n    (Name\n      of\n      Issuer)\n     \n    Common\n      Stock, $0.001 par value\n    (Title\n      of\n      Class of Securities)\n     \n    20061Q106 \n    \n      \n    \n     \n    (CUSIP\n      NUMBER)\n    \n    December\n      8, 2005\n     \n    (Date\n      of\n      Event Which Requires Filing of this Statement)\n     \n    Check\n      the\n      appropriate box to designate the rule pursuant to which this Schedule is\n  

In [19]:
dt.datetime.now()

datetime.datetime(2020, 2, 12, 16, 17, 12, 99071)

In [6]:
import os
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import re
from codecs import decode
from sqlalchemy import create_engine, inspect
import datetime as dt
from pathos.multiprocessing import Pool


dbname = os.getenv("PGDATABASE")

host = os.getenv("PGHOST", "localhost")

conn_string = "postgresql://" + host + "/" + dbname




def get_index_url(file_name): 
    
    # This is a Python version of the function of the same name in scrape_filing_doc_functions.R
    
    regex = "/(\\d+)/(\\d{10}-\\d{2}-\\d{6})"
    matches = re.findall(regex, file_name)[0]
    
    cik = matches[0]
    acc_no = matches[1]
    
    path = re.sub("[^\\d]", "", acc_no)
    
    url = "https://www.sec.gov/Archives/edgar/data/" + cik + "/" + path + "/" + acc_no + "-index.htm"
    
    return(url)
    
    

def get_file_path(file_name, document):
    
    url = re.sub("(\\d{10})-(\\d{2})-(\\d{6})\\.txt", "\\1\\2\\3", file_name)
    
    path = url + '/' + document
    
    return(path)



def get_file_text_from_directory(file_name, document, directory):
    
    path = directory + '/' + get_file_path(file_name, document)
    f = open(path, 'r')
    txt = f.read()
    f.close()
    return(txt)
    

def fix_unmatched_page_tags(text):
    
    # First fix missing right dels
    
    start_tag_r_regex = '<PAGE[^>]' 
    end_tag_r_regex = '</PAGE[^>]'
    
    corrected_r_start = '<PAGE>\n' # Introduce newline in case newline replace by right del
    corrected_r_end = '</PAGE>\n'
    
    fixed_content = re.sub(start_tag_r_regex, corrected_r_start, text)
    fixed_content = re.sub(end_tag_r_regex, corrected_r_end, fixed_content)
    
    # Now fix missing left dels
    
    start_tag_l_regex = '[^<]PAGE>' 
    end_tag_l_regex = '[^<]/PAGE>'
    
    corrected_l_start = '\n<PAGE>' # Introduce newline in case newline replace by left del
    corrected_l_end = '\n</PAGE>'
    
    fixed_content = re.sub(start_tag_l_regex, corrected_l_start, fixed_content)
    fixed_content = re.sub(end_tag_l_regex, corrected_l_end, fixed_content)
    
    return(fixed_content)


def clean_text(text):
    
    # this function gets rid of unwanted characters and spaces
    
    result = fix_unmatched_page_tags(text) # First fix tags which are missing delimeters
    
    char_list = ['\xa0', '&#160;', '&#\n160;']
    
    for c in char_list:
        
        result = re.sub(c, ' ', result) 
        
    return(result)


def get_bounded_text(text, lower_bound = None, upper_bound = None):
    
    if(lower_bound is not None):
        
        if(upper_bound is not None):
            
            if(lower_bound >= upper_bound):
                
                raise ValueError("upper_bound not more than lower_bound")
                
            else:
                
                return(text[lower_bound:upper_bound])
            
        else:
            
            return(text[lower_bound:])
        
    else:
        
        if(upper_bound is not None):
            
            return(text[lower_bound:upper_bound])
        
        else:
            
            return(text)

   
    
def get_main_doc_text(file_name, document, directory):
  
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    soup = BeautifulSoup(full_text, 'html5lib')
    main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
    
    return(main_doc_text)
    
   
   
def find_last_search_start(regex, text):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return(None)
    
    else:
        
        end = 0
        
        while(search is not None):
            
            start = end + search.start()
            end = end + search.end()
            search = re.search(regex, text[end:])
        
    return(start)
    
    


def find_last_search_end(regex, text):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return(None)
    
    else:
        
        end = 0
        
        while(search is not None):
            
            end = end + search.end()
            search = re.search(regex, text[end:])
        
    return(end)
   
   
   
    
def get_title_page_end_lower_bound(text, upper_bound = None):
    
    rep_q_as_items = is_rep_q_as_items(text)
    
    if(upper_bound is None):
        upper_bound = get_title_page_end_upper_bound(text)
    
    text_raised = text.upper()[:upper_bound]
    
    if(not rep_q_as_items):
        
        last_search = find_last_search_end('\((?:NAME|CUSIP|SEDOL|DATE|TITLE|AMENDMENT)(.*?\s)*?' + \
                     '(?:ISSUER|SECURITIES|NUMBER|STATEMENT|SCHEDULE|NO\.?|#)\)', text_raised)
        
        if(last_search):
            
            return(last_search)
        
        else:
            return(0)
        
    else:
        
        return(0)

        
        
def get_title_page_end_upper_bound(text, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        rep_q_as_items = is_rep_q_as_items(text)

    text_raised = text.upper()

    if(rep_q_as_items):

        end = re.search('ITEM\s*[#\.\:]?\s*[\(]?\s*1[24]\s*[\)]?[\.\:]?', text_raised).start()

        regex = 'ITEM\s*[#\.\:]?\s*[\(]?\s*1\s*[\)]?[\.\:]?'

        search = re.search(regex, text_raised[:end])

        return(search.start())

    else:

        regex = '[\(]?\s*1\s*[\)]?\s*[:\.]{0,1}\s*NAME[S]?\s+(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?' + \
                '(\s*/\s*)?(S\.S\.\s+)?(\s+(?:OR|AND))\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[S]?\.\s+' + \
                '(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?'     

        search = re.search(regex, text_raised)

        if(search):

            return(search.start())

        else:
            regex = '(?<!DESCRIBED\sIN)\s*ITEM\s*[#\.\:]?\s*[\(]?\s*[0-9]{1,2}\s*' + \
                    '[\)]?[\.\:]?'
            search = re.search(regex, text_raised)

            return(search.start())



def find_regex1_end(text):
    
    text_lowered = text.lower()

    regex1 = 'but\s+shall\s+be\s+subject\s+to\s+all\s+other\s+provisions\s+of\s+the\s+act\s*' + \
              '(\(however,\s+see\s+the\s+notes\s*\))?(\.)?'

    end = find_last_search_end(regex1, text_lowered)
    
    if(end is not None):
        
        return(end)
    
    else:
        # Use -1 to distinguish cases where regex was not found from other failures
        return(-1)
        
        
            
            
def find_title_page_end(text):
    
    rep_q_as_items = is_rep_q_as_items(text)
    
    upper_bound = get_title_page_end_upper_bound(text, rep_q_as_items)
    
    text_raised = text.upper()[:upper_bound]
    
    regex1_end = find_regex1_end(text)
    
    num_cusip_lines = len(re.findall('(?:CUSIP|SEDOL)', text_raised))
    
    if(regex1_end != -1):
        
        return(regex1_end)
    
    elif(num_cusip_lines < 2):
        
        return(upper_bound)
        
    else:
            
        
        rep_start_re = ['(?:CUSIP|SEDOL)', 'SCHEDULE\s+13[DG](/A)?', 'SC\s+13[DG](/A)?', \
                        'PAGE', '13[DG](/A)?']

        pot_results = []

        for regex in rep_start_re:

            start = find_last_search_start(regex, text_raised)

            if(start):
                pot_results.append(start)
                
        result = min(pot_results)
        
        return(result)
        

def is_rep_q_as_items(text, q1_start = None):
    
    # this function works on the basis that the the actual "items" in the real item section does not go beyond
    # Item 10. So by searching for Item 12 or 14 (in SC 13G and SC 13D respectively), we can detect whether
    # a filer has erroneously labelled the questions in the reporting pages as items
    
    if(q1_start is None):
      
        q1_start = find_orthodox_cover_page_q1_start(text)
    
    if(q1_start == -1):
    
        text_raised = text.upper()
        
        regex = '\n\s*ITEM\s*(\.)?\s*[\(]?\s*1[24]\s*[\)]?(\.)?'
        
        search = re.search(regex, text_raised)
        
        if(search):
            return(True)
        else:
            return(False)
            
    else:
      
        return(False)
        
        
        
def find_orthodox_cover_page_q1_start(text, lower_bound = None, upper_bound = None):

    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()

    regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?'

    regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
    
    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
             'PERSON[\(]?[S]?[\)]?'
    
    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
             'ABOVE\s+PERSON[\(]?[S]?[\)]?'
    
    regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'
    
    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
             '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
             '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'
    
    
    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'
    
    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'
    
    regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
              'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
    
    for i in range(len(regex_list)):
        
        search = re.search(regex_list[i], text_raised)
        
        if(search):
            
            break

    if(search):
        
        return(search.start())
    
    else:
        
        return(-1)   


def cover_page_start_is_rep_as_q(text, form_type, lower_bound = None, upper_bound = None, rep_q_as_items = None):
    # this function is for cases where is_rep_q_as_items is True
    
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
        
    search = None
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)

    if(re.search('SC 13D', form_type)):
        
        if(rep_q_as_items):
            
            search = re.search('\n\s*ITEM\s+[\(\|]?\s?1\s?[\)\|]?\s*[:\.]{0,1}(.)+?' + \
                  '\n\s*ITEM\s+[\(\|]?\s?14\s?[\)\|]?\s*[:\.]{0,1}', text_raised, flags = re.DOTALL)
            
        else:
            return(-1)
        
    if(re.search('SC 13G', form_type)):
        
        if(rep_q_as_items):
            
            search = re.search('\n\s*ITEM\s+[\(\|]?\s?1\s?[\)\|]?\s*[:\.]{0,1}(.)+?' + \
                  '\n\s*ITEM\s+[\(\|]?\s?12\s?[\)\|]?\s*[:\.]{0,1}', text_raised, flags = re.DOTALL)
            
        else:
            return(-1)
            
    if(search):
        
        return(search.start() + lower_bound)
    
    else:
        
        return(-1)



def find_cover_page_q1_start(text, form_type, lower_bound = None, upper_bound = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
         rep_q_as_items = is_rep_q_as_items(get_bounded_text(text, lower_bound, upper_bound))
            
    if(rep_q_as_items):
        
        result = cover_page_start_is_rep_as_q(text, form_type, lower_bound, upper_bound, rep_q_as_items)
        
    else:
        
        result = find_orthodox_cover_page_q1_start(text, lower_bound, upper_bound)
        
    return(result)

    
        
def cover_page_start(text, form_type, lower_bound = None, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text, cover_page_q1)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_cover_page_q1_start(text, form_type, lower_bound, cover_page_q1, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)\s*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)
        
        
def find_cover_pages_last_question(text, rep_q_as_items = None,  lower_bound = None, upper_bound = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(lower_bound is not None and lower_bound > 0):
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[lower_bound:upper_bound]
            
        else:
            
            text_raised = text.upper()[lower_bound:]
            
    else:
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[:upper_bound]
            
        else:
            
            text_raised = text.upper() 
    
    if(rep_q_as_items):
        
        regex = 'ITEM\s*[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?'
        
    else:
    
        regex = '[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?[\*]?\s*(\(SEE\s+INSTRUCTIONS\))?'

    search = re.search(regex, text_raised)

    if(search is None):
        return(None)
    
    end = 0

    while(search is not None):
        
        end = end + search.end()
        search = re.search(regex, text_raised[end:])

    if(lower_bound is not None and lower_bound > 0):
        
        end = end + lower_bound
        
    return(end)       
        

    
def find_cover_pages_end(text, form_type, rep_q_as_items = None, lower_bound = None, upper_bound = None):
    
    if(upper_bound is None):
        
        upper_bound = get_item_section_start(text, form_type)
    
    if(lower_bound is None):
        
        lower_bound = find_cover_pages_last_question(text, rep_q_as_items, None, upper_bound)
    
    end = None
        
    # First check for footnotes
    
    last_footnote_start = find_last_footnote_index_end(text, lower_bound, upper_bound)
    
    if(last_footnote_start != -1):
        
        end = last_footnote_start
        
        search = re.search('\n\s*\n', text[end:upper_bound])

        if(search is not None):

            end = end + search.end()

            return(end)
        
 
    answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'

    last_answer = re.search(answer_regex, text[lower_bound:upper_bound])

    if(last_answer is not None):

        end = lower_bound + last_answer.end()
        return(end)

    # Finally, try finding a key stopword in all caps, such as SCHEDULE 13D, CUSIP, etc...

    end = first_header_word_after_cover_page(text, form_type, lower_bound, \
                                       upper_bound, rep_q_as_items)

    if(end != -1):

        return(end)

    else:

        return(-1)
    

      
 
def find_last_footnote_index_end(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   
    
    # first try regex1
    
    last_footnote_ind_end  = find_last_search_end(regex1, bounded_text)
    
    if(last_footnote_ind_end is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_ind_end + lower_bound
            
        else: 
            
            result = last_footnote_ind_end
            
        return(result)
            
    else:
        
        # Try regex2
        
        last_footnote_ind_end = find_last_search_end(regex2, bounded_text)
    
        if(last_footnote_ind_end is not None):

            if(lower_bound is not None):

                result = last_footnote_ind_end + lower_bound

            else: 

                result = last_footnote_ind_end

            return(result)
        
        else:
            
            return(-1)
            
            
     
      
def find_last_footnote_start(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   
    
    # first try regex1
    
    last_footnote_start = find_last_search_start(regex1, bounded_text)
    
    if(last_footnote_start is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_start + lower_bound
            
        else: 
            
            result = last_footnote_start
            
        return(result)
            
    else:
        
        # Try regex2
        
        last_footnote_start = find_last_search_start(regex2, bounded_text)
    
        if(last_footnote_start is not None):

            if(lower_bound is not None):

                result = last_footnote_start + lower_bound

            else: 

                result = last_footnote_start

            return(result)
        
        else:
            
            return(-1)
            
            
        

def first_header_word_after_cover_page(text, form_type, cover_page_last_q = None, upper_bound = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(cover_page_last_q is None):
        
        cover_page_last_q = find_cover_pages_last_question(text, rep_q_as_items,  lower_bound, upper_bound)
        
    if(cover_page_last_q == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
    
    else:
        
        text_to_search = get_bounded_text(text, cover_page_last_q, upper_bound)
        
        text_raised = text_to_search.upper()

        regex = '\n\s*(CUSIP|SEDOL|SCHEDULE\s+13[DG]|PAGE|13[DG])'

        search = re.search(regex, text_raised)

        if(search):

            num_forward = search.start()
            
            start = cover_page_last_q + num_forward

            return(start)

        else:

            return(-1)

        


 

def num_cusip_sedol_before_index(text, index = None):

    try:
        if(index):
            text_lowered = text.lower()[:index]
        else:
            text_lowered = text.lower()
        
        num_cusip_sedol = len(re.findall('(cusip|sedol)', text_lowered))
        
        return(num_cusip_sedol)

    except Exception as e:
        print(e)
        return(None)

    
def find_explanatory_statement_start(text, lower_bound = None, upper_bound = None):
    
    # This function is designed to get the start of the explanatory/amendment statement 
    # that is sometimes found between the end of the cover pages and the start of the item section 
    
    

    regex_list = ['\n\s*explanatory\s+note', '\n\s*amendment\s+(number|no)(\.)?\s*[0-9]+\s*\n',\
                  '\n\s*schedule\s+13[dg]\s+amendment\s+(number|no)(\.)?\s*[0-9]+\s*\n',\
                  '\n\s*this\s+amendment\s+(number|no)(\.)?\s*[0-9]+\s+', \
                    '\n\s*pursuant\s+to\s+rule\s+13d-', '\n\s*this\s+amended\s+schedule\s+13[dg]', \
'\n\s*the\s+undersigned(\s+reporting\s+person(s)?)?\s+hereby\s+amend\s+(the|their)\s+schedule\s+13[dg]',\
                  '\n\s*the\s+schedule\s+13[dg]\s+was\s+initially\s+filed',\
                 '\n(.)+hereby\s+amends\s+the\s+schedule\s+13[dg]',\
                  '\n\s*the\s+filing\s+of\s+this\s+schedule\s+13[dg]',\
                 '\n\s*the\s+filing\s+of\s+this\s+statement\s+on\s+schedule\s+13[dg]',\
                 '\n\s*the\s+reporting\s+person(s)?\s+listed\s+']

    if(lower_bound):

        if(upper_bound):

            text_lowered = text.lower()[lower_bound:upper_bound]

        else:

            text_lowered = text.lower()[lower_bound:]

    else:

        if(upper_bound):

            text_lowered = text.lower()[:upper_bound]

        else:

            text_lowered = text.lower()

    search_starts = []

    for pattern in regex_list:

        search = re.search(pattern, text_lowered)

        if(search):

            search_starts.append(search.start())

    if(len(search_starts)):

        if(lower_bound):

            return(min(search_starts) + lower_bound)

        else:

            return(min(search_starts))

    else:

        return(-1)

    
def get_item_section_start(text, form_type):    
    
    
    if(re.search('SC\s+13D', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?\s*security\s+and\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?\s*identity\s+and\s+background',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*source\s+and\s+amount\s+of\s+funds',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*purpose\s+of\s+transaction',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*interest\s+in\s+securities\s+of\s+the\s+issuer',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*contracts,\s+arrangements,\s+understandings',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*material\s+to\s+be\s+filed\s+as\s+exhibits'
                  ]
                       
        
    elif(re.search('SC\s+13G', form_type)):
        
        re_list = ['\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+issuer',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*a[\)]?[#\.\;\:]?\s*name[s]?\s+of\s+person[s]?\s+filing',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*b[\)]?[#\.\;\:]?\s*address\s+of\s+principle',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*c[\)]?[#\.\;\:]?\s*citizenship',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*d[\)]?[#\.\;\:]?\s*title\s+of\s+class',
                   '\n\s*[#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*e[\)]?[#\.\;\:]?\s*cusip\s+number',
                   '\n\s*[#\.\;\:]?\s*3[#\.\;\:]?\s*if\s+this\s+statement\s+is\s+filed\s+pursuant',
                   '\n\s*[#\.\;\:]?\s*4[#\.\;\:]?\s*ownership',
                   '\n\s*[#\.\;\:]?\s*5[#\.\;\:]?\s*ownership\s+of\s+five',
                   '\n\s*[#\.\;\:]?\s*6[#\.\;\:]?\s*ownership\s+of\s+more',
                   '\n\s*[#\.\;\:]?\s*7[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*8[#\.\;\:]?\s*identification\s+and\s+classification',
                   '\n\s*[#\.\;\:]?\s*9[#\.\;\:]?\s*notice\s+of\s+dissolution',
                   '\n\s*[#\.\;\:]?\s*10[#\.\;\:]?\s*certification'
                  ]
        
    else:
        
        # Not a Schedule 13D(/A) or 13G(/A)
        return(None)
   
    cover_pages_end = find_cover_pages_last_question(text)
    
    if(cover_pages_end):

        text_lowered = text[cover_pages_end:].lower()

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*(?:[0-9])[#\.\;\:]?', text_lowered)
        
        if(search):
            
            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(cover_pages_end + search.start() + num_to_item)  
        
        else:
            return(-1) # ie. assume no Item section (this probably happens with 13D/A and 13G/A)
    
    else:
        
        text_lowered = text.lower() # Assume NO REPORTING PAGES (this happens, especially with 13D/A and 13G/A)

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*[0-9][#\.\;\:]?', text_lowered)

        if(search):

            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(search.start() + num_to_item)  
        
        else: 
             
            result = -1 # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    search_str = search.group(0)
            
                    num_to_item = re.search('item', search_str).start()
                    
                    result = search.start() + num_to_item
                    break
            
            
            return(result)     
    
    
def get_signatures_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_lowered = get_bounded_text(text, lower_bound, upper_bound).lower()
    
    regex1 = '\n\s*(signature|signatures)\s*(\.)?\n'
    
    regex2 = 'the\s+following\s+certification\s+shall\s+be\s+included\s+if\s+the\s+statement\s+is\s+filed\s+' + \
             'pursuant to rule 13d-1\(b\)'
    
    regex3 = 'by\s+signing\s+below\s+i\s+certify\s+that,\s+to\s+the\s+best\s+of\s+my\s+knowledge'

    regex4 = 'after\s+reasonable\s+inquiry\s+'
    
    regex_list = [regex1, regex2, regex3, regex4]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_lowered)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
      
        return(-1)
        
        
def get_exhibit_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_upper = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    regex0 = '\n\s*EXHIBIT\s+INDEX\s*\n'
    
    regex1 = '\n\s*EXHIBIT\s+[0-9A-Z](:)?\s*\n'
    
    regex2 = '\n\s*APPENDIX\s+[0-9A-Z](:)?\s*\n'
    
    regex_list = [regex0, regex1, regex2]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_upper)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
        return(-1)
    
    
    
def has_exhibit_break(text, cover_page_start, signature_start):
    
    exhibit_st = get_exhibit_sec_start(text, cover_page_start, signature_start)
    
    if(exhibit_st != -1):
        
        return(True)
    
    else:
        
        return(False)    
    

def find_orthodox_cover_page_q1_start_end(text, lower_bound = None, upper_bound = None):

    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()

    regex0 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?'

    regex2 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
    
    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
             'PERSON[\(]?[S]?[\)]?'
    
    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
             'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
             'ABOVE\s+PERSON[\(]?[S]?[\)]?'
    
    regex5 = '[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*' + \
             'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'
    
    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
             'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
             '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
             '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'
    
    
    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
             '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'
    
    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex9 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?.'
    
    regex10 = '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?\s*(.){0,50}\s*' + \
              'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8, regex9, regex10]
    
    
    for i in range(len(regex_list)):
        
        search = re.search(regex_list[i], text_raised)
        
        if(search):
            
            break

    if(search):
        
        return(search.start(), search.end())
    
    else:
        
        return(-1, -1)

 
 
 
def find_all_orthodox_q1_starts(text, exhibit_start):
    
    # Finds all orthodox q1s BEFORE the exhibit section if it exists in the main text
    # (we do not want cover pages from exhibit parts)
    
    lst = []
    
    start, end = find_orthodox_cover_page_q1_start_end(text)
    
    while(start != -1):
        
        lst.append(start)
        p_start, p_end = find_orthodox_cover_page_q1_start_end(text, end)
        
        if(p_start != -1):
            
            start = end + p_start
            end = end + p_end
            
        else:
            
            start = -1
            
    if(exhibit_start is not None and exhibit_start != -1):
        
        result = [i for i in lst if i < exhibit_start]
        return(result)

    else:
        
        return(lst)


def has_jumbled_order(text, form_type, exhibit_start):
    
    # This function is defined to be true if there are item sections or signature sections in the parts of the
    # text which are before the last instance of an orthodox q1 of a cover page (hence "jumbled")
    # this can include cases where for instance, an order goes cover_page -> items -> signatures -> 
    # cover_page -> items -> signatures 
    
    result = False # Assume false till proven otherwise
    
    q1_starts = find_all_orthodox_q1_starts(text, exhibit_start)

    for i in range(len(q1_starts)):

        if(i == 0):

            segment = get_bounded_text(text, 0, q1_starts[i])

        else:

            segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

        has_items = (get_item_section_start(segment, form_type) != -1)
        has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

    return(result)         
         



         
def is_schedule_to(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*(?:SCHEDULE|SC)\s+TO(/A)?\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)
        
        
        
def has_table_of_contents(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*TABLE\s+OF\s+CONTENTS\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)
        
    
    
def get_key_indices(file_name, document, form_type, directory):
    
    key_info = {}
    
    text = get_main_doc_text(file_name, document, directory)
    
    key_info['file_name'] = [file_name]
    key_info['document'] = [document]
    key_info['form_type'] = [form_type]
    key_info['title_page_end_lower_bound'] = [find_title_page_end(text)]
    key_info['cover_page_q1_start'] = [find_orthodox_cover_page_q1_start(text)]
    key_info['is_rep_q_as_items'] = [is_rep_q_as_items(text, key_info['cover_page_q1_start'][0])]
    if(key_info['is_rep_q_as_items'][0]):
        
        key_info['cover_page_q1_start'] = [cover_page_start_is_rep_as_q(text, form_type, \
                                                lower_bound = key_info['title_page_end_lower_bound'][0])]
    
    key_info['is_schedule_to'] = [is_schedule_to(text)]
    key_info['has_table_of_contents'] = [has_table_of_contents(text)]
    
    key_info['num_cusip_sedol_b_q1'] = [num_cusip_sedol_before_index(text, \
                                                                    key_info['cover_page_q1_start'][0])]
    key_info['cover_page_start'] = [cover_page_start(text, form_type, \
            cover_page_q1 = key_info['cover_page_q1_start'][0], \
                                                     rep_q_as_items = key_info['is_rep_q_as_items'][0])]
    
    
    key_info['item_section_start'] = [get_item_section_start(text, form_type)]
    key_info['cover_page_last_q_end'] = [find_cover_pages_last_question(text, \
                        key_info['is_rep_q_as_items'][0], key_info['cover_page_q1_start'][0], \
                                                                        key_info['item_section_start'][0])]
    key_info['cover_page_end'] = [find_cover_pages_end(text, form_type, key_info['is_rep_q_as_items'][0],\
                                key_info['cover_page_last_q_end'][0], key_info['item_section_start'][0])]
    
    key_info['num_cusip_b_items'] = [num_cusip_sedol_before_index(text, \
                                                                  index = key_info['item_section_start'][0])]
    key_info['signature_start'] = [get_signatures_sec_start(text, key_info['item_section_start'][0])]
    key_info['exhibit_start'] = [get_exhibit_sec_start(text, key_info['signature_start'][0])]
    key_info['main_text_length'] = [len(text)]
    
    if(key_info['cover_page_start'][0] != -1 and key_info['item_section_start'][0] != -1\
      and key_info['item_section_start'][0] > key_info['cover_page_start'][0]):
        
        amend_l_bound = key_info['cover_page_start'][0]
        
    else:
        
        amend_l_bound = None
    
    key_info['explanatory_statement_start'] = find_explanatory_statement_start(text, lower_bound = amend_l_bound, upper_bound = key_info['item_section_start'][0])
    
    key_info['has_jumbled_order'] = [has_jumbled_order(text, form_type, key_info['exhibit_start'][0])]
    
    key_info['has_exhibit_break'] = [has_exhibit_break(text, key_info['cover_page_start'][0],\
                                                       key_info['signature_start'][0])]
    

    
    key_info_df = pd.DataFrame(key_info)
    
    return(key_info_df)

    


def get_file_list_df(engine, num_files = None):

    inspector = inspect(engine)
    
    if('sc13dg_indexes' in inspector.get_table_names(schema='edgar')):
        
        sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
                 INNER JOIN edgar.filings AS b
                 USING(file_name)
                 LEFT JOIN edgar.sc13dg_indexes AS c
                 USING(file_name, document)
                 WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
                 AND a.downloaded
                 AND right(a.file_name, 24) = a.document
                 AND c.file_name IS NULL
              """
        
    else:
        
        sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
                 INNER JOIN edgar.filings AS b
                 USING(file_name)
                 WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
                 AND a.downloaded
                 AND right(a.file_name, 24) = a.document
              """
              
    if(num_files is not None):
      
        sql = sql + " LIMIT " + str(num_files)
        
    df = pd.read_sql(sql, engine)
    
    return(df)
    
    
    
def write_indexes_to_table(file_name, document, form_type, directory, engine):
    
    try:
        
        df = get_key_indices(file_name, document, form_type, directory)
        df['success'] = True
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)
        return(True)
        
    except:
      
        df = pd.DataFrame({'file_name': [file_name], 'document': [document], 'form_type': [form_type], \
                  'title_page_end_lower_bound': [-2], 'cover_page_q1_start': [-2], 'is_rep_q_as_items': [None],\
                  'is_schedule_to': [None],  'has_table_of_contents': [None], 'num_cusip_sedol_b_q1': [-2],\
                  'cover_page_start': [-2], 'item_section_start': [-2], 'cover_page_last_q_end': [-2],\
                  'cover_page_end': [-2], 'num_cusip_b_items': [-2], 'signature_start': [-2], \
                  'exhibit_start': [-2], 'main_text_length': [-2], 'explanatory_statement_start': [-2],\
                  'has_jumbled_order': [None], 'has_exhibit_break': [None], 'success': [False]})
            
        df.to_sql('sc13dg_indexes', engine, schema="edgar", if_exists="append", index=False)        
        return(False)
    
    
def process_batch(df, directory, engine, num_cores = 12):
  
    p = Pool(num_cores)
  
    try:
      
        success = pd.Series(p.map(lambda i: write_indexes_to_table(df.loc[i, 'file_name'], df.loc[i, 'document'],\
                                    df.loc[i, 'form_type'], directory) , range(start, end)), ignore_index = True)
        p.close()
        
        num_success = success.sum()
        return(num_success)
      
    except Exception as e:
      
        print(e)
        p.close()
        return(None)
  
  


In [119]:
class TimedOutExc(Exception):
    """
    Raised when a timeout happens
    """

def timeout(timeout):
    """
    Return a decorator that raises a TimedOutExc exception
    after timeout seconds, if the decorated function did not return.
    """

    def decorate(f):

        def handler(signum, frame):
            raise TimedOutExc()

        def new_f(*args, **kwargs):

            old_handler = signal.signal(signal.SIGALRM, handler)
            signal.alarm(timeout)

            result = f(*args, **kwargs)  # f() always returns, in this scheme

            signal.signal(signal.SIGALRM, old_handler)  # Old signal handler is restored
            signal.alarm(0)  # Alarm removed

            return result

        new_f.__name__ = f.__name__
        return new_f

    return decorate


In [94]:
import signal
def handler(signum, frame):
    raise TimedOutExc()



In [105]:
# Set the signal handler and a 5-second alarm
signal.signal(signal.SIGALRM, handler)
signal.alarm(5)
answer = 0
# This function may hang indefinitely
for i in range(100000000):
    
    answer = answer + i

signal.alarm(0)

Signal handler called with signal 14


0

In [104]:
answer

49999995000000

In [106]:
signal.alarm(0)

0

In [121]:
decorator = timeout(20)

In [109]:
decorator

<function __main__.timeout.<locals>.decorate(f)>

In [135]:
def h(num, timeout):
    
    signal.signal(signal.SIGALRM, handler)
    signal.alarm(timeout)
    
    answer = 0
    for i in range(num):
    
        answer = answer + i

    signal.alarm(0)
    
    return(answer)

In [141]:
h(100000000, 5)

Signal handler called with signal 14


4999999950000000

In [129]:
g = decorator(g)

In [133]:
new_g = decorator(g)

In [134]:
new_g(2000000000)

TimedOutExc: 

In [115]:
g.func_name

AttributeError: 'function' object has no attribute 'func_name'

In [116]:
g.__name__

'g'

In [100]:
def find_cover_pages_end(text, form_type, rep_q_as_items = None, lower_bound = None, upper_bound = None):
    
    if(upper_bound is None):
        
        upper_bound = get_item_section_start(text, form_type)
    
    if(lower_bound is None):
        
        lower_bound = find_cover_pages_last_question(text, rep_q_as_items, None, upper_bound)
        
    if(lower_bound is None):
        # If, after searching, there is no last cover page question, return None
        return(None)
    
    end = None
        
    # First check for footnotes
    
    last_footnote_start = find_last_footnote_index_end(text, lower_bound, upper_bound)
    
    if(last_footnote_start != -1):
        
        end = last_footnote_start
        
        search = re.search('\n\s*\n', text[end:upper_bound])

        if(search is not None):

            end = end + search.end()

            return(end)
        
 
    answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n?'

    last_answer = re.search(answer_regex, text[lower_bound:upper_bound])

    if(last_answer is not None):
        
        if(lower_bound is not None):
            end = lower_bound + last_answer.end()
        
        return(end)

    # Finally, try finding a key stopword in all caps, such as SCHEDULE 13D, CUSIP, etc...

    end = first_header_word_after_cover_page(text, form_type, lower_bound, \
                                       upper_bound, rep_q_as_items)

    if(end != -1):

        return(end)

    else:

        return(-1)

In [11]:
indexes_df.loc[indexes_df['success'] == False]

file_name  \
493      edgar/data/1137774/0001137774-04-000198.txt   
494        edgar/data/80255/0000080255-04-000424.txt   
495       edgar/data/892960/0001048703-04-000092.txt   
496      edgar/data/1103406/0001139020-04-000100.txt   
497      edgar/data/1005972/0001015402-04-001514.txt   
498       edgar/data/767920/0000017283-04-000588.txt   
499      edgar/data/1228958/0001095449-04-000071.txt   
500       edgar/data/935699/0001012975-04-000133.txt   
501        edgar/data/77543/0000938775-04-000041.txt   
508      edgar/data/1051359/0001125282-04-002494.txt   
509      edgar/data/1037388/0001047469-04-014603.txt   
511      edgar/data/1074961/0001144204-04-006080.txt   
517        edgar/data/77543/0000950123-04-005336.txt   
523       edgar/data/749750/0001183740-04-000029.txt   
526      edgar/data/1020455/0000941655-04-000013.txt   
528       edgar/data/805900/0001193125-04-068694.txt   
551       edgar/data/723924/0001178952-04-000006.txt   
558       edgar/data/907608/0001048703-04-000090.txt   
564      edgar/data/1103406/0001139020-04-000157.txt   
569        edgar/data/85408/0000017283-04-000593.txt   
587       edgar/data/894351/0001048703-04-000057.txt   
589       edgar/data/894351/0001048703-04-000072.txt   
591       edgar/data/894351/0001048703-04-000089.txt   
616       edgar/data/766504/0001277006-04-000011.txt   
620      edgar/data/1027162/0001277006-04-000005.txt   
622       edgar/data/904290/0001104659-04-010584.txt   
643       edgar/data/832925/0001048703-04-000078.txt   
645       edgar/data/832925/0001048703-04-000088.txt   
651      edgar/data/1256071/0001256071-04-000001.txt   
699       edgar/data/907608/0001048703-04-000058.txt   
...                                              ...   
1111559   edgar/data/813634/0001116502-09-001953.txt   
1111595  edgar/data/1095616/9999999997-02-033788.txt   
1111632  edgar/data/1134340/0001144204-07-030299.txt   
1111661  edgar/data/1478982/0001144204-10-025834.txt   
1111681  edgar/data/1405057/0001144204-09-041325.txt   
1111700   edgar/data/884589/0000884589-03-000021.txt   
1111783  edgar/data/1057436/0001193125-09-146566.txt   
1111796  edgar/data/1042046/0001354488-10-000346.txt   
1111801   edgar/data/921669/0001193125-11-228611.txt   
1111885  edgar/data/1457530/0001144204-09-061183.txt   
1111934  edgar/data/1096142/0001354488-10-000266.txt   
1111946   edgar/data/886982/0000950123-02-009528.txt   
1111958  edgar/data/1279364/0000935836-10-000124.txt   
1111960   edgar/data/820027/0001193125-12-058893.txt   
1112004  edgar/data/1312625/0001213900-10-000603.txt   
1112023  edgar/data/1034054/0000916641-03-000270.txt   
1112039  edgar/data/1329505/0001019687-10-000598.txt   
1112050  edgar/data/1266719/0001144204-10-005282.txt   
1112080  edgar/data/1483338/0001354488-10-000458.txt   
1112114  edgar/data/1024401/0000950129-99-003786.txt   
1112160   edgar/data/803014/0000935836-10-000113.txt   
1112187   edgar/data/310568/0001193125-12-056397.txt   
1112192   edgar/data/911147/0000950134-01-508948.txt   
1112233  edgar/data/1039399/0001193125-12-059123.txt   
1112248  edgar/data/1386198/0000950123-10-012232.txt   
1112280    edgar/data/38777/0000038777-10-000075.txt   
1112328  edgar/data/1258602/0001437749-10-000419.txt   
1112350  edgar/data/1097609/0000950144-00-013093.txt   
1112362  edgar/data/1006892/0001193125-12-058941.txt   
1112369  edgar/data/1195739/0001048703-10-000106.txt   

                         document form_type  title_page_end_lower_bound  \
493      0001137774-04-000198.txt    SC 13G                          -2   
494      0000080255-04-000424.txt    SC 13G                          -2   
495      0001048703-04-000092.txt    SC 13D                          -2   
496      0001139020-04-000100.txt  SC 13D/A                          -2   
497      0001015402-04-001514.txt  SC 13D/A                          -2   
498      0000017283-04-000588.txt  SC 13G/A                          -2   
499      0001095449-04-000071.txt  SC 13G/A  

In [71]:
495, 498, 517, 523, 526, 528

(495, 499)

In [107]:
i = 517
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/77543/0000950123-04-005336.txt  0000950123-04-005336.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        2122                 2279   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              2172                7777   

  cover_page_last_q_end cover_page_end  num_cusip_b_items  signature_start  \
0                  None           None                  3            14418   

   exhibit_start  main_text_length  explanatory_statement_start  \
0          15473             16093                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [ ]:
569 # first character of each line missing

In [116]:
i = 528
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/805900/0001193125-04-068694.txt  0001193125-04-068694.txt   

  form_type title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13D/A                       None                   -1   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0               True           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     1                -1                6172   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   6046            6072                  1             6234   

   exhibit_start  main_text_length  explanatory_statement_start  \
0           7371              7507                         3894   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [255]:
i = 1111700
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/884589/0000884589-03-000021.txt  0000884589-03-000021.txt   

  form_type title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                       None                   -1   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     0                -1                  -1   

  cover_page_last_q_end cover_page_end  num_cusip_b_items  signature_start  \
0                  None           None                  0               -1   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1                64                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [262]:
tt = clean_text(get_file_text_from_directory(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory))
tt

'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n Cm+1TFL23b6R4EPzbHVjBXWQoLYdU23POf1XYOtwSRfoEFFcDzxJk7yfez3wVCNE\n oQJoN4HWI3Fyo7z9jYcubQ==\n\n<SEC-DOCUMENT>0000884589-03-000021.txt : 20030218\n<SEC-HEADER>0000884589-03-000021.hdr.sgml : 20030217\n<ACCEPTANCE-DATETIME>20030218081028\nACCESSION NUMBER:\t\t0000884589-03-000021\nCONFORMED SUBMISSION TYPE:\tSC 13G\nPUBLIC DOCUMENT COUNT:\t\t1\nFILED AS OF DATE:\t\t20030218\n\nSUBJECT COMPANY:\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tLONE STAR STEAKHOUSE & SALOON INC\n\t\tCENTRAL INDEX KEY:\t\t\t0000883670\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tRETAIL-EATING PLACES [5812]\n\t\tIRS NUMBER:\t\t\t\t481109495\n\t\tSTATE OF INCORPORATION:\t\t\tDE\n\t\tFISCAL YEAR END:\t\t\t1231\n\n\tFILING 

In [263]:
soup = BeautifulSoup(tt, 'html5lib')
soup

<html><head></head><body>-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 Cm+1TFL23b6R4EPzbHVjBXWQoLYdU23POf1XYOtwSRfoEFFcDzxJk7yfez3wVCNE
 oQJoN4HWI3Fyo7z9jYcubQ==

<sec-document>0000884589-03-000021.txt : 20030218
<sec-header>0000884589-03-000021.hdr.sgml : 20030217
<acceptance-datetime>20030218081028
ACCESSION NUMBER:		0000884589-03-000021
CONFORMED SUBMISSION TYPE:	SC 13G
PUBLIC DOCUMENT COUNT:		1
FILED AS OF DATE:		20030218

SUBJECT COMPANY:	

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			LONE STAR STEAKHOUSE &amp; SALOON INC
		CENTRAL INDEX KEY:			0000883670
		STANDARD INDUSTRIAL CLASSIFICATION:	RETAIL-EATING PLACES [5812]
		IRS NUMBER:				481109495
		STATE OF INCORPORATION:			DE
		FISCAL YEAR END:			1231

	FILING VALUES:
		FORM TYPE:		SC 13G
		SEC ACT:	

In [281]:
soup.find('document').getText()

'\nSC 13G\n1\nstar.txt\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\n'

In [269]:
lst = soup.find('document').findAll()

tp = ''

for tag in lst:
    
    tp = tp + tag.get_text()

In [270]:
tp

'SC 13G\n1\nstar.txt\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\n1\nstar.txt\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\nstar.txt\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\n\n \n\n\n \n                                 UNITED STATES\n                       SECURITIES AND EXCHANGE COMMISSION\n                              Washington, D.C. 20549\n\n                                 SCHEDULE 13G\n\n\n                   Under the Securities Exchange Act of 1934\n                             (Amendment No. 0)*\n\n\n\n\n                    LONE STAR STEAKHOUSE AND SALOON  INC.   (star)\n                   -----------------------------------------\n                               (Name of Issuer)\n\n\n                               Common Stock\n                   -----------------------------------------\n                     (Title of Class of Securities)\n\n                                 542307103\n                 

In [278]:
soup.find('document').findAll()[6].get_text()

'\n                                 UNITED STATES\n                       SECURITIES AND EXCHANGE COMMISSION\n                              Washington, D.C. 20549\n\n                                 SCHEDULE 13G\n\n\n                   Under the Securities Exchange Act of 1934\n                             (Amendment No. 0)*\n\n\n\n\n                    LONE STAR STEAKHOUSE AND SALOON  INC.   (star)\n                   -----------------------------------------\n                               (Name of Issuer)\n\n\n                               Common Stock\n                   -----------------------------------------\n                     (Title of Class of Securities)\n\n                                 542307103\n                   -----------------------------------------\n                              (CUSIP Number)\n\n                              December 31, 2002\n                   -----------------------------------------\n            (Date of Event Which Requires Filing of th

In [257]:
i

1111700

In [258]:
get_index_url(indexes_df.loc[i, 'file_name'])

TypeError: get_index_url() takes 1 positional argument but 3 were given

In [259]:
get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

'\nSC 13G\n1\nstar.txt\n13G FOR LONESTAR STEAKHOUSE AND SALOON\n\n \n\n\n\n'

In [254]:
i = 1111661
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

KeyboardInterrupt: 

In [250]:
get_index_url('edgar/data/1134340/0001144204-07-030299.txt')

'https://www.sec.gov/Archives/edgar/data/1134340/000114420407030299/0001144204-07-030299-index.htm'

In [221]:
i = 622
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/904290/0001104659-04-010584.txt  0001104659-04-010584.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13D/A                        1853                 1908   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1853               28251   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                  21933           22341                  2               -1   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1             40148                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [222]:
get_index_url('edgar/data/904290/0001104659-04-010584.txt')

'https://www.sec.gov/Archives/edgar/data/904290/000110465904010584/0001104659-04-010584-index.htm'

In [220]:
i = 620
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1027162/0001277006-04-000005.txt  0001277006-04-000005.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                         338                   -1   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     1                -1                 341   

  cover_page_last_q_end cover_page_end  num_cusip_b_items  signature_start  \
0                  None           None                  1               -1   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1               870                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [239]:
soup.find(text = 'Signature').parent.parent.parent.parent

<div style="font-family:'Times New Roman';">

<p style="margin:0in 0in .0001pt;"><font face="Times New Roman" size="2" style="font-size:10.0pt;"> </font></p>

<table border="0" cellpadding="0" cellspacing="0" style="border-collapse:collapse;width:100.0%;" width="100%">
 <tbody><tr>
  <td style="padding:0in .7pt .7pt .7pt;width:20.0%;" valign="top" width="20%">
  <p align="center" style="font-size:1.0pt;margin:0in 0in .0001pt 10.0pt;text-align:center;text-indent:-10.0pt;"> </p>
  </td>
  <td style="padding:0in .7pt .7pt .7pt;width:60.0%;" valign="top" width="60%">
  <p align="center" style="margin:0in 0in .0001pt;text-align:center;"><b><font face="Times New Roman" size="5" style="font-size:18.0pt;font-weight:bold;">UNITED
  STATES</font></b></p>
  </td>
  <td style="padding:0in .7pt .7pt .7pt;width:20.08%;" valign="bottom" width="20%">
  <p style="font-size:1.0pt;margin:0in 0in .0001pt;"> </p>
  </td>
 </tr>
 <tr>
  <td style="padding:0in .7pt .7pt .7pt;width:20.0%;" valign="top" width=

In [229]:
url = 'https://www.sec.gov/Archives/edgar/data/760436/000110465904010584/0001104659-04-010584.txt'
page = requests.get(url)
soup = BeautifulSoup(page.text, 'html5lib')

In [230]:
print(soup.get_text())

-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 C8TNtwH6DCTkP4khMEBCcuLc6wHOTBUbJf1hlHTyBqC76/RqeDQqT2m2FOJ7gemn
 Uqbnf/h5vltgvetl5cexuw==

0001104659-04-010584.txt : 20040420
0001104659-04-010584.hdr.sgml : 20040420
20040420120555
ACCESSION NUMBER:		0001104659-04-010584
CONFORMED SUBMISSION TYPE:	SC 13D/A
PUBLIC DOCUMENT COUNT:		3
FILED AS OF DATE:		20040420

SUBJECT COMPANY:	

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			MAI SYSTEMS CORP
		CENTRAL INDEX KEY:			0000760436
		STANDARD INDUSTRIAL CLASSIFICATION:	SERVICES-COMPUTER INTEGRATED SYSTEMS DESIGN [7373]
		IRS NUMBER:				222554549
		STATE OF INCORPORATION:			DE
		FISCAL YEAR END:			1231

	FILING VALUES:
		FORM TYPE:		SC 13D/A
		SEC ACT:		1934 Act
		SEC FILE NUMBER:	005-38111
		FILM NUMBER:		04742194

	

In [233]:
print(soup.find('document').get_text())


SC 13D/A
1
a04-4614_1sc13da.htm
SC 13D/A













 


 
  
   
  
  
  UNITED
  STATES
  
  
   
  
 
 
  
   
  
  
  SECURITIES
  AND EXCHANGE
  COMMISSION
  
  
   
  
 
 
  
   
  
  
  Washington,
  D.C. 20549
  
  
   
  
 
 
  
   
  
  
   
  
  
   
  
 
 
  
   
  
  
  SCHEDULE
  13D
  
  
   
  
 


Under the Securities
Exchange Act of 1934 
(Amendment No. 6)*



MAI Systems Corporation



(Name
of Issuer)

 



Common Stock



(Title
of Class of Securities)

 



552620 20 5



(CUSIP
Number)

 



Richard R. Ressler, c/o W. Brian Kretzmer, c/o MAI
Systems Corporation, Enterprise Way, Lake Forest, CA  92630



(Name,
Address and Telephone Number of Person
Authorized to Receive Notices and Communications)

 



April 9, 2004



(Date
of Event which Requires Filing of this Statement)

If the filing person has
previously filed a statement on Schedule 13G to report the acquisition
that is the subject of this Schedule 13D, and is filing this
schedule because of §§240.13d-1

In [216]:
i = 616
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/766504/0001277006-04-000011.txt  0001277006-04-000011.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                         327                   -1   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     1                -1                 330   

  cover_page_last_q_end cover_page_end  num_cusip_b_items  signature_start  \
0                  None           None                  1               -1   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1               853                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [218]:
t[330:]

'Item 1\n(a) SAMEX Mining Corp.\n(b) 301-32920 Ventura Avenue\n    Abbotsford, BC\n    V2S 6J3\n    Canada\n\nItem 2\n(a) Sprott Asset Management Inc.\n(b) Suite 2700, South Tower\n    Royal Bank Plaza\n    P.O. Box 27\n    Toronto, Ontario  M5J 2J1\n    Canada\n(c) Canadian\n(d) Common Shares\n(e) 795912104\n\nItem 3\nn/a\n\nItem 4\n(a) n/a\n(b) n/a\n(c) (i) 4,100,000\n    (ii) 38,110\n    (iii) 4,100,000\n    (iv)  38,110\n\nItem 5\nn/a\n\nItem 6\nn/a\n\nItem 7\nn/a\n\nItem 8\nn/a\n\nItem 9\nn/a\n\nItem 11\nJune 7, 2004\nNeal Nenadovic\nChief Financial Officer\n\n\n'

In [ ]:
'edgar/data/766504/0001277006-04-000011.txt' # Interesting short form case

In [219]:
get_index_url('edgar/data/766504/0001277006-04-000011.txt')

'https://www.sec.gov/Archives/edgar/data/766504/000127700604000011/0001277006-04-000011-index.htm'

In [207]:
print(t[:1546])


SC 13G
1
edgrdc.txt
SC 13G


                             UNITED STATES
                  SECURITIES AND EXCHANGE COMMISSION
                        Washington, D.C. 20549


                             SCHEDULE 13G

               Under the Securities Exchange Act of 1934


                           (Amendment No. )*


                      Rowan Companies, Incorporated
                             (Name of Issuer)

                               Common Stock
                      (Title of Class of Securities)

                                779382100
                              (CUSIP Number)

                              April 30, 2004
         (Date of Event Which Requires Filing of this Statement)


heck the appropriate box to designate the rule pursuant to which this
chedule is filed:
X] Rule 13d-1(b)
 ] Rule 13d-1(c)
 ] Rule 13d-1(d)


The remainder of this cover page shall be filled out for a reporting
erson's initial filing on this form with respect to the subject class

In [206]:
print(t[4150:])



tem 1(a)     Name of Issuer:
       Rowan Companies, Incorporated

tem 1(b)     Address of Issuer's Principal Executive Offices:
       2800 Post Oak Boulevard, Suite 5450
       Houston, TX  77056-6127

tem 2(a)     Name of Person(s) Filing:
       Capital Research and Management Company and The Growth Fund of
       America, Inc.

tem 2(b)     Address of Principal Business Office or, if none,
       Residence:
       333 South Hope Street
       Los Angeles, CA  90071

tem 2(c)     Citizenship:   N/A

tem 2(d)     Title of Class of Securities:
       Common Stock

tem 2(e)     CUSIP Number:
       779382100

tem 3     If this statement is filed pursuant to sections 240.13d-1(b)
       or 240.13d-2(b) or (c), check whether the person filing is a:
       (d)     [X]     Investment company registered under section 8
            of the Investment Company Act of 1940 (15 U.S.C. 80a-8).
       (e)      [X]     An investment adviser in accordance with
            section 240.13d-1(b)(1)(i

In [184]:
print(t[6754:11827])

Bank		BK
Insurance Company		IC
Investment Company		IV
Investment Advisor		IA
Employee Benefit Plan, Pension Fund, or Endowment Fund		EP
Parent Holding Company		HC
Corporation		CO
Partnership		PN
Individual		IN
Other		OO
Notes:
Attach as many copies of the second part of the cover page as are needed, one reporting person per page.


Filing persons may, in order to avoid unnecessary duplication, answer items on the schedules (Schedule 13D, 13G, or 14D-1) by appropriate cross-references to an item or items on the cover page(s).  This approach may only be used where the cover page item or items provide all the disclosure required by the schedule item.  Moreover, such a use of a cover page item will result in the item becoming a part of the schedule and accordingly being considered as "filed" for purposes of Section 18 of the Securities Exchange Act or otherwise subject to the liabilities of that section of the Act.
Reporting persons may comply with their cover page filing requirements by f

In [182]:
print(t[11827:17436])






Security and Issuer
Common shares, without par value
Pine Valley Mining Corporation
Suite 501, 535 Thurlow Street
Vancouver, BC  V6E 3L2
("Pine Valley")
Identity and Background
Mark Smith is a United States citizen and a businessman with an address at 5090 Warwick Terrace, Pittsburgh, Pennsylvania, USA  15123.  Mr. Smith is the Chairman and a director of Pine Valley.
During the last five years, Mr. Smith has not been convicted in a criminal proceeding or been a party to any civil proceeding of a judicial or administrative body of competent jurisdiction as a result of which it was or is subject to a judgment, decree or final order enjoining future violations of, or prohibiting or mandating activities subject to, federal or state securities laws or finding of any violation with respect to such laws.
Source and Amount of Funds or Other Considerations
Mr. Smith originally acquired 10,083,537 common shares of Pine Valley through purchases in the open market.
On September 7, 2001, in co

In [252]:
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                             directory)

In [251]:
i

1111632

In [253]:
print(t)


SC 13G/A
1
v077071_sc13ga.htm


  
    


  
     
    UNITED
      STATES
    SECURITIES
      AND EXCHANGE COMMISSION
     WASHINGTON,
      D.C. 20549
     
    SCHEDULE
      13G
     
    UNDER
      THE SECURITIES EXCHANGE ACT OF 1934
    (AMENDMENT
      NO. 3)
     
    INCREDIMAIL
      LTD. 
    
      
    
    (Name
      of
      Issuer)
    
    ORDINARY
      SHARES, PAR VALUE NIS 0.01 PER SHARE
     
    (Title
      of
      Class of Securities)
    
    M5364E
      104
    
       (CUSIP
      Number)
     
    Check
      the
      appropriate box to designate the rule pursuant to which this
      Schedule
     
    is
      filed:
x Rule
      13d-1(c)
     
    *The
      remainder of this cover page shall be filled out for a reporting person's
      initial filing on this form with respect to the subject class of securities,
      and
      for any subsequent amendment containing information which would alter the
      disclosures provided in a prior cover page.

In [214]:
get_signatures_sec_start(t)

-1

In [215]:
def get_bounded_text(text, lower_bound = None, upper_bound = None):
    
    if(lower_bound is not None and lower_bound != -1):
        
        if(upper_bound is not None and upper_bound != -1):
            
            if(lower_bound >= upper_bound):
                
                raise ValueError("upper_bound not more than lower_bound")
                
            else:
                
                return(text[lower_bound:upper_bound])
            
        else:
            
            return(text[lower_bound:])
        
    else:
        
        if(upper_bound is not None and upper_bound != -1):
            
            return(text[:upper_bound])
        
        else:
            
            return(text)

In [ ]:
def get_signatures_sec_start(text, lower_bound = None, upper_bound = None):
    
    text_lowered = get_bounded_text(text, lower_bound, upper_bound).lower()
    
    regex1 = '\n\s*(signature|signatures)\s*(\.)?\n'
    
    regex2 = 'the\s+following\s+certification\s+shall\s+be\s+included\s+if\s+the\s+statement\s+is\s+filed\s+' + \
             'pursuant to rule 13d-1\(b\)'
    
    regex3 = 'by\s+signing\s+below\s+i\s+certify\s+that,\s+to\s+the\s+best\s+of\s+my\s+knowledge'

    regex4 = 'after\s+reasonable\s+inquiry\s+'
    
    regex_list = [regex1, regex2, regex3, regex4]
    
    regex_search = None
    
    for i in range(len(regex_list)):
        
        regex_search = re.search(regex_list[i], text_lowered)
        
        if(regex_search):
            
            break
        
    if(regex_search):
        
        if(lower_bound is not None):
        
            return(regex_search.start() + lower_bound)
        
        else:
            
            return(regex_search.start())
    
    else:
      
        return(-1)

In [198]:
i

140

In [199]:
get_item_section_start(t, indexes_df.loc[i, 'form_type'])

-1

In [193]:
find_cover_pages_last_question(t)

3827

In [173]:
print(t[6513:])

- Please classify each "reporting person" according to the following breakdown and place the appropriate symbol (or symbols, i.e., if more than one is applicable, insert all applicable symbols) on the form:
Category	Symbol
Broker-Dealer		BD
Bank		BK
Insurance Company		IC
Investment Company		IV
Investment Advisor		IA
Employee Benefit Plan, Pension Fund, or Endowment Fund		EP
Parent Holding Company		HC
Corporation		CO
Partnership		PN
Individual		IN
Other		OO
Notes:
Attach as many copies of the second part of the cover page as are needed, one reporting person per page.


Filing persons may, in order to avoid unnecessary duplication, answer items on the schedules (Schedule 13D, 13G, or 14D-1) by appropriate cross-references to an item or items on the cover page(s).  This approach may only be used where the cover page item or items provide all the disclosure required by the schedule item.  Moreover, such a use of a cover page item will result in the item becoming a part of the schedule and 

In [178]:
t[11827:]

'\n\n\n\n\nSecurity and Issuer\nCommon shares, without par value\nPine Valley Mining Corporation\nSuite 501, 535 Thurlow Street\nVancouver, BC  V6E 3L2\n("Pine Valley")\nIdentity and Background\nMark Smith is a United States citizen and a businessman with an address at 5090 Warwick Terrace, Pittsburgh, Pennsylvania, USA  15123.  Mr. Smith is the Chairman and a director of Pine Valley.\nDuring the last five years, Mr. Smith has not been convicted in a criminal proceeding or been a party to any civil proceeding of a judicial or administrative body of competent jurisdiction as a result of which it was or is subject to a judgment, decree or final order enjoining future violations of, or prohibiting or mandating activities subject to, federal or state securities laws or finding of any violation with respect to such laws.\nSource and Amount of Funds or Other Considerations\nMr. Smith originally acquired 10,083,537 common shares of Pine Valley through purchases in the open market.\nOn Septemb

In [162]:
get_index_url('edgar/data/749750/0001183740-04-000029.txt')

'https://www.sec.gov/Archives/edgar/data/749750/000118374004000029/0001183740-04-000029-index.htm'

In [133]:
indexes_df.loc[indexes_df['has_jumbled_order'] == True]

file_name  \
140      edgar/data/1133256/0001193125-04-099611.txt   
180        edgar/data/80255/0000080255-04-000418.txt   
241      edgar/data/1295249/0001144204-04-008961.txt   
264       edgar/data/788920/0000892569-04-000701.txt   
271        edgar/data/80255/0000080255-04-000421.txt   
288      edgar/data/1110781/0001015402-04-002061.txt   
350       edgar/data/355948/0000080255-04-000418.txt   
448      edgar/data/1241883/0001015402-04-001741.txt   
457       edgar/data/887921/0000898822-04-000275.txt   
594      edgar/data/1277154/0001028212-04-000033.txt   
702      edgar/data/1286062/0001062993-04-001028.txt   
703      edgar/data/1054217/0000950134-04-006686.txt   
770       edgar/data/915477/0000950144-04-003737.txt   
804      edgar/data/1287745/0000950136-04-001877.txt   
1008     edgar/data/1287833/0000950136-04-001876.txt   
1010     edgar/data/1287833/0000950136-04-001875.txt   
1012     edgar/data/1055565/0000906280-04-000174.txt   
1156      edgar/data/924355/0000924355-04-000136.txt   
1169     edgar/data/1055565/0000906280-04-000220.txt   
1451      edgar/data/353569/0000080255-04-000320.txt   
1454     edgar/data/1061096/0000897069-04-000396.txt   
1543     edgar/data/1081290/0000891618-04-000045.txt   
1644     edgar/data/1013467/0000080255-04-000277.txt   
1975      edgar/data/355948/0000080255-04-000164.txt   
2166     edgar/data/1046102/0000945234-04-000084.txt   
2234     edgar/data/1076352/0001193125-04-018161.txt   
2271     edgar/data/1182836/0000950134-04-000754.txt   
2503      edgar/data/869561/0000891020-04-000221.txt   
2565     edgar/data/1160543/0000950152-04-002193.txt   
2869     edgar/data/1179638/0000950144-04-001312.txt   
...                                              ...   
1110837  edgar/data/1019849/0000950124-06-005259.txt   
1110967   edgar/data/863650/0001193125-07-031184.txt   
1111123   edgar/data/812906/0000080255-00-000414.txt   
1111134   edgar/data/812906/0000080255-07-000057.txt   
1111223  edgar/data/1015483/0001085146-07-000101.txt   
1111229   edgar/data/934637/0000934637-01-000013.txt   
1111283  edgar/data/1157995/0001161532-02-000027.txt   
1111296  edgar/data/1040272/0000929638-10-000159.txt   
1111305  edgar/data/1283709/0001085146-07-000250.txt   
1111363  edgar/data/1377630/0000072971-10-000325.txt   
1111460   edgar/data/215219/0001085146-07-000116.txt   
1111566  edgar/data/1420529/0000950123-10-011866.txt   
1111567   edgar/data/924168/0000950152-04-002221.txt   
1111607    edgar/data/72971/0000072971-10-000085.txt   
1111608    edgar/data/72971/0000072971-10-000443.txt   
1111696  edgar/data/1138234/0000891020-02-000128.txt   
1111741   edgar/data/822370/0001144204-10-020809.txt   
1111792   edgar/data/911002/0000072971-09-001017.txt   
1111843  edgar/data/1174550/0001075793-03-000111.txt   
1111953  edgar/data/1260321/0001019056-03-000831.txt   
1111985  edgar/data/1139650/0000891618-03-006287.txt   
1111991  edgar/data/1267351/0001108017-03-000731.txt   
1112051   edgar/data/356028/0001193125-12-125677.txt   
1112102  edgar/data/1278059/0001144204-11-042439.txt   
1112130  edgar/data/1389818/0000950123-10-003117.txt   
1112157  edgar/data/1414636/0001387131-11-001875.txt   
1112234  edgar/data/1045986/0001144204-12-004920.txt   
1112430  edgar/data/1371489/0000072971-10-001030.txt   
1112466    edgar/data/72971/0000072971-10-000212.txt   
1112481   edgar/data/905448/0000950123-10-088156.txt   

                         document form_type  title_page_end_lower_bound  \
140      0001193125-04-099611.txt    SC 13D                       21016   
180      0000080255-04-000418.txt  SC 13G/A                        1691   
241      0001144204-04-008961.txt    SC 13D                        2081   
264      0000892569-04-000701.txt  SC 13D/A                        1641   
271      0000080255-04-000421.txt  SC 13G/A                        1710   
288      0001015402-04-002061.txt  SC 13D/A                        2194   
350      0000080255-04-000418.txt  SC 13G/A  

In [155]:
indexes_df.loc[indexes_df['has_table_of_contents'] == True]

file_name  \
116        edgar/data/26820/0000936392-04-000577.txt   
255      edgar/data/1290035/0000936392-04-000577.txt   
264       edgar/data/788920/0000892569-04-000701.txt   
300       edgar/data/906551/0000950153-04-001523.txt   
361      edgar/data/1284472/0000919567-04-000043.txt   
459      edgar/data/1081290/0000950134-04-006085.txt   
479      edgar/data/1080731/0000919567-04-000042.txt   
487       edgar/data/919567/0000919567-04-000041.txt   
703      edgar/data/1054217/0000950134-04-006686.txt   
727        edgar/data/86115/0000893220-04-001132.txt   
770       edgar/data/915477/0000950144-04-003737.txt   
841       edgar/data/865477/0000950133-04-001277.txt   
1495     edgar/data/1198560/0000950152-04-001109.txt   
1498     edgar/data/1198560/0000950152-04-001111.txt   
1543     edgar/data/1081290/0000891618-04-000045.txt   
1807      edgar/data/702513/0000950149-04-000276.txt   
2103      edgar/data/933210/0000950134-04-001815.txt   
2166     edgar/data/1046102/0000945234-04-000084.txt   
2271     edgar/data/1182836/0000950134-04-000754.txt   
2535      edgar/data/906326/0000936392-04-000119.txt   
2565     edgar/data/1160543/0000950152-04-002193.txt   
2604     edgar/data/1160543/0000950152-04-001103.txt   
2606     edgar/data/1160545/0000950152-04-001101.txt   
2880     edgar/data/1106835/0000936392-04-000053.txt   
2883     edgar/data/1082423/0000936392-04-000053.txt   
2939     edgar/data/1084332/0000936392-04-000026.txt   
2988       edgar/data/86115/0000893220-04-000195.txt   
2994     edgar/data/1022926/0000950152-04-000808.txt   
3018     edgar/data/1272270/0000950149-04-000398.txt   
3040     edgar/data/1284465/0001156973-04-000345.txt   
...                                              ...   
1105922  edgar/data/1451928/0000950123-10-092065.txt   
1105982  edgar/data/1470423/0000950123-11-012934.txt   
1106001  edgar/data/1376067/0000950123-10-109198.txt   
1106032  edgar/data/1401678/0000950123-10-112079.txt   
1106122   edgar/data/101830/0000903423-98-000405.txt   
1106183   edgar/data/842180/0000950123-11-012187.txt   
1106389  edgar/data/1557978/0000913849-18-000193.txt   
1106689  edgar/data/1720339/0001144204-17-053591.txt   
1106927   edgar/data/849145/0001144204-11-017147.txt   
1107492   edgar/data/900371/0000950123-11-031544.txt   
1108735  edgar/data/1449258/0000890163-11-000009.txt   
1109157  edgar/data/1092601/0001213900-19-003225.txt   
1110731  edgar/data/1317728/0000950123-10-025424.txt   
1110837  edgar/data/1019849/0000950124-06-005259.txt   
1111110   edgar/data/904913/0000950152-07-000930.txt   
1111162   edgar/data/828747/0000950134-07-012665.txt   
1111252   edgar/data/949341/0000950152-07-000906.txt   
1111292  edgar/data/1134226/0000950123-10-013288.txt   
1111375    edgar/data/69970/0000950152-07-001440.txt   
1111558  edgar/data/1065865/0000950134-03-012627.txt   
1111566  edgar/data/1420529/0000950123-10-011866.txt   
1111567   edgar/data/924168/0000950152-04-002221.txt   
1111985  edgar/data/1139650/0000891618-03-006287.txt   
1111991  edgar/data/1267351/0001108017-03-000731.txt   
1112130  edgar/data/1389818/0000950123-10-003117.txt   
1112240   edgar/data/935761/0000950123-10-003018.txt   
1112243  edgar/data/1317728/0000950123-11-104610.txt   
1112307  edgar/data/1012477/0000950005-00-000554.txt   
1112334  edgar/data/1065191/0001019056-01-500228.txt   
1112481   edgar/data/905448/0000950123-10-088156.txt   

                         document form_type  title_page_end_lower_bound  \
116      0000936392-04-000577.txt  SC 13G/A                        1346   
255      0000936392-04-000577.txt  SC 13G/A                        1346   
264      0000892569-04-000701.txt  SC 13D/A                        1641   
300      0000950153-04-001523.txt    SC 13D                        1779   
361      0000919567-04-000043.txt    SC 13D                        2802   
459      0000950134-04-006085.txt  SC 13D/A                        1819   
479      0000919567-04-000042.txt    SC 13D  

In [156]:
get_index_url('edgar/data/788920/0000892569-04-000701.txt')

'https://www.sec.gov/Archives/edgar/data/788920/000089256904000701/0000892569-04-000701-index.htm'

In [159]:
def find_cover_pages_last_question(text, rep_q_as_items = None,  lower_bound = None, upper_bound = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text)
    
    if(lower_bound is not None and lower_bound > 0):
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[lower_bound:upper_bound]
            
        else:
            
            text_raised = text.upper()[lower_bound:]
            
    else:
        
        if(upper_bound is not None and upper_bound > 0):
            
            text_raised = text.upper()[:upper_bound]
            
        else:
            
            text_raised = text.upper() 
    
    if(rep_q_as_items):
        
        regex = '\n\s*ITEM\s*[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?'
        
        search = re.search(regex, text_raised)
        
    else:
    
        regex0 = '\n\s*[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?[\*]?\s*(\(SEE\s+INSTRUCTIONS\))?'
        regex1 = '\n\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?[\*]?\s*(\(SEE\s+INSTRUCTIONS\))?[\(\|]?\s*1[24]\s*[\)\|]?\s*[\:\.]?\s'
        
        regex_list = [regex0, regex1]
        
        for pat in regex_list:
        
            search = re.search(pat, text_raised)
        
            if(search is not None):
            
                regex = pat
                break

    if(search is None):
        return(None)
    
    end = 0

    while(search is not None):
        
        end = end + search.end()
        search = re.search(regex, text_raised[end:])

    if(lower_bound is not None and lower_bound > 0):
        
        end = end + lower_bound
        
    return(end)       

In [195]:
def get_item_section_start(text, form_type):    
    
    
    if(re.search('SC\s+13D', form_type)):
        
        re_list = ['\n\s*[item]*\s*([#\.\;\:]?\s*1[#\.\;\:]?)?\s*security\s+and\s+issuer',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?)?\s*identity\s+and\s+background',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*3[#\.\;\:]?)?\s*source\s+and\s+amount\s+of\s+funds',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*4[#\.\;\:]?)?\s*purpose\s+of\s+transaction',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*5[#\.\;\:]?)?\s*interest\s+in\s+securities\s+of\s+the\s+issuer',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*6[#\.\;\:]?)?\s*contracts,\s+arrangements,\s+understandings',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*7[#\.\;\:]?)?\s*material\s+to\s+be\s+filed\s+as\s+exhibits'
                  ]
                       
        
    elif(re.search('SC\s+13G', form_type)):
        
        re_list = ['\n\s*[item]*\s*([#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*a[\)]?)?[#\.\;\:]?\s*name\s+of\s+issuer',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*1[#\.\;\:]?[\(]?\s*b[\)]?)?[#\.\;\:]?\s*address\s+of\s+issuer',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*a[\)]?)?[#\.\;\:]?\s*name[s]?\s+of\s+person[s]?\s+filing',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*b[\)]?)?[#\.\;\:]?\s*address\s+of\s+principle',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*c[\)]?)?[#\.\;\:]?\s*citizenship',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*d[\)]?)?[#\.\;\:]?\s*title\s+of\s+class',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*2[#\.\;\:]?[\(]?\s*e[\)]?)?[#\.\;\:]?\s*cusip\s+number',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*3[#\.\;\:]?)?\s*if\s+this\s+statement\s+is\s+filed\s+pursuant',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*4[#\.\;\:]?)?\s*ownership',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*5[#\.\;\:]?)?\s*ownership\s+of\s+five',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*6[#\.\;\:]?)?\s*ownership\s+of\s+more',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*7[#\.\;\:]?)?\s*identification\s+and\s+classification',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*8[#\.\;\:]?)?\s*identification\s+and\s+classification',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*9[#\.\;\:]?)?\s*notice\s+of\s+dissolution',
                   '\n\s*[item]*\s*([#\.\;\:]?\s*10[#\.\;\:]?)?\s*certification'
                  ]
        
    else:
        
        # Not a Schedule 13D(/A) or 13G(/A)
        return(None)
   
    cover_pages_end = find_cover_pages_last_question(text)
    
    if(cover_pages_end):

        text_lowered = text[cover_pages_end:].lower()

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*(?:[0-9])[#\.\;\:]?', text_lowered)
        
        if(search):
            
            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(cover_pages_end + search.start() + num_to_item)  
        
        else:
            result = -1 # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    result = cover_pages_end + search.start()
                    break
            
            
            return(result)     
    
    else:
        
        text_lowered = text.lower() # Assume NO REPORTING PAGES (this happens, especially with 13D/A and 13G/A)

        search = re.search('\n\s*item\s*[#\.\;\:]?\s*[0-9][#\.\;\:]?', text_lowered)

        if(search):

            search_str = search.group(0)
            
            num_to_item = re.search('item', search_str).start()

            return(search.start() + num_to_item)  
        
        else: 
             
            result = -1 # ie. assume no Item section (this probably happens with 13D/A and 13G/A) if no matches in
                          # re_list
                
            for i in range(len(re_list)):
                
                search = re.search(re_list[i], text_lowered)
                
                if(search):
                    
                    result = search.start()
                    break
            
            
            return(result)     

In [3314]:
i = 140
t = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)
t

'\nSC 13D\n1\ndsc13d.htm\nSCHEDULE 13D\n\n\nSchedule 13D\n\n \n\n SECURITIES AND EXCHANGE COMMISSION  Washington, D.C. 20549  \xa0 \xa0\nSCHEDULE 13D  \xa0 \xa0 Under The Securities Exchange Act of 1934  \xa0 \xa0 \xa0 \xa0 ANALEX CORPORATION  (Name of Issuer)  \xa0 \xa0 Common Stock, par value $0.02 per share  (Title of Class of Securities)  \xa0 \xa0 032653107  (CUSIP Number of Class of Securities)  \xa0 Sterling E. Phillips, Jr.  c/o Analex Corporation  5904 Richmond Highway, Suite 300  Alexandria, VA 22303  (703) 329-9400  \xa0 Copy To:  Jane K. P. Tam  2099 Pennsylvania Avenue, N.W.  Suite 100  Washington, D.C. 20006  (202) 457-7114  (Name, Address and\nTelephone Number of Person Authorized to Receive Notices and Communications)  \xa0 \xa0 May 28, 2004  (Date of Event which\nRequires Filing of this Statement)  \xa0 If the filing person has previously\nfiled a statement on Schedule 13G to report the acquisition that is the subject of this Schedule 13D, and is filing this schedule b

In [201]:
i = 140
get_key_indices(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], \
                indexes_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1133256/0001193125-04-099611.txt  0001193125-04-099611.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                       21016                 1015   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     1              1015               21026   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                  19447           21013                  1            50888   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1             51684                           -1   

   has_jumbled_order  has_exhibit_break  
0               True              False

In [140]:
q1_starts = find_all_orthodox_q1_starts(t, -1)
q1_starts

[1015, 3572, 5972, 8466, 10868, 13452, 16029, 18424, 23402, 24863]

In [153]:
j = 7
print(t[q1_starts[j]:q1_starts[j+1]])

 

















  1.
 
 Name of Reporting Person I.R.S. Identification No. of above person   DRG Irrevocable Trust
 
 



  2.
 
 Check the Appropriate Box if a Member of a Group (a)  x (b)  •
 
 



  3.
 
 SEC Use Only  
 
 



  4.
 
 Source of Funds   PF
 
 



  5.
 
 Check Box if Disclosure of Legal Proceedings Is Required Pursuant to Items 2(d) Or 2(e)  
 
•



  6.
 
 Citizenship or Place of Organization   United States of America
 
 










 NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH
 
   7.    Sole Voting Power           700,000 (1)   8.    Shared Voting Power           0(2)   9.    Sole Dispositive Power           700,000 (1) 10.    Shared Dispositive Power             0












11.
 
 Aggregate Amount Beneficially Owned by Each Reporting Person  
700,000 (1) (2)
 
 



12.
 
 Check Box if the Aggregate Amount in Row (11) Excludes Certain Shares  
 
 •  



13.
 
 Percent of Class Represented by Amount in Row (11)   4.6%(3)
 
 



14.
 
 Type

In [147]:
form_type = 'SC 13D'
for i in range(len(q1_starts)):

        if(i == 0):

            segment = get_bounded_text(t, 0, q1_starts[i])

        else:

            segment = get_bounded_text(t, q1_starts[i-1], q1_starts[i])

        has_items = (get_item_section_start(segment, form_type) != -1)
        has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

In [148]:
result

True

In [149]:
i

8

In [ ]:
def has_jumbled_order(text, form_type, exhibit_start):
    
    # This function is defined to be true if there are item sections or signature sections in the parts of the
    # text which are before the last instance of an orthodox q1 of a cover page (hence "jumbled")
    # this can include cases where for instance, an order goes cover_page -> items -> signatures -> 
    # cover_page -> items -> signatures 
    
    result = False # Assume false till proven otherwise
    
    q1_starts = find_all_orthodox_q1_starts(text, exhibit_start)

    for i in range(len(q1_starts)):

        if(i == 0):

            segment = get_bounded_text(text, 0, q1_starts[i])

        else:

            segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

        has_items = (get_item_section_start(segment, form_type) != -1)
        has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

    return(result)         

In [135]:
get_index_url('edgar/data/1389818/0000950123-10-003117.txt')

'https://www.sec.gov/Archives/edgar/data/1389818/000095012310003117/0000950123-10-003117-index.htm'

In [115]:
def get_title_page_end_upper_bound(text, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        rep_q_as_items = is_rep_q_as_items(text)

    text_raised = text.upper()

    if(rep_q_as_items):

        end = re.search('ITEM\s*[#\.\:]?\s*[\(]?\s*1[24]\s*[\)]?[\.\:]?', text_raised).start()

        regex = 'ITEM\s*[#\.\:]?\s*[\(]?\s*1\s*[\)]?[\.\:]?'

        search = re.search(regex, text_raised[:end])
        
        if(search):
            return(search.start())
        else:
            return(None)

    else:

        regex = '[\(]?\s*1\s*[\)]?\s*[:\.]{0,1}\s*NAME[S]?\s+(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?' + \
                '(\s*/\s*)?(S\.S\.\s+)?(\s+(?:OR|AND))\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[S]?\.\s+' + \
                '(OF\s+(?:REPORTING|ABOVE)\s+PERSON[S]?)?'     

        search = re.search(regex, text_raised)

        if(search):

            return(search.start())

        else:
            regex = '(?<!DESCRIBED\sIN)\s*ITEM\s*[#\.\:]?\s*[\(]?\s*[0-9]{1,2}\s*' + \
                    '[\)]?[\.\:]?'
            search = re.search(regex, text_raised)
            
            if(search):

                return(search.start())
            
            else:
                
                return(None)

In [119]:
get_index_url('edgar/data/723924/0001178952-04-000006.txt')

'https://www.sec.gov/Archives/edgar/data/723924/000117895204000006/0001178952-04-000006-index.htm'

In [92]:
get_index_url('edgar/data/904290/0001104659-04-010584.txt')

'https://www.sec.gov/Archives/edgar/data/904290/000110465904010584/0001104659-04-010584-index.htm'

In [168]:
get_key_indices('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                'SC 13D', directory)

file_name                  document  \
0  edgar/data/1483338/0001354488-10-000458.txt  0001354488-10-000458.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13D                        1689                 1946   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1857                3601   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   3279            3294                  3            12721   

   exhibit_start  main_text_length  explanatory_statement_start  \
0          13137             13393                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [15]:
directory = '/media/igow/6TB/data/edgar'

In [14]:
get_index_url('edgar/data/893739/0000893739-19-000012.txt')

'https://www.sec.gov/Archives/edgar/data/893739/000089373919000012/0000893739-19-000012-index.htm'

In [ ]:
def get_main_doc_text(file_name, document, directory):
  
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    soup = BeautifulSoup(full_text, 'html5lib')
    main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
    
    return(main_doc_text)

In [60]:
def get_main_doc_text(file_name, document, directory):
     
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    
    try:
        soup = BeautifulSoup(full_text, 'html5lib')
        main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
        
    except:
        
        try:
            soup = BeautifulSoup(full_text, 'lxml')
            main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
            
        except:
            
            soup = BeautifulSoup(full_text, 'html.parser')
            main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
    
    return(main_doc_text)

In [61]:
get_main_doc_text('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory)

"\nSC 13D\n1\nsc13d_72052.htm\nFORM SC 13D\n\nsc13d_72052.htm\n\n\n\n\n\n\n\nUNITED\nSTATES\nSECURITIES\nAND EXCHANGE COMMISSION\nWashington,\nD.C. 20549\n\n\nSCHEDULE\n13D\nUnder\nthe Securities Exchange Act of 1934\n(Amendment\nNo.  )\n\nHawk\nSystems, Inc.\n(Name\nof Issuer)\n\nCommon\nStock\n(Title\nof Class of Securities)\n\n42013J\n204\n(CUSIP\nNumber)\n\n\nDavid\nCoriaty\nc/o\nHawk Systems, Inc.\n2385\nNW Executive Center Drive, Suite 100\nBoca\nRaton, FL 33431\n(561)\n962-2885\n__________________________________\n(Name,\nAddress and Telephone Number of Person\nAuthorized\nto Receive Notices and Communications)\n\n\nFebruary\n19, 2009\n(Date of\nEvent which Requires Filing of this Statement)\n\n\nIf the\nfiling person has previously filed a statement on Schedule 13G to report the\nacquisition that is the subject of this Schedule 13D, and is filing this\nschedule because of §§  240.13d-1(e), 240.13d-1(f) or 240.13d-1(g), check\nthe following box. o\n\n\nNOTE:  Schedules\nfiled in

In [18]:
print(get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory))

-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC
 kVbsGjp5eapMmVYMi/BL3w==

<SEC-DOCUMENT>0001354488-10-000458.txt : 20100217
<SEC-HEADER>0001354488-10-000458.hdr.sgml : 20100217
<ACCEPTANCE-DATETIME>20100217114703
ACCESSION NUMBER:		0001354488-10-000458
CONFORMED SUBMISSION TYPE:	SC 13D
PUBLIC DOCUMENT COUNT:		2
FILED AS OF DATE:		20100217
DATE AS OF CHANGE:		20100217

FILED BY:		

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			Coriaty David
		CENTRAL INDEX KEY:			0001483338

	FILING VALUES:
		FORM TYPE:		SC 13D

	MAIL ADDRESS:	
		STREET 1:		2385 NW EXECUTIVE CENTER DRIVE
		STREET 2:		SUITE 100
		CITY:			BOCA RATON
		STATE:			FL
		ZIP:			33431

SUBJECT COMPANY:	

	COMPANY DATA:	
		COMPANY CONFORM

In [19]:
soup = BeautifulSoup(get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory), 'html5lib')

In [36]:
soup_alt = BeautifulSoup(clean_text(get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory)), 'lxml')

In [39]:
soup_alt2 = BeautifulSoup(clean_text(get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory)), 'html.parser')

In [20]:
soup

<html><head></head><body bgcolor="#ffffff" style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt">-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC
 kVbsGjp5eapMmVYMi/BL3w==

<sec-document>0001354488-10-000458.txt : 20100217
<sec-header>0001354488-10-000458.hdr.sgml : 20100217
<acceptance-datetime>20100217114703
ACCESSION NUMBER:		0001354488-10-000458
CONFORMED SUBMISSION TYPE:	SC 13D
PUBLIC DOCUMENT COUNT:		2
FILED AS OF DATE:		20100217
DATE AS OF CHANGE:		20100217

FILED BY:		

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			Coriaty David
		CENTRAL INDEX KEY:			0001483338

	FILING VALUES:
		FORM TYPE:		SC 13D

	MAIL ADDRESS:	
		STREET 1:		2385 NW EXECUTIVE CENTER DRIVE
		STREET 2:	

In [38]:
soup.find('document')

In [37]:
soup_alt.find('document')

<document>
<type>SC 13D
<sequence>1
<filename>sc13d_72052.htm
<description>FORM SC 13D
<text>
<title>sc13d_72052.htm</title>
<!-- Licensed to: issuer201-->
<!-- Document Created using EDGARizerAgent 5.1.5.0 -->
<!-- Copyright 1995 - 2009 Thomson Reuters. All rights reserved. -->
<div>
<hr noshade="" size="4" style="MARGIN-TOP: -5px; COLOR: #000000"/>
<hr noshade="" size="1" style="MARGIN-TOP: -10px; COLOR: #000000"/>
</div>
<div align="center" style="TEXT-INDENT: 0pt; DISPLAY: block; MARGIN-LEFT: 0pt; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt; FONT-WEIGHT: bold">UNITED
STATES</font></div>
<div align="center" style="TEXT-INDENT: 0pt; DISPLAY: block; MARGIN-LEFT: 0pt; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt; FONT-WEIGHT: bold">SECURITIES
AND EXCHANGE COMMISSION</font></div>
<div align="center" style="TEXT-INDENT: 0pt; DISPLAY: block; MARGIN-LEFT: 0pt; MARGIN-RIGHT: 0pt"><font style

In [40]:
soup_alt2.find('document')

<document>
<type>SC 13D
<sequence>1
<filename>sc13d_72052.htm
<description>FORM SC 13D
<text>
<html>
<head>
<title>sc13d_72052.htm</title>
<!-- Licensed to: issuer201-->
<!-- Document Created using EDGARizerAgent 5.1.5.0 -->
<!-- Copyright 1995 - 2009 Thomson Reuters. All rights reserved. -->
</head>
<body bgcolor="#ffffff" style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt">
<div>
<hr noshade="" size="4" style="MARGIN-TOP: -5px; COLOR: #000000"/>
<hr noshade="" size="1" style="MARGIN-TOP: -10px; COLOR: #000000"/>
</div>
<div align="center" style="TEXT-INDENT: 0pt; DISPLAY: block; MARGIN-LEFT: 0pt; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt; FONT-WEIGHT: bold">UNITED
STATES</font></div>
<div align="center" style="TEXT-INDENT: 0pt; DISPLAY: block; MARGIN-LEFT: 0pt; MARGIN-RIGHT: 0pt"><font style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt; FONT-WEIGHT: bold">SECURITIES
AND EXCHANGE COMMISSION</fon

In [22]:
t = clean_text(get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory))

In [25]:
re.search('<DOCUMENT>', t)

<re.Match object; span=(1765, 1775), match='<DOCUMENT>'>

In [26]:
re.search('</DOCUMENT>', t)

<re.Match object; span=(75512, 75523), match='</DOCUMENT>'>

In [28]:
u = get_file_text_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt',\
                             directory)

In [29]:
re.search('</DOCUMENT>', u)

<re.Match object; span=(76382, 76393), match='</DOCUMENT>'>

In [32]:
print(soup.prettify())

<html>
 <head>
 </head>
 <body bgcolor="#ffffff" style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt">
  -----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC
 kVbsGjp5eapMmVYMi/BL3w==
  <sec-document>
   0001354488-10-000458.txt : 20100217
   <sec-header>
    0001354488-10-000458.hdr.sgml : 20100217
    <acceptance-datetime>
     20100217114703
ACCESSION NUMBER:		0001354488-10-000458
CONFORMED SUBMISSION TYPE:	SC 13D
PUBLIC DOCUMENT COUNT:		2
FILED AS OF DATE:		20100217
DATE AS OF CHANGE:		20100217

FILED BY:		

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			Coriaty David
		CENTRAL INDEX KEY:			0001483338

	FILING VALUES:
		FORM TYPE:		SC 13D

	MAIL ADDRESS:	
		STREET 1:		2385 NW EXE

In [ ]:
def get_file_text_from_directory(file_name, document, directory):
    
    path = directory + '/' + get_file_path(file_name, document)
    f = open(path, 'r')
    txt = f.read()
    f.close()
    return(txt)
    

def fix_unmatched_page_tags(text):
    
    # First fix missing right dels
    
    start_tag_r_regex = '<PAGE[^>]' 
    end_tag_r_regex = '</PAGE[^>]'
    
    corrected_r_start = '<PAGE>\n' # Introduce newline in case newline replace by right del
    corrected_r_end = '</PAGE>\n'
    
    fixed_content = re.sub(start_tag_r_regex, corrected_r_start, text)
    fixed_content = re.sub(end_tag_r_regex, corrected_r_end, fixed_content)
    
    # Now fix missing left dels
    
    start_tag_l_regex = '[^<]PAGE>' 
    end_tag_l_regex = '[^<]/PAGE>'
    
    corrected_l_start = '\n<PAGE>' # Introduce newline in case newline replace by left del
    corrected_l_end = '\n</PAGE>'
    
    fixed_content = re.sub(start_tag_l_regex, corrected_l_start, fixed_content)
    fixed_content = re.sub(end_tag_l_regex, corrected_l_end, fixed_content)
    
    return(fixed_content)


def clean_text(text):
    
    # this function gets rid of unwanted characters and spaces
    
    result = fix_unmatched_page_tags(text) # First fix tags which are missing delimeters
    
    char_list = ['\xa0', '&#160;', '&#\n160;']
    
    for c in char_list:
        
        result = re.sub(c, ' ', result) 
        
    return(result)

In [41]:
def get_file_content_from_directory(file_name, document, directory):
    
    path = directory + '/' + get_file_path(file_name, document)
    f = open(path, 'rb')
    txt = f.read()
    f.close()
    return(txt)

In [43]:
test = get_file_content_from_directory('edgar/data/1483338/0001354488-10-000458.txt', '0001354488-10-000458.txt', directory)

In [44]:
test

b'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC\n kVbsGjp5eapMmVYMi/BL3w==\n\n<SEC-DOCUMENT>0001354488-10-000458.txt : 20100217\n<SEC-HEADER>0001354488-10-000458.hdr.sgml : 20100217\n<ACCEPTANCE-DATETIME>20100217114703\nACCESSION NUMBER:\t\t0001354488-10-000458\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20100217\nDATE AS OF CHANGE:\t\t20100217\n\nFILED BY:\t\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tCoriaty David\n\t\tCENTRAL INDEX KEY:\t\t\t0001483338\n\n\tFILING VALUES:\n\t\tFORM TYPE:\t\tSC 13D\n\n\tMAIL ADDRESS:\t\n\t\tSTREET 1:\t\t2385 NW EXECUTIVE CENTER DRIVE\n\t\tSTREET 2:\t\tSUITE 100\n\t\tCITY:\t\t\tBOCA RATON\n\t\tS

In [45]:
fix_unmatched_page_tags(test)

TypeError: cannot use a string pattern on a bytes-like object

In [46]:
def fix_unmatched_page_tags_alt(text):
    
    # First fix missing right dels
    
    start_tag_r_regex = b'<PAGE[^>]' 
    end_tag_r_regex = b'</PAGE[^>]'
    
    corrected_r_start = b'<PAGE>\n' # Introduce newline in case newline replace by right del
    corrected_r_end = b'</PAGE>\n'
    
    fixed_content = re.sub(start_tag_r_regex, corrected_r_start, text)
    fixed_content = re.sub(end_tag_r_regex, corrected_r_end, fixed_content)
    
    # Now fix missing left dels
    
    start_tag_l_regex = b'[^<]PAGE>' 
    end_tag_l_regex = b'[^<]/PAGE>'
    
    corrected_l_start = b'\n<PAGE>' # Introduce newline in case newline replace by left del
    corrected_l_end = b'\n</PAGE>'
    
    fixed_content = re.sub(start_tag_l_regex, corrected_l_start, fixed_content)
    fixed_content = re.sub(end_tag_l_regex, corrected_l_end, fixed_content)
    
    return(fixed_content)

In [48]:
fix_unmatched_page_tags_alt(test)

b'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC\n kVbsGjp5eapMmVYMi/BL3w==\n\n<SEC-DOCUMENT>0001354488-10-000458.txt : 20100217\n<SEC-HEADER>0001354488-10-000458.hdr.sgml : 20100217\n<ACCEPTANCE-DATETIME>20100217114703\nACCESSION NUMBER:\t\t0001354488-10-000458\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20100217\nDATE AS OF CHANGE:\t\t20100217\n\nFILED BY:\t\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tCoriaty David\n\t\tCENTRAL INDEX KEY:\t\t\t0001483338\n\n\tFILING VALUES:\n\t\tFORM TYPE:\t\tSC 13D\n\n\tMAIL ADDRESS:\t\n\t\tSTREET 1:\t\t2385 NW EXECUTIVE CENTER DRIVE\n\t\tSTREET 2:\t\tSUITE 100\n\t\tCITY:\t\t\tBOCA RATON\n\t\tS

In [52]:
def clean_text_alt(text):
    
    # this function gets rid of unwanted characters and spaces
    
    result = fix_unmatched_page_tags_alt(text) # First fix tags which are missing delimeters
    
    char_list = [b'\xa0', b'&#160;', b'&#\n160;']
    
    for c in char_list:
        
        result = re.sub(c, b' ', result) 
        
    return(result)

In [53]:
clean_text_alt(test)

b'-----BEGIN PRIVACY-ENHANCED MESSAGE-----\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC\n kVbsGjp5eapMmVYMi/BL3w==\n\n<SEC-DOCUMENT>0001354488-10-000458.txt : 20100217\n<SEC-HEADER>0001354488-10-000458.hdr.sgml : 20100217\n<ACCEPTANCE-DATETIME>20100217114703\nACCESSION NUMBER:\t\t0001354488-10-000458\nCONFORMED SUBMISSION TYPE:\tSC 13D\nPUBLIC DOCUMENT COUNT:\t\t2\nFILED AS OF DATE:\t\t20100217\nDATE AS OF CHANGE:\t\t20100217\n\nFILED BY:\t\t\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tCoriaty David\n\t\tCENTRAL INDEX KEY:\t\t\t0001483338\n\n\tFILING VALUES:\n\t\tFORM TYPE:\t\tSC 13D\n\n\tMAIL ADDRESS:\t\n\t\tSTREET 1:\t\t2385 NW EXECUTIVE CENTER DRIVE\n\t\tSTREET 2:\t\tSUITE 100\n\t\tCITY:\t\t\tBOCA RATON\n\t\tS

In [57]:
soup_new = BeautifulSoup(test, 'html5lib')

In [58]:
soup_new

<html><head></head><body bgcolor="#ffffff" style="DISPLAY: inline; FONT-FAMILY: Times New Roman; FONT-SIZE: 10pt">-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 LvErIjyauRMD1sh0Xy4G28nJE9BPSXcrXwQNKWS0uyJBIzy85vSm1LuECMbiJjkC
 kVbsGjp5eapMmVYMi/BL3w==

<sec-document>0001354488-10-000458.txt : 20100217
<sec-header>0001354488-10-000458.hdr.sgml : 20100217
<acceptance-datetime>20100217114703
ACCESSION NUMBER:		0001354488-10-000458
CONFORMED SUBMISSION TYPE:	SC 13D
PUBLIC DOCUMENT COUNT:		2
FILED AS OF DATE:		20100217
DATE AS OF CHANGE:		20100217

FILED BY:		

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			Coriaty David
		CENTRAL INDEX KEY:			0001483338

	FILING VALUES:
		FORM TYPE:		SC 13D

	MAIL ADDRESS:	
		STREET 1:		2385 NW EXECUTIVE CENTER DRIVE
		STREET 2:	

In [59]:
soup_new.find('document')

In [282]:
timeout_df = get_file_list_df(engine)

In [283]:
timeout_df

file_name                  document  \
0   edgar/data/1374170/0001374170-10-000016.txt  0001374170-10-000016.txt   
1    edgar/data/914374/0000950109-99-001277.txt  0000950109-99-001277.txt   
2    edgar/data/315066/0000315066-94-001415.txt  0000315066-94-001415.txt   
3   edgar/data/1100663/0000215457-18-002286.txt  0000215457-18-002286.txt   
4    edgar/data/102909/0000932471-18-003787.txt  0000932471-18-003787.txt   
5   edgar/data/1037016/0000101830-07-000006.txt  0000101830-07-000006.txt   
6    edgar/data/904080/0001086364-14-000227.txt  0001086364-14-000227.txt   
7     edgar/data/37525/0000950144-99-005933.txt  0000950144-99-005933.txt   
8   edgar/data/1552448/0001144204-17-009831.txt  0001144204-17-009831.txt   
9    edgar/data/315126/0001140361-03-000478.txt  0001140361-03-000478.txt   
10  edgar/data/1611388/0001193125-19-040096.txt  0001193125-19-040096.txt   
11     edgar/data/4904/0000927016-00-000377.txt  0000927016-00-000377.txt   
12   edgar/data/790705/0000950123-11-011321.txt  0000950123-11-011321.txt   
13  edgar/data/1010643/0000948221-04-000086.txt  0000948221-04-000086.txt   
14  edgar/data/1029160/0000921530-97-000021.txt  0000921530-97-000021.txt   
15  edgar/data/1120295/0000950148-02-000371.txt  0000950148-02-000371.txt   
16   edgar/data/909791/0001012870-97-000177.txt  0001012870-97-000177.txt   
17    edgar/data/10742/0000010742-04-000008.txt  0000010742-04-000008.txt   
18  edgar/data/1422849/0001422849-19-000049.txt  0001422849-19-000049.txt   
19   edgar/data/864047/0000950144-00-001353.txt  0000950144-00-001353.txt   
20  edgar/data/1447380/0001569502-16-000027.txt  0001569502-16-000027.txt   
21   edgar/data/712034/0000936753-07-000022.txt  0000936753-07-000022.txt   
22  edgar/data/1034659/0000950131-97-001327.txt  0000950131-97-001327.txt   
23   edgar/data/723188/0000950128-97-000309.txt  0000950128-97-000309.txt   
24  edgar/data/1361658/0000315066-10-003798.txt  0000315066-10-003798.txt   
25  edgar/data/1076378/0000950172-02-001371.txt  0000950172-02-001371.txt   
26   edgar/data/799290/0000950109-94-000209.txt  0000950109-94-000209.txt   
27  edgar/data/1297376/0001013228-15-000617.txt  0001013228-15-000617.txt   
28  edgar/data/1102578/0001102578-09-000153.txt  0001102578-09-000153.txt   
29  edgar/data/1096199/0001193125-12-060935.txt  0001193125-12-060935.txt   
..                                          ...                       ...   
34   edgar/data/867665/0000728618-96-000077.txt  0000728618-96-000077.txt   
35  edgar/data/1033412/0000912057-97-005275.txt  0000912057-97-005275.txt   
36  edgar/data/1377452/0001193125-10-204693.txt  0001193125-10-204693.txt   
37     edgar/data/4427/0000729057-96-000227.txt  0000729057-96-000227.txt   
38  edgar/data/1390113/0001193125-12-009242.txt  0001193125-12-009242.txt   
39  edgar/data/1668428/0000905148-17-000935.txt  0000905148-17-000935.txt   
40  edgar/data/1056568/0001056568-03-000060.txt  0001056568-03-000060.txt   
41  edgar/data/1056084/0001140361-09-020978.txt  0001140361-09-020978.txt   
42  edgar/data/1402479/0000315066-13-002638.txt  0000315066-13-002638.txt   
43   edgar/data/217084/0000905608-00-000019.txt  0000905608-00-000019.txt   
44  edgar/data/1005141/0000950142-97-000292.txt  0000950142-97-000292.txt   
45   edgar/data/879933/0000919859-01-500028.txt  0000919859-01-500028.txt   
46  edgar/data/1011632/0000912057-01-510136.txt  0000912057-01-510136.txt   
47   edgar/data/315066/0000315066-96-001040.txt  0000315066-96-001040.txt   
48  edgar/data/1422848/0001422848-13-000042.txt  0001422848-13-000042.txt   
49   edgar/data/766524/0000766524-98-000542.txt  0000766524-98-000542.txt   
50  edgar/data/1364742/0001086364-10-007344.txt  0001086364-10-007344.txt   
51  edgar/data/1169870/0001104659-04-001145.txt  0001104659-04-001145.txt   
52  edgar/data/1056831/0000919574-11-000237.txt  0000919574-11-000237.txt   
53   edgar/data/814375/0000814375-00-000020.txt  0000814375-00-000020.txt   
54  edgar/data/1486957/0001144204-

In [285]:
i = 0
get_index_url(timeout_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1374170/000137417010000016/0001374170-10-000016-index.htm'

In [286]:
get_key_indices(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'],\
                timeout_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1374170/0001374170-10-000016.txt  0001374170-10-000016.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        2000                 2324   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              2160                4307   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   4212            4230                  3             7760   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1              8321                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [377]:
i = 63
get_key_indices(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'],\
                timeout_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1727674/0001010549-18-000018.txt  0001010549-18-000018.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                        1203                 1260   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1203                2350   

  cover_page_last_q_end cover_page_end  num_cusip_b_items  signature_start  \
0                  None           None                  2             5619   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1              5894                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [360]:
i = 53
get_key_indices(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'],\
                timeout_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/814375/0000814375-00-000020.txt  0000814375-00-000020.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0    SC 13G                        1285                 1299   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     1              1299                  -1   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   2145            2535                  2             3251   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1              3491                           -1   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [362]:
t3 = get_main_doc_text(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'], directory)

In [364]:
t3[2145:2535]

'INVESTMENT ADVISER\n\nSCHEDULE 13G\n\n(22,315)Item 1\n(a)\nRYERSON TULL INC.\n(b)\n2621 West 15th Place\nChicago, Illinois  60608\n\n(22,316)Item 2\n(a)\nDonald Smith & Co., Inc.\n\n(b)\nEast 80 Route 4 - Suite 360\nParamus, New Jersey  07652\n\n(c)\nNot applicable\n\n(d)\nCommon\n\n(e)\nCUSIP = 78375P107\n\n(22,317)Item 3\n(e)\nInvestment Advisor registered under section 203 of the Investment Advisers Act\n of 1940\n\n'

In [361]:
get_index_url('edgar/data/814375/0000814375-00-000020.txt')

'https://www.sec.gov/Archives/edgar/data/814375/000081437500000020/0000814375-00-000020-index.htm'

In [352]:
i = 49
get_key_indices(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'],\
                timeout_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/766524/0000766524-98-000542.txt  0000766524-98-000542.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1061                 1321   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1167               13161   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                  12805           12808                  6            20417   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1             21102                           -1   

   has_jumbled_order  has_exhibit_break  
0               True              False

In [354]:
t2 = get_main_doc_text(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'], directory)

In [356]:
t2[20417:]

'\n     Signature\n\n     Name/Title:    Frederick S. Marius\n     Vice President and Counsel\n\n     Date:     August 6, 1998\n\n\nFor this and all future filings, reference is made to Power\nof Attorney dated November 9, 1992, with respect to duly\nauthorized signatures on behalf of Marsh & McLennan\nCompanies, Inc., Putnam Investments, Inc., Putnam Investment\nManagement, Inc., The Putnam Advisory Company, Inc. and any\nPutnam Fund wherever applicable.\n\nFor this and all future filings, reference is made to an\nAgreement dated June 28, 1990, with respect to one filing of\nSchedule 13G on behalf of said entities, pursuant to Rule\n13d-1(f)(1).\n\n\n\n\n\n\n                     Page 11 of 11 Pages\n\n\n\n'

In [ ]:
'(BD|BK|IC|IV|IA|EP|HC|CO|PN|IN|OO|0O|O0|00)'

In [ ]:
Broker Dealer                                                   BD
	Bank                                                            BK
	Insurance Company                                               IC
	Investment Company                                              IV
	Investment Advisor                                              IA
	Employee Benefit Plan, Pension Fund, or Endowment Fund          EP
	Parent Holding Company                                          HC
	Corporation                                                     CO
	Partnership                                                     PN
	Individual                                                      IN
	Other                                                           OO

In [353]:
get_index_url('edgar/data/766524/0000766524-98-000542.txt')

'https://www.sec.gov/Archives/edgar/data/766524/000076652498000542/0000766524-98-000542-index.htm'

In [331]:
get_index_url('edgar/data/895421/0001021408-01-503753.txt')

'https://www.sec.gov/Archives/edgar/data/895421/000102140801503753/0001021408-01-503753-index.htm'

In [314]:
i = 28
get_key_indices(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'],\
                timeout_df.loc[i, 'form_type'], directory)

file_name                  document  \
0  edgar/data/1102578/0001102578-09-000153.txt  0001102578-09-000153.txt   

  form_type  title_page_end_lower_bound  cover_page_q1_start  \
0  SC 13G/A                        1836                 1959   

   is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0              False           False                  False   

   num_cusip_sedol_b_q1  cover_page_start  item_section_start  \
0                     2              1836               11038   

   cover_page_last_q_end  cover_page_end  num_cusip_b_items  signature_start  \
0                   5983            6282                  2            17083   

   exhibit_start  main_text_length  explanatory_statement_start  \
0             -1             18998                         5886   

   has_jumbled_order  has_exhibit_break  
0              False              False

In [405]:
sql = """SELECT * FROM edgar.sc13dg_indexes
         WHERE cover_page_last_q_end = cover_page_end
         AND success
      """
eg = pd.read_sql(sql, engine)
eg

file_name                  document  \
0   edgar/data/1273805/0001277164-09-000002.txt  0001277164-09-000002.txt   
1   edgar/data/1367859/0001277164-10-000002.txt  0001277164-10-000002.txt   
2   edgar/data/1277164/0001277164-09-000002.txt  0001277164-09-000002.txt   
3   edgar/data/1367859/0001277164-11-000003.txt  0001277164-11-000003.txt   
4   edgar/data/1277164/0001277164-09-000016.txt  0001277164-09-000016.txt   
5   edgar/data/1593181/0001144204-15-003193.txt  0001144204-15-003193.txt   
6   edgar/data/1504222/0001144204-14-065582.txt  0001144204-14-065582.txt   
7   edgar/data/1593181/0001144204-14-047653.txt  0001144204-14-047653.txt   
8   edgar/data/1559281/0001144204-14-007493.txt  0001144204-14-007493.txt   
9   edgar/data/1079282/0001144204-15-058628.txt  0001144204-15-058628.txt   
10  edgar/data/1593181/0001144204-14-065582.txt  0001144204-14-065582.txt   
11   edgar/data/832847/0001277164-09-000005.txt  0001277164-09-000005.txt   
12  edgar/data/1617659/0001062993-14-005190.txt  0001062993-14-005190.txt   
13  edgar/data/1593181/0001213900-19-013184.txt  0001213900-19-013184.txt   
14   edgar/data/832847/0001277164-11-000002.txt  0001277164-11-000002.txt   
15   edgar/data/832847/0001277164-10-000008.txt  0001277164-10-000008.txt   
16  edgar/data/1277164/0001277164-09-000015.txt  0001277164-09-000015.txt   
17   edgar/data/898225/0001047469-03-000326.txt  0001047469-03-000326.txt   
18  edgar/data/1288750/0001062993-14-005646.txt  0001062993-14-005646.txt   
19  edgar/data/1617659/0001062993-14-005655.txt  0001062993-14-005655.txt   
20  edgar/data/1593181/0001144204-14-043696.txt  0001144204-14-043696.txt   
21   edgar/data/832847/0001277164-09-000015.txt  0001277164-09-000015.txt   
22  edgar/data/1448695/0001213900-19-013184.txt  0001213900-19-013184.txt   
23  edgar/data/1593181/0001144204-15-032769.txt  0001144204-15-032769.txt   
24  edgar/data/1273805/0001277164-12-000008.txt  0001277164-12-000008.txt   
25  edgar/data/1367859/0001277164-12-000010.txt  0001277164-12-000010.txt   
26  edgar/data/1277164/0001277164-10-000002.txt  0001277164-10-000002.txt   
27  edgar/data/1141673/0001144204-14-073094.txt  0001144204-14-073094.txt   
28  edgar/data/1423746/0001615774-17-005329.txt  0001615774-17-005329.txt   
29  edgar/data/1470177/0001144204-14-007493.txt  0001144204-14-007493.txt   
30  edgar/data/1427030/0001144204-14-047653.txt  0001144204-14-047653.txt   
31  edgar/data/1288750/0001062993-14-005190.txt  0001062993-14-005190.txt   
32  edgar/data/1408146/0001062993-14-005655.txt  0001062993-14-005655.txt   
33  edgar/data/1593181/0001144204-14-073094.txt  0001144204-14-073094.txt   
34   edgar/data/899647/0001047469-03-000326.txt  0001047469-03-000326.txt   
35  edgar/data/1402371/0001144204-15-032769.txt  0001144204-15-032769.txt   
36  edgar/data/1277164/0001277164-09-000005.txt  0001277164-09-000005.txt   
37  edgar/data/1277164/0001277164-12-000008.txt  0001277164-12-000008.txt   
38  edgar/data/1277164/0001277164-11-000002.txt  0001277164-11-000002.txt   
39  edgar/data/1277164/0001277164-11-000003.txt  0001277164-11-000003.txt   
40  edgar/data/1367859/0001277164-09-000013.txt  0001277164-09-000013.txt   
41   edgar/data/832847/0001277164-09-000014.txt  0001277164-09-000014.txt   
42  edgar/data/1381054/0001144204-15-003193.txt  0001144204-15-003193.txt   
43  edgar/data/1593181/0001615774-17-005329.txt  0001615774-17-005329.txt   
44  edgar/data/1617659/0001062993-14-005646.txt  0001062993-14-005646.txt   
45  edgar/data/1277164/0001277164-10-000008.txt  0001277164-10-000008.txt   
46  edgar/data/1277164/0001277164-09-000013.txt  0001277164-09-000013.txt   
47  edgar/data/1467434/0001144204-14-043696.txt  0001144204-14-043696.txt   
48  edgar/data/1559281/0001144204-15-058628.txt  0001144204-15-058628.txt   
49   edgar/data/832847/0001277164-09-000016.txt  0001277164-09-000016.txt   
50  edgar/data/1277164/0001277164-12-000010.txt  0001277164-12-000010.txt   
51  edgar/data/1277164/0001277164-

In [ ]:
def has_jumbled_order(text, form_type, exhibit_start):
    
    # This function is defined to be true if there are item sections or signature sections in the parts of the
    # text which are before the last instance of an orthodox q1 of a cover page (hence "jumbled")
    # this can include cases where for instance, an order goes cover_page -> items -> signatures -> 
    # cover_page -> items -> signatures 
    
    result = False # Assume false till proven otherwise
    
    q1_starts = find_all_orthodox_q1_starts(text, exhibit_start)

    for i in range(len(q1_starts)):

        if(i == 0):

            segment = get_bounded_text(text, 0, q1_starts[i])

        else:

            segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

        has_items = (get_item_section_start(segment, form_type) != -1)
        has_signatures = (get_signatures_sec_start(segment) != -1)

        if(has_items or has_signatures):

            result = True
            break

    return(result)         

In [413]:
indexes_df = pd.read_sql('SELECT * FROM edgar.sc13dg_indexes', engine)

In [414]:
indexes_df

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2        edgar/data/1163453/0001019687-04-000771.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
9        edgar/data/1163453/0001019687-04-001131.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
12       edgar/data/1279095/0001144204-04-004297.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
16       edgar/data/1135338/0000919574-04-001356.txt   
17        edgar/data/923877/0000807249-04-000123.txt   
18       edgar/data/1135338/0000919574-04-001735.txt   
19       edgar/data/1279095/0001144204-04-007831.txt   
20       edgar/data/1135338/0000919574-04-001367.txt   
21       edgar/data/1135338/0000919574-04-001873.txt   
22       edgar/data/1135338/0000919574-04-001745.txt   
23       edgar/data/1135338/0000919574-04-001385.txt   
24        edgar/data/925765/0000926274-04-000155.txt   
25       edgar/data/1135338/0000919574-04-001749.txt   
26       edgar/data/1135338/0000919574-04-001895.txt   
27       edgar/data/1135338/0000919574-04-001407.txt   
28        edgar/data/927752/0000950142-04-002200.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
...                                              ...   
1368332  edgar/data/1125920/0000215457-19-002604.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368334   edgar/data/893691/0000215457-19-004906.txt   
1368335  edgar/data/1104186/0000919574-19-001286.txt   
1368336  edgar/data/1118417/0001104659-19-008720.txt   
1368337  edgar/data/1201792/0001037389-19-000146.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368339  edgar/data/1621563/0000807985-19-000028.txt   
1368340  edgar/data/1395064/0001104659-19-060139.txt   
1368341  edgar/data/1050045/0001104659-19-071096.txt   
1368342   edgar/data/826020/0001062993-19-004564.txt   
1368343  edgar/data/1527541/0001104659-19-056194.txt   
1368344  edgar/data/1504103/0001193125-19-279063.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368346  edgar/data/1581164/0001104659-19-071304.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   
1368349  edgar/data/1320854/0001085146-19-000414.txt   
1368350  edgar/data/1430308/0001214659-19-000763.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368352   edgar/data/862831/0000215457-19-004043.txt   
1368353  edgar/data/1045810/0000215457-19-004826.txt   
1368354  edgar/data/1564584/0000895421-19-000289.txt   
1368355  edgar/data/1534126/0000950157-19-000740.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368357  edgar/data/1655020/0001144204-19-008356.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   
1368359  edgar/data/1124941/0001104659-19-038258.txt   
1368360  edgar/data/1560258/0001193125-19-297684.txt   
1368361  edgar/data/1404574/0000921895-19-001932.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001019687-04-000771.txt    SC 13D                           1   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G  

In [418]:
indexes_df.loc[indexes_df['has_jumbled_order'] == True]

file_name  \
140      edgar/data/1133256/0001193125-04-099611.txt   
180        edgar/data/80255/0000080255-04-000418.txt   
241      edgar/data/1295249/0001144204-04-008961.txt   
264       edgar/data/788920/0000892569-04-000701.txt   
271        edgar/data/80255/0000080255-04-000421.txt   
288      edgar/data/1110781/0001015402-04-002061.txt   
350       edgar/data/355948/0000080255-04-000418.txt   
448      edgar/data/1241883/0001015402-04-001741.txt   
457       edgar/data/887921/0000898822-04-000275.txt   
594      edgar/data/1277154/0001028212-04-000033.txt   
702      edgar/data/1286062/0001062993-04-001028.txt   
703      edgar/data/1054217/0000950134-04-006686.txt   
770       edgar/data/915477/0000950144-04-003737.txt   
804      edgar/data/1287745/0000950136-04-001877.txt   
1008     edgar/data/1287833/0000950136-04-001876.txt   
1010     edgar/data/1287833/0000950136-04-001875.txt   
1012     edgar/data/1055565/0000906280-04-000174.txt   
1156      edgar/data/924355/0000924355-04-000136.txt   
1169     edgar/data/1055565/0000906280-04-000220.txt   
1451      edgar/data/353569/0000080255-04-000320.txt   
1454     edgar/data/1061096/0000897069-04-000396.txt   
1543     edgar/data/1081290/0000891618-04-000045.txt   
1644     edgar/data/1013467/0000080255-04-000277.txt   
1975      edgar/data/355948/0000080255-04-000164.txt   
2166     edgar/data/1046102/0000945234-04-000084.txt   
2234     edgar/data/1076352/0001193125-04-018161.txt   
2271     edgar/data/1182836/0000950134-04-000754.txt   
2503      edgar/data/869561/0000891020-04-000221.txt   
2565     edgar/data/1160543/0000950152-04-002193.txt   
2869     edgar/data/1179638/0000950144-04-001312.txt   
...                                              ...   
1366376   edgar/data/878720/0000950148-03-001352.txt   
1366387    edgar/data/80255/0000080255-03-000022.txt   
1366389    edgar/data/82536/0000109501-03-000006.txt   
1366456  edgar/data/1262857/0001144204-03-005428.txt   
1366468  edgar/data/1240909/0000891618-03-003485.txt   
1366515   edgar/data/842013/0000914317-04-001447.txt   
1366536   edgar/data/929994/0000903764-95-000001.txt   
1366592  edgar/data/1082249/0000950123-03-008964.txt   
1366594  edgar/data/1096208/0001108017-03-000735.txt   
1366603    edgar/data/18532/0000950134-03-014450.txt   
1366720    edgar/data/20232/0001010192-96-000002.txt   
1366729  edgar/data/1164239/0000891618-04-000556.txt   
1366822     edgar/data/6955/0000080255-04-000016.txt   
1366865  edgar/data/1016869/0001021771-04-000049.txt   
1366878  edgar/data/1286058/0001062993-04-001032.txt   
1367036     edgar/data/8462/0000874724-97-000002.txt   
1367093    edgar/data/37008/0000899983-97-000019.txt   
1367149   edgar/data/752714/0000080255-04-000149.txt   
1367339   edgar/data/829608/0000936392-98-000202.txt   
1367424  edgar/data/1665487/0001104659-18-037040.txt   
1367435   edgar/data/886171/0000889812-96-001339.txt   
1367525  edgar/data/1002081/0000926274-97-000015.txt   
1367644   edgar/data/848448/0000945621-96-000044.txt   
1367782   edgar/data/874724/0000874724-97-000003.txt   
1367836   edgar/data/903417/0000927025-98-000017.txt   
1367856  edgar/data/1604821/0001193125-19-031430.txt   
1367881  edgar/data/1254370/0000072971-19-000345.txt   
1367890  edgar/data/1528382/0001193125-19-037827.txt   
1368287  edgar/data/1386809/0001144204-07-024379.txt   
1368308  edgar/data/1058854/0001058854-18-000024.txt   

                         document form_type  title_page_end_lower_bound  \
140      0001193125-04-099611.txt    SC 13D                       21016   
180      0000080255-04-000418.txt  SC 13G/A                        1691   
241      0001144204-04-008961.txt    SC 13D                        2081   
264      0000892569-04-000701.txt  SC 13D/A                        1641   
271      0000080255-04-000421.txt  SC 13G/A                        1710   
288      0001015402-04-002061.txt  SC 13D/A                        2194   
350      0000080255-04-000418.txt  SC 13G/A  

In [431]:
get_index_url('edgar/data/788920/0000892569-04-000701.txt')

'https://www.sec.gov/Archives/edgar/data/788920/000089256904000701/0000892569-04-000701-index.htm'

In [421]:
text = get_main_doc_text(indexes_df.loc[140, 'file_name'], indexes_df.loc[140, 'document'], directory)

q1_starts = find_all_orthodox_q1_starts(text, -1)

for i in range(len(q1_starts)):

    if(i == 0):

        segment = get_bounded_text(text, 0, q1_starts[i])

    else:

        segment = get_bounded_text(text, q1_starts[i-1], q1_starts[i])

    has_items = (get_item_section_start(segment, 'SC 13D') != -1)
    has_signatures = (get_signatures_sec_start(segment) != -1)

    if(has_items or has_signatures):

        result = True
        break

In [424]:
i

8

In [ ]:
def has_table_of_contents(text, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    if(re.search('\n\s*TABLE\s+OF\s+CONTENTS\s*\n', text_raised)):
        
        return(True)
    
    else:
        
        return(False)

In [ ]:
indexes_df.loc[indexes_df['has_table_of_contents'] == True]

In [425]:
q1_starts

[1015, 3572, 5972, 8466, 10868, 13452, 16029, 18424, 23402, 24863]

In [432]:
indexes_df.loc[indexes_df['has_table_of_contents'] == True]

file_name  \
116        edgar/data/26820/0000936392-04-000577.txt   
255      edgar/data/1290035/0000936392-04-000577.txt   
264       edgar/data/788920/0000892569-04-000701.txt   
300       edgar/data/906551/0000950153-04-001523.txt   
361      edgar/data/1284472/0000919567-04-000043.txt   
459      edgar/data/1081290/0000950134-04-006085.txt   
479      edgar/data/1080731/0000919567-04-000042.txt   
487       edgar/data/919567/0000919567-04-000041.txt   
703      edgar/data/1054217/0000950134-04-006686.txt   
727        edgar/data/86115/0000893220-04-001132.txt   
770       edgar/data/915477/0000950144-04-003737.txt   
841       edgar/data/865477/0000950133-04-001277.txt   
1495     edgar/data/1198560/0000950152-04-001109.txt   
1498     edgar/data/1198560/0000950152-04-001111.txt   
1543     edgar/data/1081290/0000891618-04-000045.txt   
1807      edgar/data/702513/0000950149-04-000276.txt   
2103      edgar/data/933210/0000950134-04-001815.txt   
2166     edgar/data/1046102/0000945234-04-000084.txt   
2271     edgar/data/1182836/0000950134-04-000754.txt   
2535      edgar/data/906326/0000936392-04-000119.txt   
2565     edgar/data/1160543/0000950152-04-002193.txt   
2604     edgar/data/1160543/0000950152-04-001103.txt   
2606     edgar/data/1160545/0000950152-04-001101.txt   
2880     edgar/data/1106835/0000936392-04-000053.txt   
2883     edgar/data/1082423/0000936392-04-000053.txt   
2939     edgar/data/1084332/0000936392-04-000026.txt   
2988       edgar/data/86115/0000893220-04-000195.txt   
2994     edgar/data/1022926/0000950152-04-000808.txt   
3018     edgar/data/1272270/0000950149-04-000398.txt   
3040     edgar/data/1284465/0001156973-04-000345.txt   
...                                              ...   
1360197   edgar/data/923603/0000950123-10-106322.txt   
1360320  edgar/data/1061219/0000950123-11-003498.txt   
1360509  edgar/data/1210618/0000950123-11-001682.txt   
1360639  edgar/data/1342126/0000950123-11-013782.txt   
1360932  edgar/data/1352903/0001193125-12-168312.txt   
1360943   edgar/data/908733/0000950123-11-056899.txt   
1360944   edgar/data/908733/0000950123-11-056906.txt   
1361133  edgar/data/1382868/0001193125-11-146242.txt   
1361182  edgar/data/1450426/0001144204-11-033352.txt   
1362174  edgar/data/1029145/0000919574-14-005637.txt   
1362212   edgar/data/929351/0001193125-16-789769.txt   
1363266  edgar/data/1277742/0001193125-15-028016.txt   
1365089  edgar/data/1096325/0000950152-02-000768.txt   
1365145  edgar/data/1118941/0000950152-01-001099.txt   
1365233  edgar/data/1082993/0000912057-01-538565.txt   
1365652  edgar/data/1206708/0000898080-03-000057.txt   
1365768  edgar/data/1131154/0000909567-03-000325.txt   
1365790  edgar/data/1186612/0000950123-02-009813.txt   
1366242   edgar/data/924373/0000950148-03-000766.txt   
1366329   edgar/data/843562/0000950146-96-000826.txt   
1366340  edgar/data/1207031/0001108017-03-000426.txt   
1366345  edgar/data/1051848/0000950153-03-001858.txt   
1366374  edgar/data/1132859/0000891020-03-001713.txt   
1366376   edgar/data/878720/0000950148-03-001352.txt   
1366592  edgar/data/1082249/0000950123-03-008964.txt   
1366594  edgar/data/1096208/0001108017-03-000735.txt   
1366603    edgar/data/18532/0000950134-03-014450.txt   
1366729  edgar/data/1164239/0000891618-04-000556.txt   
1366779   edgar/data/914435/0000950144-96-003212.txt   
1367769   edgar/data/868512/0000898431-97-000231.txt   

                         document form_type  title_page_end_lower_bound  \
116      0000936392-04-000577.txt  SC 13G/A                        1346   
255      0000936392-04-000577.txt  SC 13G/A                        1346   
264      0000892569-04-000701.txt  SC 13D/A                        1641   
300      0000950153-04-001523.txt    SC 13D                        1779   
361      0000919567-04-000043.txt    SC 13D                        2802   
459      0000950134-04-006085.txt  SC 13D/A                        1819   
479      0000919567-04-000042.txt    SC 13D  

In [441]:
indexes_df.loc[np.logical_and(indexes_df['has_table_of_contents'] == True, indexes_df['exhibit_start'] > 0)]

file_name  \
300       edgar/data/906551/0000950153-04-001523.txt   
361      edgar/data/1284472/0000919567-04-000043.txt   
459      edgar/data/1081290/0000950134-04-006085.txt   
479      edgar/data/1080731/0000919567-04-000042.txt   
487       edgar/data/919567/0000919567-04-000041.txt   
841       edgar/data/865477/0000950133-04-001277.txt   
1495     edgar/data/1198560/0000950152-04-001109.txt   
1498     edgar/data/1198560/0000950152-04-001111.txt   
1543     edgar/data/1081290/0000891618-04-000045.txt   
2271     edgar/data/1182836/0000950134-04-000754.txt   
2535      edgar/data/906326/0000936392-04-000119.txt   
2565     edgar/data/1160543/0000950152-04-002193.txt   
2994     edgar/data/1022926/0000950152-04-000808.txt   
3018     edgar/data/1272270/0000950149-04-000398.txt   
3163     edgar/data/1121404/0000950123-04-001727.txt   
3354     edgar/data/1198534/0000950134-04-002085.txt   
3648     edgar/data/1088193/0000950150-04-000158.txt   
3739      edgar/data/885080/0000936392-04-000117.txt   
4019     edgar/data/1105982/0000950153-04-000390.txt   
4049     edgar/data/1065837/0000950148-04-000309.txt   
4308     edgar/data/1229195/0001176721-04-000117.txt   
4694     edgar/data/1104678/0000950124-04-002747.txt   
4798     edgar/data/1022368/0000950124-04-002747.txt   
5000     edgar/data/1104678/0000950124-04-002323.txt   
5400     edgar/data/1269977/0000950123-04-009101.txt   
5518     edgar/data/1080029/0000950134-04-011159.txt   
5802      edgar/data/742685/0000950134-04-009925.txt   
6049      edgar/data/742685/0000950134-04-012963.txt   
6179      edgar/data/742685/0000950134-04-013290.txt   
6201      edgar/data/742685/0000950134-04-011128.txt   
...                                              ...   
1347039  edgar/data/1380609/0000950137-07-001844.txt   
1348900  edgar/data/1073021/0000889810-98-000194.txt   
1350370  edgar/data/1336528/0001193125-13-002379.txt   
1350564  edgar/data/1398551/0000950142-13-002325.txt   
1352128  edgar/data/1023966/0000950152-99-009595.txt   
1352318   edgar/data/929546/0000905718-00-000388.txt   
1355677   edgar/data/812128/0000812128-00-000028.txt   
1355785   edgar/data/920707/0000950153-06-003011.txt   
1356129   edgar/data/889409/0000950144-01-510245.txt   
1356451   edgar/data/939158/0000950144-07-001310.txt   
1356804  edgar/data/1270953/0000950134-07-002671.txt   
1356976  edgar/data/1018103/0000950123-07-004092.txt   
1357448   edgar/data/944077/0000935836-98-000140.txt   
1357486  edgar/data/1047644/0000950148-03-001781.txt   
1358380   edgar/data/803352/0000950144-96-006484.txt   
1360320  edgar/data/1061219/0000950123-11-003498.txt   
1361182  edgar/data/1450426/0001144204-11-033352.txt   
1362174  edgar/data/1029145/0000919574-14-005637.txt   
1363266  edgar/data/1277742/0001193125-15-028016.txt   
1365089  edgar/data/1096325/0000950152-02-000768.txt   
1365233  edgar/data/1082993/0000912057-01-538565.txt   
1365652  edgar/data/1206708/0000898080-03-000057.txt   
1366242   edgar/data/924373/0000950148-03-000766.txt   
1366329   edgar/data/843562/0000950146-96-000826.txt   
1366345  edgar/data/1051848/0000950153-03-001858.txt   
1366374  edgar/data/1132859/0000891020-03-001713.txt   
1366592  edgar/data/1082249/0000950123-03-008964.txt   
1366603    edgar/data/18532/0000950134-03-014450.txt   
1366779   edgar/data/914435/0000950144-96-003212.txt   
1367769   edgar/data/868512/0000898431-97-000231.txt   

                         document form_type  title_page_end_lower_bound  \
300      0000950153-04-001523.txt    SC 13D                        1779   
361      0000919567-04-000043.txt    SC 13D                        2802   
459      0000950134-04-006085.txt  SC 13D/A                        1819   
479      0000919567-04-000042.txt    SC 13D                        2800   
487      0000919567-04-000041.txt    SC 13D                        2801   
841      0000950133-04-001277.txt  SC 13D/A                           1   
1495     0000950152-04-001109.txt  SC 13D/A  

In [444]:
get_index_url('edgar/data/1284472/0000919567-04-000043.txt')

'https://www.sec.gov/Archives/edgar/data/1284472/000091956704000043/0000919567-04-000043-index.htm'

In [434]:
tp = get_main_doc_text('edgar/data/26820/0000936392-04-000577.txt', '0000936392-04-000577.txt', directory)

In [436]:
print(tp)


SC 13G/A
1
a98568sc13gza.htm
SCHEDULE 13G AMENDMENT NO. 3



Phoenix Footwear Group, Inc



Table of Contents

OMB APPROVAL
OMB Number: 3235-0145
Expires: December 31, 2005
Estimated average burden
hours per response...11




UNITED STATES
SECURITIES AND EXCHANGE COMMISSION
Washington, D.C. 20549

SCHEDULE 13G

Under the Securities Exchange Act of 1934
(Amendment No. 3)*

PHOENIX FOOTWEAR GROUP, INC.

(Name of Issuer)

Common Stock, $.01 Par Value

(Title of Class of Securities)

71903M 10 0

(Cusip Number)

May 19, 2004

(Date of Event Which Requires Filing of this Statement)

Check the appropriate box to designate the rule pursuant to which this Schedule is filed:

        x Rule 13d-1 (b)

        o Rule 13d-1 (c)

        o Rule 13d-1 (d)

*The remainder of this cover page shall be filled out for a reporting person’s initial filing on this form with respect to the subject class of securities, and for any subsequent amendment containing information which would alter the disclosures

In [427]:
q1_starts[8]

23402

In [428]:
text[22402:23402]

' Agreement, the Pequot Funds, Sterling E. Phillips, Jr., J. Richard Knop, C.W. Gilluly, Peter Belford, Sr., Arthur A. Hutchins, Joseph H. Saul, Gerald McNichols and DRG Irrevocable Trust (collectively, the\n“Voting Stockholders”) entered into a Voting Agreement (the “Voting Agreement”), pursuant to which parties have agreed to vote or cause to be voted, all securities of the Company they own or over which they have voting control at\nthe annual meeting of stockholders in favor of certain proposals relating to the conversion of the Senior Subordinated Notes into Series B Preferred Stock, and the exercise of the Investors’ Common Stock Warrants to purchase the Company’s\nCommon Stock.  \xa0 As a result of their entering into the Voting\nAgreement, the Voting Stockholders, including the Reporting Persons, may be deemed to constitute a group for the purposes of Rule 13d-5 under the Exchange Act.  \xa0\n 18 \n\n\n\n\n\n Information with respect to each Reporting Person is provided below:  

In [426]:
text[q1_starts[8]:q1_starts[9]]

'NAME OF REPORTING PERSON\n\xa0\xa0\n (b) RESIDENCE OR BUSINESS ADDRESS\n\xa0\xa0\n (c) PRESENT PRINCIPALOCCUPATION OREMPLOYMENT AND THE NAME, PRINCIPAL BUSINESS AND ADDRESS OF ORGANIZATION\nIN WHICH SUCH EMPLOYMENT IS CONDUCTED (IF APPLICABLE)\n\xa0\xa0\n (f) CITIZENSHIP OR PLACE OF ORGANIZATION\n\n Sterling E. Phillips, Jr.\n\xa0\xa0\n c/o Analex Corporation 5904 Richmond Highway\nSuite 300 Alexandria, VA 22303\n\xa0\xa0\n Chairman and Chief Executive Officer, Analex Corporation, a government and defense contractor 5904 Richmond Highway Suite 300 Alexandria, VA 22303\n\xa0\xa0\nU.S.A.\n\n\n\n\n\n\n J. Richard Knop\n\xa0\xa0\n One Discovery Square 12010 Sunset Hills Road\nSuite 700 Reston, VA 20190\n\xa0\xa0\n Chairman and Co-CEO Windsor Group, LLC, an investment\nbank One Discovery Square 12010 Sunset Hills Road Suite 700 Reston, VA 20190\n\xa0\xa0\nU.S.A.\n\n\n\n\n\n\n C.W. Gilluly\n\xa0\xa0\n 415 1st St, SE Washington, DC 20003\n\xa0\xa0\n Private investor 415 1st St, SE Washington

In [423]:
segment

' \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\xa0\xa01.\n\xa0\n Name of Reporting Person I.R.S. Identification No. of above person \xa0 DRG Irrevocable Trust\n\xa0\n\xa0\n\n\n\n\xa0\xa02.\n\xa0\n Check the Appropriate Box if a Member of a Group (a)\xa0\xa0x (b)\xa0\xa0•\n\xa0\n\xa0\n\n\n\n\xa0\xa03.\n\xa0\n SEC Use Only \xa0\n\xa0\n\xa0\n\n\n\n\xa0\xa04.\n\xa0\n Source of Funds \xa0 PF\n\xa0\n\xa0\n\n\n\n\xa0\xa05.\n\xa0\n Check Box if Disclosure of Legal Proceedings Is Required Pursuant to Items 2(d) Or 2(e) \xa0\n\xa0\n•\n\n\n\n\xa0\xa06.\n\xa0\n Citizenship or Place of Organization \xa0 United States of America\n\xa0\n\xa0\n\n\n\n\n\n\n\n\n\n\n NUMBER\xa0OF SHARES BENEFICIALLY OWNED\xa0BY EACH REPORTING PERSON WITH\n\xa0\n \xa0\xa07.\xa0\xa0\xa0\xa0Sole Voting Power \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0700,000 (1) \xa0\xa08.\xa0\xa0\xa0\xa0Shared Voting Power \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa00(2) \xa0\xa09.\xa0\xa0\xa0\xa0Sole Dispositive Power \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0700,

In [419]:
get_index_url('edgar/data/1133256/0001193125-04-099611.txt')

'https://www.sec.gov/Archives/edgar/data/1133256/000119312504099611/0001193125-04-099611-index.htm'

In [407]:
eg.loc[0, 'item_section_start']

2693

In [411]:
get_index_url('edgar/data/1593181/0001144204-15-003193.txt')

'https://www.sec.gov/Archives/edgar/data/1593181/000114420415003193/0001144204-15-003193-index.htm'

In [402]:
answer_regex = '\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]*)*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n'

In [403]:
t4 = get_main_doc_text('edgar/data/1277164/0001277164-09-000002.txt', '0001277164-09-000002.txt', directory)

In [ ]:
'(BD|BK|IC|IV|IA|EP|HC|CO|PN|IN|OO|0O|O0|00)'

In [410]:
t4[2672:2710]

'\n\n\n\n\n \tPage 4 of 7\n\n\nItem 1(a).\tName o'

In [385]:
re.search(answer_regex, '     IA\n').group(0)

'     IA\n'

In [386]:
re.search(answer_regex,  t[3523:4000]).group(0)

'\n    IA\n'

In [390]:
re.search(answer_regex,  t[3523:6523]).group(0)

'\n    IA\n'

In [392]:
instructions_included(t, 'SC 13G/A')

(True, 4147)

In [393]:
find_cover_pages_last_question(t, rep_q_as_items = False,  lower_bound = 1959, upper_bound = 4147)

3644

In [394]:
find_cover_pages_end(t, 'SC 13G/A', rep_q_as_items = False, lower_bound = 3644, upper_bound = 4147)

3734

In [396]:
t[1836:3734]

'\n\nCUSIP NO. 002535201\n          ---------\n- -------------------------------------------------------------------------------\n 1  NAMES OF REPORTING PERSONS.\n    I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY).\n\n    EARNEST Partners, LLC\n- -------------------------------------------------------------------------------\n 2  CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n    (a) [  ]\n    (b) [  ]\n- -------------------------------------------------------------------------------\n 3  SEC USE ONLY\n- -------------------------------------------------------------------------------\n 4  CITIZENSHIP OR PLACE OF ORGANIZATION  State of Georgia\n- -------------------------------------------------------------------------------\n              5    SOLE VOTING POWER  715,812\nNUMBER OF     -----------------------------------------------------------------\nSHARES\nBENEFICIALLY  6    SHARED VOTING POWER  466,529\nOWNED BY      --------------------------------

In [389]:
 t[3523:6556]

'-------------------------------------------------------------------------\n12  TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n- -------------------------------------------------------------------------------\n    IA\n- -------------------------------------------------------------------------------\n\n- -------------------------------------------------------------------------------\n\n- -------------------------------------------------------------------------------\n\n- -------------------------------------------------------------------------------\n\n- -------------------------------------------------------------------------------\n\n\t\t\t\tINSTRUCTIONS FOR SCHEDULE 13G\n\nInstructions for Cover Page\n\n(1)\tNames and I.R.S. Identification Numbers of Reporting Persons--Furnish\nthe full legal name of each person for whom the report is filed--i.e.,\neach person required to sign the schedule itself--including each\nmember of a group. Do not include the name of a person required to be\nid

In [316]:
t = get_main_doc_text(timeout_df.loc[i, 'file_name'], timeout_df.loc[i, 'document'], directory)
print(t)


SC 13G/A
1
aan13g5th0709.txt
AARON'S INC - 07/31/2009


                                 UNITED STATES
                       SECURITIES AND EXCHANGE COMMISSION
                            Washington, D.C.  20549

                                  SCHEDULE 13G

                   Under the Securities Exchange Act of 1934
                             (Amendment No._5_)*


                                  AARON'S INC.
- -------------------------------------------------------------------------------
                                (Name of Issuer)

                                  Common Stock
- -------------------------------------------------------------------------------
                         (Title of Class of Securities)

                                   002535201
                        ------------------------------
                                 (CUSIP Number)

                                   07/31/2009
- ---------------------------------------------------------------

In [327]:
def instructions_included(text, form_type, lower_bound = None, upper_bound = None):
    
    text_raised = get_bounded_text(text, lower_bound, upper_bound).upper()
    
    regex0 = '\n\s*INSTRUCTIONS\s+FOR\s+(SCHEDULE|SC)\s+13[DG](/A)?'
    regex1 = '\n\s*INSTRUCTIONS\s+FOR\s+COVER\s+PAGE'
    regex2 = '\n\s*GENERAL\s+INSTRUCTIONS'
    
    re_list = [regex0, regex1, regex2]
    
    result_bool = False # Assume False till proven otherwise
    result_index = -1 # Likewise, assume -1 till there is an index for a search found
    
    for pattern in re_list:
        
        search = re.search(pattern, text_raised)
        
        if(search):
            
            result_bool = True
            
            if(lower_bound is not None and lower_bound != -1):
            
                result_index = search.start() + lower_bound
                
            else:
                
                result_index = search.start()
                
            break
            
    return(result_bool, result_index)
    

In [328]:
instructions_included(t, 'SC 13G/A')

(True, 4147)

In [329]:
t[1836:4147]

'\n\nCUSIP NO. 002535201\n          ---------\n- -------------------------------------------------------------------------------\n 1  NAMES OF REPORTING PERSONS.\n    I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY).\n\n    EARNEST Partners, LLC\n- -------------------------------------------------------------------------------\n 2  CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n    (a) [  ]\n    (b) [  ]\n- -------------------------------------------------------------------------------\n 3  SEC USE ONLY\n- -------------------------------------------------------------------------------\n 4  CITIZENSHIP OR PLACE OF ORGANIZATION  State of Georgia\n- -------------------------------------------------------------------------------\n              5    SOLE VOTING POWER  715,812\nNUMBER OF     -----------------------------------------------------------------\nSHARES\nBENEFICIALLY  6    SHARED VOTING POWER  466,529\nOWNED BY      --------------------------------

In [379]:
print(t)


SC 13G/A
1
aan13g5th0709.txt
AARON'S INC - 07/31/2009


                                 UNITED STATES
                       SECURITIES AND EXCHANGE COMMISSION
                            Washington, D.C.  20549

                                  SCHEDULE 13G

                   Under the Securities Exchange Act of 1934
                             (Amendment No._5_)*


                                  AARON'S INC.
- -------------------------------------------------------------------------------
                                (Name of Issuer)

                                  Common Stock
- -------------------------------------------------------------------------------
                         (Title of Class of Securities)

                                   002535201
                        ------------------------------
                                 (CUSIP Number)

                                   07/31/2009
- ---------------------------------------------------------------

In [445]:
get_index_url('edgar/data/1137774/0001137774-04-000179.txt')

'https://www.sec.gov/Archives/edgar/data/1137774/000113777404000179/0001137774-04-000179-index.htm'

In [284]:
sql = """SELECT a.file_name, a.document, b.form_type FROM edgar.filing_docs_processed AS a
                 INNER JOIN edgar.filings AS b
                 USING(file_name)
                 WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
                 AND a.downloaded
                 AND right(a.file_name, 24) = a.document
              """

all_files_df = pd.read_sql(sql, engine)

KeyboardInterrupt: 

In [ ]:
SELECT COUNT(*) FROM edgar.filing_docs_processed AS a
INNER JOIN edgar.filings AS b
USING(file_name)
WHERE b.form_type IN ('SC 13D', 'SC 13D/A', 'SC 13G', 'SC 13G/A')
AND a.downloaded
AND right(a.file_name, 24) = a.document

In [446]:
indexes_df.loc[indexes_df['cover_page_q1_start'] > 0]

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2        edgar/data/1163453/0001019687-04-000771.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
9        edgar/data/1163453/0001019687-04-001131.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
12       edgar/data/1279095/0001144204-04-004297.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
16       edgar/data/1135338/0000919574-04-001356.txt   
17        edgar/data/923877/0000807249-04-000123.txt   
18       edgar/data/1135338/0000919574-04-001735.txt   
19       edgar/data/1279095/0001144204-04-007831.txt   
20       edgar/data/1135338/0000919574-04-001367.txt   
21       edgar/data/1135338/0000919574-04-001873.txt   
22       edgar/data/1135338/0000919574-04-001745.txt   
23       edgar/data/1135338/0000919574-04-001385.txt   
24        edgar/data/925765/0000926274-04-000155.txt   
25       edgar/data/1135338/0000919574-04-001749.txt   
26       edgar/data/1135338/0000919574-04-001895.txt   
27       edgar/data/1135338/0000919574-04-001407.txt   
28        edgar/data/927752/0000950142-04-002200.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
...                                              ...   
1368332  edgar/data/1125920/0000215457-19-002604.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368334   edgar/data/893691/0000215457-19-004906.txt   
1368335  edgar/data/1104186/0000919574-19-001286.txt   
1368336  edgar/data/1118417/0001104659-19-008720.txt   
1368337  edgar/data/1201792/0001037389-19-000146.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368339  edgar/data/1621563/0000807985-19-000028.txt   
1368340  edgar/data/1395064/0001104659-19-060139.txt   
1368341  edgar/data/1050045/0001104659-19-071096.txt   
1368342   edgar/data/826020/0001062993-19-004564.txt   
1368343  edgar/data/1527541/0001104659-19-056194.txt   
1368344  edgar/data/1504103/0001193125-19-279063.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368346  edgar/data/1581164/0001104659-19-071304.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   
1368349  edgar/data/1320854/0001085146-19-000414.txt   
1368350  edgar/data/1430308/0001214659-19-000763.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368352   edgar/data/862831/0000215457-19-004043.txt   
1368353  edgar/data/1045810/0000215457-19-004826.txt   
1368354  edgar/data/1564584/0000895421-19-000289.txt   
1368355  edgar/data/1534126/0000950157-19-000740.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368357  edgar/data/1655020/0001144204-19-008356.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   
1368359  edgar/data/1124941/0001104659-19-038258.txt   
1368360  edgar/data/1560258/0001193125-19-297684.txt   
1368361  edgar/data/1404574/0000921895-19-001932.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001019687-04-000771.txt    SC 13D                           1   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G  

In [462]:
def get_title_page(file_name, document, directory, cover_page_start, cover_page_q1_start, num_cusip_sedol_b_q1):
    
    if(cover_page_start > 0):
        if(num_cusip_sedol_b_q1 <= 1):
            text = get_main_doc_text(file_name, document, directory)[:cover_page_q1_start]
        else:
            text = get_main_doc_text(file_name, document, directory)[:cover_page_start]
        return(text)
    else:
        return(None)

In [703]:
get_amendment_number(text)

In [674]:
find_info_start(text)

NameError: name 'search_result_list' is not defined

In [705]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/897226/000089722604000245/0000897226-04-000245-index.htm'

In [829]:
indexes_df.loc[indexes_df['is_rep_q_as_items'] == True]

file_name  \
10        edgar/data/893949/0000814133-04-000115.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
52         edgar/data/77449/0000315066-04-001429.txt   
143      edgar/data/1002663/0000315066-04-001679.txt   
306       edgar/data/906551/0000315066-04-001430.txt   
388      edgar/data/1094392/0000814133-04-000123.txt   
426        edgar/data/85408/0000315066-04-001525.txt   
427       edgar/data/770949/0000315066-04-001523.txt   
445        edgar/data/84278/0000315066-04-001524.txt   
449       edgar/data/805900/0001193125-04-074106.txt   
451       edgar/data/887921/0000315066-04-001431.txt   
561      edgar/data/1034054/0000315066-04-001433.txt   
590      edgar/data/1014507/0000315066-04-001527.txt   
656      edgar/data/1050606/0000315066-04-001526.txt   
710       edgar/data/918964/0000315066-04-001434.txt   
726      edgar/data/1019671/0000315066-04-001682.txt   
840      edgar/data/1103777/0000814133-04-000112.txt   
855       edgar/data/823094/0000315066-04-001683.txt   
857       edgar/data/943605/0000315066-04-001684.txt   
882      edgar/data/1094243/0000315066-04-001529.txt   
955       edgar/data/914024/0000315066-04-001528.txt   
1055     edgar/data/1223165/0000315066-04-001681.txt   
1159     edgar/data/1022671/0000315066-04-001530.txt   
1250     edgar/data/1015820/0000315066-04-000947.txt   
1287     edgar/data/1088033/0000315066-04-000952.txt   
1298      edgar/data/906551/0000315066-04-000948.txt   
1334     edgar/data/1091748/0000315066-04-000902.txt   
1402      edgar/data/918386/0000315066-04-000949.txt   
1412      edgar/data/912465/0000315066-04-000950.txt   
1427      edgar/data/758938/0000315066-04-000951.txt   
...                                              ...   
1367987   edgar/data/799721/0000315066-98-000922.txt   
1368005   edgar/data/910988/0000315066-98-000061.txt   
1368045   edgar/data/315066/0000315066-19-001807.txt   
1368057   edgar/data/315066/0000315066-98-000499.txt   
1368058   edgar/data/315066/0000315066-98-000511.txt   
1368059   edgar/data/315066/0000315066-98-000636.txt   
1368060   edgar/data/315066/0000315066-98-000677.txt   
1368088   edgar/data/315066/0000315066-19-000916.txt   
1368099   edgar/data/948845/0000315066-98-000812.txt   
1368101   edgar/data/100790/0000315066-98-001182.txt   
1368114  edgar/data/1016243/0000315066-98-001865.txt   
1368144   edgar/data/315066/0000315066-19-001039.txt   
1368145   edgar/data/315066/0000315066-19-001116.txt   
1368146   edgar/data/912750/0000315066-19-001242.txt   
1368148  edgar/data/1459417/0000315066-19-001675.txt   
1368150   edgar/data/920042/0000354204-98-000555.txt   
1368152   edgar/data/104778/0000104778-98-000023.txt   
1368160   edgar/data/896397/0000315066-98-001602.txt   
1368165  edgar/data/1590714/0000315066-19-001756.txt   
1368190   edgar/data/315066/0000315066-97-001723.txt   
1368191   edgar/data/315066/0000315066-97-001725.txt   
1368226   edgar/data/315066/0000315066-98-001933.txt   
1368227   edgar/data/315066/0000315066-98-001950.txt   
1368239   edgar/data/798941/0000315066-19-001038.txt   
1368263  edgar/data/1690820/0000315066-18-001913.txt   
1368279  edgar/data/1042893/0000315066-19-000963.txt   
1368299   edgar/data/315066/0000315066-19-001421.txt   
1368321    edgar/data/49754/0000315066-19-000981.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   

                         document form_type  title_page_end_lower_bound  \
10       0000814133-04-000115.txt  SC 13G/A                         166   
14       0000315066-04-001678.txt  SC 13G/A                           1   
52       0000315066-04-001429.txt  SC 13G/A                           1   
143      0000315066-04-001679.txt  SC 13G/A                           1   
306      0000315066-04-001430.txt  SC 13G/A                           1   
388      0000814133-04-000123.txt  SC 13G/A                         163   
426      0000315066-04-001525.txt  SC 13G/A  

In [989]:
i = 28
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13D/A
1
sc13da1-evergreen.txt
AMENDMENT NO. 1



                                  UNITED STATES
                       SECURITIES AND EXCHANGE COMMISSION
                             WASHINGTON, D.C. 20549

                                  SCHEDULE 13D

                    Under the Securities Exchange Act of 1934
                                (AMENDMENT NO. 1)

                              EVERGREEN SOLAR, INC.
                                (Name of Issuer)

                     COMMON STOCK, PAR VALUE $.01 PER SHARE
                         (Title of Class of Securities)

                                   3033R 10 8
                                 (CUSIP Number)

                             KENNETH M. SOCHA, ESQ.
                              PERSEUS 2000, L.L.C.
                       2099 PENNSYLVANIA AVENUE, SUITE 900
                             WASHINGTON, D.C. 20006
                                 (212) 452-0101
                     (Name, Address and Telephone N

In [1007]:
i = 29
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13G/A
1
cnu13g42204.txt
CONTINUCARE CORP


UNITED STATES
SECURITIES AND EXCHANGE COMMISSION
Washington, D.C. 20549


SCHEDULE 13G

Under the Securities Exchange Act of 1934

(Amendment No. _3__)*

ContinuCare Corporation
(Name of Issuer)

Common Stock**
(Title of Class of Securities)

212172100
(CUSIP Number)

April 21, 2004
(Date of Event Which Requires Filing of this Statement)

Check the appropriate box to designate the rule pursuant to which this Schedule
is filed:
[X] Rule 13d-1(b)
[  ] Rule 13d-1(c)
[  ] Rule 13d-1(d)

*The remainder of this cover page shall be filled out for a reporting person's
initial filing on this form with respect to the subject class of securities,
and for any subsequent amendment containing information which would alter
the disclosures provided in a prior cover page.

The information required on the remainder of this cover page shall not be
deemed to be filed for the purpose of Section 18 of the Securities Exchange
Act of 1934 (Act) or otherwise subje

In [1080]:
i = 52
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13G/A
1
filing.txt
DOC ONE


SCHEDULE 13G

Amendment No. 1
The Pep Boys - Manny Moe & Jack
Common Stock
Cusip #713278109


In [1114]:
i = 762248
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13G/A
1


                 SECURITIES AND EXCHANGE COMMISSION

                     Washington, D.C. 20549

                          Schedule 13G


           Under the Securities Exchange Act of 1934
                       (Amendment No. 5)*

                          CINTAS CORP.
                    FORMERLY UNITOG CO. NEW
            _______________________________________
                        (Name of Issuer)


                          Common Stock
            _______________________________________
                 (Title of Class of Securities)

                            172908105
                       FORMERLY 913267100

                         (CUSIP Number)


Check the following box if a fee is being paid with this
statement ____.  (A fee is not required only if the filing
person: (1) has a previous statement on file reporting beneficial
ownership of more than five percent of the class of securities
described in Item 1; and (2) has filed no amendment subsequent
th

In [1093]:
i = 762248
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/723254/0000080255-99-000481.txt  0000080255-99-000481.txt   

  form_type  amendment_number  \
0  SC 13G/A                 5   

                                         issuer_name security_class  \
0  CINTAS CORP.\n                    FORMERLY UNI...   Common Stock   

                                               cusip  
0  172908105\n                       FORMERLY 913...

In [1111]:
get_index_url('edgar/data/937797/0000950123-10-006037.txt')

'https://www.sec.gov/Archives/edgar/data/937797/000095012310006037/0000950123-10-006037-index.htm'

In [1181]:
i = 458250
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13D/A
1
v54956sc13dza.htm
SC 13D/A



sc13dza






 
 




SECURITIES AND EXCHANGE COMMISSION


Washington, D.C. 20549


SCHEDULE 13D/A



Under the Securities Exchange Act of 1934
(Amendment No. 1)*


ASCENT MEDIA CORPORATION


 


(Name of Issuer)


Series A Common Stock, par value $0.01 per share
Series B Common Stock, par value $0.01 per share

 


(Title of Class of Securities)


Series A Common Stock: 043632 108
Series B Common Stock: 043632 207

 


(CUSIP Numbers)


John C. Malone
c/o Liberty Media Corporation
12300 Liberty Boulevard
Englewood, Colorado 80112
(720) 875-4000

 
(Name, Address and Telephone Number of Person Authorized


to Receive Notices and Communications)


January 22, 2010

 


(Date of Events which Require Filing of this Statement)



     If the filing person has previously filed a statement on Schedule 13G to report the
acquisition that is the subject of this Schedule 13D, and is filing this schedule because of Rule
13d-1(e), 13d-1(f) or 13d-1(g), che

In [1135]:
i = 458250
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/937797/0000950123-10-006037.txt  0000950123-10-006037.txt   

  form_type  amendment_number               issuer_name  \
0  SC 13D/A                 1  ASCENT MEDIA CORPORATION   

                                      security_class  \
0  Series A Common Stock, par value $0.01 per sha...   

                                               cusip  \
0  Series A Common Stock: 043632 108\nSeries B Co...   

                                communicator_details date_of_event_for_filing  
0  John C. Malone\nc/o Liberty Media Corporation\...         January 22, 2010

In [1112]:
indexes_df.loc[indexes_df['file_name'] == 'edgar/data/937797/0000950123-10-006037.txt']

file_name                  document  \
458250  edgar/data/937797/0000950123-10-006037.txt  0000950123-10-006037.txt   

       form_type  title_page_end_lower_bound  cover_page_q1_start  \
458250  SC 13D/A                        1872                 2035   

       is_rep_q_as_items is_schedule_to has_table_of_contents  \
458250             False          False                 False   

        num_cusip_sedol_b_q1  cover_page_start   ...    cover_page_last_q_end  \
458250                     3              1979   ...                   3406.0   

        cover_page_end  num_cusip_b_items  signature_start  exhibit_start  \
458250            5558                  3            11500             -1   

        main_text_length  explanatory_statement_start  has_jumbled_order  \
458250             11939                         5814              False   

       has_exhibit_break success  
458250             False    True  

[1 rows x 21 columns]

In [1105]:
indexes_df.loc[indexes_df['file_name'] == 'edgar/data/5405/0000950123-94-000784.txt']

file_name                  document  \
414532  edgar/data/5405/0000950123-94-000784.txt  0000950123-94-000784.txt   

       form_type  title_page_end_lower_bound  cover_page_q1_start  \
414532    SC 13G                        1920                 2093   

       is_rep_q_as_items is_schedule_to has_table_of_contents  \
414532             False          False                 False   

        num_cusip_sedol_b_q1  cover_page_start   ...    cover_page_last_q_end  \
414532                     2              1977   ...                   3432.0   

        cover_page_end  num_cusip_b_items  signature_start  exhibit_start  \
414532            3549                  2             8628             -1   

        main_text_length  explanatory_statement_start  has_jumbled_order  \
414532              9851                           -1              False   

       has_exhibit_break success  
414532             False    True  

[1 rows x 21 columns]

In [1172]:
indexes_df.loc[indexes_df['file_name'] == 'edgar/data/1070732/0001193125-14-430819.txt']

file_name                  document  \
362097  edgar/data/1070732/0001193125-14-430819.txt  0001193125-14-430819.txt   

       form_type  title_page_end_lower_bound  cover_page_q1_start  \
362097  SC 13G/A                        1536                 1552   

       is_rep_q_as_items is_schedule_to has_table_of_contents  \
362097             False          False                 False   

        num_cusip_sedol_b_q1  cover_page_start   ...    cover_page_last_q_end  \
362097                     1              1552   ...                   2767.0   

        cover_page_end  num_cusip_b_items  signature_start  exhibit_start  \
362097            3313                  2             6940             -1   

        main_text_length  explanatory_statement_start  has_jumbled_order  \
362097              8199                           -1              False   

       has_exhibit_break success  
362097             False    True  

[1 rows x 21 columns]

In [1200]:
regex = '\sIF\s+THE\s+FILING\s+PERSON\s+HAS\s+PREVIOUSLY\s+FILED\s+A\s+STATEMENT\s+ON\s+SCHEDULE\s+13G' +\
    '\s+TO\s+REPORT\s+THE\s+ACQUISITION\s+THAT\s+IS\s+THE\s+SUBJECT\s+OF\s+THIS\s+SCHEDULE\s+13D,\s+' +\
    'AND\s+IS\s+FILING\s+THIS\s+SCHEDULE\s+BECAUSE\s+OF\s+RULE\s+13D-1\(E\),\s+13D-1\(F\)\s+OR' +\
    '\s+13D-1\(G\),\s+CHECK\s+THE\s+FOLLOWING\s+BOX(.)+\n'

re.search(regex, text.upper()).group(0)

' IF THE FILING PERSON HAS PREVIOUSLY FILED A STATEMENT ON SCHEDULE 13G\nTO REPORT THE ACQUISITION THAT IS THE SUBJECT OF THIS SCHEDULE 13D, AND IS\nFILING THIS SCHEDULE BECAUSE OF RULE 13D-1(E), 13D-1(F) OR 13D-1(G), CHECK THE\nFOLLOWING BOX |_|.\n'

In [1202]:
re.search('X', re.findall(regex, text.upper())[0])

In [1191]:
indexes_df.loc[indexes_df['form_type'] == 'SC 13D']

file_name  \
2        edgar/data/1163453/0001019687-04-000771.txt   
32       edgar/data/1050377/0001193125-04-068397.txt   
48        edgar/data/904534/0001144204-04-005373.txt   
71        edgar/data/878556/0000919574-04-001218.txt   
72       edgar/data/1284771/0001140905-04-000047.txt   
75       edgar/data/1265816/0000919574-04-001338.txt   
82       edgar/data/1085869/0001193125-04-059071.txt   
86       edgar/data/1260182/0001005150-04-001649.txt   
103      edgar/data/1275323/0000909518-04-000358.txt   
120      edgar/data/1280496/0001015402-04-002477.txt   
123      edgar/data/1013746/0000950142-04-001802.txt   
135      edgar/data/1227728/0001193125-04-062424.txt   
136      edgar/data/1274520/0001177456-04-000209.txt   
140      edgar/data/1133256/0001193125-04-099611.txt   
145      edgar/data/1288341/0001193125-04-103757.txt   
146      edgar/data/1227728/0000921530-04-000245.txt   
160      edgar/data/1272801/0001144204-04-004534.txt   
161       edgar/data/795615/0001047469-04-021069.txt   
174      edgar/data/1075628/0001169232-04-003420.txt   
181      edgar/data/1047537/0000943374-04-000308.txt   
187      edgar/data/1292348/0001108017-04-000314.txt   
189      edgar/data/1061464/0001061464-04-000010.txt   
206       edgar/data/354383/0000905729-04-000162.txt   
218      edgar/data/1295315/0001123292-04-000291.txt   
220      edgar/data/1289297/0000921530-04-000245.txt   
225       edgar/data/899881/0001035704-04-000300.txt   
234      edgar/data/1122322/0001193125-04-090192.txt   
237       edgar/data/857073/0001210052-04-000022.txt   
241      edgar/data/1295249/0001144204-04-008961.txt   
246      edgar/data/1287361/0001062993-04-000848.txt   
...                                              ...   
1368032  edgar/data/1018519/0000950123-98-004925.txt   
1368105  edgar/data/1401412/0001213900-19-009859.txt   
1368111   edgar/data/903213/0000892569-98-002739.txt   
1368112   edgar/data/904571/0001047469-98-043104.txt   
1368118  edgar/data/1626127/0000919574-18-003203.txt   
1368158   edgar/data/939318/0000941302-98-000083.txt   
1368170  edgar/data/1049429/0000950133-98-003149.txt   
1368171   edgar/data/845577/0000897423-98-000162.txt   
1368174   edgar/data/934979/0000934979-98-000013.txt   
1368177  edgar/data/1490281/0001140361-19-023397.txt   
1368208   edgar/data/706116/0000927016-98-004348.txt   
1368209  edgar/data/1072617/0000891618-98-004590.txt   
1368220  edgar/data/1068592/0000950123-98-007810.txt   
1368223  edgar/data/1072386/0001047469-98-038061.txt   
1368225   edgar/data/914329/0000950135-98-006236.txt   
1368231  edgar/data/1056477/0000950133-98-002545.txt   
1368235  edgar/data/1502541/0001213900-19-019892.txt   
1368245   edgar/data/313143/0000938775-97-000018.txt   
1368247  edgar/data/1054263/0000950172-98-000822.txt   
1368248  edgar/data/1002813/0001061693-98-000002.txt   
1368250   edgar/data/943658/0000949111-98-000031.txt   
1368260  edgar/data/1510295/0001510295-18-000082.txt   
1368262  edgar/data/1189136/0001104659-18-025663.txt   
1368281   edgar/data/350129/0000950147-98-000540.txt   
1368285  edgar/data/1792243/0001599916-19-000152.txt   
1368287  edgar/data/1386809/0001144204-07-024379.txt   
1368308  edgar/data/1058854/0001058854-18-000024.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   

                         document form_type  title_page_end_lower_bound  \
2        0001019687-04-000771.txt    SC 13D                           1   
32       0001193125-04-068397.txt    SC 13D                        1383   
48       0001144204-04-005373.txt    SC 13D                           1   
71       0000919574-04-001218.txt    SC 13D                        2701   
72       0001140905-04-000047.txt    SC 13D                        1854   
75       0000919574-04-001338.txt    SC 13D                        2505   
82       0001193125-04-059071.txt    SC 13D  

In [1553]:
prev_13g_filed(text)

True

In [1552]:
i = 82
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13D
1
dsc13d.htm
SCHEDULE 13 D


Schedule 13 D

 









 OMB APPROVAL



 OMB Number:
  
3235-0145



 Expires:
  
December 31, 2005



 Estimated average burden

 hours per response . . . 11


       UNITED STATES  SECURITIES AND EXCHANGE COMMISSION  Washington, D.C. 20549      SCHEDULE 13D      Under The Securities Exchange Act of 1934  (Amendment
No.            )*          PERFICIENT, INC.  (Name of Issuer)      Common Stock  (Title of Class of Securities)      71375U 101  (CUSIP Number)      Morton H. Meyerson  3401 Armstrong Ave.  Dallas, Texas 75205  (214) 443-1945  (Name, Address and Telephone Number of Person Authorized to Receive Notices and Communications)      April 6, 2004  (Date of Event which Requires Filing of this Statement)
   If the filing person has previously filed a statement on Schedule 13G to
report the acquisition that is the subject of this Schedule 13D, and is filing this schedule because of Sections 240.13d-1(e), 240.13d-1(f) or 240.13d-1(g), check the

In [1256]:
text_raised = text.upper()
    
regex = '\sIF\s+THE\s+FILING\s+PERSON\s+HAS\s+PREVIOUSLY\s+FILED\s+A\s+STATEMENT\s+ON\s+SCHEDULE\s+13G' +\
'\s+TO\s+REPORT\s+THE\s+ACQUISITION\s+(?:THAT|WHICH)\s+IS\s+THE\s+SUBJECT\s+OF\s+THIS\s+SCHEDULE\s+13D,\s+' +\
'AND\s+IS\s+FILING\s+THIS\s+SCHEDULE\s+BECAUSE\s+OF\s+RULE[S]?\s+13D-1\(E\),\s+13D-1\(F\)[,]?\s+OR' +\
'\s+13D-1\(G\),\s+CHECK\s+THE\s+FOLLOWING\s+BOX(.+)(?:\n|$|[A-Z]{3})'

re.findall(regex, text_raised)[0]

'.\xa0\xa0¨'

In [1355]:
re.findall(regex, text.upper())

['.\xa0\xa0X  \xa0 NOTE: SCHEDULES FILED IN PAPER FORMAT SHALL INCLUDE A SIGNED ORIGINAL AND FIVE COPIES OF THE']

In [1354]:
regex = '\s+BECAUSE\s+OF\s+(?:SECTION|RULE)[S]?\s+(?:240\s*\.\s*)?13[\-]?[\(]?D[\)]?[\-]?1[\(]?E[\)]?,' + \
    '\s+(?:240\s*\.\s*)?13[\-]?[\(]?D[\)]?[\-]?1[\(]?F[\)]?[,]?\s+OR\s+' + \
    '(?:240\s*\.\s*)?13[\-]?[\(]?D[\)]?[\-]?1[\(]?G[\)]?,\s+CHECK\s+THE\s+' + \
    'FOLLOWING\s+BOX(.+)(?:\n|$)'

In [1359]:
print(text.upper())


SC 13D
1
DSC13D.HTM
SCHEDULE 13 D


SCHEDULE 13 D

 









 OMB APPROVAL



 OMB NUMBER:
  
3235-0145



 EXPIRES:
  
DECEMBER 31, 2005



 ESTIMATED AVERAGE BURDEN

 HOURS PER RESPONSE . . . 11


       UNITED STATES  SECURITIES AND EXCHANGE COMMISSION  WASHINGTON, D.C. 20549      SCHEDULE 13D      UNDER THE SECURITIES EXCHANGE ACT OF 1934  (AMENDMENT
NO.            )*          PERFICIENT, INC.  (NAME OF ISSUER)      COMMON STOCK  (TITLE OF CLASS OF SECURITIES)      71375U 101  (CUSIP NUMBER)      MORTON H. MEYERSON  3401 ARMSTRONG AVE.  DALLAS, TEXAS 75205  (214) 443-1945  (NAME, ADDRESS AND TELEPHONE NUMBER OF PERSON AUTHORIZED TO RECEIVE NOTICES AND COMMUNICATIONS)      APRIL 6, 2004  (DATE OF EVENT WHICH REQUIRES FILING OF THIS STATEMENT)
   IF THE FILING PERSON HAS PREVIOUSLY FILED A STATEMENT ON SCHEDULE 13G TO
REPORT THE ACQUISITION THAT IS THE SUBJECT OF THIS SCHEDULE 13D, AND IS FILING THIS SCHEDULE BECAUSE OF SECTIONS 240.13D-1(E), 240.13D-1(F) OR 240.13D-1(G), CHECK THE

In [1297]:
text

'\nSC 13D\n1\ndsc13d.htm\nSCHEDULE 13 D\n\n\nSchedule 13 D\n\n \n\n\n\n\n\n\n\n\n\n OMB APPROVAL\n\n\n\n OMB Number:\n\xa0\xa0\n3235-0145\n\n\n\n Expires:\n\xa0\xa0\nDecember\xa031,\xa02005\n\n\n\n Estimated\xa0average\xa0burden\n\n hours per response\xa0.\xa0.\xa0. 11\n\n\n \xa0 \xa0 \xa0 UNITED STATES  SECURITIES AND EXCHANGE COMMISSION  Washington, D.C. 20549  \xa0 \xa0 SCHEDULE 13D  \xa0 \xa0 Under The Securities Exchange Act of 1934  (Amendment\nNo.\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0)*  \xa0 \xa0 \xa0 \xa0 PERFICIENT, INC.  (Name of Issuer)  \xa0 \xa0 Common Stock  (Title of Class of Securities)  \xa0 \xa0 71375U 101  (CUSIP Number)  \xa0 \xa0 Morton H. Meyerson  3401 Armstrong Ave.  Dallas, Texas 75205  (214) 443-1945  (Name, Address and Telephone Number of Person Authorized to Receive Notices and Communications)  \xa0 \xa0 April 6, 2004  (Date of Event which Requires Filing of this Statement)\n \xa0 If the filing person has previously filed a statement on Schedule 1

In [1295]:
i = 82
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13D
1
dsc13d.htm
SCHEDULE 13 D


Schedule 13 D

 









 OMB APPROVAL



 OMB Number:
  
3235-0145



 Expires:
  
December 31, 2005



 Estimated average burden

 hours per response . . . 11


       UNITED STATES  SECURITIES AND EXCHANGE COMMISSION  Washington, D.C. 20549      SCHEDULE 13D      Under The Securities Exchange Act of 1934  (Amendment
No.            )*          PERFICIENT, INC.  (Name of Issuer)      Common Stock  (Title of Class of Securities)      71375U 101  (CUSIP Number)      Morton H. Meyerson  3401 Armstrong Ave.  Dallas, Texas 75205  (214) 443-1945  (Name, Address and Telephone Number of Person Authorized to Receive Notices and Communications)      April 6, 2004  (Date of Event which Requires Filing of this Statement)
   If the filing person has previously filed a statement on Schedule 13G to
report the acquisition that is the subject of this Schedule 13D, and is filing this schedule because of Sections 240.13d-1(e), 240.13d-1(f) or 240.13d-1(g), check the

In [1274]:
regex = '\s+BECAUSE\s+OF\s+(?:RULE[S]?\s+13[\-]?[\(]?D[\)]?[\-]?1[\(]?E[\)]?,\s+13[\-]?[\(]?D[\)]?[\-]?1[\(]?F[\)]?\s+OR' +\
    '\s+13[\-]?[\(]?D[\)]?[\-]?1[\(]?G[\)]?,\s+CHECK\s+THE\s+FOLLOWING\s+BOX(.+)(?:\n|$)'

In [1238]:
text[-1]

'¨'

In [1192]:
i = 2
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/1163453/0001019687-04-000771.txt  0001019687-04-000771.txt   

  form_type amendment_number      issuer_name  \
0    SC 13D             None  Aqua Dyne, Inc.   

                            security_class      cusip  \
0  Common Stock, par value $.001 per share  03840K202   

                                communicator_details date_of_event_for_filing  
0  Greg Paxton\n                           Global...           March 31, 2001

In [1534]:
regex = 'PREVIOUSLY\s+FILED(?:(.)*)(?:SCHEDULE\s+|SC\s+)?13G(?:(.)*)CHECK\s+' + \
            '(?:T)?HE\s+FOLLOWING\s+BOX(?:\.)?\s*(.*)(?:\n|$)'
re.search(regex, text.upper())

In [ ]:
i = 82
t = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)

In [1535]:
text.upper()

'\nSC 13D\n1\nGLOBALPOWER_13D-040504.TXT\n\n\n\n                       SECURITIES AND EXCHANGE COMMISSION\n                             WASHINGTON, D.C. 20549\n\n                                  SCHEDULE 13D\n                                 (RULE 13D-101)\n\n             INFORMATION TO BE INCLUDED IN STATEMENTS FILED PURSUANT\n            TO RULE 13D-1(A) AND AMENDMENTS THERETO FILED PURSUANT TO\n                                  RULE 13D-2(A)\n\n                                 AQUA DYNE, INC.\n- --------------------------------------------------------------------------------\n                                (NAME OF ISSUER)\n\n                     COMMON STOCK, PAR VALUE $.001 PER SHARE\n- --------------------------------------------------------------------------------\n                         (TITLE AND CLASS OF SECURITIES)\n\n                                    03840K202\n- --------------------------------------------------------------------------------\n                        

In [1537]:
def prev_13g_filed(text):
    
    text_raised = text.upper()
    
    regex = 'CHECK\s+(?:T)?HE\s+FOLLOWING\s+BOX(?:\.)?\s*(.*)(?:\n|$)'

    
    box = re.findall(regex, text_raised)[0]
    
    if(re.search('X', box) is not None):
        
        return(True)
    
    else:
        return(False)


In [1174]:
eg.loc[0]

file_name                   edgar/data/1070732/0001193125-14-430819.txt
document                                       0001193125-14-430819.txt
form_type                                                      SC 13G/A
amendment_number                                                      5
issuer_name                            Eaton Vance\nSenior Income Trust
security_class                                  Auction Preferred Stock
cusip                                              27826S202  27826S301
date_of_event_for_filing                              November 28, 2014
Name: 0, dtype: object

In [1177]:
re.findall('[A-Z0-9]{6,9}', eg.loc[0, 'cusip'])

['27826S202', '27826S301']

In [1555]:
def get_prev_13g_filed_box(text):
    
    text_raised = text.upper()

    regex = 'CHECK\s+(?:T)?HE\s+FOLLOWING\s+BOX(?:\.)?\s*(.*)(?:\n|$)'

    results = re.findall(regex, text_raised)

    if(len(results)):

        box = results[0]

        if(re.search('X', box) is not None):

            return(True)

        else:
            return(False)
 

def prev_13g_filed(text, form_type):
    
    if(re.search('SC 13D', form_type)):
    
        if(not is_rep_q_as_items):
            
            return(get_prev_13g_filed_box(text))
            
    else:
        
        return(False)

In [1567]:
Check the appropriate box to designate the rule pursuant to which this Schedule
is filed:
[X] Rule 13d-1(b)
[  ] Rule 13d-1(c)
[  ] Rule 13d-1(d)

regex = 'CHECK\s+THE\s+APPROPRIATE\s+BOX\s+TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+TO\s+WHICH\s+' + \
        'THIS\s+SCHEDULE\s+IS\s+FILED:\s*(.*)RULE\s+13D-1\s*[\(]?B[\)]?\s+(.*)RULE\s+13D-1\s*[\(]?C[\)]?\s+' + \
        '(.*)RULE\s+13D-1\s*[\(]?B[\)]?\s*(?:\n|$)'

SyntaxError: invalid syntax (<ipython-input-1567-dc5ce578cfe9>, line 1)

In [1751]:
regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+TO\s+WHICH\s+' + \
            'THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)'
boxes = re.findall(regex, t.upper(), re.DOTALL)[0]
boxes

('X\n\t', 'B', '', 'C', 'O\n\t', 'C')

In [1752]:
ind_l = [boxes[1], boxes[3], boxes[5]]
ind_l

['B', 'C', 'C']

In [ ]:
rule_13_d1_b = (re.search('[Xý]', boxes[0]) is not None)
    rule_13_d1_c = (re.search('[Xý]', boxes[1]) is not None)
    rule_13_d1_d = (re.search('[Xý]', boxes[2]) is not None)

In [1753]:
rule_13_d1_b = False
rule_13_d1_c = False
rule_13_d1_d = False

for i in range(len(ind_l)):
    
    if(ind_l[i] == 'B'):
        
        rule_13_d1_b = rule_13_d1_b or (re.search('[Xý]', boxes[2 * i]) is not None)
        
    elif(ind_l[i] == 'C'):
        
        rule_13_d1_c = rule_13_d1_c or (re.search('[Xý]', boxes[2 * i]) is not None)
        
    elif(ind_l[i] == 'D'):
        
        rule_13_d1_d = rule_13_d1_d or (re.search('[Xý]', boxes[2 * i]) is not None)
        
(rule_13_d1_b, rule_13_d1_c, rule_13_d1_d)

(True, False, False)

In [1583]:
regex = 'CHECK\s+THE\s+APPROPRIATE\s+BOX\s+TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+TO\s+WHICH\s+' + \
        'THIS\s+SCHEDULE\s+IS\s+FILED:\s*(.*)RULE\s+13D-1\s*[\(\|]?B[\)\|]?\s+(.*)RULE\s+13D-1\s*[\(\|]?C[\)\|]?\s+' + \
        '(.*)RULE\s+13D-1\s*[\(\|]?D[\)\|]?\s*(?:\n|$)'

re.findall(regex, t.upper(), re.DOTALL)

[('[\nX \n]\xa0\xa0', '[\nX \n]\xa0\xa0', '[\n\n]\xa0\xa0')]

In [1780]:
regex = 'RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
        '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
        '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)'
        
search = re.search(regex, t.upper())
search

<re.Match object; span=(411, 465), match='RULE 13D-1(B)\nÝ\xa0\xa0RULE 13D-1(C)\n¨\xa0\xa0R>

In [ ]:
re.search()

In [1798]:
t.upper()[0:search.start()][::-1]

'\xa0\xa0¨\n\xa0\n)TNEMETATS SIHT FO GNILIF SERIUQER HCIHW TNEVE FO ETAD(\n4002 ,91 HCRAM\n\xa0\n)REBMUN PISUC(\n601046907\n\xa0\n)SEITIRUCES FO SSALC FO ELTIT(\nKCOTS NOMMOC\n\xa0\n)REUSSI FO EMAN(\n.CNI ,LANOITANRETNI ESUOHTNEP\n\xa0\n*)___ .ON TNEMDNEMA(\n4391 FO TCA EGNAHCXE SEITIRUCES EHT REDNU\nG31 ELUDEHCS\n\xa0\n94502 .C.D ,NOTGNIHSAW\nNOISSIMMOC EGNAHCXE DNA SEITIRUCES\nSETATS DETINU\n\n\n\nG31 CS\n\n\n\nG31 ELUDEHCS\nMTH.G31ESUOHTNEPROTACREM\n1\nG31 CS\n'

In [1817]:
regex = '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
        '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
        '(.*)RULE\s+13D\s*-\s*1\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)'
        
boxes = re.findall(regex, t.upper()[(search.start() - num_back):], re.DOTALL)[0]
boxes

('\n¨\xa0\xa0', 'B', 'Ý\xa0\xa0', 'C', '¨\xa0\xa0', 'D')

In [1809]:
num_back = re.search('\n', t.upper()[0:search.start()][::-1]).end()
num_back

4

In [1810]:
t.upper()[(search.start() - num_back):]

'\n¨\xa0\xa0RULE 13D-1(B)\nÝ\xa0\xa0RULE 13D-1(C)\n¨\xa0\xa0RULE 13D-1(D)\n\n\n\n\n\n\nSCHEDULE 13G'

In [2347]:
def get_rules_pursuant_to_13g_boxes_fixed_num(text, num_boxes):
    
    text_raised = text.upper()
    
    if(num_boxes == 3):
    
        regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+' + \
            'TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

        boxes_list = re.findall(regex, text_raised, re.DOTALL)

        if(len(boxes_list)):

            boxes = boxes_list[0]

        else:

            regex = 'RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'


            search = re.search(regex, text_raised)
            num_back = re.search('\n', text_raised[0:search.start()][::-1]).end()

            regex = '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

            boxes = re.findall(regex, text_raised[(search.start() - num_back):], re.DOTALL)[0]
            
    elif(num_boxes == 2):
        
        regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+' + \
        'TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*' + \
        '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
        '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

        boxes_list = re.findall(regex, text_raised, re.DOTALL)

        if(len(boxes_list)):

            boxes = boxes_list[0]

        else:

            regex = 'RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'


            search = re.search(regex, text_raised)
            num_back = re.search('\n', text_raised[0:search.start()][::-1]).end()

            regex = '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

            boxes = re.findall(regex, text_raised[(search.start() - num_back):], re.DOTALL)[0]
            
    elif(num_boxes == 1):
        
        
        regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+' + \
        'TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*' + \
        '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

        boxes_list = re.findall(regex, text_raised, re.DOTALL)

        if(len(boxes_list)):

            boxes = boxes_list[0]

        else:

            regex = 'RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'


            search = re.search(regex, text_raised)
            num_back = re.search('\n', text_raised[0:search.start()][::-1]).end()

            regex = '(.*)RULE\s+13D\s*-\s*[1]?\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

            boxes = re.findall(regex, text_raised[(search.start() - num_back):], re.DOTALL)[0]
            
    else:
        
        boxes = None
            
    return(boxes)

In [1911]:
def get_rules_pursuant_to_13g_boxes(text):
    
    try:
        boxes = get_rules_pursuant_to_13g_boxes_fixed_num(text, 3)
        return(boxes)
        
    except:
        
        try:
            boxes = get_rules_pursuant_to_13g_boxes_fixed_num(text, 2)
            return(boxes)
        
        except:
            
            try:
                boxes = get_rules_pursuant_to_13g_boxes_fixed_num(text, 1)
                return(boxes)
                
            except:
                
                return(None)

In [1905]:
[i for i in range(0, 2, 2)]

[0]

In [1925]:
ind_l = [boxes[i] for i in range(1, len(boxes), 2)]
ind_l

['B']

In [1922]:
re.search('[XÝý]', boxes[2 * 0])

<re.Match object; span=(1, 2), match='X'>

In [1918]:
boxes[2 * 0]

'\n¨\xa0\xa0'

In [2104]:
get_rules_pursuant_to_13g(m)

(False, False, True)

In [2450]:
def get_rules_pursuant_to_13g(text):
    
    text_raised = text.upper()
    
    boxes = get_rules_pursuant_to_13g_boxes(text)

    ind_l = [boxes[i] for i in range(1, len(boxes), 2)]

    rule_13_d1_b = False
    rule_13_d1_c = False
    rule_13_d1_d = False

    for i in range(len(ind_l)):

        if(ind_l[i] == 'B'):

            rule_13_d1_b = rule_13_d1_b or (re.search('[XÝý1Þ]', boxes[2 * i]) is not None)

        elif(ind_l[i] == 'C'):

            rule_13_d1_c = rule_13_d1_c or (re.search('[XÝý1Þ]', boxes[2 * i]) is not None)

        elif(ind_l[i] == 'D'):

            rule_13_d1_d = rule_13_d1_d or (re.search('[XÝý1Þ]', boxes[2 * i]) is not None)
            
    if((not (rule_13_d1_b or rule_13_d1_c or rule_13_d1_d)) and len(boxes) <= 2):
        # Assume short form
        
        search_b = re.search('\nRULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*B\s*[\)\|]?\s*\n', text_raised)
        search_c = re.search('\nRULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*C\s*[\)\|]?\s*\n', text_raised)
        search_d = re.search('\nRULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*D\s*[\)\|]?\s*\n', text_raised)
        
        if(search_b):
            
            rule_13_d1_b = True
            
        if(search_c):
            
            rule_13_d1_c = True
            
        if(search_d):
            
            rule_13_d1_d = True


    return(rule_13_d1_b, rule_13_d1_c, rule_13_d1_d)
    
    
    
    

In [2286]:
print('Þ')

Þ


In [2117]:
get_rules_pursuant_to_13g_boxes(m)

('O\n  \n  \n  ', 'B', 'O\n  \n  \n  ', 'C', 'O\n  \n  \n  ', 'D')

In [ ]:
except:
        regex_b = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+' + \
        'PURSUANT\s+TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+' + \
        '13D\s*-\s*1\s*[\(\|]?\s*B\s*[\)\|]?\s+'
        
        regex_c = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+' + \
        'PURSUANT\s+TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+' + \
        '13D\s*-\s*1\s*[\(\|]?\s*C\s*[\)\|]?\s+'
        
        regex_d = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+' + \
        'PURSUANT\s+TO\s+WHICH\s+THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+' + \
        '13D\s*-\s*1\s*[\(\|]?\s*D\s*[\)\|]?\s+'
        
        search_b = re.findall(regex_b, text_raised) 
        search_c = re.findall(regex_c, text_raised) 
        search_d = re.findall(regex_d, text_raised)
        
        if(search_b is not None):
            
            rule_13_d1_b = (re.search('X', boxes[0]) is not None)
        

In [ ]:
else:
        
        full_text_upper = 
        
        regex_b = 'THIS\s+STATEMENT\s+IS\s+FILED\s+PURSUANT\s+TO\s+RULE\s+13D-1(b)'

In [2073]:
def get_title_page(file_name, document, directory, cover_page_start, cover_page_q1_start, title_page_end_lower_bound, num_cusip_sedol_b_q1):
    
    if(cover_page_start > 0):
        if(num_cusip_sedol_b_q1 <= 1):
            text = get_main_doc_text(file_name, document, directory)[:cover_page_q1_start]
        else:
            text = get_main_doc_text(file_name, document, directory)[:cover_page_start]
        return(text)
    else:
        if(cover_page_q1_start > 0):
            
            text = get_main_doc_text(file_name, document, directory)[:cover_page_q1_start]
            
        else:
            
            if(title_page_end_lower_bound):
                
                text = get_main_doc_text(file_name, document, directory)[:title_page_end_lower_bound]
                
            else:
                
                text = None
                
    return(text)

In [1556]:
indexes_df.loc[np.logical_or(indexes_df['form_type'] == 'SC 13G', indexes_df['form_type'] == 'SC 13G/A')]

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
34       edgar/data/1135338/0000902664-04-000933.txt   
37       edgar/data/1135338/0001283411-04-000005.txt   
38       edgar/data/1135338/0001283411-04-000012.txt   
39       edgar/data/1135338/0001283411-04-000013.txt   
42        edgar/data/884300/0000884300-04-000036.txt   
43        edgar/data/884300/0000884300-04-000033.txt   
44        edgar/data/884300/0000884300-04-000039.txt   
46       edgar/data/1040261/0001193125-04-088739.txt   
49       edgar/data/1164123/0001141218-04-000038.txt   
50       edgar/data/1164123/0001141218-04-000039.txt   
52         edgar/data/77449/0000315066-04-001429.txt   
61       edgar/data/1084569/0000950124-04-001981.txt   
62       edgar/data/1084569/0000950124-04-002902.txt   
70       edgar/data/1071955/0001071955-04-000071.txt   
73       edgar/data/1057083/0001058854-04-000102.txt   
83        edgar/data/771992/0001013594-04-000142.txt   
...                                              ...   
1368320  edgar/data/1364742/0000215457-19-003079.txt   
1368321    edgar/data/49754/0000315066-19-000981.txt   
1368322  edgar/data/1070732/0001214659-19-001245.txt   
1368325  edgar/data/1507640/0001172661-11-000254.txt   
1368326  edgar/data/1271375/0001193125-12-059659.txt   
1368327  edgar/data/1364742/0000215457-19-001480.txt   
1368328  edgar/data/1364742/0000215457-19-001593.txt   
1368329  edgar/data/1364742/0000215457-19-001612.txt   
1368330  edgar/data/1364742/0000215457-19-002280.txt   
1368331  edgar/data/1524931/0000215457-19-000919.txt   
1368332  edgar/data/1125920/0000215457-19-002604.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368334   edgar/data/893691/0000215457-19-004906.txt   
1368335  edgar/data/1104186/0000919574-19-001286.txt   
1368336  edgar/data/1118417/0001104659-19-008720.txt   
1368337  edgar/data/1201792/0001037389-19-000146.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368339  edgar/data/1621563/0000807985-19-000028.txt   
1368340  edgar/data/1395064/0001104659-19-060139.txt   
1368346  edgar/data/1581164/0001104659-19-071304.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   
1368349  edgar/data/1320854/0001085146-19-000414.txt   
1368350  edgar/data/1430308/0001214659-19-000763.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368352   edgar/data/862831/0000215457-19-004043.txt   
1368353  edgar/data/1045810/0000215457-19-004826.txt   
1368354  edgar/data/1564584/0000895421-19-000289.txt   
1368357  edgar/data/1655020/0001144204-19-008356.txt   
1368360  edgar/data/1560258/0001193125-19-297684.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G                        1220   
7        0001035674-04-000008.txt    SC 13G  

In [1927]:
get_rules_pursuant_to_13g(t)

(True, False, False)

In [2247]:
regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+TO\s+WHICH\s+' + \
            'THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

In [ ]:
get_rules_pursuant_to_13g(text)

This statement is filed pursuant to Rule 13d-1(b)

In [1966]:
sc13g_df = indexes_df.loc[np.logical_and(np.logical_or(indexes_df['form_type'] == 'SC 13G',\
                            indexes_df['form_type'] == 'SC 13G/A'), indexes_df['success'] == True)].copy().reset_index(drop = True)

In [1967]:
sc13g_df

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2         edgar/data/897484/0001144204-04-008811.txt   
3        edgar/data/1035674/0001035674-04-000005.txt   
4        edgar/data/1035674/0001035674-04-000006.txt   
5         edgar/data/704159/0001015402-04-001460.txt   
6        edgar/data/1035674/0001035674-04-000008.txt   
7        edgar/data/1120914/0001056568-04-000061.txt   
8         edgar/data/893949/0000814133-04-000115.txt   
9        edgar/data/1064728/0000902219-04-001079.txt   
10        edgar/data/704159/0001015402-04-001462.txt   
11       edgar/data/1064728/0000315066-04-001678.txt   
12         edgar/data/75681/0000065103-04-000134.txt   
13       edgar/data/1068878/0001068878-04-000003.txt   
14       edgar/data/1135338/0000902664-04-000933.txt   
15       edgar/data/1135338/0001283411-04-000005.txt   
16       edgar/data/1135338/0001283411-04-000012.txt   
17       edgar/data/1135338/0001283411-04-000013.txt   
18        edgar/data/884300/0000884300-04-000036.txt   
19        edgar/data/884300/0000884300-04-000033.txt   
20        edgar/data/884300/0000884300-04-000039.txt   
21       edgar/data/1040261/0001193125-04-088739.txt   
22       edgar/data/1164123/0001141218-04-000038.txt   
23       edgar/data/1164123/0001141218-04-000039.txt   
24         edgar/data/77449/0000315066-04-001429.txt   
25       edgar/data/1084569/0000950124-04-001981.txt   
26       edgar/data/1084569/0000950124-04-002902.txt   
27       edgar/data/1071955/0001071955-04-000071.txt   
28       edgar/data/1057083/0001058854-04-000102.txt   
29        edgar/data/771992/0001013594-04-000142.txt   
...                                              ...   
1003373  edgar/data/1364742/0000215457-19-003079.txt   
1003374    edgar/data/49754/0000315066-19-000981.txt   
1003375  edgar/data/1070732/0001214659-19-001245.txt   
1003376  edgar/data/1507640/0001172661-11-000254.txt   
1003377  edgar/data/1271375/0001193125-12-059659.txt   
1003378  edgar/data/1364742/0000215457-19-001480.txt   
1003379  edgar/data/1364742/0000215457-19-001593.txt   
1003380  edgar/data/1364742/0000215457-19-001612.txt   
1003381  edgar/data/1364742/0000215457-19-002280.txt   
1003382  edgar/data/1524931/0000215457-19-000919.txt   
1003383  edgar/data/1125920/0000215457-19-002604.txt   
1003384  edgar/data/1697828/0001104659-19-008126.txt   
1003385   edgar/data/893691/0000215457-19-004906.txt   
1003386  edgar/data/1104186/0000919574-19-001286.txt   
1003387  edgar/data/1118417/0001104659-19-008720.txt   
1003388  edgar/data/1201792/0001037389-19-000146.txt   
1003389   edgar/data/820478/0000820478-19-000033.txt   
1003390  edgar/data/1621563/0000807985-19-000028.txt   
1003391  edgar/data/1395064/0001104659-19-060139.txt   
1003392  edgar/data/1581164/0001104659-19-071304.txt   
1003393   edgar/data/315066/0000315066-19-001394.txt   
1003394   edgar/data/315066/0000315066-19-001396.txt   
1003395  edgar/data/1320854/0001085146-19-000414.txt   
1003396  edgar/data/1430308/0001214659-19-000763.txt   
1003397   edgar/data/937729/0001193125-19-028143.txt   
1003398   edgar/data/862831/0000215457-19-004043.txt   
1003399  edgar/data/1045810/0000215457-19-004826.txt   
1003400  edgar/data/1564584/0000895421-19-000289.txt   
1003401  edgar/data/1655020/0001144204-19-008356.txt   
1003402  edgar/data/1560258/0001193125-19-297684.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001144204-04-008811.txt  SC 13G/A                        1918   
3        0001035674-04-000005.txt    SC 13G                           1   
4        0001035674-04-000006.txt    SC 13G                           1   
5        0001015402-04-001460.txt    SC 13G                        1220   
6        0001035674-04-000008.txt    SC 13G  

In [ ]:
15, 49, 50

In [2474]:
failures = []
df_list = []
for i in range(1000):
    
    j = cover_page_q1_start(get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory))  
    
    t = get_title_page(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'],\
               directory, sc13g_df.loc[i, 'cover_page_start'], j,\
                    sc13g_df.loc[i, 'title_page_end_lower_bound'], sc13g_df.loc[i, 'num_cusip_sedol_b_q1'])
    
    try:
        rule_13_d1_b, rule_13_d1_c, rule_13_d1_d = get_rules_pursuant_to_13g(t)
        
        df = pd.DataFrame({'file_name': [sc13g_df.loc[i, 'file_name']], \
                           'document': [sc13g_df.loc[i, 'document']],\
                           'form_type': [sc13g_df.loc[i, 'form_type']],\
                           'rule_13_d1_b': [rule_13_d1_b],\
                           'rule_13_d1_c': [rule_13_d1_c],
                           'rule_13_d1_d': [rule_13_d1_d]})
        
        df_list.append(df)
        
    except:
        failures.append(i)

rules_13g_bcd_df = pd.concat(df_list, ignore_index = True)

In [2527]:
all(sc13g_df['success'])

True

In [2475]:
rules_13g_bcd_df

file_name                  document  \
0     edgar/data/897484/0001144204-04-004169.txt  0001144204-04-004169.txt   
1     edgar/data/704159/0001015402-04-001458.txt  0001015402-04-001458.txt   
2     edgar/data/897484/0001144204-04-008811.txt  0001144204-04-008811.txt   
3    edgar/data/1035674/0001035674-04-000005.txt  0001035674-04-000005.txt   
4    edgar/data/1035674/0001035674-04-000006.txt  0001035674-04-000006.txt   
5     edgar/data/704159/0001015402-04-001460.txt  0001015402-04-001460.txt   
6    edgar/data/1035674/0001035674-04-000008.txt  0001035674-04-000008.txt   
7    edgar/data/1120914/0001056568-04-000061.txt  0001056568-04-000061.txt   
8    edgar/data/1064728/0000902219-04-001079.txt  0000902219-04-001079.txt   
9     edgar/data/704159/0001015402-04-001462.txt  0001015402-04-001462.txt   
10   edgar/data/1068878/0001068878-04-000003.txt  0001068878-04-000003.txt   
11   edgar/data/1135338/0000902664-04-000933.txt  0000902664-04-000933.txt   
12   edgar/data/1135338/0001283411-04-000005.txt  0001283411-04-000005.txt   
13   edgar/data/1135338/0001283411-04-000012.txt  0001283411-04-000012.txt   
14   edgar/data/1135338/0001283411-04-000013.txt  0001283411-04-000013.txt   
15    edgar/data/884300/0000884300-04-000036.txt  0000884300-04-000036.txt   
16    edgar/data/884300/0000884300-04-000033.txt  0000884300-04-000033.txt   
17    edgar/data/884300/0000884300-04-000039.txt  0000884300-04-000039.txt   
18   edgar/data/1040261/0001193125-04-088739.txt  0001193125-04-088739.txt   
19   edgar/data/1164123/0001141218-04-000038.txt  0001141218-04-000038.txt   
20   edgar/data/1164123/0001141218-04-000039.txt  0001141218-04-000039.txt   
21   edgar/data/1084569/0000950124-04-001981.txt  0000950124-04-001981.txt   
22   edgar/data/1084569/0000950124-04-002902.txt  0000950124-04-002902.txt   
23   edgar/data/1071955/0001071955-04-000071.txt  0001071955-04-000071.txt   
24   edgar/data/1057083/0001058854-04-000102.txt  0001058854-04-000102.txt   
25    edgar/data/771992/0001013594-04-000142.txt  0001013594-04-000142.txt   
26   edgar/data/1228958/0001095449-04-000077.txt  0001095449-04-000077.txt   
27   edgar/data/1072922/0001072922-04-000005.txt  0001072922-04-000005.txt   
28   edgar/data/1162663/0001162663-04-000011.txt  0001162663-04-000011.txt   
29   edgar/data/1162663/0001016964-04-000105.txt  0001016964-04-000105.txt   
..                                           ...                       ...   
662   edgar/data/860644/0000860644-04-000007.txt  0000860644-04-000007.txt   
663  edgar/data/1171759/0001125282-04-000981.txt  0001125282-04-000981.txt   
664   edgar/data/716643/0001140361-04-001005.txt  0001140361-04-001005.txt   
665  edgar/data/1126294/0000888002-04-000574.txt  0000888002-04-000574.txt   
666   edgar/data/910606/0000902219-04-000922.txt  0000902219-04-000922.txt   
667   edgar/data/769874/0001121584-04-000043.txt  0001121584-04-000043.txt   
668   edgar/data/872589/0000950123-04-002024.txt  0000950123-04-002024.txt   
669  edgar/data/1284472/0000919567-04-000032.txt  0000919567-04-000032.txt   
670  edgar/data/1134156/0001104659-04-003984.txt  0001104659-04-003984.txt   
671  edgar/data/1133902/0000913849-04-000093.txt  0000913849-04-000093.txt   
672  edgar/data/1284472/0000919567-04-000033.txt  0000919567-04-000033.txt   
673  edgar/data/1030484/0000892712-04-000225.txt  0000892712-04-000225.txt   
674   edgar/data/868725/0000088525-04-000020.txt  0000088525-04-000020.txt   
675  edgar/data/1169581/0001169232-04-000760.txt  0001169232-04-000760.txt   
676   edgar/data/845818/0000903954-04-000036.txt  0000903954-04-000036.txt   
677   edgar/data/874385/0000898430-04-001290.txt  0000898430-04-001290.txt   
678   edgar/data/874385/0000908737-04-000155.txt  0000908737-04-000155.txt   
679  edgar/data/1113260/0000897069-04-000309.txt  0000897069-04-000309.txt   
680  edgar/data/1045425/0000913414-04-000381.txt  0000913414-04-000381.txt   
681   edgar/data/315852/0000898430-04-001085.txt  0000898430-

In [2476]:
rules_13g_bcd_df.shape[0]

692

In [2477]:
rules_13g_bcd_df['rule_13_d1_b'].sum()

336

In [2478]:
100.00 * rules_13g_bcd_df['rule_13_d1_b'].sum()/rules_13g_bcd_df.shape[0]

48.554913294797686

In [2479]:
rules_13g_bcd_df['rule_13_d1_c'].sum()

284

In [2480]:
rules_13g_bcd_df['rule_13_d1_d'].sum()

66

In [2481]:
100.00 * rules_13g_bcd_df['rule_13_d1_c'].sum()/rules_13g_bcd_df.shape[0]

41.040462427745666

In [2482]:
100.00 * np.logical_or(rules_13g_bcd_df['rule_13_d1_b'], rules_13g_bcd_df['rule_13_d1_c']).sum()/rules_13g_bcd_df.shape[0]

86.99421965317919

In [2483]:
100.00 * np.logical_and(rules_13g_bcd_df['rule_13_d1_b'], rules_13g_bcd_df['rule_13_d1_c']).sum()/rules_13g_bcd_df.shape[0]

2.601156069364162

In [2484]:
100.00 * np.logical_and(rules_13g_bcd_df['rule_13_d1_b'], rules_13g_bcd_df['rule_13_d1_d']).sum()/rules_13g_bcd_df.shape[0]

0.0

In [2485]:
100.00 * np.logical_and(rules_13g_bcd_df['rule_13_d1_c'], rules_13g_bcd_df['rule_13_d1_d']).sum()/rules_13g_bcd_df.shape[0]

0.14450867052023122

In [2237]:
rules_13g_bcd_df.loc[np.logical_and(rules_13g_bcd_df['rule_13_d1_c'], rules_13g_bcd_df['rule_13_d1_d'])]

file_name                  document  \
182  edgar/data/887921/0000898822-04-000275.txt  0000898822-04-000275.txt   

    form_type  rule_13_d1_b  rule_13_d1_c  rule_13_d1_d  
182  SC 13G/A         False          True          True

In [2323]:
rules_13g_bcd_df.loc[np.logical_and(rules_13g_bcd_df['rule_13_d1_b'], rules_13g_bcd_df['rule_13_d1_d'])]

file_name                  document  \
424  edgar/data/1167946/0001193125-04-003615.txt  0001193125-04-003615.txt   
484   edgar/data/933508/0000062741-04-000052.txt  0000062741-04-000052.txt   
606    edgar/data/82811/0000062741-04-000053.txt  0000062741-04-000053.txt   

    form_type  rule_13_d1_b  rule_13_d1_c  rule_13_d1_d  
424  SC 13G/A          True         False          True  
484  SC 13G/A          True         False          True  
606  SC 13G/A          True         False          True

In [2366]:
i = 606
j = cover_page_q1_start(get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory))  
    
t = get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory)[:j]

In [2345]:
get_rules_pursuant_to_13g(t)

(True, False, True)

In [2367]:
get_rules_pursuant_to_13g_boxes(t)

('[X] ', 'B', '[ ] ', 'C', '[ ] ', 'D')

In [2368]:
get_rules_pursuant_to_13g(t)

(True, False, False)

In [2335]:
get_index_url('edgar/data/933508/0000062741-04-000052.txt')

'https://www.sec.gov/Archives/edgar/data/933508/000006274104000052/0000062741-04-000052-index.htm'

In [2338]:
t

'\nSC 13G/A\n1\ndsc13ga.htm\nAMENDMENT NO. 10 TO SCHEDULE 13G\n\n\nAmendment No. 10 to Schedule 13G\n\n \n\n SCHEDULE 13G  \xa0 [ 26,852a] Reg. s240.13d-102(Schedule 13G) Information to be included in  Statements Filed Pursuant to s240.13d-1(b), (c) and (d) and Amendments  Thereto Filed Pursuant to s240.13d-2.  \xa0 SECURITIES AND EXCHANGE COMMISSION  Washington, D.C. 20549  \xa0 SCHEDULE 13G  \xa0 Under the Securities Exchange Act of 1934  (Amendment No. 10)  \xa0 Quilmes Industrial SA  (Name of Issuer)  \xa0 American Depositary Receipts  (Title of Class of Securities)\n \xa0 74838Y108  (CUSIP Number)  \xa0 31st December 2003 –\nAnnual Amendment  (Date of Event Which Requires Filing of this Statement)\n \xa0 Check the appropriate box to designate the rule pursuant to which this\nSchedule is filed:  x Rule 13d-1(b)  ¨ Rule 13d-(c)  ¨ Rule 13d-1(d)  \xa0 * The remainder of this cover page shall be filled out for a reporting person’s initial\nfiling on this form with respect to the subje

In [2324]:
get_index_url('edgar/data/1167946/0001193125-04-003615.txt')

'https://www.sec.gov/Archives/edgar/data/1167946/000119312504003615/0001193125-04-003615-index.htm'

In [2134]:
get_index_url('edgar/data/887921/0000898822-04-000275.txt')

'https://www.sec.gov/Archives/edgar/data/887921/000089882204000275/0000898822-04-000275-index.htm'

In [2129]:
np.logical_and(rules_13g_bcd_df['rule_13_d1_c'], rules_13g_bcd_df['rule_13_d1_d']).sum()

1

In [2322]:
100.00 * np.logical_and(rules_13g_bcd_df['rule_13_d1_b'], np.logical_and(rules_13g_bcd_df['rule_13_d1_c'],\
                                         rules_13g_bcd_df['rule_13_d1_d'])).sum()/rules_13g_bcd_df.shape[0]

0.0

In [2238]:
100.00 * np.logical_and(~rules_13g_bcd_df['rule_13_d1_b'], np.logical_and(~rules_13g_bcd_df['rule_13_d1_c'],\
                                         ~rules_13g_bcd_df['rule_13_d1_d'])).sum()/rules_13g_bcd_df.shape[0]

5.780346820809249

In [2369]:
none_s = np.logical_and(~rules_13g_bcd_df['rule_13_d1_b'], np.logical_and(~rules_13g_bcd_df['rule_13_d1_c'],\
                                         ~rules_13g_bcd_df['rule_13_d1_d']))


                       

In [2137]:
i = 37
m = get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory) 

In [2111]:
re.search('[Xx]', bs[0])

In [2372]:
rules_13g_bcd_df.loc[none_s].shape()

TypeError: 'tuple' object is not callable

In [2374]:
none_s.sum()

35

In [2138]:
bs = get_rules_pursuant_to_13g_boxes(m)
bs

('O\n    \xa0\n    ', 'B', 'O\n    \xa0\n    ', 'C', 'Þ\n    \xa0\n    ', 'D')

In [ ]:
66, 68, 69, 292

In [2309]:
i = 649
m = get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory) 

In [2251]:
re.search(regex, m)

In [2259]:
re.search('1\.\nNAMES OF REPORTING PERSONS', m.upper()).start()

1817

In [2310]:
bs = get_rules_pursuant_to_13g_boxes(m[:1800])
bs

('[]         ', 'B', '[]         ', 'C', '[]         ', 'D')

In [2282]:
re.search('þ', bs[0])

In [2283]:
re.search('Þ', bs[0])

<re.Match object; span=(0, 1), match='Þ'>

In [2308]:
get_rules_pursuant_to_13g(m[:1817])

(False, True, False)

In [2299]:
print(m)


SC 13G/A
1
rnbo.txt

UNITED STATES
SECURITIES AND EXCHANGE COMMISSION
Washington, D.C. 20549

SCHEDULE 13G	Amendment No. 7

(Name of Issuer)
	RAINBOW TECHNOLOGIES INC.

(Title of Class of Securities)
Common Stock

(CUSIP Number)
	750862104

Rule 13d-1(b)

NAME OF REPORTING PERSON
Private Capital Management

I.R.S. IDENTIFICATION NO.
59-3654603

MEMBER OF A GROUP?
(b) X

PLACE OF ORGANIZATION
Delaware

NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH:
SOLE VOTING POWER 	0
SHARED VOTING POWER	3,868,714
SOLE DISPOSITIVE POWER 	0
SHARED DISPOSITIVE POWER 	3,868,714

AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON
	3,868,714

PERCENT OF CLASS REPRESENTED BY AGGREGATE AMOUNT BENEFICIALLY
OWNED
	14.4%

TYPE OF REPORTING PERSON
IA

NAME OF REPORTING PERSON
Bruce S. Sherman

I.R.S. IDENTIFICATION NO.


MEMBER OF A GROUP?
(b) X

CITIZENSHIP
U.S. Citizen

NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH:
SOLE VOTING POWER 	0
SHARED VOTING POWER 	3,8

In [2219]:
regex = 'CHECK\s+THE\s+APPROPRIATE\s+(?:BOX\s+)?TO\s+DESIGNATE\s+THE\s+RULE\s+PURSUANT\s+TO\s+WHICH\s+' + \
            'THIS\s+SCHEDULE\s+(?:13G\s+)?IS\s+FILED:\s*(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s+' + \
            '(.*)RULE\s+13D\s*-\s*1\s*[-]?\s*[\(\|]?\s*(B|C|D)\s*[\)\|]?\s*(?:\n|$)?'

re.findall(regex, m.upper(), re.DOTALL)


[('¨\n', 'B', '¨\n', 'C', 'X\n', 'D')]

In [2223]:
tt = 'Check the appropriate box to designate the\nrule pursuant to which this Schedule is filed:  \xa0\n\n\n¨\nRule 13d-1(b)  \xa0\n\n\n¨\nRule 13d-1(c)  \xa0\n\n\nx\nRule 13d-1(d)'

In [2224]:
re.findall(regex, tt.upper(), re.DOTALL)

[('¨\n', 'B', '¨\n', 'C', 'X\n', 'D')]

In [2246]:
print(m)


SC 13G
1
quebecor.txt











OMB APPROVAL




UNITED STATES


OMB Number:     3235-0145



SECURITIES AND EXCHANGE COMMISSION

Expires:      October 31,2002




Washington, D.C. 20549


Estimated average burden
hours per response.... 14.90







































SCHEDULE  13G



















Under the Securities Exchange Act of 1934



















(Amendment No.

) *

















Quebecor World Inc





(Name of Issuer)

















Common Sub Voting





(Title of Class of Securities)




















74820310









(CUSIP Number)


















12/31/2003




(Date of Event Which Requires Filing of this Statement)
















Check the appropriate box to designate the rule pursuant to which
this Schedule is filed:














0
Rule 13d-1 (b)




















0
Rule 13d-1(c)





















1
Rule 13d-1(d)

































* The remainder of this cover page shall be filled out for a
reporting person's initial 

In [2375]:
get_index_url('edgar/data/1203866/0001156973-04-000564.txt')

'https://www.sec.gov/Archives/edgar/data/1203866/000115697304000564/0001156973-04-000564-index.htm'

In [2487]:
rules_13g_bcd_df.loc[none_s]

file_name                  document  \
66    edgar/data/763212/0001104659-04-016445.txt  0001104659-04-016445.txt   
68    edgar/data/897226/0000897226-04-000239.txt  0000897226-04-000239.txt   
69    edgar/data/897226/0000897226-04-000244.txt  0000897226-04-000244.txt   
75    edgar/data/744187/0001104659-04-010757.txt  0001104659-04-010757.txt   
76    edgar/data/763212/0001104659-04-013741.txt  0001104659-04-013741.txt   
78    edgar/data/763212/0001104659-04-013743.txt  0001104659-04-013743.txt   
79    edgar/data/897226/0000897226-04-000245.txt  0000897226-04-000245.txt   
83    edgar/data/763212/0001104659-04-010765.txt  0001104659-04-010765.txt   
87    edgar/data/763212/0001104659-04-010763.txt  0001104659-04-010763.txt   
90    edgar/data/897226/0000897226-04-000238.txt  0000897226-04-000238.txt   
91    edgar/data/897226/0000897226-04-000237.txt  0000897226-04-000237.txt   
99    edgar/data/763212/0001104659-04-010759.txt  0001104659-04-010759.txt   
100   edgar/data/763212/0001104659-04-016443.txt  0001104659-04-016443.txt   
101   edgar/data/763212/0001104659-04-016444.txt  0001104659-04-016444.txt   
103   edgar/data/763212/0001104659-04-010760.txt  0001104659-04-010760.txt   
109   edgar/data/763212/0001104659-04-013745.txt  0001104659-04-013745.txt   
111   edgar/data/897226/0000897226-04-000246.txt  0000897226-04-000246.txt   
117   edgar/data/763212/0001104659-04-010757.txt  0001104659-04-010757.txt   
118   edgar/data/763212/0001104659-04-013746.txt  0001104659-04-013746.txt   
120   edgar/data/763212/0001104659-04-010758.txt  0001104659-04-010758.txt   
121   edgar/data/763212/0001104659-04-016442.txt  0001104659-04-016442.txt   
137   edgar/data/763212/0001104659-04-010761.txt  0001104659-04-010761.txt   
138   edgar/data/763212/0001104659-04-010762.txt  0001104659-04-010762.txt   
147  edgar/data/1070235/0001104659-04-010759.txt  0001104659-04-010759.txt   
215   edgar/data/880117/0000902219-04-001133.txt  0000902219-04-001133.txt   
247   edgar/data/855931/0001104659-04-010760.txt  0001104659-04-010760.txt   
483   edgar/data/709283/0000897226-04-000145.txt  0000897226-04-000145.txt   
488   edgar/data/904121/0001205613-04-000006.txt  0001205613-04-000006.txt   
544   edgar/data/819706/0000897226-04-000233.txt  0000897226-04-000233.txt   
553   edgar/data/720005/0000897226-04-000191.txt  0000897226-04-000191.txt   
558  edgar/data/1091284/0000950136-04-000393.txt  0000950136-04-000393.txt   
559  edgar/data/1091284/0000950136-04-000394.txt  0000950136-04-000394.txt   
568   edgar/data/819706/0000897226-04-000192.txt  0000897226-04-000192.txt   
593   edgar/data/917273/0001104659-04-007245.txt  0001104659-04-007245.txt   
649  edgar/data/1064060/0001179591-04-000011.txt  0001179591-04-000011.txt   

    form_type  rule_13_d1_b  rule_13_d1_c  rule_13_d1_d  
66   SC 13G/A         False         False         False  
68   SC 13G/A          True         False         False  
69   SC 13G/A          True         False         False  
75   SC 13G/A         False         False         False  
76     SC 13G         False         False         False  
78     SC 13G         False         False         False  
79   SC 13G/A          True         False         False  
83   SC 13G/A         False         False         False  
87   SC 13G/A         False         False         False  
90     SC 13G          True         False         False  
91   SC 13G/A          True         False         False  
99   SC 13G/A         False         False         False  
100  SC 13G/A         False         False         False  
101  SC 13G/A         False         False         False  
103  SC 13G/A         False         False         False  
109    SC 13G         False         False         False  
111  SC 13G/A          True         False         False  
117  SC 13G/A         False         False         False  
118  SC 13G/A         False         False         False  
120  SC 13G/A         False         False         False  
121  SC 13G/

In [2096]:
get_index_url('edgar/data/1203866/0001156973-04-000564.txt')

'https://www.sec.gov/Archives/edgar/data/1203866/000115697304000564/0001156973-04-000564-index.htm'

In [2489]:
failures

[8,
 11,
 12,
 24,
 57,
 66,
 67,
 69,
 72,
 73,
 74,
 76,
 77,
 78,
 79,
 80,
 100,
 116,
 128,
 129,
 132,
 146,
 158,
 167,
 170,
 171,
 172,
 181,
 182,
 183,
 184,
 196,
 197,
 204,
 205,
 207,
 208,
 209,
 212,
 213,
 214,
 218,
 221,
 226,
 231,
 235,
 237,
 240,
 241,
 270,
 278,
 279,
 282,
 286,
 295,
 296,
 297,
 312,
 316,
 322,
 337,
 338,
 355,
 366,
 371,
 375,
 377,
 380,
 382,
 386,
 390,
 395,
 402,
 415,
 428,
 438,
 439,
 440,
 441,
 442,
 443,
 444,
 445,
 454,
 455,
 456,
 457,
 458,
 460,
 461,
 462,
 465,
 466,
 473,
 474,
 475,
 476,
 477,
 483,
 485,
 486,
 487,
 489,
 491,
 492,
 504,
 505,
 506,
 507,
 508,
 509,
 510,
 511,
 512,
 518,
 519,
 520,
 521,
 522,
 523,
 524,
 531,
 538,
 539,
 541,
 542,
 543,
 544,
 545,
 546,
 547,
 548,
 549,
 550,
 552,
 553,
 554,
 555,
 556,
 557,
 558,
 559,
 560,
 561,
 562,
 563,
 564,
 565,
 566,
 567,
 568,
 569,
 570,
 571,
 572,
 573,
 574,
 575,
 576,
 577,
 578,
 579,
 580,
 581,
 582,
 583,
 584,
 585,
 586,
 58

In [2461]:
print(t)


SC 13G/A
1
a04-6754_4sc13ga.htm
SC 13G/A













 


 
  
   
  
  
  UNITED STATES
  
  
  OMB APPROVAL
  
 
 
  
   
  
  
  SECURITIES AND EXCHANGE COMMISSION
  
  
  OMB Number: 
  3235-0145
  
 
 
  
   
  
  
  Washington, D.C. 20549
  
  
  Expires:
  December 31, 1997
  
 
 
  
   
  
  
  SCHEDULE 13G
  
  
  Estimated average burden
  hours per response. . 14.90
  
 


 

Under the Securities Exchange Act of 1934
(Amendment No. 2)*

 



Ligand Pharmaceuticals



(Name of Issuer)

 



Common



(Title of Class of Securities)

 



53220K207



(CUSIP Number)

 



 



(Date of Event Which Requires Filing of this Statement)

 

Check the appropriate box to
designate the rule pursuant to which this Schedule is filed: 


 
  
  o
  
  
  Rule
  13d-1(b)
  
 
 
  
  o
  
  
  Rule
  13d-1(c)
  
 
 
  
  o
  
  
  Rule
  13d-1(d)
  
 


 

Check the
following box if a fee is being paid with this statement o.
(A fee is not required only if the filing person: (1) has a previ

In [2107]:
get_index_url('edgar/data/763212/0001104659-04-016445.txt')

'https://www.sec.gov/Archives/edgar/data/763212/000110465904016445/0001104659-04-016445-index.htm'

In [ ]:
68, 69, 79, 90, 91, 111, 483, 544, 553, 568

In [2473]:
i = 568
j = cover_page_q1_start(get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory))  
    
t = get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory)[:j]
get_rules_pursuant_to_13g(t)

(True, False, False)

In [2463]:
get_rules_pursuant_to_13g(t)

(True, False, False)

In [2376]:
rules_13g_bcd_df.loc[none_s]

file_name                  document  \
66    edgar/data/763212/0001104659-04-016445.txt  0001104659-04-016445.txt   
68    edgar/data/897226/0000897226-04-000239.txt  0000897226-04-000239.txt   
69    edgar/data/897226/0000897226-04-000244.txt  0000897226-04-000244.txt   
75    edgar/data/744187/0001104659-04-010757.txt  0001104659-04-010757.txt   
76    edgar/data/763212/0001104659-04-013741.txt  0001104659-04-013741.txt   
78    edgar/data/763212/0001104659-04-013743.txt  0001104659-04-013743.txt   
79    edgar/data/897226/0000897226-04-000245.txt  0000897226-04-000245.txt   
83    edgar/data/763212/0001104659-04-010765.txt  0001104659-04-010765.txt   
87    edgar/data/763212/0001104659-04-010763.txt  0001104659-04-010763.txt   
90    edgar/data/897226/0000897226-04-000238.txt  0000897226-04-000238.txt   
91    edgar/data/897226/0000897226-04-000237.txt  0000897226-04-000237.txt   
99    edgar/data/763212/0001104659-04-010759.txt  0001104659-04-010759.txt   
100   edgar/data/763212/0001104659-04-016443.txt  0001104659-04-016443.txt   
101   edgar/data/763212/0001104659-04-016444.txt  0001104659-04-016444.txt   
103   edgar/data/763212/0001104659-04-010760.txt  0001104659-04-010760.txt   
109   edgar/data/763212/0001104659-04-013745.txt  0001104659-04-013745.txt   
111   edgar/data/897226/0000897226-04-000246.txt  0000897226-04-000246.txt   
117   edgar/data/763212/0001104659-04-010757.txt  0001104659-04-010757.txt   
118   edgar/data/763212/0001104659-04-013746.txt  0001104659-04-013746.txt   
120   edgar/data/763212/0001104659-04-010758.txt  0001104659-04-010758.txt   
121   edgar/data/763212/0001104659-04-016442.txt  0001104659-04-016442.txt   
137   edgar/data/763212/0001104659-04-010761.txt  0001104659-04-010761.txt   
138   edgar/data/763212/0001104659-04-010762.txt  0001104659-04-010762.txt   
147  edgar/data/1070235/0001104659-04-010759.txt  0001104659-04-010759.txt   
215   edgar/data/880117/0000902219-04-001133.txt  0000902219-04-001133.txt   
247   edgar/data/855931/0001104659-04-010760.txt  0001104659-04-010760.txt   
483   edgar/data/709283/0000897226-04-000145.txt  0000897226-04-000145.txt   
488   edgar/data/904121/0001205613-04-000006.txt  0001205613-04-000006.txt   
544   edgar/data/819706/0000897226-04-000233.txt  0000897226-04-000233.txt   
553   edgar/data/720005/0000897226-04-000191.txt  0000897226-04-000191.txt   
558  edgar/data/1091284/0000950136-04-000393.txt  0000950136-04-000393.txt   
559  edgar/data/1091284/0000950136-04-000394.txt  0000950136-04-000394.txt   
568   edgar/data/819706/0000897226-04-000192.txt  0000897226-04-000192.txt   
593   edgar/data/917273/0001104659-04-007245.txt  0001104659-04-007245.txt   
649  edgar/data/1064060/0001179591-04-000011.txt  0001179591-04-000011.txt   

    form_type  rule_13_d1_b  rule_13_d1_c  rule_13_d1_d  
66   SC 13G/A         False         False         False  
68   SC 13G/A         False         False         False  
69   SC 13G/A         False         False         False  
75   SC 13G/A         False         False         False  
76     SC 13G         False         False         False  
78     SC 13G         False         False         False  
79   SC 13G/A         False         False         False  
83   SC 13G/A         False         False         False  
87   SC 13G/A         False         False         False  
90     SC 13G         False         False         False  
91   SC 13G/A         False         False         False  
99   SC 13G/A         False         False         False  
100  SC 13G/A         False         False         False  
101  SC 13G/A         False         False         False  
103  SC 13G/A         False         False         False  
109    SC 13G         False         False         False  
111  SC 13G/A         False         False         False  
117  SC 13G/A         False         False         False  
118  SC 13G/A         False         False         False  
120  SC 13G/A         False         False         False  
121  SC 13G/

In [2101]:
j = cover_page_q1_start(get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory))  
    
t = get_title_page(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'],\
           directory, sc13g_df.loc[i, 'cover_page_start'], j,\
                sc13g_df.loc[i, 'title_page_end_lower_bound'], sc13g_df.loc[i, 'num_cusip_sedol_b_q1'])

In [2102]:
t

'\nSC 13G/A\n1\nc85643sc13gza.txt\nAMENDMENT NO.4 TO SCHEDULE 13G\n\n\n                                                             OMB APPROVAL\n                                                      --------------------------\n                                                      OMB Number:      3235-0145\n                                                      Expires: December 31, 2005\n                                                      Estimated average burden\n                                                      hours per response......11\n\n                                 UNITED STATES\n                       SECURITIES AND EXCHANGE COMMISSION\n                             WASHINGTON, DC 20549\n\n                                  SCHEDULE 13G\n\n                   UNDER THE SECURITIES EXCHANGE ACT OF 1934\n                               (AMENDMENT NO. 4)*\n\n                           WHITEHALL JEWELLERS, INC.\n- ---------------------------------------------------------------

In [2085]:
rules_13g_bcd_df['rule_13_d1_d'].sum()

87

In [2486]:
sc13g_df.loc[failures]

file_name                  document  \
8     edgar/data/893949/0000814133-04-000115.txt  0000814133-04-000115.txt   
11   edgar/data/1064728/0000315066-04-001678.txt  0000315066-04-001678.txt   
12     edgar/data/75681/0000065103-04-000134.txt  0000065103-04-000134.txt   
24     edgar/data/77449/0000315066-04-001429.txt  0000315066-04-001429.txt   
57   edgar/data/1002663/0000315066-04-001679.txt  0000315066-04-001679.txt   
66   edgar/data/1137774/0001137774-04-000179.txt  0001137774-04-000179.txt   
67   edgar/data/1137774/0001137774-04-000180.txt  0001137774-04-000180.txt   
69     edgar/data/80255/0000080255-04-000409.txt  0000080255-04-000409.txt   
72     edgar/data/80255/0000080255-04-000410.txt  0000080255-04-000410.txt   
73     edgar/data/80255/0000080255-04-000414.txt  0000080255-04-000414.txt   
74    edgar/data/766524/0000766524-04-000177.txt  0000766524-04-000177.txt   
76     edgar/data/80255/0000080255-04-000418.txt  0000080255-04-000418.txt   
77    edgar/data/880804/0000895421-04-000118.txt  0000895421-04-000118.txt   
78     edgar/data/80255/0000080255-04-000417.txt  0000080255-04-000417.txt   
79     edgar/data/80255/0000080255-04-000423.txt  0000080255-04-000423.txt   
80    edgar/data/880804/0000216543-04-000108.txt  0000216543-04-000108.txt   
100   edgar/data/763212/0001104659-04-010766.txt  0001104659-04-010766.txt   
116  edgar/data/1017815/0000732847-04-000012.txt  0000732847-04-000012.txt   
128    edgar/data/80255/0000080255-04-000421.txt  0000080255-04-000421.txt   
129    edgar/data/80255/0000080255-04-000422.txt  0000080255-04-000422.txt   
132   edgar/data/353569/0000884306-04-000060.txt  0000884306-04-000060.txt   
146   edgar/data/906551/0000315066-04-001430.txt  0000315066-04-001430.txt   
158  edgar/data/1137774/0001137774-04-000176.txt  0001137774-04-000176.txt   
167   edgar/data/355948/0000080255-04-000418.txt  0000080255-04-000418.txt   
170   edgar/data/906304/0000906304-04-000301.txt  0000906304-04-000301.txt   
171   edgar/data/906304/0000906304-04-000307.txt  0000906304-04-000307.txt   
172   edgar/data/906304/0000906304-04-000290.txt  0000906304-04-000290.txt   
181   edgar/data/906304/0000906304-04-000295.txt  0000906304-04-000295.txt   
182   edgar/data/906304/0000906304-04-000296.txt  0000906304-04-000296.txt   
183  edgar/data/1094392/0000814133-04-000123.txt  0000814133-04-000123.txt   
..                                           ...                       ...   
865  edgar/data/1013467/0000814133-04-000068.txt  0000814133-04-000068.txt   
872  edgar/data/1094366/0000315066-04-000966.txt  0000315066-04-000966.txt   
887  edgar/data/1171759/0000315066-04-000965.txt  0000315066-04-000965.txt   
892  edgar/data/1013467/0000906304-04-000166.txt  0000906304-04-000166.txt   
900  edgar/data/1094561/0000216543-04-000098.txt  0000216543-04-000098.txt   
902    edgar/data/52827/0000950135-04-000138.txt  0000950135-04-000138.txt   
903    edgar/data/52827/0001193125-04-001579.txt  0001193125-04-001579.txt   
911   edgar/data/770949/0000766524-04-000125.txt  0000766524-04-000125.txt   
912   edgar/data/770949/0000315066-04-000967.txt  0000315066-04-000967.txt   
916  edgar/data/1080731/0000919567-04-000011.txt  0000919567-04-000011.txt   
918  edgar/data/1041017/0000950134-04-002106.txt  0000950134-04-002106.txt   
922  edgar/data/1163542/0001057439-04-000011.txt  0001057439-04-000011.txt   
936   edgar/data/812191/0000216543-04-000081.txt  0000216543-04-000081.txt   
938  edgar/data/1013467/0000080255-04-000277.txt  0000080255-04-000277.txt   
939  edgar/data/1080731/0000919567-04-000022.txt  0000919567-04-000022.txt   
942   edgar/data/800458/0000906304-04-000169.txt  0000906304-04-000169.txt   
945   edgar/data/943819/0000315066-04-000975.txt  0000315066-04-000975.txt   
946   edgar/data/744187/0000051964-04-000009.txt  0000051964-04-000009.txt   
947   edgar/data/943819/0000315066-04-001306.txt  0000315066-04-001306.txt   
951   edgar/data/890926/0000766524-04-000126.txt  0000766524-

In [2490]:
len(failures)

308

In [2651]:
sql = """SELECT * FROM edgar.sc13dg_indexes WHERE item_section_start < cover_page_start 
         AND NOT has_jumbled_order
      """

weird_df = pd.read_sql(sql, engine)

In [2652]:
weird_df

file_name                  document  \
0   edgar/data/1134538/0000950130-02-000912.txt  0000950130-02-000912.txt   
1   edgar/data/1134538/0001193125-03-019776.txt  0001193125-03-019776.txt   
2   edgar/data/1134538/0001193125-03-019790.txt  0001193125-03-019790.txt   
3   edgar/data/1166769/0001193125-03-019790.txt  0001193125-03-019790.txt   
4   edgar/data/1134538/0000950130-03-001790.txt  0000950130-03-001790.txt   
5   edgar/data/1134538/0001193125-03-086982.txt  0001193125-03-086982.txt   
6   edgar/data/1134538/0001193125-03-086988.txt  0001193125-03-086988.txt   
7   edgar/data/1134538/0000950130-02-004125.txt  0000950130-02-004125.txt   
8   edgar/data/1166769/0001193125-03-086988.txt  0001193125-03-086988.txt   
9   edgar/data/1166769/0001193125-03-019776.txt  0001193125-03-019776.txt   
10  edgar/data/1166769/0001193125-03-086982.txt  0001193125-03-086982.txt   
11  edgar/data/1166769/0000950130-02-004125.txt  0000950130-02-004125.txt   
12  edgar/data/1166769/0000950130-02-000912.txt  0000950130-02-000912.txt   
13  edgar/data/1166769/0000950130-03-001790.txt  0000950130-03-001790.txt   

   form_type  title_page_end_lower_bound  cover_page_q1_start  \
0     SC 13D                        2023                 3685   
1   SC 13D/A                        1785                 3480   
2   SC 13D/A                        1704                 2121   
3   SC 13D/A                        1704                 2121   
4   SC 13D/A                        2080                 3742   
5   SC 13D/A                        1796                 3378   
6   SC 13D/A                        1706                 2123   
7   SC 13D/A                        2078                 3741   
8   SC 13D/A                        1706                 2123   
9   SC 13D/A                        1785                 3480   
10  SC 13D/A                        1796                 3378   
11  SC 13D/A                        2078                 3741   
12    SC 13D                        2023                 3685   
13  SC 13D/A                        2080                 3742   

    is_rep_q_as_items  is_schedule_to  has_table_of_contents  \
0               False           False                  False   
1               False           False                  False   
2               False           False                  False   
3               False           False                  False   
4               False           False                  False   
5               False           False                  False   
6               False           False                  False   
7               False           False                  False   
8               False           False                  False   
9               False           False                  False   
10              False           False                  False   
11              False           False                  False   
12              False           False                  False   
13              False           False                  False   

    num_cusip_sedol_b_q1  cover_page_start   ...     cover_page_last_q_end  \
0                      1              3685   ...                      None   
1                      1              3480   ...                      None   
2                      1              2121   ...                      None   
3                      1              2121   ...                      None   
4                      1              3742   ...                      None   
5                      1              3378   ...                      None   
6                      1              2123   ...                      None   
7                      1              3741   ...                      None   
8                      1              2123   ...                      None   
9                      1              3480   ...                      None   
10                     1              3378   ...                      None   
11       

In [2648]:
get_index_url('edgar/data/1134538/0000950130-02-000912.txt')

'https://www.sec.gov/Archives/edgar/data/1134538/000095013002000912/0000950130-02-000912-index.htm'

In [2655]:
weird_df['document'].unique()

array(['0000950130-02-000912.txt', '0001193125-03-019776.txt',
       '0001193125-03-019790.txt', '0000950130-03-001790.txt',
       '0001193125-03-086982.txt', '0001193125-03-086988.txt',
       '0000950130-02-004125.txt'], dtype=object)

In [2653]:
l = 1
m = get_main_doc_text(weird_df.loc[l, 'file_name'], weird_df.loc[l, 'document'], directory)

In [2654]:
print(m)


SC 13D/A
1
dsc13da.txt
AMENDMENT NO 3 TO SCHEDULE 13D



                      SECURITIES AND EXCHANGE COMMISSION
                            Washington, D.C. 20549

                                SCHEDULE 13D/A
                                (Rule 13d-101)

                                Amendment No. 3

          INFORMATION TO BE INCLUDED IN STATEMENTS FILED PURSUANT TO
                  RULE 13d-1(a) AND AMENDMENTS THERETO FILED
                           PURSUANT TO RULE 13d-2(a)

                                 Accenture Ltd
                               (Name of Issuer)

             Class A common shares, par value $0.0000225 per share
                        (Title of Class of Securities)

                                  G1150G 11 1
                                (CUSIP Number)

                              Douglas G. Scrivner
                              1661 Page Mill Road
                          Palo Alto, California 94304
                           Telephone: 

In [2614]:
class SC_Document:
    
    def __init__(self, file_name, document, form_type):
        
        self.file_name = file_name
        self.document = document
        self.form_type = form_type
        self.is_rep_q_as_items = None
        self.is_schedule_to = None
        self.has_table_of_contents = None
        self.has_jumbled_order = None
        self.success = False
        self.title_page_end_lower_bound = -2
        self.cover_page_q1_start = -2
        self.cover_page_start = -2
        self.num_cusip_sedol_b_q1 = -2
        self.cover_page_last_q_end = -2
        self.cover_page_end = -2
        self.num_cusip_b_items = -2
        self.item_section_start = -2
        self.signature_start = -2
        self.exhibit_start = -2
        self.main_text_length = -2
        self.explanatory_statement_start = -2
        
    def make_indexes_df(self):
        
        d = {'file_name': [self.file_name],
             'document': [self.document],
             'form_type': [self.form_type],
             'is_rep_q_as_items': [self.is_rep_q_as_items],
             'is_schedule_to': [self.is_schedule_to],
             'has_table_of_contents': [self.has_table_of_contents],
             'has_jumbled_order': [self.has_jumbled_order],
             'success': [self.success],
             'title_page_end_lower_bound': [self.title_page_end_lower_bound],
             'cover_page_q1_start': [self.cover_page_q1_start],
             'cover_page_start': [self.cover_page_start],
             'num_cusip_sedol_b_q1': [self.num_cusip_sedol_b_q1],
             'cover_page_last_q_end': [self.cover_page_last_q_end],
             'cover_page_end': [self.cover_page_end],
             'num_cusip_b_items': [self.num_cusip_b_items],
             'item_section_start': [self.item_section_start],
             'signature_start': [self.signature_start],
             'exhibit_start': [self.exhibit_start],
             'main_text_length': [self.main_text_length],
             'explanatory_statement_start': [self.explanatory_statement_start]}
        
        df = pd.DataFrame(d)
        
        return(df)

In [2615]:
doco = SC_Document('edgar/data/1137774/0001137774-04-000198.txt', '0001137774-04-000198.txt', 'SC 13G')

In [2616]:
doco.make_indexes_df()

file_name                  document  \
0  edgar/data/1137774/0001137774-04-000198.txt  0001137774-04-000198.txt   

  form_type is_rep_q_as_items is_schedule_to has_table_of_contents  \
0    SC 13G              None           None                  None   

  has_jumbled_order  success  title_page_end_lower_bound  cover_page_q1_start  \
0              None    False                          -2                   -2   

   cover_page_start  num_cusip_sedol_b_q1  cover_page_last_q_end  \
0                -2                    -2                     -2   

   cover_page_end  num_cusip_b_items  item_section_start  signature_start  \
0              -2                 -2                  -2               -2   

   exhibit_start  main_text_length  explanatory_statement_start  
0             -2                -2                           -2

In [2612]:
indexes_df.loc[493]

file_name                      edgar/data/1137774/0001137774-04-000198.txt
document                                          0001137774-04-000198.txt
form_type                                                           SC 13G
title_page_end_lower_bound                                              -2
cover_page_q1_start                                                     -2
is_rep_q_as_items                                                     None
is_schedule_to                                                        None
has_table_of_contents                                                 None
num_cusip_sedol_b_q1                                                    -2
cover_page_start                                                        -2
item_section_start                                                      -2
cover_page_last_q_end                                                   -2
cover_page_end                                                          -2
num_cusip_b_items        

In [2491]:
(sc13g_df.loc[failures, 'is_rep_q_as_items'] == True).sum()

51

In [2492]:
(sc13g_df.loc[failures, 'is_rep_q_as_items'] == False).sum()

257

In [2605]:
(sc13g_df.loc[failures, 'cover_page_q1_start'] == -1).sum()

3

In [2609]:
(sc13g_df.loc[failures, 'exhibit_start'] != -1).sum()

23

In [ ]:
get_item_section

In [2521]:
real_failures = []

for i in failures:

    try:
        j = cover_page_q1_start(get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory))  

        t = get_main_doc_text(rules_13g_bcd_df.loc[i, 'file_name'], rules_13g_bcd_df.loc[i, 'document'], directory)[:j]
        get_rules_pursuant_to_13g(t)
        
    except:
        
        real_failures.append(i)

    

In [2552]:
i = failures[7]
j = cover_page_q1_start(get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory))  

t = get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory)[:j]
get_rules_pursuant_to_13g(t)

TypeError: object of type 'NoneType' has no len()

In [2646]:
k = 150
i = failures[k]
t = get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory)

In [2647]:
print(t)


SC 13G/A
1
innov.txt

UNITED STATES
SECURITIES AND EXCHANGE COMMISSION
Washington, D.C. 20549

SCHEDULE 13G

Under the Securities Exchange Act of 1934
(Amendment)

NAME OF ISSUER				INNOVATIVE SOLUTIONS AND SUPPORT INC.

TITLE OF CLASS OF SECURITIES		Common

CUSIP NUMBER				45769N105


The remainder of this cover page shall be filled out for a reporting person's
initial filing on this form with respect to the subject class of securities,
and for any subsequent amendment containing information which would alter the
disclosures provided in a prior cover page.

The information required in the remainder of this cover page shall not be
deemed to be "filed" for the purpose of Section 18 of the Securities Exchange
Act of 1934 ("Act") or otherwise subject to the liabilities of that section
of the Act but shall be subject to all other provisions of the Act (however,
see the Notes).
























Page 1 of 10 Pages



13G

CUSIP No.	45769N105							Page 2 of 10 Pages
- ---------------

In [2634]:
fee_paid_with_statement(t)

False

In [2574]:
def fee_paid_with_statement(text):
    
    text_lowered = text.lower()
    
    regex = 'check\s+the\s+following\s+box\s+if\s+a\s+fee\s+is\s+being\s+' + \
            'paid\s+with\s+this\s+statement\s+([^\.\(\n]*)'
        
    search = re.findall(regex, text_lowered)
    
    if(len(search)):
        
        box = search[0]
        
        if(re.search('[XÝý1Þ]', box) is not None):
            
            return(True)
        
        else:
            
            return(False)
        
    else:
        
        return(False)
            
            

In [2578]:
fee_paid_with_statement(t)

False

In [2573]:
regex = 'check\s+the\s+following\s+box\s+if\s+a\s+fee\s+is\s+being\s+' + \
            'paid\s+with\s+this\s+statement\s+([^\.\(\n]*)'
        
search = re.findall(regex, t.lower())
search

['____']

In [2522]:
len(real_failures)

90

In [2536]:
get_rules_pursuant_to_13g_boxes(t)

('\n\tFILED PURSUANT TO ', 'B')

In [2520]:
print(t)


SC 13G
1
s13g_914819.txt
SCHEDULE 13G



                                 UNITED STATES
                       SECURITIES AND EXCHANGE COMMISSION
                              WASHINGTON, DC 20549


                                  SCHEDULE 13G


                   UNDER THE SECURITIES EXCHANGE ACT OF 19341


                              PHARMION CORPORATION
                                (Name of Issuer)

                          COMMON STOCK, $.001 PAR VALUE
                         (Title of Class of Securities)

                                   71715B 40 9
                                 (CUSIP Number)

                                NOVEMBER 6, 2003
             (Date of Event Which Requires Filing of this Statement)


            Check the appropriate box to designate the rule pursuant
                        to which this Schedule is filed:

                                |_| Rule 13d-1(b)

                                |X| Rule 13d-1(c)

                            

In [2079]:
get_index_url('edgar/data/874992/0000906304-04-000168.txt 	')

'https://www.sec.gov/Archives/edgar/data/874992/000090630404000168/0000906304-04-000168-index.htm'

In [1962]:
(sc13g_df.loc[failures, 'success'] == True).sum()

313

In [1964]:
(sc13g_df.loc[failures, 'success'] == False).sum()

59

In [1960]:
get_index_url('edgar/data/893949/0000814133-04-000115.txt')

'https://www.sec.gov/Archives/edgar/data/893949/000081413304000115/0000814133-04-000115-index.htm'

In [1956]:
len(failures)

404

In [1665]:
sc13g_df.loc[84]

file_name                      edgar/data/897226/0000897226-04-000239.txt
document                                         0000897226-04-000239.txt
form_type                                                        SC 13G/A
title_page_end_lower_bound                                           1761
cover_page_q1_start                                                   238
is_rep_q_as_items                                                   False
is_schedule_to                                                      False
has_table_of_contents                                               False
num_cusip_sedol_b_q1                                                    1
cover_page_start                                                      238
item_section_start                                                   1763
cover_page_last_q_end                                                 NaN
cover_page_end                                                       1338
num_cusip_b_items                     

In [1648]:
sc13g_df.loc[failures, 'is_rep_q_as_items'].sum()

42

In [1701]:
failures.index(93)

29

In [2061]:
get_rules_pursuant_to_13g(t)

(True, False, False)

In [1709]:
i

124

In [1733]:
sc13g_df.loc[failures]

file_name                  document  \
8     edgar/data/893949/0000814133-04-000115.txt  0000814133-04-000115.txt   
11   edgar/data/1064728/0000315066-04-001678.txt  0000315066-04-001678.txt   
12     edgar/data/75681/0000065103-04-000134.txt  0000065103-04-000134.txt   
22   edgar/data/1164123/0001141218-04-000038.txt  0001141218-04-000038.txt   
23   edgar/data/1164123/0001141218-04-000039.txt  0001141218-04-000039.txt   
24     edgar/data/77449/0000315066-04-001429.txt  0000315066-04-001429.txt   
32   edgar/data/1162663/0001162663-04-000011.txt  0001162663-04-000011.txt   
33   edgar/data/1162663/0001016964-04-000105.txt  0001016964-04-000105.txt   
47   edgar/data/1291274/0000950135-04-003061.txt  0000950135-04-003061.txt   
48   edgar/data/1162663/0001016964-04-000175.txt  0001016964-04-000175.txt   
50    edgar/data/356213/0000924355-04-000146.txt  0000924355-04-000146.txt   
52   edgar/data/1162663/0001016964-04-000107.txt  0001016964-04-000107.txt   
53   edgar/data/1162663/0001016964-04-000156.txt  0001016964-04-000156.txt   
57   edgar/data/1002663/0000315066-04-001679.txt  0000315066-04-001679.txt   
66   edgar/data/1137774/0001137774-04-000179.txt  0001137774-04-000179.txt   
67   edgar/data/1137774/0001137774-04-000180.txt  0001137774-04-000180.txt   
69     edgar/data/80255/0000080255-04-000409.txt  0000080255-04-000409.txt   
70    edgar/data/880804/0000924355-04-000130.txt  0000924355-04-000130.txt   
72     edgar/data/80255/0000080255-04-000410.txt  0000080255-04-000410.txt   
73     edgar/data/80255/0000080255-04-000414.txt  0000080255-04-000414.txt   
74    edgar/data/766524/0000766524-04-000177.txt  0000766524-04-000177.txt   
76     edgar/data/80255/0000080255-04-000418.txt  0000080255-04-000418.txt   
77    edgar/data/880804/0000895421-04-000118.txt  0000895421-04-000118.txt   
78     edgar/data/80255/0000080255-04-000417.txt  0000080255-04-000417.txt   
79     edgar/data/80255/0000080255-04-000423.txt  0000080255-04-000423.txt   
80    edgar/data/880804/0000216543-04-000108.txt  0000216543-04-000108.txt   
84    edgar/data/897226/0000897226-04-000239.txt  0000897226-04-000239.txt   
85    edgar/data/897226/0000897226-04-000244.txt  0000897226-04-000244.txt   
90    edgar/data/917273/0001193125-04-077680.txt  0001193125-04-077680.txt   
93   edgar/data/1027796/0001058217-04-000131.txt  0001058217-04-000131.txt   
..                                           ...                       ...   
927  edgar/data/1055610/0000950129-04-000539.txt  0000950129-04-000539.txt   
931  edgar/data/1220692/0000950136-04-000249.txt  0000950136-04-000249.txt   
932  edgar/data/1220692/0000950136-04-000581.txt  0000950136-04-000581.txt   
937  edgar/data/1170752/0000950152-04-001038.txt  0000950152-04-001038.txt   
938    edgar/data/82811/0000062741-04-000053.txt  0000062741-04-000053.txt   
939  edgar/data/1171759/0000315066-04-000965.txt  0000315066-04-000965.txt   
943   edgar/data/913144/0000812295-04-000039.txt  0000812295-04-000039.txt   
944  edgar/data/1013467/0000906304-04-000166.txt  0000906304-04-000166.txt   
946  edgar/data/1044197/0001044197-04-000034.txt  0001044197-04-000034.txt   
953  edgar/data/1094561/0000216543-04-000098.txt  0000216543-04-000098.txt   
955    edgar/data/52827/0000950135-04-000138.txt  0000950135-04-000138.txt   
956   edgar/data/858558/0000017283-04-000514.txt  0000017283-04-000514.txt   
957    edgar/data/52827/0001193125-04-001579.txt  0001193125-04-001579.txt   
965   edgar/data/770949/0000766524-04-000125.txt  0000766524-04-000125.txt   
966   edgar/data/770949/0000315066-04-000967.txt  0000315066-04-000967.txt   
969  edgar/data/1044197/0001044197-04-000017.txt  0001044197-04-000017.txt   
970   edgar/data/769874/0000884589-04-000042.txt  0000884589-04-000042.txt   
972  edgar/data/1080731/0000919567-04-000011.txt  0000919567-04-000011.txt   
974  edgar/data/1041017/0000950134-04-002106.txt  0000950134-04-002106.txt   
975  edgar/data/1094515/0000950117-04-000650.txt  0000950117-

In [1710]:
70, 72, 73, 76, 77, 84, 124

(70, 72, 73, 76, 77, 84, 124)

In [1741]:
'ý'.encode()

b'\xc3\xbd'

In [1745]:
print('\xcy')

SyntaxError: (unicode error) 'unicodeescape' codec can't decode bytes in position 0-2: truncated \xXX escape (<ipython-input-1745-938ec7846a7c>, line 1)

In [2062]:
get_rules_pursuant_to_13g(t)

(True, False, False)

In [1981]:
get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory)            [:1090]

'\nSC 13G\n1\namer.htm\n\n\n\n\n13G HTML File\n\nDOCUMENT TYPE             SC 13G\nTEXT\n\n\n\nSECURITIES AND EXCHANGE COMMISSION\n\nWashington,  D.C.    20549\n\nSCHEDULE 13G\nUnder the Securities Exchange Act of 1934\n\n\nName of Issuer:       American Homestar Corporation\n_____________________________________________________\n\nTitle of Class\nof Securities:  Common Stock\n\nCUSIP Number:    026652107\n\n1)  NAME AND I.R.S. IDENTIFICATION NO. OF REPORTING PERSON\n\n\tPrudential Financial, Inc.\t    22-3703799\n\n2.) MEMBER OF A GROUP: \t(a)  N/A\n\t\t\t\t\t(b)  N/A\n\n3)  SEC USE ONLY:\n\n\n\n4)  PLACE OF ORGANIZATION:\tNew Jersey\n\nNUMBER OF SHARES BENEFICIALLY OWNED BY REPORTING PERSON WITH:\n\n5)  Sole Voting Power:\t\t0\t\t\tNot\nApplicable\n6)  Shared Voting Power:\t860,697\t\tSee Exhibit A\n7)  Sole Dispositive Power:\t0\t\tNot Applicable\n8)  Shared Dispositive Power:\t860,697\t\tSee Exhibit A\n\n9)  AGGREGATE AMOUNT BENEFICIALLY OWNED:\n\t\t\t860,697\tSee Exhibit A \n\n10)

In [2070]:
sc13g_df.loc[i]

file_name                      edgar/data/1137774/0001137774-04-000176.txt
document                                          0001137774-04-000176.txt
form_type                                                         SC 13G/A
title_page_end_lower_bound                                            1123
cover_page_q1_start                                                     -1
is_rep_q_as_items                                                    False
is_schedule_to                                                       False
has_table_of_contents                                                False
num_cusip_sedol_b_q1                                                     2
cover_page_start                                                        -1
item_section_start                                                    1125
cover_page_last_q_end                                                 1118
cover_page_end                                                        1125
num_cusip_b_items        

In [2064]:
failures[26]

132

In [2072]:
i = failures[28]
j = cover_page_q1_start(get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory))  
t = get_title_page(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'],\
               directory, sc13g_df.loc[i, 'cover_page_start'], j,\
                    sc13g_df.loc[i, 'num_cusip_sedol_b_q1'])
print(t)

None


In [2071]:
j

1377

In [2026]:
m[:472]

'\nSC 13G/A\n1\nptek0404b.txt\n\n                                UNITED STATES\n                      SECURITIES AND EXCHANGE COMMISSION\n\n                            Washington, D.C.  20549\n\n                                 SCHEDULE 13G\n\n                   Under the Securities Exchange Act of 1934\n\n                          (Amendment No.  1 )\n\n\nNAME OF ISSUER:  PTEK Holdings, Inc.\n\nTITLE OF CLASS OF SECURITIES:  Common\n\nCUSIP NUMBER:  69366M104\n\nCUSIP NO.  69366M104\n\n(1)   '

In [2069]:
j

1377

In [2010]:
regex2 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S[\.]?)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'
re.search(regex2, m.upper())

In [2067]:
m = get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory)            

In [2068]:
print(m)


SC 13G/A
1
navi.htm




13G HTML File

DOCUMENT TYPE             SC 13G/A
TEXT



SECURITIES AND EXCHANGE COMMISSION

Washington,  D.C.    20549

SCHEDULE 13G
Under the Securities Exchange Act of 1934

Amendment  # 2

Name of Issuer:       Navistar International Corp.
_____________________________________________________

Title of Class
of Securities:  Common Stock

CUSIP Number:    63934E108

1)  NAME AND I.R.S. IDENTIFICATION NO. OF REPORTING PERSON

	Prudential Financial, Inc.	    22-3703799

2.) MEMBER OF A GROUP: 	(a)  N/A
					(b)  N/A

3)  SEC USE ONLY:



4)  PLACE OF ORGANIZATION:	New Jersey

NUMBER OF SHARES BENEFICIALLY OWNED BY REPORTING PERSON WITH:

5)  Sole Voting Power:		75,198			See Exhibit
A
6)  Shared Voting Power:	8,395,752		See Exhibit A
7)  Sole Dispositive Power:	75,198		See Exhibit A
8)  Shared Dispositive Power:	8,442,373		See Exhibit A

9)  AGGREGATE AMOUNT BENEFICIALLY OWNED:
			8,517,571	See Exhibit A 

10)  AGGREGATE AMOUNT IN ROW (9) EXCLUDES SHARES:	Not 

In [1894]:
i

651

In [2028]:
cover_page_q1_start(m)

249

In [1668]:
m = get_main_doc_text(sc13g_df.loc[i, 'file_name'], sc13g_df.loc[i, 'document'], directory)

In [2021]:
def cover_page_q1_start(text):
    
    text_raised = text.upper()

    regex0 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+(?:REPORTING|ABOVE|REPORT)'
    
    regex1 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?'

    regex2 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S[\.]?)?\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.'

    regex3 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*' + \
         'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)\s+(\s+THE)?ABOVE\s+' + \
         'PERSON[\(]?[S]?[\)]?'

    regex4 = '(NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+)?[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.\|]{0,1}\s*S\.S\.\s+OR\s+' + \
         'I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+(?:OF|OR)(\s+THE)?\s+' + \
         'ABOVE\s+PERSON[\(]?[S]?[\)]?'

    regex5 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?\s+FILING\s+(?:PARTY|PARTIES|PERSON|PERSONS)'

    regex6 = 'NAME[\(]?[S]?[\)]?\s+(?:OF|OR)(\s+THE)?(\s+(?:REPORTING|ABOVE|REPORT))?\s+' + \
         'PERSON[\(]?[S]?[\)]?\s+(S\.S\.\s+OR\s+I\.R\.S\.\s+IDENTIFICATION\s+NO[\(]?[S]?[\)]?\.\s+' + \
         '(?:OF|OR)(\s+THE)?\s+ABOVE\s+PERSON[\(]?[S]?[\)]?)?' + \
         '\s+[\(\|]?\s*[1L]\s*[\)\|]?\s*[:\.]{0,1}(\s*[\(\|]\s*A\s*[\)\|])?'


    regex7 = '\n\s*[\(\|]?\s1\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
         '[\(\|]?\s2\s?[\)\|]?\s*[:\.]{0,1}([A-Z0-9\s\.\(\)_]?)+?' + \
         '[\(\|]?\s3\s?[\)\|]?\s*[:\.]{0,1}\s+(.)+\s*\(SEC USE ONLY\)'

    regex8 = 'NAME[\(]?[S]?[\)]?\s+(?:AND|OF|OR)(\s+I[\.]?R[\.]?S)?\s+NUMBER\s+OF\s+REPORTING\s+PERSON[S]?'
    
    regex_list = [regex0, regex1, regex2, regex3, regex4, regex5, regex6, regex7, regex8]
    
    index = -1
    
    for pattern in regex_list:
        
        search = re.search(pattern, text_raised)
        
        if(search):
            
            index = search.start()
            break
            
    return(index)

In [1691]:
re.search(regex9, m.upper())

In [1694]:
regex2 == regex9

True

In [1680]:
m[:249]

'\nSC 13G/A\n1\nbandag.txt\n\nUNITED STATES\nSECURITIES AND EXCHANGE COMMISSION\nWashington, D.C. 20549\n\nSCHEDULE 13G\tAmendment No. 8\n\n(Name of Issuer)\n\tBANDAG INC CL-A\n\n(Title of Class of Securities)\nCommon Stock\n\n(CUSIP Number)\n\t059815308\n\nRule 13d-1(b)\n\n'

In [1896]:
get_index_url(sc13g_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/766524/000076652404000149/0000766524-04-000149-index.htm'

In [1626]:
t

'\nSC 13G\n1\nmercatorpenthouse13g.htm\nSCHEDULE 13G\n\n\n\nSC 13G\n\n\n\nUNITED STATES\nSECURITIES AND EXCHANGE COMMISSION\nWashington, D.C. 20549\n\xa0\nSCHEDULE 13G\nUnder the Securities Exchange Act of 1934\n(Amendment No. ___)*\n\xa0\nPENTHOUSE INTERNATIONAL, INC.\n(Name of Issuer)\n\xa0\nCommon Stock\n(Title of Class of Securities)\n\xa0\n709640106\n(CUSIP Number)\n\xa0\nMarch 19, 2004\n(Date of Event Which Requires Filing of this Statement)\n\xa0\n¨\xa0\xa0Rule 13d-1(b)\ný\xa0\xa0Rule 13d-1(c)\n¨\xa0\xa0Rule 13d-1(d)\n\n\n\n\n\n\nSCHEDULE 13G'

In [1604]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/75681/000006510304000134/0000065103-04-000134-index.htm'

In [1428]:
i = 414532
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/5405/0000950123-94-000784.txt  0000950123-94-000784.txt   

  form_type amendment_number                      issuer_name  \
0    SC 13G             None  AMERICAN MAIZE-PRODUCTS COMPANY   

                                      security_class  \
0  Class A Common Stock:         Class B Common S...   

                                          cusip  
0  CLASS A:  027339 20 9;  CLASS B: 027339 30 8

In [1430]:
rep_q_13d_df = indexes_df.loc[np.logical_and(np.logical_or(indexes_df['form_type'] == 'SC 13D', \
            indexes_df['form_type'] == 'SC 13D/A'), indexes_df['is_rep_q_as_items'] == True)].copy().reset_index(drop = True)
rep_q_13d_df

file_name                  document  \
0      edgar/data/805900/0001193125-04-074106.txt  0001193125-04-074106.txt   
1      edgar/data/805900/0001193125-04-052528.txt  0001193125-04-052528.txt   
2      edgar/data/902256/0001193125-04-074106.txt  0001193125-04-074106.txt   
3     edgar/data/1026733/0000315066-04-001840.txt  0000315066-04-001840.txt   
4     edgar/data/1026733/0000315066-04-001963.txt  0000315066-04-001963.txt   
5      edgar/data/315066/0000315066-04-001840.txt  0000315066-04-001840.txt   
6      edgar/data/315066/0000315066-04-001963.txt  0000315066-04-001963.txt   
7      edgar/data/315066/0000315066-04-002169.txt  0000315066-04-002169.txt   
8     edgar/data/1026733/0000315066-04-002169.txt  0000315066-04-002169.txt   
9     edgar/data/1035096/0001104659-07-039783.txt  0001104659-07-039783.txt   
10    edgar/data/1035096/0001104659-07-044659.txt  0001104659-07-044659.txt   
11    edgar/data/1035096/0001104659-07-038073.txt  0001104659-07-038073.txt   
12    edgar/data/1035096/0001104659-07-039783.txt  0001104659-07-039783.txt   
13    edgar/data/1035096/0001104659-07-042610.txt  0001104659-07-042610.txt   
14    edgar/data/1035096/0001104659-07-042610.txt  0001104659-07-042610.txt   
15    edgar/data/1035096/0001104659-07-044659.txt  0001104659-07-044659.txt   
16    edgar/data/1035096/0001104659-07-038073.txt  0001104659-07-038073.txt   
17    edgar/data/1359055/0001047469-08-011649.txt  0001047469-08-011649.txt   
18    edgar/data/1359055/0001047469-08-011649.txt  0001047469-08-011649.txt   
19     edgar/data/835344/0000315066-94-001909.txt  0000315066-94-001909.txt   
20     edgar/data/726514/0000315066-94-001586.txt  0000315066-94-001586.txt   
21     edgar/data/315066/0000315066-94-001183.txt  0000315066-94-001183.txt   
22     edgar/data/315066/0000315066-94-001224.txt  0000315066-94-001224.txt   
23     edgar/data/315066/0000315066-94-001298.txt  0000315066-94-001298.txt   
24     edgar/data/315066/0000315066-94-001220.txt  0000315066-94-001220.txt   
25     edgar/data/315066/0000315066-94-001221.txt  0000315066-94-001221.txt   
26     edgar/data/315066/0000318989-94-000008.txt  0000318989-94-000008.txt   
27     edgar/data/836190/0000318989-94-000021.txt  0000318989-94-000021.txt   
28     edgar/data/882363/0000315066-94-001182.txt  0000315066-94-001182.txt   
29     edgar/data/315066/0000315066-94-001511.txt  0000315066-94-001511.txt   
...                                           ...                       ...   
1617   edgar/data/318989/0000315066-96-001389.txt  0000315066-96-001389.txt   
1618   edgar/data/318989/0000315066-96-001477.txt  0000315066-96-001477.txt   
1619  edgar/data/1011440/0001011440-99-000099.txt  0001011440-99-000099.txt   
1620   edgar/data/874019/0000950132-00-000691.txt  0000950132-00-000691.txt   
1621   edgar/data/315066/0000315066-95-001636.txt  0000315066-95-001636.txt   
1622   edgar/data/315066/0000315066-95-002302.txt  0000315066-95-002302.txt   
1623   edgar/data/709283/0000315066-94-001767.txt  0000315066-94-001767.txt   
1624   edgar/data/926764/0000315066-96-000107.txt  0000315066-96-000107.txt   
1625   edgar/data/318989/0000315066-96-001900.txt  0000315066-96-001900.txt   
1626  edgar/data/1026734/0000315066-98-001579.txt  0000315066-98-001579.txt   
1627   edgar/data/318989/0000318989-94-000001.txt  0000318989-94-000001.txt   
1628   edgar/data/820756/0000315066-95-002719.txt  0000315066-95-002719.txt   
1629   edgar/data/315066/0000315066-95-002720.txt  0000315066-95-002720.txt   
1630   edgar/data/318989/0000315066-95-003131.txt  0000315066-95-003131.txt   
1631   edgar/data/721356/0000318989-94-000019.txt  0000318989-94-000019.txt   
1632   edgar/data/835344/0000315066-94-001585.txt  0000315066-94-001585.txt   
1633    edgar/data/80134/0000315066-95-002394.txt  0000315066-95-002394.txt   
1634    edgar/data/86346/0000315066-96-000091.txt  0000315066-96-000091.txt   
1635   edgar/data/315066/0000315066-94-001913.txt  0000315066-94-001913.txt   
1636   edga

In [ ]:
rep_q_13d_df

In [1454]:
def get_main_doc_text(file_name, document, directory):
     
    full_text = clean_text(get_file_text_from_directory(file_name, document, directory))
    
    try:
        soup = BeautifulSoup(full_text, 'html5lib')
        main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
        
    except:
        
        try:
            soup = BeautifulSoup(full_text, 'lxml')
            main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
            
        except:
            
            soup = BeautifulSoup(full_text, 'html.parser')
            main_doc_text = soup.find(["document", "DOCUMENT"]).get_text()
    
    return(main_doc_text)            

In [1514]:
j = 49
get_index_url(rep_q_13d_df.loc[list_13g[j], 'file_name'])

'https://www.sec.gov/Archives/edgar/data/315066/000031506697001723/0000315066-97-001723-index.htm'

In [1508]:
len(list_13g)

50

In [1507]:
list_13g = []
for i in range(rep_q_13d_df.shape[0]):
    text = get_main_doc_text(rep_q_13d_df.loc[i, 'file_name'], rep_q_13d_df.loc[i, 'document'], directory).upper()
    
    if(re.search('13G', text) is not None):
        print(i)
        list_13g.append(i)

157
191
200
221
297
345
365
404
406
415
486
524
565
583
589
605
606
651
652
680
681
683
792
816
994
999
1134
1149
1156
1176
1177
1262
1284
1304
1358
1401
1420
1436
1467
1470
1475
1504
1505
1507
1535
1536
1586
1595
1619
1645


In [1504]:
rep_q_13d_df.loc[1186, 'file_name']

'edgar/data/98246/0000950123-02-008099.txt'

In [1503]:
get_index_url('edgar/data/875523/0000950123-02-008099.txt')

'https://www.sec.gov/Archives/edgar/data/875523/000095012302008099/0000950123-02-008099-index.htm'

In [1452]:
rep_q_13d_df.loc[i, 'file_name']

'edgar/data/1035096/0001104659-07-039783.txt'

In [ ]:
Rule 13d-1(e), 13d-1(f), or 13d-1(g)

In [ ]:
      company_name      | form_type |   cik   | date_filed |                  file_name                  
------------------------+-----------+---------+------------+---------------------------------------------
 COLT TELECOM GROUP PLC | SC 13G/A  | 1026733 | 2000-02-14 | edgar/data/1026733/0000315066-00-000670.txt
 COLT TELECOM GROUP PLC | SC 13D    | 1026733 | 2002-01-14 | edgar/data/1026733/0000315066-02-000119.txt
 COLT TELECOM GROUP PLC | SC 13G/A  | 1026733 | 2001-02-14 | edgar/data/1026733/0000315066-01-000879.txt
 COLT TELECOM GROUP PLC | SC 13G/A  | 1026733 | 2001-10-10 | edgar/data/1026733/0000315066-01-500878.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2002-08-08 | edgar/data/1026733/0000315066-02-002136.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2002-08-19 | edgar/data/1026733/0000315066-02-002272.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2002-12-31 | edgar/data/1026733/0000315066-02-002709.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2004-11-02 | edgar/data/1026733/0000315066-04-002169.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2004-08-02 | edgar/data/1026733/0000315066-04-001840.txt
 COLT TELECOM GROUP PLC | SC 13D/A  | 1026733 | 2004-08-18 | edgar/data/1026733/0000315066-04-001963.txt
 COLT TELECOM GROUP PLC | SC 13G    | 1026733 | 1997-02-14 | edgar/data/1026733/0000315066-97-001316.txt
 COLT TELECOM GROUP PLC | SC 13G/A  | 1026733 | 1998-02-11 | edgar/data/1026733/0000315066-98-000893.txt


In [1441]:
get_index_url('edgar/data/1026733/0000315066-01-000879.txt')

'https://www.sec.gov/Archives/edgar/data/1026733/000031506601000879/0000315066-01-000879-index.htm'

In [1438]:
rep_q_13d_df.loc[i, 'file_name']

'edgar/data/1026733/0000315066-04-001840.txt'

In [1439]:
indexes_df.loc[indexes_df['file_name'].apply(lambda x: re.search('1026733/0000315066', x) is not None)]

file_name  \
6267     edgar/data/1026733/0000315066-04-001840.txt   
6351     edgar/data/1026733/0000315066-04-001963.txt   
30241    edgar/data/1026733/0000315066-04-002169.txt   
403921   edgar/data/1026733/0000315066-02-002272.txt   
534316   edgar/data/1026733/0000315066-02-002136.txt   
550640   edgar/data/1026733/0000315066-02-002709.txt   
562007   edgar/data/1026733/0000315066-98-000893.txt   
775399   edgar/data/1026733/0000315066-01-500878.txt   
807077   edgar/data/1026733/0000315066-97-001316.txt   
916906   edgar/data/1026733/0000315066-02-000119.txt   
978733   edgar/data/1026733/0000315066-00-000670.txt   
1309209  edgar/data/1026733/0000315066-01-000879.txt   

                         document form_type  title_page_end_lower_bound  \
6267     0000315066-04-001840.txt  SC 13D/A                          24   
6351     0000315066-04-001963.txt  SC 13D/A                          24   
30241    0000315066-04-002169.txt  SC 13D/A                          23   
403921   0000315066-02-002272.txt  SC 13D/A                          25   
534316   0000315066-02-002136.txt  SC 13D/A                          24   
550640   0000315066-02-002709.txt  SC 13D/A                          22   
562007   0000315066-98-000893.txt  SC 13G/A                           1   
775399   0000315066-01-500878.txt  SC 13G/A                           1   
807077   0000315066-97-001316.txt    SC 13G                           1   
916906   0000315066-02-000119.txt    SC 13D                           1   
978733   0000315066-00-000670.txt  SC 13G/A                           1   
1309209  0000315066-01-000879.txt  SC 13G/A                           1   

         cover_page_q1_start is_rep_q_as_items is_schedule_to  \
6267                     140              True          False   
6351                     140              True          False   
30241                    220              True          False   
403921                   141              True          False   
534316                   140              True          False   
550640                   138              True          False   
562007                   182              True          False   
775399                   136              True          False   
807077                   180              True          False   
916906                   134              True          False   
978733                   171              True          False   
1309209                  178              True          False   

        has_table_of_contents  num_cusip_sedol_b_q1  cover_page_start   ...    \
6267                    False                     2               120   ...     
6351                    False                     2               120   ...     
30241                   False                     2               200   ...     
403921                  False                     2               121   ...     
534316                  False                     2               120   ...     
550640                  False                     2               118   ...     
562007                  False                     2               159   ...     
775399                  False                     2               117   ...     
807077                  False                     2               157   ...     
916906                  False                     2               114   ...     
978733                  False                     2               151   ...     
1309209                 False                     2               159   ...     

         cover_page_last_q_end  cover_page_end  num_cusip_b_items  \
6267                     744.0             751                  4   
6351                     744.0             751                  4   
30241                    824.0             831                  4   
403921                   758.0             766                  4   
534316                   757.0             765                  4   
550640                  

In [1074]:
re.strip('_', eg.loc[0, 'issuer_name'])

AttributeError: module 're' has no attribute 'strip'

In [1171]:
get_index_url('edgar/data/1070732/0001193125-14-430819.txt')

'https://www.sec.gov/Archives/edgar/data/1070732/000119312514430819/0001193125-14-430819-index.htm'

In [1143]:
i = 111
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/891456/0000950129-04-001810.txt  0000950129-04-001810.txt   

  form_type  amendment_number                              issuer_name  \
0  SC 13D/A                 4  PLAINS EXPLORATION & PRODUCTION COMPANY   

                            security_class      cusip  \
0  COMMON STOCK, PAR VALUE $0.01 PER SHARE  726505100   

                                communicator_details date_of_event_for_filing  
0  D. MARTIN PHILLIPS\n                          ...           MARCH 18, 2004

In [1169]:
i = 250
text = get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1'])
print(text)


SC 13G/A
1
a04-4587_3sc13ga.htm
SC 13G/A













 


 
  
   
  
  
  UNITED STATES
  
  
  OMB APPROVAL
  
 
 
  
   
  
  
  SECURITIES AND EXCHANGE COMMISSION
  
  
  OMB Number: 
  3235-0145
  
 
 
  
   
  
  
  Washington, D.C. 20549
  
  
  Expires:
  December 31, 2005
  
 
 
  
   
  
  
  SCHEDULE 13G
  
  
  Estimated average burden
  hours per response. . 11
  
 


 

Under the Securities Exchange Act of 1934
(Amendment No.  4)*

 



Research In Motion



(Name of Issuer)

 



Common



(Title of Class of Securities)

 



760975102



(CUSIP Number)

 



 



(Date of Event Which Requires Filing of this Statement)

 

Check the appropriate box to
designate the rule pursuant to which this Schedule is filed: 


 
  
  o
  
  
  Rule
  13d-1(b)
  
 
 
  
  o
  
  
  Rule
  13d-1(c)
  
 
 
  
  o
  
  
  Rule
  13d-1(d)
  
 


 

Check the following box if a fee is being paid with this
statement. o. (A fee is not required only if the filing person: (1) has a previous
s

In [1170]:
i = 130
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/356213/0000924355-04-000146.txt  0000924355-04-000146.txt   

  form_type  amendment_number                  issuer_name  \
0    SC 13G                 0  Pinnacle Entertainment Inc.   

               security_class      cusip date_of_event_for_filing  
0  Common Stock, no par value  723456109                  5/28/04

In [1168]:
i = 250
eg = title_page_info_df(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
                   indexes_df.loc[i, 'form_type'], directory, indexes_df.loc[i, 'cover_page_start'],\
                   indexes_df.loc[i, 'cover_page_q1_start'], indexes_df.loc[i, 'num_cusip_sedol_b_q1'])

eg

file_name                  document  \
0  edgar/data/763212/0001104659-04-010759.txt  0001104659-04-010759.txt   

  form_type  amendment_number         issuer_name security_class      cusip  \
0  SC 13G/A                 4  Research In Motion         Common  760975102   

  date_of_event_for_filing  
0

In [955]:
find_info_start(text)

433

In [958]:
eg.loc[0, 'communicator_details']

'Greg Paxton\n                           Global Power & Water, Inc.\n                           1117 Desert Lane, Suite 665\n                             Las Vegas, Nevada 89102\n                             Telephone: 707-732-9262'

In [ ]:

             INFORMATION TO BE INCLUDED IN STATEMENTS FILED PURSUANT
           TO RULES 13d-1(b), (c) AND (d) AND AMENDMENTS THERETO FILED
                              PURSUANT TO 13d-2(b)


In [1014]:
def find_info_start(text):

    text_raised = text.upper()
    
    regex0 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+TO\s+' + \
         'RULE\s+13D-1\(A\)\s+AND\s+AMENDMENTS\s+THERETO\s+FILED\s+PURSUANT\s+TO\s+RULE\s+13D-2\(A\)'

    regex1 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+' +\
    'TO\s+RULES\s+13D-1\(B\),\s+\(C\)\s+AND\s+\(D\)\s+AND\s+AMENDMENTS\s+THERETO\s+FILED\s+' +\
    'PURSUANT\s+TO\s+13D-2\(B\)'

    regex2 = '\(AMENDMENT\s+(NO|NUMBER)(\.)?(.)*\)[^\s]*\s'
    regex3 = '\s*AMENDMENT\s+(NO|NUMBER)(\.)?\s+[^\)]*\s'
    regex4 = '\s*UNDER\s+THE\s+SECURITIES\s+(AND\s+)?EXCHANGE\s+ACT\s+OF\s+1934'
    
    re_list = [regex0, regex1, regex2, regex3, regex4]
    
    result = None # Assume no result if searches unsuccessful
    
    search_result_list = []
    
    for pattern in re_list:
        
        search = find_last_search_end(pattern, text_raised)
        
        if(search is not None):
            
            search_result_list.append(search)
            
    if(len(search_result_list)):
        
        result = max(search_result_list)
        
    return(result)

In [1129]:


amendment_number = get_amendment_number(text)

info_start = find_info_start(text)

text_to_search = text[info_start:]

text_raised = text_to_search.upper()

answers_ahead = re.search('^\s*NAME\s+OF\s+ISSUER', text_raised)

starts_dict = {}
ends_dict = {}

answer_dict = {}

if(not answers_ahead):

    answer_dict['amendment_number'] = amendment_number

    regex_dict = {'issuer_name': '\s\(\s*NAME\s+OF\s+ISSUER\s*\)\s',
                  'security_class': '\s\(\s*TITLE\s+(OF|AND)\s+CLASS\s+OF\s+SECURITIES\s*\)\s',
                  'cusip': '\s\(\s*CUSIP\s+(NO|NUMBER)\s*(\.)?\s*[^\)]*\)\s', 
                  'sedol': '\s\(\s*SEDOL\s+(NO|NUMBER)\s*(\.)?\s*[^\)]*\)\s',
                  'communicator_details': '\s\(\s*NAME,\s+ADDRESS\s+AND\s+TELEPHONE\s+NUMBER[^\)]*\)\s',
                  'secondary_communicator': '\sWITH\s+A\s+COPY\s+TO\s',
                  'date_of_event_for_filing': '\s\(\s*DATE\s+OF\s+EVENT[^\)]*\)\s'}

    for name, pattern in regex_dict.items():

        search = re.search(pattern, text_raised)

        if(search is not None):

            starts_dict[name] = search.start()
            ends_dict[name] = search.end()

    l = list(starts_dict.values())
    l_ord = l.copy()
    l_ord.sort()

    order_ind = [l.index(x) for x in l_ord]
    order = [list(starts_dict.keys())[i] for i in order_ind]

    for i in range(len(order)):

        if(i == 0):

            answer = text_to_search[0:starts_dict[order[i]]]
            answer = answer.lstrip('\_\-\n\s ')
            answer = answer.rstrip('\_\-\n\s ')
            answer_dict[order[i]] = [answer]

        else:

            answer = text_to_search[ends_dict[order[i-1]]:starts_dict[order[i]]]
            answer = answer.lstrip('\_\-\n\s ')
            answer = answer.rstrip('\_\-\n\s ')
            answer_dict[order[i]] = [answer]

    df = pd.DataFrame(answer_dict)

In [1130]:
starts_dict

{'issuer_name': 32,
 'security_class': 154,
 'cusip': 260,
 'communicator_details': 391,
 'date_of_event_for_filing': 513}

In [1131]:
ends_dict

{'issuer_name': 50,
 'security_class': 186,
 'cusip': 277,
 'communicator_details': 490,
 'date_of_event_for_filing': 570}

In [1133]:
text_to_search[0:32]

'\n\nASCENT MEDIA CORPORATION\n\n\n\xa0\n\n'

In [1126]:
df

issuer_name  \
0  ASCENT MEDIA CORPORATION   

                                      security_class  \
0  Series A Common Stock, par value $0.01 per sha...   

                                communicator_details date_of_event_for_filing  
0  Series A Common Stock: 043632 108\nSeries B Co...         January 22, 2010

In [1137]:
pd.DataFrame({'a': [4], 'b': [6, 7]})

ValueError: arrays must all be same length

In [1138]:
d1 = {'a': [1], 'b': [2]}
d2 = {'a': [3], 'b': [4]}

In [1139]:
d1 + d2

TypeError: unsupported operand type(s) for +: 'dict' and 'dict'

In [1001]:
order

['issuer_name',
 'security_class',
 'cusip',
 'communicator_details',
 'secondary_communicator',
 'date_of_event_for_filing']

In [1002]:
starts_dict

{'issuer_name': 52,
 'security_class': 162,
 'cusip': 265,
 'communicator_details': 576,
 'secondary_communicator': 780,
 'date_of_event_for_filing': 1072}

In [1003]:
ends_dict

{'issuer_name': 124,
 'security_class': 255,
 'cusip': 344,
 'communicator_details': 747,
 'secondary_communicator': 796,
 'date_of_event_for_filing': 1183}

In [1004]:
text[796:1072]

'                 2099 PENNSYLVANIA AVENUE, SUITE 900\n                             WASHINGTON, D.C. 20006\n                                 (212) 452-0101\n                     (Name, Address and Telephone Number of\n                      Person Authorized to Receive Notices\n    '

In [1076]:
df

issuer_name  \
0                        PEOPLES COMMUNITY BANCOR...   

                           security_class        cusip  \
0  COMMON STOCK, $.01 PAR VALUE PER SHARE  71086E 10 7   

                                communicator_details  \
0  Thomas J. Noe\n                      Peoples C...   

                        date_of_event_for_filing  
0                                 April 27, 2004

In [919]:
eg.loc[0]

issuer_name                                   INTERPORE INTERNATIONAL, INC...
security_class                                               COMMON STOCK\n- 
cusip                                                                        
date_of_event_for_filing                                   MARCH 23, 2004\n- 
Name: 0, dtype: object

In [1304]:
title_page_info_df??

In [1305]:
def title_page_info_df(file_name, document, form_type, directory, cover_page_start, cover_page_q1_start, num_cusip_sedol_b_q1):
    
    text = get_title_page(file_name, document, directory, cover_page_start, cover_page_q1_start,
                    num_cusip_sedol_b_q1)
    
    amendment_number = get_amendment_number(text)
    
    info_start = find_info_start(text)
    
    text_to_search = text[info_start:]
    
    text_raised = text_to_search.upper()
    
    answers_ahead = re.search('^\s*NAME\s+OF\s+ISSUER', text_raised)
    
    starts_dict = {}
    ends_dict = {}
    
    answer_dict = {'file_name': [file_name],
                   'document': [document],
                   'form_type': [form_type]}
    
    if(not answers_ahead):
        
        answer_dict['amendment_number'] = amendment_number
        
        regex_dict = {'issuer_name': '\s\(\s*NAME\s+OF\s+ISSUER\s*\)\s',
                      'security_class': '\s\(\s*TITLE\s+(OF|AND)\s+CLASS\s+OF\s+SECURITIES\s*\)\s',
                      'cusip': '\s\(\s*CUSIP\s+(NO|NUMBER)\s*(\.)?\s*[^\)]*\)\s', 
                      'sedol': '\s\(\s*SEDOL\s+(NO|NUMBER)\s*(\.)?\s*[^\)]*\)\s',
                      'communicator_details': '\s\(\s*NAME,\s+ADDRESS\s+AND\s+TELEPHONE\s+NUMBER[^\)]*\)\s',
                      'secondary_communicator': '\sWITH\s+A\s+COPY\s+TO\s',
                      'date_of_event_for_filing': '\s\(\s*DATE\s+OF\s+EVENT[^\)]*\)\s'}
        
        for name, pattern in regex_dict.items():
            
            search = re.search(pattern, text_raised)
            
            if(search is not None):
                
                starts_dict[name] = search.start()
                ends_dict[name] = search.end()
          
        l = list(starts_dict.values())
        l_ord = l.copy()
        l_ord.sort()
        
        order_ind = [l.index(x) for x in l_ord]
        order = [list(starts_dict.keys())[i] for i in order_ind]
        
        for i in range(len(order)):
            
            if(i == 0):
                
                answer = text_to_search[0:starts_dict[order[i]]]
                answer = answer.strip('\_\-\n\s \xa0\*\^')
                answer_dict[order[i]] = [answer]
                
            else:
                
                answer = text_to_search[ends_dict[order[i-1]]:starts_dict[order[i]]]
                answer = answer.strip('\_\-\n\s \xa0\*\^')
                answer_dict[order[i]] = [answer]
        
        df = pd.DataFrame(answer_dict)
        return(df)
    
    else:
        
        return(None)
    

In [851]:
d = {'a': 5, 'b': 6, 'c': -10}

In [886]:
l = list(d.values())
l

[5, 6, -10]

In [901]:
' -------   c  aoat ----  --'.strip('- ')

'c  aoat'

In [872]:
l.index(-10)

0

In [891]:
ll = l.copy()

In [892]:
l

[5, 6, -10]

In [895]:
ll

[-10, 5, 6]

In [897]:
order = [l.index(x) for x in ll]
order

[2, 0, 1]

In [900]:
order_k = [list(d.keys())[i] for i in order]
order_k

['c', 'a', 'b']

In [894]:
ll.sort()

In [874]:
ord(l)

TypeError: ord() expected string of length 1, but list found

In [869]:
[l.index(x) for x in l.sort()]

TypeError: 'NoneType' object is not iterable

In [867]:
d[1]

KeyError: 1

In [825]:
text[index:]

'\n\n\nSpectraSite, Inc.\n\n\n\n(Name\nof Issuer)\n\n\xa0\n\n\n\nCommon Stock, par value $.01\n\n\n\n(Title\nof Class of Securities)\n\n\xa0\n\n\n\n84761M 10 4\n\n\n\n(CUSIP\nNumber)\n\n\xa0\n\n\n\nJohn F. Hartigan, Esq.\nMorgan, Lewis & Bockius LLP\n300 S. Grand Avenue\nLos Angeles, CA 90071\n(213) 612-2500\n\n\n\n(Name,\nAddress and Telephone Number of Person\nAuthorized to Receive Notices and Communications)\n\n\xa0\n\n\n\nMay 14, 2004\n\n\n\n(Date\nof Event which Requires Filing of this Statement)\n\nIf the filing person has\npreviously filed a statement on Schedule\xa013G to report the acquisition\nthat is the subject of this Schedule\xa013D, and is filing this\nschedule\xa0because of §§240.13d-1(e), 240.13d-1(f) or 240.13d-1(g), check\nthe following box. o\n\nNote: Schedules filed in paper format shall\ninclude a signed original and five copies of the schedule, including all exhibits.\nSee §240.13d-7 for other parties to whom copies are to be sent. \n\n* The remainder of this cov

In [823]:
index = find_info_start(text)
index

473

In [824]:
text[index:]

'\n\n\nSpectraSite, Inc.\n\n\n\n(Name\nof Issuer)\n\n\xa0\n\n\n\nCommon Stock, par value $.01\n\n\n\n(Title\nof Class of Securities)\n\n\xa0\n\n\n\n84761M 10 4\n\n\n\n(CUSIP\nNumber)\n\n\xa0\n\n\n\nJohn F. Hartigan, Esq.\nMorgan, Lewis & Bockius LLP\n300 S. Grand Avenue\nLos Angeles, CA 90071\n(213) 612-2500\n\n\n\n(Name,\nAddress and Telephone Number of Person\nAuthorized to Receive Notices and Communications)\n\n\xa0\n\n\n\nMay 14, 2004\n\n\n\n(Date\nof Event which Requires Filing of this Statement)\n\nIf the filing person has\npreviously filed a statement on Schedule\xa013G to report the acquisition\nthat is the subject of this Schedule\xa013D, and is filing this\nschedule\xa0because of §§240.13d-1(e), 240.13d-1(f) or 240.13d-1(g), check\nthe following box. o\n\nNote: Schedules filed in paper format shall\ninclude a signed original and five copies of the schedule, including all exhibits.\nSee §240.13d-7 for other parties to whom copies are to be sent. \n\n* The remainder of this cov

In [795]:
text_raised = text.upper()
    
regex0 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+TO\s+' + \
     'RULE\s+13D-1(A)\s+AND\s+AMENDMENTS\s+THERETO\s+FILED\s+PURSUANT\s+TO\s+RULE\s+13D-2(A)'

regex1 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+TO\s+RULES\s+13D-1(B),\s+' + \
     '(C)\s+AND\s+(D)\s+AND\s+AMENDMENTS\s+THERETO\s+FILE\s+PURSUANT\s+TO\s+13D-2(B)'

regex2 = '\(AMENDMENT\s+(NO|NUMBER)(\.)?(.)*\)'
regex3 = '\s*AMENDMENT\s+(NO|NUMBER)(\.)?\s+[^\)]*\s'
regex4 = '\s*UNDER\s+THE\s+SECURITIES\s+(AND\s+)?EXCHANGE\s+ACT\s+OF\s+1934'

re_list = [regex0, regex1, regex2, regex3, regex4]

result = None # Assume no result if searches unsuccessful

search_result_list = []

for pattern in re_list:

    search = re.search(pattern, text_raised)

    if(search is not None):

        search_result_list.append(search.end())

if(len(search_result_list)):

    result = max(search_result_list)

In [797]:
re.search(re_list[2], text_raised)

<re.Match object; span=(292, 310), match='(AMENDMENT NO. __)'>

In [796]:
re.search(re_list[3], text_raised)

In [799]:
re.findall('[^\)]*', 'GAGTETAE   AGERWGTAGT ) agerga')

['GAGTETAE   AGERWGTAGT ', '', ' agerga', '']

In [ ]:
re.search(re_list[4], text_raised)

In [749]:
search_result_list

[321]

In [737]:
regex4 = '\s*UNDER\s+THE\s+SECURITIES\s+(AND\s+)?EXCHANGE\s+ACT\s+OF\s+1934'

In [743]:
re.search(regex4, text.upper()).group(0)

'\n     \n                       \n     \n    UNDER\n      THE SECURITIES EXCHANGE ACT OF 1934'

In [496]:
get_index_url('edgar/data/766524/0000766524-04-000102.txt')

'https://www.sec.gov/Archives/edgar/data/766524/000076652404000102/0000766524-04-000102-index.htm'

In [494]:
indexes_df.loc[1351, 'file_name']

'edgar/data/766524/0000766524-04-000102.txt'

In [449]:
get_index_url('edgar/data/897484/0001144204-04-004169.txt')

'https://www.sec.gov/Archives/edgar/data/897484/000114420404004169/0001144204-04-004169-index.htm'

In [ ]:
def title_page_info_df(file_name, document, form_type, directory, cover_page_start)

In [ ]:
edgar/data/704159/0001015402-04-001460.txt

In [538]:
def get_amendment_number(text):
    
    text_raised = text.upper()
    
    regex0 = '\(AMENDMENT\s+(NO|NUMBER)(\.)?(.)*\)'
    regex1 = '\n\s*AMENDMENT\s+(NO|NUMBER)(\.)?\s*(.)*\s'
    
    re_list = [regex0, regex1]
    
    for pattern in re_list:
        
        amendment_piece = re.search(pattern, text_raised)
        
        if(amendment_piece is not None):
            break
            
    if(amendment_piece is not None):
    
        number_search = re.search('[0-9]+', amendment_piece.group(0))

        if(number_search is not None):

            result = int(number_search.group(0))

        else:

            result = None

        return(result)
    
    else:
        
        return(None)

In [761]:
def find_last_search_end(regex, text):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return(None)
    
    else:
        
        end = 0
        
        while(search is not None):
            
            end = end + search.end()
            search = re.search(regex, text[end:])
        
    return(end)

In [816]:
def find_info_start(text):

    text_raised = text.upper()
    
    regex0 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+TO\s+' + \
         'RULE\s+13D-1(A)\s+AND\s+AMENDMENTS\s+THERETO\s+FILED\s+PURSUANT\s+TO\s+RULE\s+13D-2(A)'

    regex1 = '\s*INFORMATION\s+TO\s+BE\s+INCLUDED\s+IN\s+STATEMENTS\s+FILED\s+PURSUANT\s+TO\s+RULES\s+13D-1(B),\s+' + \
         '(C)\s+AND\s+(D)\s+AND\s+AMENDMENTS\s+THERETO\s+FILE\s+PURSUANT\s+TO\s+13D-2(B)'

    regex2 = '\(AMENDMENT\s+(NO|NUMBER)(\.)?(.)*\)[^\s]*\s'
    regex3 = '\s*AMENDMENT\s+(NO|NUMBER)(\.)?\s+[^\)]*\s'
    regex4 = '\s*UNDER\s+THE\s+SECURITIES\s+(AND\s+)?EXCHANGE\s+ACT\s+OF\s+1934'
    
    re_list = [regex0, regex1, regex2, regex3, regex4]
    
    result = None # Assume no result if searches unsuccessful
    
    search_result_list = []
    
    for pattern in re_list:
        
        search = find_last_search_end(pattern, text_raised)
        
        if(search is not None):
            
            search_result_list.append(search)
            
    if(len(search_result_list)):
        
        result = max(search_result_list)
        
    return(result)
    

In [670]:
min([1, 7, -1,2,3])

-1

In [ ]:
get_amendment_number(text)

In [613]:
indexes_df.loc[indexes_df['form_type'] == 'SC 13D']

file_name  \
2        edgar/data/1163453/0001019687-04-000771.txt   
32       edgar/data/1050377/0001193125-04-068397.txt   
48        edgar/data/904534/0001144204-04-005373.txt   
71        edgar/data/878556/0000919574-04-001218.txt   
72       edgar/data/1284771/0001140905-04-000047.txt   
75       edgar/data/1265816/0000919574-04-001338.txt   
82       edgar/data/1085869/0001193125-04-059071.txt   
86       edgar/data/1260182/0001005150-04-001649.txt   
103      edgar/data/1275323/0000909518-04-000358.txt   
120      edgar/data/1280496/0001015402-04-002477.txt   
123      edgar/data/1013746/0000950142-04-001802.txt   
135      edgar/data/1227728/0001193125-04-062424.txt   
136      edgar/data/1274520/0001177456-04-000209.txt   
140      edgar/data/1133256/0001193125-04-099611.txt   
145      edgar/data/1288341/0001193125-04-103757.txt   
146      edgar/data/1227728/0000921530-04-000245.txt   
160      edgar/data/1272801/0001144204-04-004534.txt   
161       edgar/data/795615/0001047469-04-021069.txt   
174      edgar/data/1075628/0001169232-04-003420.txt   
181      edgar/data/1047537/0000943374-04-000308.txt   
187      edgar/data/1292348/0001108017-04-000314.txt   
189      edgar/data/1061464/0001061464-04-000010.txt   
206       edgar/data/354383/0000905729-04-000162.txt   
218      edgar/data/1295315/0001123292-04-000291.txt   
220      edgar/data/1289297/0000921530-04-000245.txt   
225       edgar/data/899881/0001035704-04-000300.txt   
234      edgar/data/1122322/0001193125-04-090192.txt   
237       edgar/data/857073/0001210052-04-000022.txt   
241      edgar/data/1295249/0001144204-04-008961.txt   
246      edgar/data/1287361/0001062993-04-000848.txt   
...                                              ...   
1368032  edgar/data/1018519/0000950123-98-004925.txt   
1368105  edgar/data/1401412/0001213900-19-009859.txt   
1368111   edgar/data/903213/0000892569-98-002739.txt   
1368112   edgar/data/904571/0001047469-98-043104.txt   
1368118  edgar/data/1626127/0000919574-18-003203.txt   
1368158   edgar/data/939318/0000941302-98-000083.txt   
1368170  edgar/data/1049429/0000950133-98-003149.txt   
1368171   edgar/data/845577/0000897423-98-000162.txt   
1368174   edgar/data/934979/0000934979-98-000013.txt   
1368177  edgar/data/1490281/0001140361-19-023397.txt   
1368208   edgar/data/706116/0000927016-98-004348.txt   
1368209  edgar/data/1072617/0000891618-98-004590.txt   
1368220  edgar/data/1068592/0000950123-98-007810.txt   
1368223  edgar/data/1072386/0001047469-98-038061.txt   
1368225   edgar/data/914329/0000950135-98-006236.txt   
1368231  edgar/data/1056477/0000950133-98-002545.txt   
1368235  edgar/data/1502541/0001213900-19-019892.txt   
1368245   edgar/data/313143/0000938775-97-000018.txt   
1368247  edgar/data/1054263/0000950172-98-000822.txt   
1368248  edgar/data/1002813/0001061693-98-000002.txt   
1368250   edgar/data/943658/0000949111-98-000031.txt   
1368260  edgar/data/1510295/0001510295-18-000082.txt   
1368262  edgar/data/1189136/0001104659-18-025663.txt   
1368281   edgar/data/350129/0000950147-98-000540.txt   
1368285  edgar/data/1792243/0001599916-19-000152.txt   
1368287  edgar/data/1386809/0001144204-07-024379.txt   
1368308  edgar/data/1058854/0001058854-18-000024.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   

                         document form_type  title_page_end_lower_bound  \
2        0001019687-04-000771.txt    SC 13D                           1   
32       0001193125-04-068397.txt    SC 13D                        1383   
48       0001144204-04-005373.txt    SC 13D                           1   
71       0000919574-04-001218.txt    SC 13D                        2701   
72       0001140905-04-000047.txt    SC 13D                        1854   
75       0000919574-04-001338.txt    SC 13D                        2505   
82       0001193125-04-059071.txt    SC 13D  

In [667]:
i = 206
print(get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1']))


SC 13D
1
kacprabsc13d_041304.htm
SCHEDULE 13D



Kalamazoo Acquisition Corporation/Prab Schedule 13D - 04/13/04



SECURITIES AND EXCHANGE COMMISSION
WASHINGTON, D.C. 20549

SCHEDULE 13D
(Rule 13d-101)


INFORMATION TO BE INCLUDED IN STATEMENTS FILED PURSUANT TO RULE 13d-1(a) AND
AMENDMENTS THERETO FILED PURSUANT TO RULE 13d-2(a)
(Amendment No. ___)





PRAB, INC.




(Name of Issuer)




 




Common Stock $0.10 Par Value




(Title of Class of Securities)




 




739413102




(CUSIP Number)




 




Gary A. Herder
Prab, Inc.
5944 East Kilgore Road
Kalamazoo, Michigan 49003
Telephone (269) 382-8200




(Name, Address and Telephone Number of Person Authorized to




Receive Notices and Communications)




 




April 5, 2004




(Date of Event Which Requires Filing of this Statement)



          If the filing person has previously filed a statement on Schedule 13G to report the acquisition which is the subject of this Schedule 13D, and is filing this schedule because of Rule 13d

In [663]:
get_index_url('edgar/data/1013746/0000950142-04-001802.txt')

'https://www.sec.gov/Archives/edgar/data/1013746/000095014204001802/0000950142-04-001802-index.htm'

In [633]:
indexes_df.loc[i]

file_name                      edgar/data/1085869/0001193125-04-059071.txt
document                                          0001193125-04-059071.txt
form_type                                                           SC 13D
title_page_end_lower_bound                                            1820
cover_page_q1_start                                                   1861
is_rep_q_as_items                                                    False
is_schedule_to                                                       False
has_table_of_contents                                                False
num_cusip_sedol_b_q1                                                     2
cover_page_start                                                      1861
item_section_start                                                    3026
cover_page_last_q_end                                                 2985
cover_page_end                                                        3015
num_cusip_b_items        

In [635]:
t = get_main_doc_text('edgar/data/1085869/0001193125-04-059071.txt', '0001193125-04-059071.txt', directory)


In [651]:
cover_page_start(t, 'SC 13D', lower_bound = 1820, cover_page_q1 = 1861, rep_q_as_items = False)

1825

In [652]:
t[1825:]

'\n SCHEDULE 13D  CUSIP No. 71375U 101  \xa0\n\n\n\n\n\n\n\n\n\n\n\n\xa0\xa01.\n\xa0\n Name of Reporting Person I.R.S. Identification No. of above person (entities only). \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0Morton H. Meyerson\n\xa0\n\xa0\n\n\n\n\xa0\xa02.\n\xa0\n Check the Appropriate Box if a Member of a Group (See Instructions) (a)\xa0\xa0¨ (b)\xa0\xa0¨\n\xa0\n\xa0\n\n\n\n\xa0\xa03.\n\xa0\n SEC Use Only \xa0\n\xa0\n\xa0\n\n\n\n\xa0\xa04.\n\xa0\n Source of Funds (See Instructions) \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0PF\n\xa0\n\xa0\n\n\n\n\xa0\xa05.\n\xa0\n Check Box if Disclosure of Legal Proceedings Is Required Pursuant to Items 2(d) or 2(e) \xa0\n\xa0\n¨\n\n\n\n\xa0\xa06.\n\xa0\n Citizenship or Place of Organization \xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0USA\n\xa0\n\xa0\n\n\n\n\n\n\n\n\n\n\n NUMBER\xa0OF SHARES BENEFICIALLY OWNED\xa0BY EACH REPORTING PERSON WITH\n\xa0\n \xa0\xa07.\xa0\xa0\xa0\xa0Sole Voting Power \xa0 \xa0\xa0\xa0\xa0\

In [650]:
def cover_page_start(text, form_type, lower_bound = None, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text, cover_page_q1)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_cover_page_q1_start(text, form_type, lower_bound, cover_page_q1, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)(.)*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)

In [639]:
indexes_df.loc[indexes_df['form_type'] == 'SC 13D']

file_name  \
2        edgar/data/1163453/0001019687-04-000771.txt   
32       edgar/data/1050377/0001193125-04-068397.txt   
48        edgar/data/904534/0001144204-04-005373.txt   
71        edgar/data/878556/0000919574-04-001218.txt   
72       edgar/data/1284771/0001140905-04-000047.txt   
75       edgar/data/1265816/0000919574-04-001338.txt   
82       edgar/data/1085869/0001193125-04-059071.txt   
86       edgar/data/1260182/0001005150-04-001649.txt   
103      edgar/data/1275323/0000909518-04-000358.txt   
120      edgar/data/1280496/0001015402-04-002477.txt   
123      edgar/data/1013746/0000950142-04-001802.txt   
135      edgar/data/1227728/0001193125-04-062424.txt   
136      edgar/data/1274520/0001177456-04-000209.txt   
140      edgar/data/1133256/0001193125-04-099611.txt   
145      edgar/data/1288341/0001193125-04-103757.txt   
146      edgar/data/1227728/0000921530-04-000245.txt   
160      edgar/data/1272801/0001144204-04-004534.txt   
161       edgar/data/795615/0001047469-04-021069.txt   
174      edgar/data/1075628/0001169232-04-003420.txt   
181      edgar/data/1047537/0000943374-04-000308.txt   
187      edgar/data/1292348/0001108017-04-000314.txt   
189      edgar/data/1061464/0001061464-04-000010.txt   
206       edgar/data/354383/0000905729-04-000162.txt   
218      edgar/data/1295315/0001123292-04-000291.txt   
220      edgar/data/1289297/0000921530-04-000245.txt   
225       edgar/data/899881/0001035704-04-000300.txt   
234      edgar/data/1122322/0001193125-04-090192.txt   
237       edgar/data/857073/0001210052-04-000022.txt   
241      edgar/data/1295249/0001144204-04-008961.txt   
246      edgar/data/1287361/0001062993-04-000848.txt   
...                                              ...   
1368032  edgar/data/1018519/0000950123-98-004925.txt   
1368105  edgar/data/1401412/0001213900-19-009859.txt   
1368111   edgar/data/903213/0000892569-98-002739.txt   
1368112   edgar/data/904571/0001047469-98-043104.txt   
1368118  edgar/data/1626127/0000919574-18-003203.txt   
1368158   edgar/data/939318/0000941302-98-000083.txt   
1368170  edgar/data/1049429/0000950133-98-003149.txt   
1368171   edgar/data/845577/0000897423-98-000162.txt   
1368174   edgar/data/934979/0000934979-98-000013.txt   
1368177  edgar/data/1490281/0001140361-19-023397.txt   
1368208   edgar/data/706116/0000927016-98-004348.txt   
1368209  edgar/data/1072617/0000891618-98-004590.txt   
1368220  edgar/data/1068592/0000950123-98-007810.txt   
1368223  edgar/data/1072386/0001047469-98-038061.txt   
1368225   edgar/data/914329/0000950135-98-006236.txt   
1368231  edgar/data/1056477/0000950133-98-002545.txt   
1368235  edgar/data/1502541/0001213900-19-019892.txt   
1368245   edgar/data/313143/0000938775-97-000018.txt   
1368247  edgar/data/1054263/0000950172-98-000822.txt   
1368248  edgar/data/1002813/0001061693-98-000002.txt   
1368250   edgar/data/943658/0000949111-98-000031.txt   
1368260  edgar/data/1510295/0001510295-18-000082.txt   
1368262  edgar/data/1189136/0001104659-18-025663.txt   
1368281   edgar/data/350129/0000950147-98-000540.txt   
1368285  edgar/data/1792243/0001599916-19-000152.txt   
1368287  edgar/data/1386809/0001144204-07-024379.txt   
1368308  edgar/data/1058854/0001058854-18-000024.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   

                         document form_type  title_page_end_lower_bound  \
2        0001019687-04-000771.txt    SC 13D                           1   
32       0001193125-04-068397.txt    SC 13D                        1383   
48       0001144204-04-005373.txt    SC 13D                           1   
71       0000919574-04-001218.txt    SC 13D                        2701   
72       0001140905-04-000047.txt    SC 13D                        1854   
75       0000919574-04-001338.txt    SC 13D                        2505   
82       0001193125-04-059071.txt    SC 13D  

In [641]:
i = 120
print(get_title_page(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'],\
               directory, indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_q1_start'],\
                    indexes_df.loc[i, 'num_cusip_sedol_b_q1']))


SC 13D
1
body_13d.htm
PETROHAWK ENERGY, LLC SC-13D 05/25/2004

Petrohawk Energy, LLC SC-13D 05/25/2004





UNITED STATESSECURITIES AND EXCHANGE COMMISSIONWashington, D.C. 20549
SCHEDULE 13D
Under the Securities Exchange Act of 1934(Amendment No.    )*


Beta Oil & Gas, Inc.

(Name of Issuer)

Common Stock, par value $.001 per share

(Title of Class of Securities)

08659A302


(CUSIP Number)

Petrohawk Energy, LLC1100 Louisiana, Suite 4400Houston, Texas 77002(832) 204-2700

(Name, Address and Telephone Number of Person Authorized toReceive Notices and Communications)

May 25, 2004

(Date of Event which Requires Filling of this Statement)



If the filing person has previously filed a statement on Schedule 13G to report the acquisition that is the subject of this Schedule 13D, and is filing this schedule because of ·· 240.13d-1(e), 240.13d-1 (f) or 240.13d-1(g), check the following box.   (    )



Note: Schedules filed in paper format shall include a signed original and five copies of

In [631]:
get_index_url('edgar/data/1085869/0001193125-04-059071.txt 	')

'https://www.sec.gov/Archives/edgar/data/1085869/000119312504059071/0001193125-04-059071-index.htm'

In [619]:
get_index_url('edgar/data/878556/0000919574-04-001218.txt')

'https://www.sec.gov/Archives/edgar/data/878556/000091957404001218/0000919574-04-001218-index.htm'

In [612]:
indexes_df

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2        edgar/data/1163453/0001019687-04-000771.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
9        edgar/data/1163453/0001019687-04-001131.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
12       edgar/data/1279095/0001144204-04-004297.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
16       edgar/data/1135338/0000919574-04-001356.txt   
17        edgar/data/923877/0000807249-04-000123.txt   
18       edgar/data/1135338/0000919574-04-001735.txt   
19       edgar/data/1279095/0001144204-04-007831.txt   
20       edgar/data/1135338/0000919574-04-001367.txt   
21       edgar/data/1135338/0000919574-04-001873.txt   
22       edgar/data/1135338/0000919574-04-001745.txt   
23       edgar/data/1135338/0000919574-04-001385.txt   
24        edgar/data/925765/0000926274-04-000155.txt   
25       edgar/data/1135338/0000919574-04-001749.txt   
26       edgar/data/1135338/0000919574-04-001895.txt   
27       edgar/data/1135338/0000919574-04-001407.txt   
28        edgar/data/927752/0000950142-04-002200.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
...                                              ...   
1368332  edgar/data/1125920/0000215457-19-002604.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368334   edgar/data/893691/0000215457-19-004906.txt   
1368335  edgar/data/1104186/0000919574-19-001286.txt   
1368336  edgar/data/1118417/0001104659-19-008720.txt   
1368337  edgar/data/1201792/0001037389-19-000146.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368339  edgar/data/1621563/0000807985-19-000028.txt   
1368340  edgar/data/1395064/0001104659-19-060139.txt   
1368341  edgar/data/1050045/0001104659-19-071096.txt   
1368342   edgar/data/826020/0001062993-19-004564.txt   
1368343  edgar/data/1527541/0001104659-19-056194.txt   
1368344  edgar/data/1504103/0001193125-19-279063.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368346  edgar/data/1581164/0001104659-19-071304.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   
1368349  edgar/data/1320854/0001085146-19-000414.txt   
1368350  edgar/data/1430308/0001214659-19-000763.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368352   edgar/data/862831/0000215457-19-004043.txt   
1368353  edgar/data/1045810/0000215457-19-004826.txt   
1368354  edgar/data/1564584/0000895421-19-000289.txt   
1368355  edgar/data/1534126/0000950157-19-000740.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368357  edgar/data/1655020/0001144204-19-008356.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   
1368359  edgar/data/1124941/0001104659-19-038258.txt   
1368360  edgar/data/1560258/0001193125-19-297684.txt   
1368361  edgar/data/1404574/0000921895-19-001932.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001019687-04-000771.txt    SC 13D                           1   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G  

In [644]:
sql = """SELECT * FROM edgar.sc13dg_indexes
         WHERE num_cusip_sedol_b_q1 = 1 
         AND cover_page_start = cover_page_q1_start;
         """

cover_page_probs_df = pd.read_sql(sql, engine)

In [645]:
cover_page_probs_df

file_name                  document  \
0       edgar/data/742685/0000950134-04-013101.txt  0000950134-04-013101.txt   
1      edgar/data/1157291/0001213900-04-000332.txt  0001213900-04-000332.txt   
2      edgar/data/1157291/0001213900-04-000420.txt  0001213900-04-000420.txt   
3        edgar/data/22252/0000935836-04-000180.txt  0000935836-04-000180.txt   
4       edgar/data/896778/0000867579-04-000286.txt  0000867579-04-000286.txt   
5      edgar/data/1296103/0000950159-04-000645.txt  0000950159-04-000645.txt   
6      edgar/data/1051094/0001193125-04-162329.txt  0001193125-04-162329.txt   
7      edgar/data/1127842/0001193125-04-154151.txt  0001193125-04-154151.txt   
8      edgar/data/1127842/0001193125-04-154160.txt  0001193125-04-154160.txt   
9      edgar/data/1132874/0001144204-04-011454.txt  0001144204-04-011454.txt   
10     edgar/data/1276470/0001013594-04-000273.txt  0001013594-04-000273.txt   
11      edgar/data/883907/0001127855-04-000501.txt  0001127855-04-000501.txt   
12     edgar/data/1057257/0001157523-04-007830.txt  0001157523-04-007830.txt   
13      edgar/data/891035/0000867579-04-000193.txt  0000867579-04-000193.txt   
14      edgar/data/764065/0000950159-04-000645.txt  0000950159-04-000645.txt   
15      edgar/data/896778/0000867579-04-000258.txt  0000867579-04-000258.txt   
16     edgar/data/1228627/0001144204-04-012557.txt  0001144204-04-012557.txt   
17      edgar/data/835664/0001099281-04-000077.txt  0001099281-04-000077.txt   
18      edgar/data/939897/0001013594-04-000293.txt  0001013594-04-000293.txt   
19      edgar/data/946486/0000867579-04-000194.txt  0000867579-04-000194.txt   
20     edgar/data/1055282/0000950159-04-000648.txt  0000950159-04-000648.txt   
21     edgar/data/1213601/0000909518-04-000798.txt  0000909518-04-000798.txt   
22      edgar/data/895728/0000898286-04-000034.txt  0000898286-04-000034.txt   
23      edgar/data/895728/0001297402-04-000003.txt  0001297402-04-000003.txt   
24     edgar/data/1132034/0001288845-04-000081.txt  0001288845-04-000081.txt   
25     edgar/data/1132034/0001288845-04-000083.txt  0001288845-04-000083.txt   
26     edgar/data/1132034/0001288845-04-000108.txt  0001288845-04-000108.txt   
27     edgar/data/1132034/0001288845-04-000110.txt  0001288845-04-000110.txt   
28      edgar/data/851520/0001056288-04-000664.txt  0001056288-04-000664.txt   
29     edgar/data/1114365/0001056288-04-000430.txt  0001056288-04-000430.txt   
...                                            ...                       ...   
99027  edgar/data/1130337/0000935836-04-000224.txt  0000935836-04-000224.txt   
99028   edgar/data/749872/0001128239-04-000067.txt  0001128239-04-000067.txt   
99029   edgar/data/913142/0001013594-04-000346.txt  0001013594-04-000346.txt   
99030  edgar/data/1298186/0000935836-04-000199.txt  0000935836-04-000199.txt   
99031   edgar/data/932903/0001056288-04-000495.txt  0001056288-04-000495.txt   
99032  edgar/data/1035744/0001169232-04-003613.txt  0001169232-04-003613.txt   
99033  edgar/data/1303476/0000927946-04-000220.txt  0000927946-04-000220.txt   
99034    edgar/data/70858/0000070858-04-000437.txt  0000070858-04-000437.txt   
99035   edgar/data/902367/0001169232-04-003905.txt  0001169232-04-003905.txt   
99036  edgar/data/1063711/0001015402-04-003020.txt  0001015402-04-003020.txt   
99037  edgar/data/1191711/0001139020-04-000191.txt  0001139020-04-000191.txt   
99038   edgar/data/723612/0000723612-04-000029.txt  0000723612-04-000029.txt   
99039   edgar/data/932267/0000943663-04-000319.txt  0000943663-04-000319.txt   
99040   edgar/data/356080/0000897226-04-000247.txt  0000897226-04-000247.txt   
99041  edgar/data/1103021/0001193125-04-152066.txt  0001193125-04-152066.txt   
99042   edgar/data/313353/0001072588-04-000359.txt  0001072588-04-000359.txt   
99043    edgar/data/96287/0001169232-04-003615.txt  0001169232-04-003615.txt   
99044    edgar/data/96287/0001169232-04-004863.txt  0001169232-04-004863.txt   
99045   edgar/data/898286/0000898286-04-0

In [647]:
indexes_df.loc[np.logical_and(indexes_df['num_cusip_sedol_b_q1'] == 2,\
                              indexes_df['cover_page_start'] == indexes_df['cover_page_q1_start'])]

file_name  \
82       edgar/data/1085869/0001193125-04-059071.txt   
90       edgar/data/1171939/0001171939-04-000004.txt   
91       edgar/data/1166971/0001166971-04-000005.txt   
162      edgar/data/1137774/0001137774-04-000179.txt   
163      edgar/data/1137774/0001137774-04-000180.txt   
232      edgar/data/1018833/0000061227-04-000010.txt   
330      edgar/data/1137774/0001137774-04-000176.txt   
345      edgar/data/1020455/0001193125-04-055553.txt   
349      edgar/data/1020455/0001193125-04-063727.txt   
407       edgar/data/947055/0000893220-04-001130.txt   
478      edgar/data/1287873/0000950157-04-000369.txt   
559       edgar/data/909645/0000950172-04-001446.txt   
685        edgar/data/86902/0001193125-04-110135.txt   
688       edgar/data/907254/0001193125-04-110135.txt   
779      edgar/data/1065833/0001193125-04-084750.txt   
789      edgar/data/1259245/0000910647-04-000270.txt   
851      edgar/data/1033444/0001193125-04-099550.txt   
982       edgar/data/874977/0001193125-04-084750.txt   
1065     edgar/data/1050825/0001166971-04-000005.txt   
1158     edgar/data/1072048/0001193125-04-092915.txt   
1160     edgar/data/1050825/0001171939-04-000004.txt   
1286     edgar/data/1088033/0001193125-04-012641.txt   
1323     edgar/data/1088033/0001193125-04-027119.txt   
1336      edgar/data/852426/0000930413-04-000443.txt   
1527     edgar/data/1187225/0001193125-04-029258.txt   
1575     edgar/data/1170752/0000950152-04-001038.txt   
1641        edgar/data/2186/0001005477-04-000593.txt   
1872       edgar/data/82536/0001137774-04-000083.txt   
2040     edgar/data/1056421/0000950136-04-000434.txt   
3070      edgar/data/904778/0001193125-04-047954.txt   
...                                              ...   
1367304  edgar/data/1008735/0000945621-98-000069.txt   
1367312   edgar/data/792863/0000729057-96-000184.txt   
1367385    edgar/data/18532/0000729057-95-000089.txt   
1367408  edgar/data/1008735/0000945621-98-000041.txt   
1367409  edgar/data/1008735/0000945621-98-000067.txt   
1367441   edgar/data/937338/0001029869-97-000089.txt   
1367456   edgar/data/910032/0000888002-98-000311.txt   
1367483     edgar/data/6955/0000729057-96-000167.txt   
1367489   edgar/data/101788/0000729057-96-000136.txt   
1367508   edgar/data/941542/0001047469-98-038841.txt   
1367534   edgar/data/790071/0000929771-98-000002.txt   
1367547  edgar/data/1021102/0001021102-98-000005.txt   
1367650   edgar/data/908156/0000950005-97-000222.txt   
1367666   edgar/data/888002/0000888002-96-000166.txt   
1367682   edgar/data/918958/0000729057-98-000213.txt   
1367726   edgar/data/811644/0000888002-97-000126.txt   
1367799   edgar/data/315016/0001029869-98-000171.txt   
1367800   edgar/data/729057/0000729057-98-000027.txt   
1367801   edgar/data/729057/0000729057-98-000033.txt   
1367814   edgar/data/942236/0000950136-96-000445.txt   
1367861   edgar/data/729057/0000729057-97-000189.txt   
1367937   edgar/data/904898/0000006164-97-000034.txt   
1367958   edgar/data/311049/0000888002-98-000114.txt   
1367972   edgar/data/891547/0000891547-97-000096.txt   
1367984   edgar/data/729057/0000729057-98-000052.txt   
1367985   edgar/data/729057/0000729057-98-000087.txt   
1368003   edgar/data/888002/0000888002-98-000013.txt   
1368098   edgar/data/886977/0000945621-98-000055.txt   
1368157   edgar/data/888002/0000888002-98-000289.txt   
1368205   edgar/data/729057/0000729057-98-000211.txt   

                         document form_type  title_page_end_lower_bound  \
82       0001193125-04-059071.txt    SC 13D                        1820   
90       0001171939-04-000004.txt  SC 13G/A                        1285   
91       0001166971-04-000005.txt  SC 13G/A                        1288   
162      0001137774-04-000179.txt    SC 13G                        1090   
163      0001137774-04-000180.txt  SC 13G/A                        1119   
232      0000061227-04-000010.txt    SC 13G                        1258   
330      0001137774-04-000176.txt  SC 13G/A  

In [706]:

print(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory))


SC 13G/A
1
sup.txt

UNITED STATES
SECURITIES AND EXCHANGE COMMISSION
Washington, D.C. 20549

SCHEDULE 13G	Amendment No. 5

(Name of Issuer)
	SUPERIOR INDUSTRIES INTERNATIONAL, INC.

(Title of Class of Securities)
Common Stock

(CUSIP Number)
	868168105

Rule 13d-1(b)

NAME OF REPORTING PERSON
Private Capital Management

I.R.S. IDENTIFICATION NO.
59-3654603

MEMBER OF A GROUP?
(b) X

PLACE OF ORGANIZATION
Delaware

NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH:
SOLE VOTING POWER 	0
SHARED VOTING POWER	3,257,367
SOLE DISPOSITIVE POWER 	0
SHARED DISPOSITIVE POWER 	3,257,367

AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON
	3,257,367

PERCENT OF CLASS REPRESENTED BY AGGREGATE AMOUNT BENEFICIALLY
OWNED
	12.2%

TYPE OF REPORTING PERSON
IA

NAME OF REPORTING PERSON
Bruce S. Sherman

I.R.S. IDENTIFICATION NO.


MEMBER OF A GROUP?
(b) X

CITIZENSHIP
U.S. Citizen

NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH:
SOLE VOTING POWER 	0
SHARED VOTI

In [2656]:
def get_reporting_pages(text):
    
    # This function is designed to take in reporting_pages_text from the output of get_text_components
    # and to split this text into the individual pages
    
    text_upper = text.upper()
    
    regex = '1[24]\s*[:\.]?\s+TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?\s*[\*]?\s*' + \
            '(\(SEE\s+INSTRUCTIONS\))?[:\.]?\s*([0-9A-Z]{2}[:;,\s])*([0-9A-Z]{2})\s+\n?'
    
    search = re.search(regex, text_upper)
    
    if(search is None):
        return(None)
    
    end = 0
    end_list = []
    
    while(search is not None):
        
        end = end + search.end()
        end_list.append(end)
        search = re.search(regex, text_upper[end:])
        
    pages = []    
        
    for i in range(len(end_list)):
        
        if(i == 0):
            pages.append(text[0:end_list[0]])
        else:
            pages.append(text[end_list[i-1]:end_list[i]])
    
    return(pages)
    
    
    


# These handle reporting page questions
    
    
def get_filing_report_q_and_a(text, form_type):
    
    # This function is designed to be used on an individual page from the list returend from get_reporting pages. It is designed to split this page in to the individual segments for each question
    # which correspond from 0 (for Cusip) through to 14 for 13D's and 0 to 12 for 13G's
    
    text_upper = text.upper()
    
    if(re.search('^SC 13D', form_type)):
        question_regex_dict = {1: '1\s*[:\.]{0,1}\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '2\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '3\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '4\s*[:\.]{0,1}\s*SOURCE\s+OF\s+FUNDS[\*]?',
                       5: '5\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+DISCLOSURE\s+OF\s+LEGAL\s+PROCEEDINGS',
                       6: '6\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       7: '7\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       8: '8\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       9: '9\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       10: '10\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       11: '11\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       12: '12\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       13: '13\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       14: '14\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
       
        num_sec = 15
       
    elif(re.search('^SC 13G', form_type)):
        
        question_regex_dict = {1: '1\s*[:\.]{0,1}\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '2\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '3\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '4\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       5: '5\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       6: '6\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       7: '7\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       8: '8\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       9: '9\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       10: '10\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       11: '11\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       12: '12\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
        
        num_sec = 13
        
    else:
        
        raise ValueError("form_type is not equal to 'SC 13D', 'SC 13 D/A', 'SC 13G' or an 'SC 13G/A'")

    start_dict = {}

    for key, regex in question_regex_dict.items():

        start_dict[key] = re.search(regex, text_upper).start()


    text_dict = {}
    for i in range(num_sec):

        if(i == 0):
            text_dict[i] = text[0:start_dict[i+1]]
        elif(i == num_sec - 1):
            text_dict[i] = text[start_dict[i]:]
        else:
            text_dict[i] = text[start_dict[i]:start_dict[i+1]]
            
    return(text_dict)    
    
    
    

def get_reporting_page_cusip_sedol(q0_text):
    
    text_upper = q0_text.upper()
    
    sd_regex = '(SCHEDULE\s+13\s*[DG]\s*(/\s*A)?|SC\s+13\s*[DG](/A)?|\s+13\s*[DG]\s*(/A)?\s{10,})'
    
    # get rid of schedule phrases
    
    cusip_text = re.sub(sd_regex, ' ', text_upper)
    
    # Next, get rid of instances of page phrases with a 13D or 13G in front. Start with most complex first
    
    pages_regex1 = '\s+13\s*[DG]\s*(/\s*A)?\s+PAGE\s+[0-9]{1,2}\s+OF\s+[0-9]{1,2}\s+(PAGES){0,1}'
    cusip_text = re.sub(pages_regex1, ' ', cusip_text)

    pages_regex2 = '\s+13\s*[DG]\s*(/\s*A)?\s+PAGE\s+[0-9]{1,2}\s+'
    cusip_text = re.sub(pages_regex2, ' ', cusip_text)

    pages_regex3 = '\s+13\s*[DG]\s*(/\s*A)?\s+[0-9]{1,2}\s+(PAGES)\s+'
    cusip_text = re.sub(pages_regex3, ' ', cusip_text)

    # Next get rid of the page phrases without 13D or G in front

    pages_regex4 = '\s+PAGE\s+[0-9]{1,2}\s+OF\s+[0-9]{1,2}\s+(PAGES){0,1}'
    cusip_text = re.sub(pages_regex4, ' ', cusip_text)

    pages_regex5 = '\s+PAGE\s+[0-9]{1,2}\s+'
    cusip_text = re.sub(pages_regex5, ' ', cusip_text)

    pages_regex6 = '\s+[0-9]{1,2}\s+(PAGES)\s+'
    cusip_text = re.sub(pages_regex6, ' ', cusip_text)
  
    # lastly any other page words
    
    page_regex_small = '(<PAGE>|PAGE|PAGES)'
    
    cusip_text = re.sub(page_regex_small, ' ', cusip_text)
    
    cusip_hdr = 'CUSIP\s+(?:NO\.|#|NUMBER):?\s+'
    sedol_hdr = 'SEDOL\s+(?:NO\.|#|NUMBER):?\s+'
    cusip_num_regex = '((?:[0-9A-Z]{1}[ -]{0,3}){4,9})'
    sedol_num_regex = '((?:[0-9A-Z]{1}[ -]{0,3}){4,7})'
    
    cusip_search = re.search(cusip_hdr, cusip_text)
    sedol_search = re.search(sedol_hdr, cusip_text)
    
    if(sedol_search is None):
        
        # Assume Cusips in this case, whether cusip regex appears or not, as these are the usual cases
        if(cusip_search is not None):
            cusips = re.findall(cusip_num_regex, cusip_text[cusip_search.end():])
            sedols = []
        else:
            cusips = re.findall(cusip_num_regex, cusip_text)
            sedols = []
        
    elif(cusip_search is None and sedol_search is not None):
        
        cusips = []
        sedols = re.findall(sedol_num_regex, cusip_text[sedol_search.end():])
        
    else: 
        
        # both cusip and sedol searches are not none, need to determine which appears first
        
        if(cusip_search.end() > sedol_search.end()):
            
            cusips = re.findall(cusip_num_regex, cusip_text[cusip_search.end():])
            sedols = re.findall(sedol_num_regex, cusip_text[sedol_search.end():cusip_search.end()])
            
        else:
            
            cusips = re.findall(cusip_num_regex, cusip_text[cusip_search.end():sedol_search.end()])
            sedols = re.findall(sedol_num_regex, cusip_text[sedol_search.end():])
            
    
    # lastly, clean cusips and sedols
    
    cusips = [re.sub('[^0-9A-Z]', '', cusip) for cusip in cusips]
    sedols = [re.sub('[^0-9A-Z]', '', sedol) for sedol in sedols]

    return(cusips, sedols)



def strip_form_statement(text, statement):

    statement_raised = re.sub('\s+', ' ', statement).upper()
    text_raised = text.upper()
    
    words = statement_raised.split(' ')

    regex_list = []

    for i in range(len(words)):
        
        if(i == 0):
            
            regex_list.append('\n\s*(?:' + '|'.join(words) + ')')
            
        else:
            regex_list.append('(?:' + '|'.join(words[i:]) + ')?')
                              
    regex = '(' + '[\s-]*'.join(regex_list) + ')'
    
    regex_start = '^(' + '[\s-]*'.join(regex_list).lstrip('\n') + ')'

    start_search = re.search(regex_start, text_raised)

    if(start_search):

        statement_parts = [start_search.group(0)] + re.findall(regex, text_raised)

    else:
        statement_parts = re.findall(regex, text_raised)
        
    result = text

    for part in statement_parts:

        start = result.upper().find(part)
        if(start != -1):
            end = start + len(part)
            result = result[:start] + ' ' + result[end:]
    
    return(result)


def eliminate_beneficial_own_statement(text):
    
    # This function is designed to get rid of the irritating 
    # 'NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH' statement, or any occurences of 
    # any part of it, around q6, q7, q8, q9, q10 (on SC 13D)
    
    result = strip_form_statement(text, 'NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH')
    
    return(result)        

    
def get_answer_text(q_text, form_type, question_number):
    
    # This function is designed to be used on all questions except question 2, in which there are boxes (a) and (b)
   
    
    # First, get rid of beneficial ownership statement
    result = eliminate_beneficial_own_statement(q_text)
      
    if(re.search("13D", form_type)):
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'SOURCE OF FUNDS[*]?',
                        5: 'CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT' + \
                           ' TO ITEMS 2\(D\) OR 2\(E\)',
                        6: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        7: 'SOLE VOTING POWER',
                        8: 'SHARED VOTING POWER',
                        9: 'SOLE DISPOSITIVE POWER',
                        10: 'SHARED DISPOSITIVE POWER', 
                        11: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        12: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW (?:\(11\)|11) EXCLUDES CERTAIN SHARES[*]?',
                        13: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (?:\(11\)|11)',
                        14: '(?:TYPES|TYPE) OF REPORTING (?:PERSONS|PERSON)[\*]?'
                       }
        
    elif(re.search("13G", form_type)):
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        5: 'SOLE VOTING POWER',
                        6: 'SHARED VOTING POWER',
                        7: 'SOLE DISPOSITIVE POWER',
                        8: 'SHARED DISPOSITIVE POWER',
                        9: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        10: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW (?:\(9\)|9) EXCLUDES CERTAIN SHARES[*]?',
                        11: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (?:\(9\)|9)',
                        12: '(?:TYPES|TYPE) OF REPORTING (?:PERSONS|PERSON)[*]?'
                       }
    
    result = re.sub('^' + str(question_number) + '\s*[:\.]?', '', result)
    
    result = re.sub('(^[\:\;\-\–\.\s]+|[\s\-]+$)', '', strip_form_statement(result, q_regex_dict[question_number]))
    
    return(result)
    
    
    
    
def q2_boxes_a_and_b(q2_text):
    
    a_start = re.search('\([aA]\)', q2_text).end()
    a_end = re.search('\([bB]\)', q2_text).start()
    b_start = re.search('\([bB]\)', q2_text).end()
    
    q2a_ticked = (re.search('[xX]', q2_text[a_start:a_end]) is not None)
    q2b_ticked = (re.search('[xX]', q2_text[b_start:]) is not None)
    
    return(q2a_ticked, q2b_ticked)
    
    
    
def q4_get_source_of_funds(q4_text, form_type):
    
    if(re.search('13D', form_type)):
    
        text = get_answer_text(q4_text, form_type, 4)

        result = re.findall('(SC|BK|AF|WC|PF|OO|00)', text)
        result = [re.sub('00', 'OO', x) for x in result]
        
        return(result)
        
    else:
        
        raise ValueError("form is not of type SC 13D or SC 13D/A")
  
  
def q5_12_box(q_text, form_type, question_number):
    
   
    if(re.search('13D', form_type)):
        
        if(question_number in [5, 12]):
        
            text = get_answer_text(q_text, form_type, question_number)
            result = (re.search('[xX1]', text) is not None)
            return(result)
    
        else:
            raise ValueError("form is of type SC 13D(/A), but question_number is not 5 or 12")
            
    elif(re.search('13G', form_type)):
        
        if(question_number == 10):
        
            text = get_answer_text(q_text, form_type, question_number)
            result = (re.search('[xX1]', text) is not None)
            return(result)
    
        else:
            raise ValueError("form is of type SC 13G(/A), but question_number is not 10")
        
    else:
        
        raise ValueError("form is not of type SC 13D(/A) or SC 13G(/A)")        
        
        
        
def q14_get_type_rep_person(q14_text, form_type, question_number):
    
    is_13d = re.search('13D', form_type) is not None
    is_13g = re.search('13G', form_type) is not None
    
    if((is_13d and question_number == 14) or (is_13g and question_number == 12)):
    
        text = get_answer_text(q14_text, form_type, question_number)

        result = re.findall('(BD|BK|IC|IV|IA|EP|HC|SA|CP|CO|C0|PN|IN|OO|00)', text)
        result = [re.sub('0', 'O', x) for x in result]
        
        return(result)
        
    else:
        
        if(is_13d):
            
            raise ValueError("form is of type SC 13D or SC 13D/A, but question number is not 14")
            
        if(is_13g):
            
            raise ValueError("form is of type SC 13G or SC 13G/A, but question number is not 12")
            
        else:
            
            raise ValueError("form is not of type SC 13D or SC 13D/A")


def get_reporting_page_df(reporting_page, form_type):
    
    q_and_a = get_filing_report_q_and_a(reporting_page, form_type)
    
    answer_dict = {}
    answer_dict['form_type'] = [form_type]
    is_13d = re.search('13D', form_type) is not None
    is_13g = re.search('13G', form_type) is not None
    
    if(is_13g):
      
      # These fields do not appear in SC 13G or SC 13G/A. Set them to None
      answer_dict['SC_13D_box_5'] = None
      answer_dict['source_of_funds'] = None
      
    
    for key, q_text in q_and_a.items():
    
        if(key == 0):
            cusips, sedols = get_reporting_page_cusip_sedol(q_text)
            answer_dict['cusips'] = [cusips]
            answer_dict['sedols'] = [sedols]
            
        elif(key == 1):
            
            answer_dict['rep_person_name'] = [get_answer_text(q_text, form_type, key)]

        elif(key == 2):

            q_2a_ticked, q_2b_ticked = q2_boxes_a_and_b(q_text)
            answer_dict['box_2a'] = [q_2a_ticked]
            answer_dict['box_2b'] = [q_2b_ticked]

        elif(key == 3):

            pass
        
        elif(key == 4 and is_13d):
            
            answer_dict['source_of_funds'] = [q4_get_source_of_funds(q_text, form_type)]
            
        elif(key == 5 and is_13d):
            
            answer_dict['SC_13D_box_5'] = [q5_12_box(q_text, form_type, key)]
            
        elif((key == 4 and is_13g) or (key == 6 and is_13d)):
            
            answer_dict['citizenship_place_of_organization'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 7 and is_13d) or (key == 5 and is_13g)):
            
            answer_dict['num_shares_sole_vp'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 8 and is_13d) or (key == 6 and is_13g)):
            
            answer_dict['num_shares_shared_vp'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 9 and is_13d) or (key == 7 and is_13g)):
            
            answer_dict['num_shares_sole_dp'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 10 and is_13d) or (key == 8 and is_13g)):
            
            answer_dict['num_shares_shared_dp'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 11 and is_13d) or (key == 9 and is_13g)):
            
            answer_dict['agg_amount_owned'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 12 and is_13d) or (key == 10 and is_13g)):
            
            answer_dict['certain_shares_exc_from_agg'] = [q5_12_box(q_text, form_type, key)]
             
        elif((key == 13 and is_13d) or (key == 11 and is_13g)):
            
            answer_dict['agg_amount_percentage_share'] = [get_answer_text(q_text, form_type, key)]
             
        elif((key == 14 and is_13d) or (key == 12 and is_13g)):
            
            answer_dict['reporting_person_type'] = [q14_get_type_rep_person(q_text, form_type, key)]
             
             
    df = pd.DataFrame(answer_dict)
             
    return(df)


def get_all_reporting_pages_df(reporting_pages_text, file_name, form_type):
    
    pages = get_reporting_pages(reporting_pages_text)
    
    df_list = []
    
    for i in range(len(pages)):
        
        df = get_reporting_page_df(pages[i], form_type)
        df['file_name'] = file_name
        df['seq'] = i + 1
        
        df_list.append(df)
        
    full_df = pd.concat(df_list, ignore_index = True)
    order = ['file_name', 'form_type', 'seq', 'cusips', 'sedols', 'rep_person_name', 'box_2a', 'box_2b', \
             'source_of_funds', 'SC_13D_box_5', 'citizenship_place_of_organization', 'num_shares_sole_vp', \
             'num_shares_shared_vp', 'num_shares_sole_dp', 'num_shares_shared_dp', 'agg_amount_owned', \
             'certain_shares_exc_from_agg', 'agg_amount_percentage_share', 'reporting_person_type']
    
    full_df = full_df[order]
    return(full_df)


In [2668]:
def get_cover_page_section(file_name, document, directory, cover_page_start, cover_page_end):
    
    t = get_bounded_text(get_main_doc_text(file_name, document, directory), cover_page_start, cover_page_end)
    
    return(t)

In [2671]:

get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])

'\n\nCUSIP No. 000002346104\n\n\n\n\n\n\xa0\n1.\nNames of Reporting Persons.Chester L.F. & Jacqueline M. Paulson, as Joint TenantsI.R.S. Identification Nos. of above persons (entities only).\n\n\n\n\n\n\xa0\n2.\nCheck the Appropriate Box if a Member of a Group (See Instructions)(a)\xa0\xa0[ \xa0\xa0 ]\xa0\xa0\xa0\xa0\xa0\xa0\xa0(b)\xa0\xa0[ X ]\n\n\n\n\n\n\xa0\n3.\nSEC USE ONLY\n\n\n\n\n\n\xa0\n4.\nCitizenship or Place of Organization\nUnited States of America\n\n\n\n\n\nNumber ofSharesBeneficiallyOwned byEach ReportingPerson With:\n5.\nSole Voting Power375,152\n\n\n\n\n\n6.\nShared Voting Power1,279,554\n\n\n\n\n\n7.\nSole Dispositive Power375,152\n\n\n\n\n\n8.\nShared Dispositive Power1,279,554\n\n\n\n\n\n\xa0\n9.\nAggregate Amount Beneficially Owned by Each Reporting Person1,654,706\n\n\n\n\n\n\xa0\n10.\nCheck if the Aggregate Amount in Row (9) Excludes Certain Shares (See Instructions)\xa0\xa0[ \xa0\xa0 ] \n\n\n\n\n\n\xa0\n11.\nPercent of Class Represented by Amount in Row (9)\n5.2

In [2658]:
indexes_df

file_name  \
0         edgar/data/897484/0001144204-04-004169.txt   
1         edgar/data/704159/0001015402-04-001458.txt   
2        edgar/data/1163453/0001019687-04-000771.txt   
3         edgar/data/897484/0001144204-04-008811.txt   
4        edgar/data/1035674/0001035674-04-000005.txt   
5        edgar/data/1035674/0001035674-04-000006.txt   
6         edgar/data/704159/0001015402-04-001460.txt   
7        edgar/data/1035674/0001035674-04-000008.txt   
8        edgar/data/1120914/0001056568-04-000061.txt   
9        edgar/data/1163453/0001019687-04-001131.txt   
10        edgar/data/893949/0000814133-04-000115.txt   
11       edgar/data/1064728/0000902219-04-001079.txt   
12       edgar/data/1279095/0001144204-04-004297.txt   
13        edgar/data/704159/0001015402-04-001462.txt   
14       edgar/data/1064728/0000315066-04-001678.txt   
15         edgar/data/75681/0000065103-04-000134.txt   
16       edgar/data/1135338/0000919574-04-001356.txt   
17        edgar/data/923877/0000807249-04-000123.txt   
18       edgar/data/1135338/0000919574-04-001735.txt   
19       edgar/data/1279095/0001144204-04-007831.txt   
20       edgar/data/1135338/0000919574-04-001367.txt   
21       edgar/data/1135338/0000919574-04-001873.txt   
22       edgar/data/1135338/0000919574-04-001745.txt   
23       edgar/data/1135338/0000919574-04-001385.txt   
24        edgar/data/925765/0000926274-04-000155.txt   
25       edgar/data/1135338/0000919574-04-001749.txt   
26       edgar/data/1135338/0000919574-04-001895.txt   
27       edgar/data/1135338/0000919574-04-001407.txt   
28        edgar/data/927752/0000950142-04-002200.txt   
29       edgar/data/1068878/0001068878-04-000003.txt   
...                                              ...   
1368332  edgar/data/1125920/0000215457-19-002604.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368334   edgar/data/893691/0000215457-19-004906.txt   
1368335  edgar/data/1104186/0000919574-19-001286.txt   
1368336  edgar/data/1118417/0001104659-19-008720.txt   
1368337  edgar/data/1201792/0001037389-19-000146.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368339  edgar/data/1621563/0000807985-19-000028.txt   
1368340  edgar/data/1395064/0001104659-19-060139.txt   
1368341  edgar/data/1050045/0001104659-19-071096.txt   
1368342   edgar/data/826020/0001062993-19-004564.txt   
1368343  edgar/data/1527541/0001104659-19-056194.txt   
1368344  edgar/data/1504103/0001193125-19-279063.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368346  edgar/data/1581164/0001104659-19-071304.txt   
1368347   edgar/data/315066/0000315066-19-001394.txt   
1368348   edgar/data/315066/0000315066-19-001396.txt   
1368349  edgar/data/1320854/0001085146-19-000414.txt   
1368350  edgar/data/1430308/0001214659-19-000763.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368352   edgar/data/862831/0000215457-19-004043.txt   
1368353  edgar/data/1045810/0000215457-19-004826.txt   
1368354  edgar/data/1564584/0000895421-19-000289.txt   
1368355  edgar/data/1534126/0000950157-19-000740.txt   
1368356  edgar/data/1777962/0001144204-19-031195.txt   
1368357  edgar/data/1655020/0001144204-19-008356.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   
1368359  edgar/data/1124941/0001104659-19-038258.txt   
1368360  edgar/data/1560258/0001193125-19-297684.txt   
1368361  edgar/data/1404574/0000921895-19-001932.txt   

                         document form_type  title_page_end_lower_bound  \
0        0001144204-04-004169.txt    SC 13G                        1912   
1        0001015402-04-001458.txt    SC 13G                        1199   
2        0001019687-04-000771.txt    SC 13D                           1   
3        0001144204-04-008811.txt  SC 13G/A                        1918   
4        0001035674-04-000005.txt    SC 13G                           1   
5        0001035674-04-000006.txt    SC 13G                           1   
6        0001015402-04-001460.txt    SC 13G  

In [2876]:
i = 8
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
get_all_reporting_pages_df(t, indexes_df.loc[i, 'file_name'], \
                           indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

file_name form_type  seq       cusips  \
0  edgar/data/1120914/0001056568-04-000061.txt  SC 13G/A    1  [693282105]   
1  edgar/data/1120914/0001056568-04-000061.txt  SC 13G/A    2  [693282105]   
2  edgar/data/1120914/0001056568-04-000061.txt  SC 13G/A    3  [693282105]   

  sedols                                    rep_person_name  box_2a  box_2b  \
0     []  Kern Capital Management, LLC\n\n              ...   False   False   
1     []                                  Robert E Kern Jr.   False   False   
2     []                                      David G. Kern   False   False   

  source_of_funds SC_13D_box_5 citizenship_place_of_organization  \
0            None         None                          Delaware   
1            None         None                            U.S.A.   
2            None         None                            U.S.A.   

  num_shares_sole_vp                               num_shares_shared_vp  \
0          1,336,000                                                      
1                     1,336,000 - (See Schedule Item 4 incorporated ...   
2                     1,336,000 -(See Schedule Item 4 incorporated b...   

  num_shares_sole_dp                               num_shares_shared_dp  \
0          1,336,000                                                      
1                     1,336,000 - (See Schedule Item 4\n            ...   
2                     1,336,000 - (See Schedule Item 4\n            ...   

                                    agg_amount_owned  \
0                                          1,336,000   
1  1,336,000 - (See Schedule Item 4\n            ...   
2  1,336,000 -(See Schedule Item 4\n             ...   

   certain_shares_exc_from_agg  \
0                        False   
1                        False   
2                        False   

                       agg_amount_percentage_share reporting_person_type  
0  9\n\n                                      5.2%                  [IA]  
1  9\n\n                                      5.2%                  [IN]  
2  9\n\n                                      5.2%                  [IN]

In [2868]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1120914/000105656804000061/0001056568-04-000061-index.htm'

In [2864]:
def get_all_reporting_pages_df(reporting_pages_text, file_name, form_type, is_rep_q_as_items):
    
    pages = get_reporting_pages(reporting_pages_text, form_type, is_rep_q_as_items)
    
    df_list = []
    
    for i in range(len(pages)):
        
        df = get_reporting_page_df(pages[i], form_type)
        df['file_name'] = file_name
        df['seq'] = i + 1
        
        df_list.append(df)
        
    full_df = pd.concat(df_list, ignore_index = True)
    order = ['file_name', 'form_type', 'seq', 'cusips', 'sedols', 'rep_person_name', 'box_2a', 'box_2b', \
             'source_of_funds', 'SC_13D_box_5', 'citizenship_place_of_organization', 'num_shares_sole_vp', \
             'num_shares_shared_vp', 'num_shares_sole_dp', 'num_shares_shared_dp', 'agg_amount_owned', \
             'certain_shares_exc_from_agg', 'agg_amount_percentage_share', 'reporting_person_type']
    
    full_df = full_df[order]
    return(full_df)

In [2892]:
i = 9
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
get_all_reporting_pages_df(t, indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

file_name form_type  seq       cusips  \
0  edgar/data/1163453/0001019687-04-001131.txt  SC 13D/A    1  [03840K202]   

  sedols  rep_person_name  box_2a  box_2b source_of_funds  SC_13D_box_5  \
0     []  Greg Paxton (1)   False    True            [SC]         False   

  citizenship_place_of_organization num_shares_sole_vp num_shares_shared_vp  \
0                         Australia      2,387,680 (1)                 None   

  num_shares_sole_dp num_shares_shared_dp agg_amount_owned  \
0      2,387,680 (1)                 None    2,387,680 (1)   

   certain_shares_exc_from_agg agg_amount_percentage_share  \
0                        False                      26.85%   

  reporting_person_type  
0                  [IN]

In [2900]:
i = 13
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
get_all_reporting_pages_df(t, indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

AttributeError: 'NoneType' object has no attribute 'start'

In [2899]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1279095/000114420404004297/0001144204-04-004297-index.htm'

In [2893]:
i = 10
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
get_all_reporting_pages_df(t, indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

AttributeError: 'NoneType' object has no attribute 'start'

In [2894]:
indexes_df.loc[10]

file_name                      edgar/data/893949/0000814133-04-000115.txt
document                                         0000814133-04-000115.txt
form_type                                                        SC 13G/A
title_page_end_lower_bound                                            166
cover_page_q1_start                                                   558
is_rep_q_as_items                                                    True
is_schedule_to                                                      False
has_table_of_contents                                               False
num_cusip_sedol_b_q1                                                    1
cover_page_start                                                      141
item_section_start                                                    704
cover_page_last_q_end                                                 673
cover_page_end                                                        704
num_cusip_b_items                     

In [2895]:
pages = get_reporting_pages(t, indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

In [2896]:
pages

['\nCUSIP Number: 705324101\nItem 1: Reporting Person: Wasatch Advisors, Inc. 87-0319391\nItem 2: Check Box If Member of Group: Not Applicable\nItem 3: SEC Use\nItem 4: Place of Organization: Utah\nItems 5-8: Number of Shares Owned With:\nItem 5: Sole Voting Power: 2,065,856\nItem 6: Shared Voting Power: 0\nItem 7: Sole Dispositive Power: 2,065,856\nItem 8: Shared Dispositive Power: 0\nItem 9: Aggregate Amount Owned: 2,065,856\nItem 10: Check Box If Aggregate Amount Excludes Certain Shares: N/A\nItem 11: Percent of Class Owned: 8.5%\nItem 12: Type of Reporting Person: IA\n\n']

In [2856]:
len(t)

8425

In [2870]:
pages[0]

'\n\n\n\n\n\n\nCUSIP No. 693282105                         13G              Page 2  of 7 Pages\n- ------------\n\n\n\n\n\n\n- --------------------------------------------------------------------------------\n1        NAME OF REPORTING PERSON\n         S.S. OR I.R.S. IDENTIFICATION NO OF ABOVE PERSON\n                          Kern Capital Management, LLC\n\n                          13-3958232\n- --------------------------------------------------------------------------------\n\n2         CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP*\n\n                                                            (a)     / /\n\n                                                            (b)     / /\n\n- --------------------------------------------------------------------------------\n3         SEC USE ONLY\n\n\n- --------------------------------------------------------------------------------\n4         CITIZENSHIP OR PLACE OF ORGANIZATION\n\n\n                                    Delaware\n- -------

In [2908]:
def get_reporting_pages(text, form_type, is_rep_q_as_items):
     
    # This function is designed to take in reporting_pages_text from the output of get_text_components
    # and to split this text into the individual pages
    
    section_length = len(text)
    
    text_upper = text.upper()
    
    if(is_rep_q_as_items):
        
        regex_last = 'ITEM\s*[:\.]?\s*1[24]'
    
    else:
        
        regex_last = '1[24]\s*[:\.]?\s+TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'
    
    last_qs = re.findall(regex_last, text_upper)
    
    num_pages = len(last_qs)
    
    if(num_pages == 1):
        pages = [text]
        return(pages)
    
    else:
    
        
        end_list = []
        

        for i in range(num_pages):
            
            if(i == 0):
                lower_bound = re.search(regex_last, text_upper).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            elif(i > 0 and i <  num_pages - 1):
            
                lower_bound = end + re.search(regex_last, text_upper[end:]).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            else:
                
                end = section_length
                
            end_list.append(end)

        pages = []    

        for i in range(len(end_list)):

            if(i == 0):
                pages.append(text[0:end_list[0]])
            else:
                pages.append(text[end_list[i-1]:end_list[i]])

        return(pages)

In [2960]:
i = 24
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
pages = get_reporting_pages(t, indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

In [2961]:
pages[0]

"\n\n\n\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Bruce A. Cordingley\n- --------------------------------------------------------------------------------\n2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- --------------------------------------------------------------------------------\n6        

In [3312]:
eq_s = np.logical_and(indexes_df['cover_page_start'] > 0, \
                      indexes_df['cover_page_start'] == indexes_df['cover_page_q1_start'])

In [ ]:
90, 91, 123, 232, 1368157

In [3313]:
indexes_df.loc[eq_s]

file_name  \
32       edgar/data/1050377/0001193125-04-068397.txt   
82       edgar/data/1085869/0001193125-04-059071.txt   
83        edgar/data/771992/0001013594-04-000142.txt   
87       edgar/data/1162663/0001162663-04-000011.txt   
88       edgar/data/1162663/0001016964-04-000105.txt   
90       edgar/data/1171939/0001171939-04-000004.txt   
91       edgar/data/1166971/0001166971-04-000005.txt   
94        edgar/data/919085/0001169232-04-002371.txt   
99        edgar/data/919085/0001169232-04-003308.txt   
112       edgar/data/949699/0001056288-04-000289.txt   
123      edgar/data/1013746/0000950142-04-001802.txt   
124      edgar/data/1162663/0001016964-04-000175.txt   
127      edgar/data/1142252/0000898822-04-000305.txt   
130       edgar/data/356213/0000924355-04-000146.txt   
133      edgar/data/1162663/0001016964-04-000107.txt   
134      edgar/data/1162663/0001016964-04-000156.txt   
140      edgar/data/1133256/0001193125-04-099611.txt   
141       edgar/data/793421/0000950142-04-002224.txt   
154      edgar/data/1203866/0000932440-04-000148.txt   
160      edgar/data/1272801/0001144204-04-004534.txt   
164       edgar/data/866368/0001099281-04-000070.txt   
169       edgar/data/880804/0000924355-04-000130.txt   
176      edgar/data/1268703/0001288845-04-000019.txt   
194       edgar/data/897226/0000897226-04-000239.txt   
196       edgar/data/897226/0000897226-04-000244.txt   
212       edgar/data/897226/0000897226-04-000245.txt   
215      edgar/data/1268519/0001013594-04-000158.txt   
216      edgar/data/1289188/0000895345-04-000293.txt   
229      edgar/data/1106400/0000935836-04-000120.txt   
232      edgar/data/1018833/0000061227-04-000010.txt   
...                                              ...   
1368003   edgar/data/888002/0000888002-98-000013.txt   
1368022    edgar/data/73076/0000073076-98-000016.txt   
1368023  edgar/data/1413898/0001193125-19-314087.txt   
1368033   edgar/data/701818/0001104659-19-074646.txt   
1368036  edgar/data/1016626/0000936924-98-000010.txt   
1368037   edgar/data/891531/0000732812-98-000115.txt   
1368098   edgar/data/886977/0000945621-98-000055.txt   
1368115   edgar/data/732812/0000732812-98-000917.txt   
1368116   edgar/data/314965/0000314965-98-000021.txt   
1368117    edgar/data/17283/0000017283-98-000392.txt   
1368135   edgar/data/889087/0000889812-98-000938.txt   
1368157   edgar/data/888002/0000888002-98-000289.txt   
1368171   edgar/data/845577/0000897423-98-000162.txt   
1368172   edgar/data/791348/0000897423-98-000160.txt   
1368187  edgar/data/1499780/0001144204-19-027014.txt   
1368221    edgar/data/41077/0000017283-98-000071.txt   
1368232   edgar/data/732812/0000017283-98-000062.txt   
1368240    edgar/data/80255/0000080255-19-002579.txt   
1368241    edgar/data/80255/0000080255-19-002507.txt   
1368246   edgar/data/827054/0000017283-98-000236.txt   
1368249   edgar/data/931015/0000732812-98-000827.txt   
1368285  edgar/data/1792243/0001599916-19-000152.txt   
1368307  edgar/data/1567548/0001493152-18-004326.txt   
1368314   edgar/data/872912/0001393825-19-000017.txt   
1368316   edgar/data/733060/0000733060-19-000006.txt   
1368333  edgar/data/1697828/0001104659-19-008126.txt   
1368338   edgar/data/820478/0000820478-19-000033.txt   
1368345  edgar/data/1571498/0001193125-19-294020.txt   
1368351   edgar/data/937729/0001193125-19-028143.txt   
1368358    edgar/data/70858/0001567619-19-014067.txt   

                         document form_type  title_page_end_lower_bound  \
32       0001193125-04-068397.txt    SC 13D                        1383   
82       0001193125-04-059071.txt    SC 13D                        1820   
83       0001013594-04-000142.txt  SC 13G/A                        1619   
87       0001162663-04-000011.txt    SC 13G                        2335   
88       0001016964-04-000105.txt  SC 13G/A                        2409   
90       0001171939-04-000004.txt  SC 13G/A                        1285   
91       0001166971-04-000005.txt  SC 13G/A  

In [3408]:
i = 232
print(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)[1277:1333])


Issuer:  QuadraMed Corporation	 			CUSIP No.: 74730W101


In [3409]:
get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)[1277:1333]

'\nIssuer:  QuadraMed Corporation\t \t\t\tCUSIP No.: 74730W101'

In [3399]:
indexes_df.loc[232, 'cover_page_q1_start']

1333

In [3406]:
test

'hall not\nbe deemed to be "filed" for the purpose of Section 18 of the Securities Exchange\nAct of 1934 ("Act") or otherwise subject to the liabilities of that section of\nthe Act but shall be subject to all other provisions of the Act (however, see\nthe Notes).\n\n\n\n\nSCHEDULE 13G\n\n\nIssuer:  QuadraMed Corporation\t \t\t\tCUSIP No.: 74730W101'

In [3405]:
test = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)[1000:1333]

In [3407]:
re.search('(PISUC|LODES)(.)*\n', test[::-1])

<re.Match object; span=(15, 56), match='PISUC\t\t\t \tnoitaroproC deMardauQ  :reussI\n'>

In [ ]:
def cover_page_start(text, form_type, lower_bound = None, cover_page_q1 = None, rep_q_as_items = None):
    
    if(rep_q_as_items is None):
        
        rep_q_as_items = is_rep_q_as_items(text, cover_page_q1)
    
    if(cover_page_q1 is None):
        
        cover_page_q1 = find_cover_page_q1_start(text, form_type, lower_bound, cover_page_q1, rep_q_as_items)
        
    if(cover_page_q1 == -1):
        
        # No question 1 found, so no cover pages, return -1
        return(-1) 
        
    else:
        
        text_to_search = text[:cover_page_q1]
    
        text_reversed_and_raised = text_to_search[::-1].upper()

        regex = '(PISUC|LODES)(.)*\n'

        search = re.search(regex, text_reversed_and_raised)

        if(search):

            num_back = search.end()

        else:

            num_back = 0

        start = cover_page_q1 - num_back

        return(start)

In [ ]:
')setoN'

In [3390]:
'Notes).'[::-1]

'.)setoN'

In [3391]:
cover_page_start??

In [3384]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/733060/000073306019000006/0000733060-19-000006-index.htm'

In [3365]:
i = 32
print(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)[1383:])

 Item 2(d) or 2(e) ¨

 6       Citizenship or Place of Organization          United States of America

     Number of Shares Beneficially Owned by Each Reporting Person With
  
 7)      Sole Voting Power          530,000

  
 8)      Shared Voting Power          16,338,188

  
 9)      Sole Dispositive Power          8,699,094

  
 10)   Shared Dispositive Power          0

 11     Aggregate Amount
Beneficially Owned by Each Reporting Person          8,699,094

 12     Check Box If the Aggregate Amount in Row (11) Excludes Certain
Shares x

 13     Percent of Class Represented by Amount in Row (11)          34.79% (1)

 14     Type of Reporting Person          IN (1)      Based upon 25,007,577 shares of PC Connection, Inc. Common Stock outstanding on April 23, 2004.
  
 2 













 1       Names of Reporting Persons          David Hall            I.R.S. Identification for Nos. of Above
Persons  

 2       Check the Appropriate Box if a Member of a
Group          (a) x          (b)

In [3360]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/891531/000073281298000115/0000732812-98-000115-index.htm'

In [3361]:
get_index_url('edgar/data/1050377/0001193125-04-068397.txt')

'https://www.sec.gov/Archives/edgar/data/1050377/000119312504068397/0001193125-04-068397-index.htm'

In [3363]:
indexes_df.loc[indexes_df['file_name'] == 'edgar/data/1050377/0001193125-04-068397.txt']

file_name                  document  \
32  edgar/data/1050377/0001193125-04-068397.txt  0001193125-04-068397.txt   

   form_type  title_page_end_lower_bound  cover_page_q1_start  \
32    SC 13D                        1383                 1013   

   is_rep_q_as_items is_schedule_to has_table_of_contents  \
32             False          False                 False   

    num_cusip_sedol_b_q1  cover_page_start   ...    cover_page_last_q_end  \
32                     1              1013   ...                   4336.0   

    cover_page_end  num_cusip_b_items  signature_start  exhibit_start  \
32            4477                  1            10720          11450   

    main_text_length  explanatory_statement_start  has_jumbled_order  \
32             11934                           -1              False   

   has_exhibit_break success  
32             False    True  

[1 rows x 21 columns]

In [3507]:
n = get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)

In [ ]:
i = 160
print(get_main_doc_text(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory)[indexes_df.loc[i, 'cover_page_start']:indexes_df.loc[i, 'cover_page_end']])

In [ ]:
edgar/data/1050377/0001193125-04-068397.txt

In [ ]:
def q4_get_source_of_funds(q4_text, form_type):
    
    if(re.search('13D', form_type)):
    
        text = get_answer_text(q4_text, form_type, 4)

        result = re.findall('(SC|BK|AF|WC|PF|OO|00)', text)
        result = [re.sub('00', 'OO', x) for x in result]
        
        return(result)
        
    else:
        
        raise ValueError("form is not of type SC 13D or SC 13D/A")

In [3537]:
def get_reporting_pages(text, form_type, is_rep_q_as_items):
     
    # This function is designed to take in reporting_pages_text from the output of get_text_components
    # and to split this text into the individual pages
    
    section_length = len(text)
    
    text_upper = text.upper()
    
    if(is_rep_q_as_items):
        
        regex_last = 'ITEM\s*[:\.]?\s*1[24]'
    
    else:
        
        regex_last = 'TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'
    
    last_qs = re.findall(regex_last, text_upper)
    
    num_pages = len(last_qs)
    print(num_pages)
    
    if(num_pages == 1):
        pages = [text]
        return(pages)
    
    else:
    
        
        end_list = []
        

        for i in range(num_pages):
            
            if(i == 0):
                lower_bound = re.search(regex_last, text_upper).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            elif(i > 0 and i <  num_pages - 1):
            
                lower_bound = end + re.search(regex_last, text_upper[end:]).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            else:
                
                end = section_length
                
            end_list.append(end)

        pages = []    

        for i in range(len(end_list)):

            if(i == 0):
                pages.append(text[0:end_list[0]])
            else:
                pages.append(text[end_list[i-1]:end_list[i]])

        return(pages)

In [ ]:
24, 37, 41, 43, 60, 69, 89, 800007

In [3513]:
indexes_df.loc[i]

file_name                      edgar/data/1207188/0001104659-04-015891.txt
document                                          0001104659-04-015891.txt
form_type                                                           SC 13D
title_page_end_lower_bound                                            1865
cover_page_q1_start                                                   1920
is_rep_q_as_items                                                    False
is_schedule_to                                                       False
has_table_of_contents                                                False
num_cusip_sedol_b_q1                                                     2
cover_page_start                                                      1865
item_section_start                                                   15287
cover_page_last_q_end                                                15221
cover_page_end                                                       15261
num_cusip_b_items        

In [3536]:
get_reporting_pages??

In [3540]:
get_reporting_pages(t, indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

7


['\n\n\xa0\n\n\n\n\n\n\n\n\n\n\n\n\n\n\xa0\n\n\n\n\n \n  ',
 '',
 '',
 '',
 '',
 '',
 '\n  CUSIP\n  No.   178566-10-5\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  1.\n  \n  \n  Names of Reporting\n  Persons. I.R.S. Identification Nos. of above persons (entities only)\n  Russell Goldsmith\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  2.\n  \n  \n  Check\n  the Appropriate Box if a Member of a Group (See Instructions)\n  \n \n \n  \n  \xa0\n  \n  \n  \xa0\n  \n  \n  (a)\n  \n  \n   ý\n  \n \n \n  \n  \xa0\n  \n  \n  \xa0\n  \n  \n  (b)\n  \n  \n   o\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  3.\n  \n  \n  SEC\n  Use Only \n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  4.\n  \n  \n  Source\n  of Funds (See Instructions)\n  PF\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  5.\n  \n  \n  Check if Disclosure of Legal Proceedings Is\n  Required Pursuant to Items 2(d) or 2(e) \n     o\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  6.\n  \n

In [3533]:
i = 800014
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
eg = get_all_reporting_pages_df(t, indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])
eg

1


 













 




 
  


AttributeError: 'NoneType' object has no attribute 'start'

In [3511]:
t

'\n\n\xa0\n\n\n\n\n\n\n\n\n\n\n\n\n\n\xa0\n\n\n\n\n \n  \n  CUSIP\n  No.   178566-10-5\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  1.\n  \n  \n  Names of Reporting\n  Persons. I.R.S. Identification Nos. of above persons (entities only)\n  Russell Goldsmith\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  2.\n  \n  \n  Check\n  the Appropriate Box if a Member of a Group (See Instructions)\n  \n \n \n  \n  \xa0\n  \n  \n  \xa0\n  \n  \n  (a)\n  \n  \n   ý\n  \n \n \n  \n  \xa0\n  \n  \n  \xa0\n  \n  \n  (b)\n  \n  \n   o\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  3.\n  \n  \n  SEC\n  Use Only \n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  4.\n  \n  \n  Source\n  of Funds (See Instructions)\n  PF\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  5.\n  \n  \n  Check if Disclosure of Legal Proceedings Is\n  Required Pursuant to Items 2(d) or 2(e) \n     o\n  \n \n \n  \n  \xa0\n  \n \n \n  \n  \xa0\n  \n  \n  6.\n  \n  \n  Citizenship or Place of O

In [3509]:
re.search('([\(]?1[\)]?)?\s*[\:\.]?\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?', t.upper())

<re.Match object; span=(92, 131), match='1.\n  \n  \n  NAMES OF REPORTING\n  PERSONS'>

In [3514]:
dd = {1: '([\(]?1[\)]?)?\s*[\:\.]?\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
   2: '([\(]?2[\)]?)?\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
   3: '([\(]?3[\)]?)?\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
   4: '([\(]?4[\)]?)?\s*[:\.]{0,1}\s*SOURCE\s+OF\s+FUNDS[\*]?',
   5: '([\(]?5[\)]?)?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+DISCLOSURE\s+OF\s+LEGAL\s+PROCEEDINGS',
   6: '([\(]?6[\)]?)?\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
   7: '([\(]?7[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
   8: '([\(]?8[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
   9: '([\(]?9[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
   10: '([\(]?10[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
   11: '([\(]?11[\)]?)?\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
   12: '([\(]?12[\)]?)?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
   13: '([\(]?13[\)]?)?\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
   14: '([\(]?14[\)]?)?\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}

In [3528]:
re.search(dd[14], t.upper())

<re.Match object; span=(1761, 1797), match='14.\n  \n  \n  TYPE OF REPORTING PERSON'>

In [3442]:
def get_all_reporting_pages_df(reporting_pages_text, file_name, form_type, is_rep_q_as_items):
    
    pages = get_reporting_pages(reporting_pages_text, form_type, is_rep_q_as_items)
    
    df_list = []
    
    for i in range(len(pages)):
        
        df = get_reporting_page_df(pages[i], form_type)
        df['file_name'] = file_name
        df['seq'] = i + 1
        
        df_list.append(df)
    
    order = ['file_name', 'form_type', 'seq', 'cusips', 'sedols', 'rep_person_name', 'box_2a', 'box_2b', \
                 'source_of_funds', 'SC_13D_box_5', 'citizenship_place_of_organization', 'num_shares_sole_vp', \
                 'num_shares_shared_vp', 'num_shares_sole_dp', 'num_shares_shared_dp', 'agg_amount_owned', \
                 'certain_shares_exc_from_agg', 'agg_amount_percentage_share', 'reporting_person_type']
    
    if(len(df_list)):
    
        full_df = pd.concat(df_list, ignore_index = True)
        full_df = full_df[order]
        
    else:
        
        full_df = pd.DataFrame(columns = order)
    
    return(full_df)

In [3441]:
pd.DataFrame(columns = ['file_name', 'form_type', 'seq', 'cusips', 'sedols', 'rep_person_name', 'box_2a', 'box_2b', \
                 'source_of_funds', 'SC_13D_box_5', 'citizenship_place_of_organization', 'num_shares_sole_vp', \
                 'num_shares_shared_vp', 'num_shares_sole_dp', 'num_shares_shared_dp', 'agg_amount_owned', \
                 'certain_shares_exc_from_agg', 'agg_amount_percentage_share', 'reporting_person_type'])

Empty DataFrame
Columns: [file_name, form_type, seq, cusips, sedols, rep_person_name, box_2a, box_2b, source_of_funds, SC_13D_box_5, citizenship_place_of_organization, num_shares_sole_vp, num_shares_shared_vp, num_shares_sole_dp, num_shares_shared_dp, agg_amount_owned, certain_shares_exc_from_agg, agg_amount_percentage_share, reporting_person_type]
Index: []

In [3492]:
get_filing_report_q_and_a??

In [3497]:
def q2_boxes_a_and_b(q2_text):
    
    a_start = re.search('[\(]?[aAcCeE][\.]?\)', q2_text).end()
    a_end = re.search('[\(]?[bBdDfF][\.]?\)', q2_text).start()
    b_start = re.search('[\(]?[bBdDfF][\.]?\)', q2_text).end()
    
    q2a_ticked = (re.search('[xX]', q2_text[a_start:a_end]) is not None)
    q2b_ticked = (re.search('[xX]', q2_text[b_start:]) is not None)
    
    return(q2a_ticked, q2b_ticked)

In [3500]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1207188/000110465904015891/0001104659-04-015891-index.htm'

In [3532]:
def get_filing_report_q_and_a(text, form_type):
    
    # This function is designed to be used on an individual page from the list returend from get_reporting pages. It is designed to split this page in to the individual segments for each question
    # which correspond from 0 (for Cusip) through to 14 for 13D's and 0 to 12 for 13G's
    
    text_upper = text.upper()
    
    if(re.search('^SC 13D', form_type)):
        question_regex_dict = {1: '([\(]?1[\)]?)?\s*[\:\.]?\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '([\(]?2[\)]?)?\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '([\(]?3[\)]?)?\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '([\(]?4[\)]?)?\s*[:\.]{0,1}\s*SOURCE\s+OF\s+FUNDS[\*]?',
                       5: '([\(]?5[\)]?)?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+DISCLOSURE\s+OF\s+LEGAL\s+PROCEEDINGS',
                       6: '([\(]?6[\)]?)?\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       7: '([\(]?7[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       8: '([\(]?8[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       9: '([\(]?9[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       10: '([\(]?10[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       11: '([\(]?11[\)]?)?\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       12: '([\(]?12[\)]?)?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       13: '([\(]?13[\)]?)?\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       14: '([\(]?14[\)]?)?\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
       
        num_sec = 15
       
    elif(re.search('^SC 13G', form_type)):
        
        question_regex_dict = {1: '([\(]?1[\)]?)?\s*[:\.]{0,1}\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '([\(]?2[\)]?)?\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '([\(]?3[\)]?)?\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '([\(]?4[\)]?)?\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       5: '([\(]?5[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       6: '([\(]?6[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       7: '([\(]?7[\)]?)?\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       8: '([\(]?8[\)]?)?\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       9: '([\(]?9[\)]?)?\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       10: '([\(]?10[\)]?)?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       11: '([\(]?11[\)]?)?\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       12: '([\(]?12[\)]?)?\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
        
        num_sec = 13
        
    else:
        
        raise ValueError("form_type is not equal to 'SC 13D', 'SC 13 D/A', 'SC 13G' or an 'SC 13G/A'")

    start_dict = {}

    for key, regex in question_regex_dict.items():

        print(key)
        print(text_upper)
        start_dict[key] = re.search(regex, text_upper).start()


    text_dict = {}
    for i in range(num_sec):

        if(i == 0):
            text_dict[i] = text[0:start_dict[i+1]]
        elif(i == num_sec - 1):
            text_dict[i] = text[start_dict[i]:]
        else:
            text_dict[i] = text[start_dict[i]:start_dict[i+1]]
            
    return(text_dict)

In [3531]:
text

'\n\n\n\n\n\n\nCUSIP No. 705904605                 13G                    Page 2 of 10 Pages\n\n- ----------------------------------------------------------------------------\n     (1)    NAMES OF REPORTING PERSONS I.R.S. IDENTIFICATION NO. OF ABOVE\n            PERSONS (ENTITIES ONLY)\n                                                       Labrador Partners L.P.\n- -----------------------------------------------------------------------------\n     (2)    CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP **\n                                                                  (a)  [X]\n                                                                  (b)  [ ]\n- -----------------------------------------------------------------------------\n     (3)    SEC USE ONLY\n- -----------------------------------------------------------------------------\n     (4)    CITIZENSHIP OR PLACE OF ORGANIZATION\n                            Delaware\n- ---------------------------------------------------------

In [3310]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1085869/000119312504059071/0001193125-04-059071-index.htm'

In [3279]:
indexes_df.loc[i]

file_name                      edgar/data/77449/0000315066-04-001429.txt
document                                        0000315066-04-001429.txt
form_type                                                       SC 13G/A
title_page_end_lower_bound                                             1
cover_page_q1_start                                                  143
is_rep_q_as_items                                                   True
is_schedule_to                                                     False
has_table_of_contents                                              False
num_cusip_sedol_b_q1                                                   2
cover_page_start                                                     124
item_section_start                                                   792
cover_page_last_q_end                                                687
cover_page_end                                                       699
num_cusip_b_items                                  

In [3269]:
get_index_url('edgar/data/1040261/0000938775-01-500020.txt')

'https://www.sec.gov/Archives/edgar/data/1040261/000093877501500020/0000938775-01-500020-index.htm'

In [2938]:
eg.loc[1, 'num_shares_shared_dp']

'1,336,000 - (See Schedule Item 4\n                                                incorporated by reference)'

In [2828]:
regex = '1[24]\s*[:\.]?\s+TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'
re.findall(regex, t)

['12       TYPE OF REPORTING PERSON',
 '12       TYPE OF REPORTING PERSON',
 '12       TYPE OF REPORTING PERSON']

In [2818]:
t

'\nCUSIP NO.  03840K202               SCHEDULE 13D             PAGE 2 OF 4 PAGES\n- --------------------------------------------------------------------------------\n\n- ----------- --------------------------------------------------------------------\n 1          NAME OF REPORTING PERSONS\n            I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n\n            Greg Paxton (1)\n- ----------- --------------------------------------------------------------------\n 2          CHECK THE APPROPRIATE  BOX  IF A MEMBER  OF A GROUP         (a)  |_|\n                                                                        (b)  |X|\n- ----------- --------------------------------------------------------------------\n 3          SEC USE ONLY\n- ----------- --------------------------------------------------------------------\n 4          SOURCE OF FUNDS\n            SC\n- ----------- --------------------------------------------------------------------\n 5          CHECK BOX IF DISCLOSUR

In [2817]:
indexes_df.loc[i]

file_name                      edgar/data/1163453/0001019687-04-001131.txt
document                                          0001019687-04-001131.txt
form_type                                                         SC 13D/A
title_page_end_lower_bound                                               1
cover_page_q1_start                                                   2211
is_rep_q_as_items                                                    False
is_schedule_to                                                       False
has_table_of_contents                                                False
num_cusip_sedol_b_q1                                                     2
cover_page_start                                                      1966
item_section_start                                                    5427
cover_page_last_q_end                                                 4699
cover_page_end                                                        4996
num_cusip_b_items        

In [2779]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/1120914/000105656804000061/0001056568-04-000061-index.htm'

In [2679]:
indexes_df.loc[i]

file_name                      edgar/data/923877/0000807249-04-000123.txt
document                                         0000807249-04-000123.txt
form_type                                                        SC 13D/A
title_page_end_lower_bound                                              1
cover_page_q1_start                                                   876
is_rep_q_as_items                                                   False
is_schedule_to                                                      False
has_table_of_contents                                               False
num_cusip_sedol_b_q1                                                    2
cover_page_start                                                      853
item_section_start                                                   9864
cover_page_last_q_end                                                9855
cover_page_end                                                       9864
num_cusip_b_items                     

In [2680]:
get_index_url('edgar/data/923877/0000807249-04-000123.txt')

'https://www.sec.gov/Archives/edgar/data/923877/000080724904000123/0000807249-04-000123-index.htm'

In [2681]:
t

'\n\n\n\nCUSIP No. 704231109\n1\nNAMES OF REPORTING PERSONS\nI.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n\nGabelli Funds, LLC\t                                           \t\tI.D. NO.\n13-4044523\n2\nCHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n(a)\n\n\n(b)\n\n3\nSEC USE ONLY\n\n4\nSOURCE OF FUNDS (SEE INSTRUCTIONS)\n    00-Funds of investment advisory clients\n\n5\nCHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED\nPURSUANT TO ITEMS 2 (d) OR 2 (e)\n\n\n6\nCITIZENSHIP OR PLACE OF ORGANIZATION\n   New York\n\nNUMBER OF\n\nSHARES\n\nBENEFICIALLY\n\nOWNED\n\nBY EACH\n\nREPORTING\n\nPERSON\n\nWITH\n\n7\n\n\n\nSOLE VOTING POWER\n\n1,135,000  (Item 5)\n\n\n8\n\n\n\nSHARED VOTING POWER\n\nNONE\n\n\n9\n\n\n\nSOLE DISPOSITIVE POWER\n\n1,135,000  (Item 5)\n\n10\n\n\n\nSHARED DISPOSITIVE POWER\n\nNONE\n11\n\n\n\nAGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON\n\n1,135,000  (Item 5)\n12\n\n\n\nCHECK BOX IF THE AGGREGATE AMOUNT IN ROW (11)

In [2703]:
def get_reporting_pages(text):
    
    # This function is designed to take in reporting_pages_text from the output of get_text_components
    # and to split this text into the individual pages
    
    text_upper = text.upper()
    
    regex = '1[24]\s*[:\.]?\s+TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?\s*[\*]?\s*' + \
            '(\(SEE\s+INSTRUCTIONS\))?[:\.]?\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?\s*)*' + \
            '([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n'
    
    search = re.search(regex, text_upper)
    
    if(search is None):
        return(None)
    
    end = 0
    end_list = []
    
    while(search is not None):
        
        end = end + search.end()
        end_list.append(end)
        search = re.search(regex, text_upper[end:])
        
    pages = []    
        
    for i in range(len(end_list)):
        
        if(i == 0):
            pages.append(text[0:end_list[0]])
        else:
            pages.append(text[end_list[i-1]:end_list[i]])
    
    return(pages)

In [2706]:
regex = '1[24]\s*[:\.]?\s+TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?\s*[\*]?\s*' + \
            '(\(SEE\s+INSTRUCTIONS\))?[:\.]?\s*([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?\s*)*' + \
            '([A-Z0]{1}[;, \.]?[A-Z0]{1}[;, \.]?)\s*\n'
re.search(regex, t[4011:]).group(0)

'14\n\n\n\nTYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n CO\n'

In [2819]:
len(get_reporting_pages(t))

TypeError: object of type 'NoneType' has no len()

In [2803]:
indexes_df.loc[i, 'form_type']

'SC 13G/A'

In [2822]:
get_reporting_pages(t)


In [3082]:
get_answer_text(qs[4], 'SC 13G', 4)

'SOURCE OF FUNDS (SEE INSTRUCTIONS) al Funds'

In [2958]:
pages = get_reporting_pages(t)

TypeError: get_reporting_pages() missing 2 required positional arguments: 'form_type' and 'is_rep_q_as_items'

In [3083]:
qs

{0: '\n\n\n\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n',
 1: '1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Bruce A. Cordingley\n- --------------------------------------------------------------------------------\n',
 2: '2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n',
 3: '3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n',
 4: '4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n',
 5: '5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- -----------------------------------------------

In [2962]:
qs = get_filing_report_q_and_a(pages[0], 'SC 13D')
qs

{0: '\n\n\n\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n',
 1: '1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Bruce A. Cordingley\n- --------------------------------------------------------------------------------\n',
 2: '2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n',
 3: '3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n',
 4: '4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n',
 5: '5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- -----------------------------------------------

In [2964]:
re.split('\n{2,}', qs[14])

['14       TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n         IN\n- --------------------------------------------------------------------------------',
 '                                       1',
 "(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan.",
 "(2) Includes (i) 519,684 shares owned by Pedcor Bancorp, of which Mr. Cordingley\nis the President and Chief Executive Officer and 42.04% owner (which includes\n3.79% owned by Mr. Cordingley's wife); (ii) 6,379,185 shares owned by Pedcor\nFinancial, LLC, of which Mr. Cordingley is the President and 32.167% ow

In [3180]:
def get_reporting_pages(text, form_type, is_rep_q_as_items):
     
    # This function is designed to take in reporting_pages_text from the output of get_text_components
    # and to split this text into the individual pages
    
    section_length = len(text)
    
    text_upper = text.upper()
    
    if(is_rep_q_as_items):
        
        regex_last = 'ITEM\s*[:\.]?\s*1[24]'
    
    else:
        
        regex_last = 'TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'
    
    last_qs = re.findall(regex_last, text_upper)
    
    num_pages = len(last_qs)
    
    if(num_pages == 1):
        pages = [text]
        return(pages)
    
    else:
    
        
        end_list = []
        

        for i in range(num_pages):
            
            if(i == 0):
                lower_bound = re.search(regex_last, text_upper).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            elif(i > 0 and i <  num_pages - 1):
            
                lower_bound = end + re.search(regex_last, text_upper[end:]).end()
                upper_bound = lower_bound + find_cover_page_q1_start(text, form_type, lower_bound, section_length, is_rep_q_as_items)
                end = cover_page_start(text, form_type, lower_bound, upper_bound, is_rep_q_as_items)
                
            else:
                
                end = section_length
                
            end_list.append(end)

        pages = []    

        for i in range(len(end_list)):

            if(i == 0):
                pages.append(text[0:end_list[0]])
            else:
                pages.append(text[end_list[i-1]:end_list[i]])

        return(pages)

In [3179]:
text = t
section_length = len(text)

text_upper = text.upper()

if(indexes_df.loc[i, 'is_rep_q_as_items']):

    regex_last = 'ITEM\s*[:\.]?\s*1[24]'

else:

    regex_last = 'TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'

last_qs = re.findall(regex_last, text_upper)
last_qs

['TYPE OF REPORTING PERSON',
 'TYPE OF REPORTING PERSON',
 'TYPE OF REPORTING PERSON',
 'TYPE OF REPORTING PERSON']

In [3206]:
i = 100
t = get_cover_page_section(indexes_df.loc[i, 'file_name'], indexes_df.loc[i, 'document'], directory, \
                       indexes_df.loc[i, 'cover_page_start'], indexes_df.loc[i, 'cover_page_end'])
pages = get_reporting_pages(t, indexes_df.loc[i, 'form_type'], indexes_df.loc[i, 'is_rep_q_as_items'])

In [3207]:
len(pages)

8

In [3208]:
pages[0]

'\n\n\n\nCUSIP NO. 726505100              SCHEDULE 13D/A\n\n(1)  Names of Reporting Persons I.R.S. Identification Nos.\n     of Above Persons (entities only)\n\n         ENCAP INVESTMENTS L.L.C.\n\n(2)  Check the Appropriate Box if a Member of a Group\n     (See Instructions)                                                  (a) [ ]\n                                                                         (b) [ ]\n\n(3)  SEC Use Only\n\n(4)  Source of Funds (See Instructions)                          OO (SEE ITEM 3)\n\n(5)  Check if Disclosure of Legal Proceedings is Required\n     Pursuant to Items 2(d) or 2(e)\n\n(6)  Citizenship or Place of Organization    EnCap Investments L.L.C. is a\n                                             limited liability company organized\n                                             under the laws of the State of\n                                             Delaware.\n\n     Number of         (7)  Sole Voting Power                                  0\n   

In [3154]:
indexes_df.loc[i]

file_name                      edgar/data/1135338/0000902664-04-000933.txt
document                                          0000902664-04-000933.txt
form_type                                                         SC 13G/A
title_page_end_lower_bound                                            1855
cover_page_q1_start                                                   2019
is_rep_q_as_items                                                    False
is_schedule_to                                                       False
has_table_of_contents                                                False
num_cusip_sedol_b_q1                                                     2
cover_page_start                                                      1855
item_section_start                                                   12345
cover_page_last_q_end                                                11929
cover_page_end                                                       12131
num_cusip_b_items        

In [3153]:
find_cover_page_q1_start??

In [3159]:
find_cover_page_q1_start(t, indexes_df.loc[i, 'form_type'], 300,\
                         len(t), indexes_df.loc[i, 'is_rep_q_as_items'])

2415

In [3190]:
def get_filing_report_q_and_a(text, form_type):
    
    # This function is designed to be used on an individual page from the list returend from get_reporting pages. It is designed to split this page in to the individual segments for each question
    # which correspond from 0 (for Cusip) through to 14 for 13D's and 0 to 12 for 13G's
    
    text_upper = text.upper()
    
    if(re.search('^SC 13D', form_type)):
        question_regex_dict = {1: '[\(]?1[\)]?\s*[:\.]{0,1}\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '[\(]?2[\)]?\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '[\(]?3[\)]?\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '[\(]?4[\)]?\s*[:\.]{0,1}\s*SOURCE\s+OF\s+FUNDS[\*]?',
                       5: '[\(]?5[\)]?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+DISCLOSURE\s+OF\s+LEGAL\s+PROCEEDINGS',
                       6: '[\(]?6[\)]?\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       7: '[\(]?7[\)]?\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       8: '[\(]?8[\)]?\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       9: '[\(]?9[\)]?\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       10: '[\(]?10[\)]?\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       11: '[\(]?11[\)]?\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       12: '[\(]?12[\)]?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       13: '[\(]?13[\)]?\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       14: '[\(]?14[\)]?\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
       
        num_sec = 15
       
    elif(re.search('^SC 13G', form_type)):
        
        question_regex_dict = {1: '[\(]?1[\)]?\s*[:\.]{0,1}\s*NAME[S]?\s+OF\s+REPORTING\s+PERSON[S]?',
                       2: '[\(]?2[\)]?\s*[:\.]{0,1}\s*CHECK\s+THE\s+APPROPRIATE\s+BOX\s+IF\s+A\s+MEMBER',
                       3: '[\(]?3[\)]?\s*[:\.]{0,1}\s*SEC\s+USE\s+ONLY',
                       4: '[\(]?4[\)]?\s*[:\.]{0,1}\s*CITIZENSHIP\s+OR\s+PLACE\s+OF\s+ORGANIZATION', 
                       5: '[\(]?5[\)]?\s*[:\.]{0,1}\s*SOLE\s+VOTING\s+POWER',
                       6: '[\(]?6[\)]?\s*[:\.]{0,1}\s*SHARED\s+VOTING\s+POWER',
                       7: '[\(]?7[\)]?\s*[:\.]{0,1}\s*SOLE\s+DISPOSITIVE\s+POWER',
                       8: '[\(]?8[\)]?\s*[:\.]{0,1}\s*SHARED\s+DISPOSITIVE\s+POWER',
                       9: '[\(]?9[\)]?\s*[:\.]{0,1}\s*AGGREGATE\s+AMOUNT\s+BENEFICIALLY\s+OWNED',
                       10: '[\(]?10[\)]?\s*[:\.]{0,1}\s*CHECK(\s+BOX)?\s+IF\s+THE\s+AGGREGATE\s+AMOUNT',
                       11: '[\(]?11[\)]?\s*[:\.]{0,1}\s*PERCENT\s+OF\s+CLASS\s+REPRESENTED',
                       12: '[\(]?12[\)]?\s*[:\.]{0,1}\s*TYPE[S]?\s+OF\s+REPORTING\s+PERSON[S]?'}
        
        num_sec = 13
        
    else:
        
        raise ValueError("form_type is not equal to 'SC 13D', 'SC 13 D/A', 'SC 13G' or an 'SC 13G/A'")

    start_dict = {}

    for key, regex in question_regex_dict.items():

        start_dict[key] = re.search(regex, text_upper).start()


    text_dict = {}
    for i in range(num_sec):

        if(i == 0):
            text_dict[i] = text[0:start_dict[i+1]]
        elif(i == num_sec - 1):
            text_dict[i] = text[start_dict[i]:]
        else:
            text_dict[i] = text[start_dict[i]:start_dict[i+1]]
            
    return(text_dict)    

In [3166]:
lower_bound = 1800
upper_bound = lower_bound + find_cover_page_q1_start(t, indexes_df.loc[i, 'form_type'], lower_bound,\
                         len(t), indexes_df.loc[i, 'is_rep_q_as_items'])
cover_page_start(text, indexes_df.loc[i, 'form_type'], lower_bound,\
                 upper_bound, indexes_df.loc[i, 'is_rep_q_as_items'])

2715

In [3174]:
re.search('(PISUC|LODES)(.)*\n', t[2415:2715][::-1].upper()).end()

158

In [3175]:
2715 - 158

2557

In [3211]:
pages[0]

'\n\n\n\nCUSIP NO. 726505100              SCHEDULE 13D/A\n\n(1)  Names of Reporting Persons I.R.S. Identification Nos.\n     of Above Persons (entities only)\n\n         ENCAP INVESTMENTS L.L.C.\n\n(2)  Check the Appropriate Box if a Member of a Group\n     (See Instructions)                                                  (a) [ ]\n                                                                         (b) [ ]\n\n(3)  SEC Use Only\n\n(4)  Source of Funds (See Instructions)                          OO (SEE ITEM 3)\n\n(5)  Check if Disclosure of Legal Proceedings is Required\n     Pursuant to Items 2(d) or 2(e)\n\n(6)  Citizenship or Place of Organization    EnCap Investments L.L.C. is a\n                                             limited liability company organized\n                                             under the laws of the State of\n                                             Delaware.\n\n     Number of         (7)  Sole Voting Power                                  0\n   

In [3212]:
qs = get_filing_report_q_and_a(page, indexes_df.loc[i, 'form_type'])

In [3213]:
qs

{0: '\n\n\n\nCUSIP NO. 726505100              SCHEDULE 13D/A\n\n',
 1: '(1)  Names of Reporting Persons I.R.S. Identification Nos.\n     of Above Persons (entities only)\n\n         ENCAP INVESTMENTS L.L.C.\n\n',
 2: '(2)  Check the Appropriate Box if a Member of a Group\n     (See Instructions)                                                  (a) [ ]\n                                                                         (b) [ ]\n\n',
 3: '(3)  SEC Use Only\n\n',
 4: '(4)  Source of Funds (See Instructions)                          OO (SEE ITEM 3)\n\n',
 5: '(5)  Check if Disclosure of Legal Proceedings is Required\n     Pursuant to Items 2(d) or 2(e)\n\n',
 6: '(6)  Citizenship or Place of Organization    EnCap Investments L.L.C. is a\n                                             limited liability company organized\n                                             under the laws of the State of\n                                             Delaware.\n\n     Number of         ',
 7: '(7

In [3209]:
page, footnotes = extract_footnotes(pages[0], indexes_df.loc[i, 'form_type'])

In [3210]:
footnotes

[]

In [3195]:
page

'\n\n\n\n\n\n\nCUSIP No. 705904605                 13G                    Page 2 of 10 Pages\n\n- ----------------------------------------------------------------------------\n     (1)    NAMES OF REPORTING PERSONS I.R.S. IDENTIFICATION NO. OF ABOVE\n            PERSONS (ENTITIES ONLY)\n                                                       Labrador Partners L.P.\n- -----------------------------------------------------------------------------\n     (2)    CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP **\n                                                                  (a)  [X]\n                                                                  (b)  [ ]\n- -----------------------------------------------------------------------------\n     (3)    SEC USE ONLY\n- -----------------------------------------------------------------------------\n     (4)    CITIZENSHIP OR PLACE OF ORGANIZATION\n                            Delaware\n- ---------------------------------------------------------

In [3144]:
t

'\n\n\n\nCUSIP NO. 726505100              SCHEDULE 13D/A\n\n(1)  Names of Reporting Persons I.R.S. Identification Nos.\n     of Above Persons (entities only)\n\n         ENCAP INVESTMENTS L.L.C.\n\n(2)  Check the Appropriate Box if a Member of a Group\n     (See Instructions)                                                  (a) [ ]\n                                                                         (b) [ ]\n\n(3)  SEC Use Only\n\n(4)  Source of Funds (See Instructions)                          OO (SEE ITEM 3)\n\n(5)  Check if Disclosure of Legal Proceedings is Required\n     Pursuant to Items 2(d) or 2(e)\n\n(6)  Citizenship or Place of Organization    EnCap Investments L.L.C. is a\n                                             limited liability company organized\n                                             under the laws of the State of\n                                             Delaware.\n\n     Number of         (7)  Sole Voting Power                                  0\n   

In [3148]:
qs

{0: '\n\n\n\nCUSIP No. 709640106\nPage 2 of 15 Pages\n\n\n\xa0\xa0\n\n ',
 1: '1\nNAME OF REPORTING PERSON\nS.S. OR I.R.S. IDENTIFICATION NO. OF ABOVE PERSON\n\nMercator Momentum Fund, L.P.\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0EIN:\xa0\xa003-0021366\n\n\n',
 2: '2\nCHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP\n(a)\xa0\xa0¨\n(b)\xa0\xa0ý\n\n\n',
 3: '3\n\nSEC USE ONLY\n\n\n',
 4: '4\n\nCITIZENSHIP OR PLACE OF ORGANIZATION\n\nCalifornia\n\n\n\nNUMBER OF\n\nSHARES\n\nBENEFICIALLY\n\nOWNED BY\n\nEACH\n\nREPORTING\n\nPERSON\n\nWITH\n\n',
 5: '5\n\nSOLE VOTING POWER\n\n0\n\n\n\n',
 6: '6\n\nSHARED VOTING POWER\n\n22,973,442\n\n\n',
 7: '7\nSOLE DISPOSITIVE POWER\n\n0\n\n\n\n',
 8: '8\n\nSHARED DISPOSITIVE POWER\n\n22,973,442\n\n\n',
 9: '9\n\nAGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON\n\n22,973,442\n\n\n',
 10: '10\n\nCHECK BOX IF THE AGGREGATE AMOUNT IN ROW (9) EXCLUDES CERTAIN SHARES\xa0\xa0¨\n  \n\n\n',
 11: '11\n\nPERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW (9)\n\n7.43%

In [3097]:
page

'\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Pedcor Financial, LLC\n- --------------------------------------------------------------------------------\n2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Working Capital\n- --------------------------------------------------------------------------------\n5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- --------------------------------------------------------------------------------\n6        CIT

In [3052]:
re.strip('a', 'aabgagdagakkka')

AttributeError: module 're' has no attribute 'strip'

In [3089]:
def clean_q_and_a(q_and_a, form_type):
    
    clean_q_and_a = {}
    
    if(re.search('13D', form_type) is not None):
        
        num_last = 14
        ben_own_statement_keys = [6, 7, 8, 9, 10, 11]
        
    elif(re.search('13G', form_type) is not None):
        
        num_last = 12
        ben_own_statement_keys = [4, 5, 6, 7, 8, 9]
    
    for key, q_text in q_and_a.items():
        
        text = q_text
        
        if(key == num_last):
            
            text = re.sub('PAGE[S]?|SCHEDULE|13[DG]|\s[1-9]+\s', '', text)
            
        if(key in ben_own_statement_keys):
            
            text = eliminate_beneficial_own_statement(text)
            
        clean_q_and_a[key] = text.strip(' \n\-')
        
    return(clean_q_and_a)

In [3095]:
qs

{0: '\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n',
 1: '1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Pedcor Financial, LLC\n- --------------------------------------------------------------------------------\n',
 2: '2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n',
 3: '3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n',
 4: '4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Working Capital\n- --------------------------------------------------------------------------------\n',
 5: '5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- --------------------------------------------------

In [3214]:
clean_qs = clean_q_and_a(qs, indexes_df.loc[i, 'form_type'])
clean_qs

{0: 'CUSIP NO. 726505100              SCHEDULE 13D/A',
 1: '(1)  Names of Reporting Persons I.R.S. Identification Nos.\n     of Above Persons (entities only)\n\n         ENCAP INVESTMENTS L.L.C.',
 2: '(2)  Check the Appropriate Box if a Member of a Group\n     (See Instructions)                                                  (a) [ ]\n                                                                         (b) [ ]',
 3: '(3)  SEC Use Only',
 4: '(4)  Source of Funds (See Instructions)                          OO (SEE ITEM 3)',
 5: '(5)  Check if Disclosure of Legal Proceedings is Required\n     Pursuant to Items 2(d) or 2(e)',
 6: '(6)  Citizenship or Place of Organization    EnCap Investments L.L.C. is a\n                                             limited liability company organized\n                                             under the laws of the State of\n                                             Delaware.',
 7: '(7)  Sole Voting Power                                  0 Ben

In [3200]:
def get_answer_text(q_text, form_type, question_number):
    
    # This function is designed to be used on all questions except question 2, 
    # in which there are boxes (a) and (b)
   
    
    # First, get rid of beneficial ownership statement
      
    if(re.search("13D", form_type)):
        
        ben_own_statement_keys = [6, 7, 8, 9, 10, 11]
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'SOURCE OF FUNDS[*]? \(SEE INSTRUCTIONS\)',
                        5: 'CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT' + \
                           ' TO ITEMS 2\(D\) OR 2\(E\)',
                        6: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        7: 'SOLE VOTING POWER',
                        8: 'SHARED VOTING POWER',
                        9: 'SOLE DISPOSITIVE POWER',
                        10: 'SHARED DISPOSITIVE POWER', 
                        11: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        12: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW \(11\) EXCLUDES CERTAIN SHARES[*]?',
                        13: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW \(11\)',
                        14: 'TYPE[S]? OF REPORTING PERSON[S]? \(SEE INSTRUCTIONS\)'
                       }
        
    elif(re.search("13G", form_type)):
        
        ben_own_statement_keys = [4, 5, 6, 7, 8, 9]
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        5: 'SOLE VOTING POWER',
                        6: 'SHARED VOTING POWER',
                        7: 'SOLE DISPOSITIVE POWER',
                        8: 'SHARED DISPOSITIVE POWER',
                        9: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        10: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW \(9\) EXCLUDES CERTAIN SHARES[*]?',
                        11: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW \(9\)',
                        12: 'TYPE[S]? OF REPORTING PERSON[S]? \(SEE INSTRUCTIONS\)'
                       }
    
    # First, get rid of beneficial ownership statement
    
    if(question_number in ben_own_statement_keys):

        result = eliminate_beneficial_own_statement(q_text)

    else:

        result = q_text
    
    result = re.sub('^[\(]?' + str(question_number) + '[\)]?\s*[:\.]?', '', result)
    
    result = re.sub('(^[\:\;\-\–\.\s]+|[\s\-]+$)', '', strip_form_statement(result, q_regex_dict[question_number]))
    
    return(result)

In [3203]:
i = 4
get_answer_text(clean_qs[i], 'SC 13G', i)

'Delaware'

In [3204]:
clean_qs[i]

'(4)    CITIZENSHIP OR PLACE OF ORGANIZATION\n                            Delaware'

In [ ]:
def strip_form_statement(text, statement):

    statement_raised = re.sub('\s+', ' ', statement).upper()
    text_raised = text.upper()
    
    words = statement_raised.split(' ')

    regex_list = []

    for i in range(len(words)):
        
        if(i == 0):
            
            regex_list.append('\n\s*(?:' + '|'.join(words) + ')')
            
        else:
            regex_list.append('(?:' + '|'.join(words[i:]) + ')?')
                              
    regex = '(' + '[\s-]*'.join(regex_list) + ')'
    
    regex_start = '^(' + '[\s-]*'.join(regex_list).lstrip('\n') + ')'

    start_search = re.search(regex_start, text_raised)

    if(start_search):

        statement_parts = [start_search.group(0)] + re.findall(regex, text_raised)

    else:
        statement_parts = re.findall(regex, text_raised)
        
    result = text

    for part in statement_parts:

        start = result.upper().find(part)
        if(start != -1):
            end = start + len(part)
            result = result[:start] + ' ' + result[end:]
    
    return(result)

In [3111]:
def eliminate_beneficial_own_statement(text):
    
    # This function is designed to get rid of the irritating 
    # 'NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH' statement, or any occurences of 
    # any part of it, around q6, q7, q8, q9, q10 (on SC 13D)
    
    result = strip_form_statement(text, 'NUMBER OF SHARES BENEFICIALLY OWNED BY EACH REPORTING PERSON WITH')
    
    return(result)       

In [3078]:
qs[4]

'4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n'

In [3205]:
extract_footnote_indices(clean_q_and_a(qs, indexes_df.loc[i, 'form_type']), pp['index'].tolist())

Empty DataFrame
Columns: [question, index]
Index: []

In [3072]:
eliminate_beneficial_own_statement(qs[6])

'6        CITIZENSHIP OR PLACE OF ORGANIZATION\n         United States of America\n- -------------------------------------------------------------------------------- '

In [3092]:
def extract_footnote_indices(q_and_a, indexes):
    
    # Warning: this function assumes q_and_a has been sufficiently cleaned so that the footnote indices 
    # can be extracted from the right of each q_and_a text
    
    questions = []
    indices = []
    
    for key, q_text in q_and_a.items():

        text = q_text
        
        search = re.search('\([0-9a-zA-Z\*]*\)$', text)
        
        while(search is not None):
            
            flag = False
            
            for index in indexes:
                
                if(search.group(0) == index):
                    
                    questions.append(key)
                    indices.append(index)
                    text = text.rstrip(index)
                    search = re.search('\([0-9a-zA-Z\*]*\)$', text)
                    flag = True
                    break
                    
            if(not flag):
                
                search = None
                    
    df = pd.DataFrame({'question': questions, 'index': indices})
    
    return(df)
    

In [3054]:
qs = get_filing_report_q_and_a(new_page, indexes_df.loc[i, 'form_type'])

In [3059]:
qs

{0: '\n\n\n\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n',
 1: '1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Bruce A. Cordingley\n- --------------------------------------------------------------------------------\n',
 2: '2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n',
 3: '3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n',
 4: '4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n',
 5: '5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- -----------------------------------------------

In [3104]:
get_answer_text??

In [2972]:
regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   

In [ ]:
regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   

In [2996]:
def extract_footnotes_by_regex(text, regex):
    
    search = re.search(regex, text)
    
    if(search is None):
        
        return([])
    
    else:
        starts = []
        footnotes = []
        last_end = 0

        while(search):

            starts.append(last_end + search.start())
            last_end = last_end + search.end()
            search = re.search(regex, text[last_end:])

        num_footnotes = len(footnotes)    

        for i in range(len(starts)):
            
            if(i == len(starts) - 1):
                
                footnote = text[starts[i]:]
                
            else:
                
                footnote = text[starts[i]:starts[i+1]]
                
            footnotes.append(footnote)
                
    return(footnotes)
        

In [2992]:
qs[14]

"14       TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n         IN\n- --------------------------------------------------------------------------------\n\n                                       1\n\n\n(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan.\n\n(2) Includes (i) 519,684 shares owned by Pedcor Bancorp, of which Mr. Cordingley\nis the President and Chief Executive Officer and 42.04% owner (which includes\n3.79% owned by Mr. Cordingley's wife); (ii) 6,379,185 shares owned by Pedcor\nFinancial, LLC, of which Mr. Cordingley is the President and 32.167% owne

In [3004]:
footnotes_eg = extract_footnotes_by_regex(qs[14], regex2)
footnotes_eg

["\n\n\n(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan.",
 "\n\n(2) Includes (i) 519,684 shares owned by Pedcor Bancorp, of which Mr. Cordingley\nis the President and Chief Executive Officer and 42.04% owner (which includes\n3.79% owned by Mr. Cordingley's wife); (ii) 6,379,185 shares owned by Pedcor\nFinancial, LLC, of which Mr. Cordingley is the President and 32.167% owner; and\n(iii) 386,619 shares and 24,666 shares which Pedcor Financial, LLC and Pedcor\nBancorp, respectively, have the right to acquire upon exercise of warrants\nacquired pursuant to Fid

In [3006]:
footnotes_eg[0]

"\n\n\n(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan."

In [ ]:
re.sub(footnotes_eg[0], '', qa)

In [3009]:
text = qs[14]

for f in footnotes_eg:
    
    text = text.replace(f, '')
    
print(text)

14       TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)
         IN
- --------------------------------------------------------------------------------

                                       1


In [3008]:
qs[14]

"14       TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n         IN\n- --------------------------------------------------------------------------------\n\n                                       1\n\n\n(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan.\n\n(2) Includes (i) 519,684 shares owned by Pedcor Bancorp, of which Mr. Cordingley\nis the President and Chief Executive Officer and 42.04% owner (which includes\n3.79% owned by Mr. Cordingley's wife); (ii) 6,379,185 shares owned by Pedcor\nFinancial, LLC, of which Mr. Cordingley is the President and 32.167% owne

In [3010]:
extract_footnotes_by_regex(qs[14], regex1) + extract_footnotes_by_regex(qs[14], regex2)

["\n\n\n(1) Includes (i) 48,730 shares held directly by Mr. Cordingley; (ii) 17,885\nshares held directly by Mr. Cordingley's wife, Denise Cordingley; (iii) 8,587\nshares which Mr. Cordingley has the right to acquire upon exercise of warrants\nacquired pursuant to Fidelity Federal Bancorp's 1994 Rights Offering; and (iv)\n56,516 shares which Mr. Cordingley has the right to acquire upon exercise of\nstock options granted under Fidelity Federal Bancorp's 1993 Director's Stock\nOption Plan.",
 "\n\n(2) Includes (i) 519,684 shares owned by Pedcor Bancorp, of which Mr. Cordingley\nis the President and Chief Executive Officer and 42.04% owner (which includes\n3.79% owned by Mr. Cordingley's wife); (ii) 6,379,185 shares owned by Pedcor\nFinancial, LLC, of which Mr. Cordingley is the President and 32.167% owner; and\n(iii) 386,619 shares and 24,666 shares which Pedcor Financial, LLC and Pedcor\nBancorp, respectively, have the right to acquire upon exercise of warrants\nacquired pursuant to Fid

In [3011]:
[1, 2, 4] + [-9, 8, 0]

[1, 2, 4, -9, 8, 0]

In [3002]:
extract_footnotes_by_regex(qs[14], regex1)

[]

In [3001]:
footnotes_eg[2]

"\n\n(3) Based on 9,618,658 shares of common stock, par value $1.00 per share, of\nFidelity Federal Bancorp believed to be outstanding by Fidelity Federal\nBancorp's management as of March 31, 2004 and computed in accordance with Rule\n13d-3(d)(1).\n\n                                       2\n\n"

In [2995]:
len(extract_footnotes_by_regex(qs[14], regex2))

3

In [2986]:
regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'  

In [3021]:
def extract_footnotes(page, form_type):
    
    qs = get_filing_report_q_and_a(page, form_type)
    
    if(re.search('13D', form_type) is not None):
        
        text = qs[14] # Get the last question
    
    elif(re.search('13G', form_type) is not None):
        
        text = qs[12] # Get the last question
        
    else:
        return(None)
    
    
    text = re.sub('\*SEE\s+INSTRUCTION(S)?\s+BEFORE\s+FILLING\s+OUT(!)?', '', text) # get rid of noise
    
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'  
    
    footnotes = extract_footnotes_by_regex(text, regex1) + extract_footnotes_by_regex(text, regex2)
    
    footnotes_cleaned = [x.strip(' \n\-') for x in footnotes]
    
    new_page = page
    
    for f in footnotes_cleaned:
        
        new_page = new_page.replace(f, '')
    
    return(new_page, footnotes_cleaned)
        
        

In [3031]:
get_index_url(indexes_df.loc[i, 'file_name'])

'https://www.sec.gov/Archives/edgar/data/925765/000092627404000155/0000926274-04-000155-index.htm'

In [3022]:
extract_footnotes(pages[0], indexes_df.loc[i, 'form_type'])

('\n\n\n\nCUSIP NO. 299333104\n- --------------------------------------------------------------------------------\n1        NAME OF REPORTING PERSONS\n         I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n         Bruce A. Cordingley\n- --------------------------------------------------------------------------------\n2        CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP (SEE INSTRUCTIONS)\n         (a) [ ]\n         (b) [X]\n- --------------------------------------------------------------------------------\n3        SEC USE ONLY\n\n- --------------------------------------------------------------------------------\n4        SOURCE OF FUNDS (SEE INSTRUCTIONS)\n         Personal Funds\n- --------------------------------------------------------------------------------\n5        CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT TO\n         ITEMS 2(d) or 2(e) [ ]\n- --------------------------------------------------------------------------------\n6       

In [3029]:
def get_footnotes_df(footnotes):
    
    regex = '^[^\s\)]*[\s\)]'
    
    indexes = []
    footnotes_c = []
    
    for f in footnotes:
        
        index = re.search(regex, f).group(0)
        footnote = f.lstrip(index)
        
        indexes.append(index)
        footnotes_c.append(footnote)
        
    df = pd.DataFrame({'index': indexes, 'footnote': footnotes_c})
    
    return(df)
        

In [ ]:
def process_cover_page(page, form_type):
    
    page_wo_footnotes, footnotes = extract_footnotes(page, form_type)
    
    footnotes_df = get_footnotes_df(footnotes)
    
    q_and_a = clean_q_and_a(get_filing_report_q_and_a(page_wo_footnotes, form_type), form_type)
    
    indexes = footnotes_df['index'].tolist()
    
    

In [3050]:
def extract_footnote_indices(q_and_a, indexes):
    
    # Warning: this function assumes q_and_a has been sufficiently cleaned so that the footnote indices 
    # can be extracted from the right of each q_and_a text
    
    questions = []
    indices = []
    
    for key, q_text in q_and_a.items():
        
        text = q_text
        
        search = re.search('\([0-9a-zA-Z\*]*\)$', text)
        
        while(search):
            
            for index in indexes:
                
                if(search.group(0) == index):
                    
                    questions.append(key)
                    indices.append(index)
                    text = text.rstrip(index)
                    search = re.search('\([0-9a-zA-Z\*]*\)$', text)
                    break
                    
                else:
                    
                    search = None
                    
    df = pd.DataFrame({'question': questions, 'index': indices})
    
    return(df)
    
    

In [ ]:
extract_footnote_indices(, pp['index'.tolist()])

In [3045]:
re.search('\(1\)', '(1)').group(0)

'(1)'

In [3040]:
re.search('(1)', '(1)')

<re.Match object; span=(1, 2), match='1'>

In [3030]:
pp = get_footnotes_df(footnotes)
pp

index                                           footnote
0   (1)   Includes (i) 48,730 shares held directly by M...
1   (2)   Includes (i) 519,684 shares owned by Pedcor B...
2   (3)   Based on 9,618,658 shares of common stock, pa...

In [3049]:
[re.sub(')', '\)', re.sub('(', '\(', index)) for index in pp['index'].tolist()]

error: missing ), unterminated subpattern at position 0

In [3028]:
pp.loc[0]

index                                                      (1
footnote    ) Includes (i) 48,730 shares held directly by ...
Name: 0, dtype: object

In [3024]:
new_page, footnotes = extract_footnotes(pages[0], indexes_df.loc[i, 'form_type'])
get_reporting_page_df(new_page, indexes_df.loc[i, 'form_type'])

form_type       cusips sedols      rep_person_name  box_2a  box_2b  \
0  SC 13D/A  [299333104]     []  Bruce A. Cordingley   False    True   

  source_of_funds  SC_13D_box_5 citizenship_place_of_organization  \
0              []         False          United States of America   

  num_shares_sole_vp num_shares_shared_vp num_shares_sole_dp  \
0        131,718 (1)        7,310,154 (2)        131,718 (1)   

  num_shares_shared_dp agg_amount_owned  certain_shares_exc_from_agg  \
0        7,310,154 (2)        7,441,872                        False   

  agg_amount_percentage_share reporting_person_type  
0                   66.4% (3)                  [IN]

In [ ]:
def get_clean_q_and_a

In [2979]:
re.findall(regex2, pages[0])

['1', '2', '3']

In [ ]:
def find_last_footnote_index_end(text, lower_bound = None, upper_bound = None):
    
    
    bounded_text = get_bounded_text(text, lower_bound, upper_bound)
        
    regex1 = '\n\s*[\(\|]?\s*[*]+\s*[\)\|]?\s*[a-zA-Z]'
    regex2 = '\n\s*[\(\|]\s*([0-9]{1,3}|[a-zA-Z]{1})\s*[\)\|]\s*[a-zA-Z]'   
    
    # first try regex1
    
    last_footnote_ind_end  = find_last_search_end(regex1, bounded_text)
    
    if(last_footnote_ind_end is not None):
        
        if(lower_bound is not None):
            
            result = last_footnote_ind_end + lower_bound
            
        else: 
            
            result = last_footnote_ind_end
            
        return(result)
            
    else:
        
        # Try regex2
        
        last_footnote_ind_end = find_last_search_end(regex2, bounded_text)
    
        if(last_footnote_ind_end is not None):

            if(lower_bound is not None):

                result = last_footnote_ind_end + lower_bound

            else: 

                result = last_footnote_ind_end

            return(result)
        
        else:
            
            return(-1)

In [ ]:
def get_footnotes(q_and_a_dict, form_type):
    
    if(re.search('13D', form_type) is not None):
        
        q_num = 14
        
    elif(re.search('13G', form_type) is not None):
        
        q_num = 12
        
    else:
        
        return(None)
    
    parts = re.split('\n{2,}', q_and_a_dict[q_num])

In [2887]:
pages[0]

'\nCUSIP NO.  03840K202               SCHEDULE 13D             PAGE 2 OF 4 PAGES\n- --------------------------------------------------------------------------------\n\n- ----------- --------------------------------------------------------------------\n 1          NAME OF REPORTING PERSONS\n            I.R.S. IDENTIFICATION NOS. OF ABOVE PERSONS (ENTITIES ONLY)\n\n            Greg Paxton (1)\n- ----------- --------------------------------------------------------------------\n 2          CHECK THE APPROPRIATE  BOX  IF A MEMBER  OF A GROUP         (a)  |_|\n                                                                        (b)  |X|\n- ----------- --------------------------------------------------------------------\n 3          SEC USE ONLY\n- ----------- --------------------------------------------------------------------\n 4          SOURCE OF FUNDS\n            SC\n- ----------- --------------------------------------------------------------------\n 5          CHECK BOX IF DISCLOSUR

In [2791]:
q2_boxes_a_and_b(qs[2])

(False, False)

In [2788]:
qs[2]

'2         CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP*\n\n                                                            (a)     / /\n\n                                                            (b)     / /\n\n- --------------------------------------------------------------------------------\n'

In [2814]:
def q2_boxes_a_and_b(q2_text):
    
    a_start = re.search('\([aAcCeE]\)', q2_text).end()
    a_end = re.search('\([bBdDfF]\)', q2_text).start()
    b_start = re.search('\([bBdDfF]\)', q2_text).end()
    
    q2a_ticked = (re.search('[xX]', q2_text[a_start:a_end]) is not None)
    q2b_ticked = (re.search('[xX]', q2_text[b_start:]) is not None)
    
    return(q2a_ticked, q2b_ticked)

In [2891]:
def q14_get_type_rep_person(q14_text, form_type, question_number):
    
    is_13d = re.search('13D', form_type) is not None
    is_13g = re.search('13G', form_type) is not None
    
    if((is_13d and question_number == 14) or (is_13g and question_number == 12)):
    
        text = get_answer_text(q14_text, form_type, question_number)

        result = re.findall('(?:[\-;,\s\.]|^)(BD|BK|IC|IV|IA|EP|HC|SA|CP|CO|C0|PN|IN|OO|00)' + \
                            '(?:[\-;,\s\.]|$)', text)
        result = [re.sub('0', 'O', x) for x in result]
        
        return(result)
        
    else:
        
        if(is_13d):
            
            raise ValueError("form is of type SC 13D or SC 13D/A, but question number is not 14")
            
        if(is_13g):
            
            raise ValueError("form is of type SC 13G or SC 13G/A, but question number is not 12")
            
        else:
            
            raise ValueError("form is not of type SC 13D or SC 13D/A")

In [2730]:
result = re.sub('^' + str(14) + '\s*[:\.]?', '', q)
result

'TYPE OF REPORTING PERSON (SEE INSTRUCTIONS)\n    IA\n\n'

In [2889]:
get_answer_text(qs[14], 'SC 13D', 14)

'IN (1)\n- ----------- --------------------------------------------------------------------\n\n(1)      Shares are held of record by Global Power & Water, Inc., a Nevada\n         corporation, for which Mr. Greg Paxton, an Australian citizen, is the\n         controlling shareholder and president.'

In [2890]:
strip_form_statement(get_answer_text(qs[14], 'SC 13D', 14), 'TYPE[S]? OF REPORTING PERSON[S]? \(SEE INSTRUCTIONS\)')

'IN (1)\n- ----------- --------------------------------------------------------------------\n\n(1)      Shares are held of record by Global Power & Water, Inc., a Nevada\n         corporation, for which Mr. Greg Paxton, an Australian citizen, is the\n         controlling shareholder and president.'

In [2795]:
pages = get_reporting_pages(t)

In [2796]:
len(pages)

3

In [2813]:
qs

{0: '- --------------------------------------------------------------------------------\n                      *SEE INSTRUCTION BEFORE FILLING OUT!\n\n\n\n\n\n\nCUSIP No. 693282105                              13G          Page 4 of 7  Pages\n         -------------\n\n\n\n\n\n\n- --------------------------------------------------------------------------------\n',
 1: '1        NAME OF REPORTING PERSON\n         S.S. OR I.R.S. IDENTIFICATION NO OF ABOVE PERSON\n                                  David G. Kern\n\n\n- --------------------------------------------------------------------------------\n\n',
 2: '2 CHECK THE APPROPRIATE BOX IF A MEMBER OF A GROUP*\n                                                                 (e)   / /\n\n                                                                 (f)   / /\n\n- --------------------------------------------------------------------------------\n',
 3: '3        SEC USE ONLY\n\n\n- ----------------------------------------------------------

In [2806]:
answer_dict = {}
form_type =  'SC 13G/A'
answer_dict['form_type'] = 'SC 13G/A'
is_13d = False
is_13g = True

if(is_13g):
    
    # These fields do not appear in SC 13G or SC 13G/A. Set them to None
    answer_dict['SC_13D_box_5'] = None
    answer_dict['source_of_funds'] = None


for key, q_text in qs.items():

    if(key == 0):
        cusips, sedols = get_reporting_page_cusip_sedol(q_text)
        answer_dict['cusips'] = [cusips]
        answer_dict['sedols'] = [sedols]

    elif(key == 1):

        answer_dict['rep_person_name'] = [get_answer_text(q_text, form_type, key)]

    elif(key == 2):

        q_2a_ticked, q_2b_ticked = q2_boxes_a_and_b(q_text)
        answer_dict['box_2a'] = [q_2a_ticked]
        answer_dict['box_2b'] = [q_2b_ticked]

    elif(key == 3):

        pass

    elif(key == 4 and is_13d):

        answer_dict['source_of_funds'] = [q4_get_source_of_funds(q_text, form_type)]

    elif(key == 5 and is_13d):

        answer_dict['SC_13D_box_5'] = [q5_12_box(q_text, form_type, key)]

    elif((key == 4 and is_13g) or (key == 6 and is_13d)):

        answer_dict['citizenship_place_of_organization'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 7 and is_13d) or (key == 5 and is_13g)):

        answer_dict['num_shares_sole_vp'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 8 and is_13d) or (key == 6 and is_13g)):

        answer_dict['num_shares_shared_vp'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 9 and is_13d) or (key == 7 and is_13g)):

        answer_dict['num_shares_sole_dp'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 10 and is_13d) or (key == 8 and is_13g)):

        answer_dict['num_shares_shared_dp'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 11 and is_13d) or (key == 9 and is_13g)):

        answer_dict['agg_amount_owned'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 12 and is_13d) or (key == 10 and is_13g)):

        answer_dict['certain_shares_exc_from_agg'] = [q5_12_box(q_text, form_type, key)]

    elif((key == 13 and is_13d) or (key == 11 and is_13g)):

        answer_dict['agg_amount_percentage_share'] = [get_answer_text(q_text, form_type, key)]

    elif((key == 14 and is_13d) or (key == 12 and is_13g)):

        answer_dict['reporting_person_type'] = [q14_get_type_rep_person(q_text, form_type, key)]

In [2809]:
pd.DataFrame(answer_dict)

form_type SC_13D_box_5 source_of_funds       cusips sedols  \
0  SC 13G/A         None            None  [693282105]     []   

                                     rep_person_name  box_2a  box_2b  \
0  Kern Capital Management, LLC\n\n              ...   False   False   

  citizenship_place_of_organization num_shares_sole_vp num_shares_shared_vp  \
0                          Delaware          1,336,000                        

  num_shares_sole_dp num_shares_shared_dp agg_amount_owned  \
0          1,336,000                             1,336,000   

   certain_shares_exc_from_agg  \
0                        False   

                       agg_amount_percentage_share reporting_person_type  
0  9\n\n                                      5.2%                  [IA]

In [ ]:
def q14_get_type_rep_person(q14_text, form_type, question_number):
    
    is_13d = re.search('13D', form_type) is not None
    is_13g = re.search('13G', form_type) is not None
    
    if((is_13d and question_number == 14) or (is_13g and question_number == 12)):
    
        text = get_answer_text(q14_text, form_type, question_number)

        result = re.findall('(BD|BK|IC|IV|IA|EP|HC|SA|CP|CO|C0|PN|IN|OO|00)', text)
        result = [re.sub('0', 'O', x) for x in result]
        
        return(result)
        
    else:
        
        if(is_13d):
            
            raise ValueError("form is of type SC 13D or SC 13D/A, but question number is not 14")
            
        if(is_13g):
            
            raise ValueError("form is of type SC 13G or SC 13G/A, but question number is not 12")
            
        else:
            
            raise ValueError("form is not of type SC 13D or SC 13D/A")

In [ ]:
get_answer_text(q_text, form_type, question_number)

In [2772]:
def get_answer_text(q_text, form_type, question_number):
    
    # This function is designed to be used on all questions except question 2, in which there are boxes (a) and (b)
   
    
    # First, get rid of beneficial ownership statement
    result = eliminate_beneficial_own_statement(q_text)
      
    if(re.search("13D", form_type)):
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'SOURCE OF FUNDS[*]?',
                        5: 'CHECK BOX IF DISCLOSURE OF LEGAL PROCEEDINGS IS REQUIRED PURSUANT' + \
                           ' TO ITEMS 2\(D\) OR 2\(E\)',
                        6: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        7: 'SOLE VOTING POWER',
                        8: 'SHARED VOTING POWER',
                        9: 'SOLE DISPOSITIVE POWER',
                        10: 'SHARED DISPOSITIVE POWER', 
                        11: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        12: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW \(11\) EXCLUDES CERTAIN SHARES[*]?',
                        13: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW \(11\)',
                        14: 'TYPE[S]? OF REPORTING PERSON[S]? \(SEE INSTRUCTIONS\)'
                       }
        
    elif(re.search("13G", form_type)):
        
        q_regex_dict = {1: '(?:NAMES|NAME) OF REPORTING (?:PERSONS|PERSON)[*]? S.S. ' + \
                         'OR I.R.S. IDENTIFICATION (?:NOS.|NO.) OF ABOVE (?:PERSONS|PERSON) \(ENTITIES ONLY\)',
                        4: 'CITIZENSHIP OR PLACE OF ORGANIZATION',
                        5: 'SOLE VOTING POWER',
                        6: 'SHARED VOTING POWER',
                        7: 'SOLE DISPOSITIVE POWER',
                        8: 'SHARED DISPOSITIVE POWER',
                        9: 'AGGREGATE AMOUNT BENEFICIALLY OWNED BY EACH REPORTING PERSON',
                        10: 'CHECK BOX IF THE AGGREGATE AMOUNT IN ROW \(9\) EXCLUDES CERTAIN SHARES[*]?',
                        11: 'PERCENT OF CLASS REPRESENTED BY AMOUNT IN ROW \(9\)',
                        12: 'TYPE[S]? OF REPORTING PERSON[S]? \(SEE INSTRUCTIONS\)'
                       }
    
    result = re.sub('^' + str(question_number) + '\s*[:\.]?', '', result)
    
    result = re.sub('(^[\:\;\-\–\.\s]+|[\s\-]+$)', '', strip_form_statement(result, q_regex_dict[question_number]))
    
    return(result)